In [ ]:
#!pip install textattack[tensorflow,optional]
#!pip install -U datasets

In [1]:
import os
import datetime

import numpy as np
import pandas as pd

import torch
import torch.nn as nn
from torch.utils.data import DataLoader, Dataset
import torchvision
import tensorflow as tf
import transformers
from transformers import CLIPProcessor, CLIPModel

import textattack
from textattack.models.wrappers import HuggingFaceModelWrapper

from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
# SVC class is too slow to train for large dataset


D:\anaconda3\envs\tf\lib\site-packages\torchvision\io\image.py:13: UserWarning: Failed to load image Python extension: '[WinError 127] 找不到指定的程序。'If you don't plan on using image functionality from `torchvision.io`, you can ignore this warning. Otherwise, there might be something wrong with your environment. Did you have `libjpeg` or `libpng` installed before building `torchvision` from source?
  warn(
D:\anaconda3\envs\tf\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
D:\anaconda3\envs\tf\lib\site-packages\transformers\utils\generic.py:260: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  torch.utils._pytree._register_pytree_node(
D:\anaconda3\envs\tf\lib\site-packages\transformers\utils\generic.py:260: UserWarning: torch.utils._p

In [2]:
from textattack import Attack
from textattack.constraints.grammaticality import PartOfSpeech
from textattack.constraints.pre_transformation import (
    InputColumnModification,
    RepeatModification,
    StopwordModification,
)
from textattack.constraints.semantics import WordEmbeddingDistance
from textattack.constraints.semantics.sentence_encoders import UniversalSentenceEncoder
from textattack.goal_functions import UntargetedClassification
from textattack.search_methods import GreedyWordSwapWIR
from textattack.transformations import WordSwapEmbedding, WordSwapWordNet 

from textattack.transformations.composite_transformation import CompositeTransformation

from textattack.attack_recipes.attack_recipe import AttackRecipe

class TFLepsilon(AttackRecipe):

    @staticmethod
    def build(model_wrapper, sim=0.5, thre=0.840845057):
        #
        # Swap words with their 50 closest embedding nearest-neighbors.
        # Embedding: Counter-fitted PARAGRAM-SL999 vectors.
        
        ## transformation = CompositeTransformation([WordSwapWordNet(), WordSwapEmbedding(max_candidates=50)])
        transformation = WordSwapEmbedding(max_candidates=50)
        #
        # Don't modify the same word twice or the stopwords defined
        # in the TextFooler public implementation.
        #
        # fmt: off
        stopwords = set(
            ["a", "about", "above", "across", "after", "afterwards", "again", "against", "ain", "all", 
             "almost", "alone", "along", "already", "also", "although", "am", "among", "amongst", "an", 
             "and", "another", "any", "anyhow", "anyone", "anything", "anyway", "anywhere", "are", "aren",
             "aren't", "around", "as", "at", "back", "been", "before", "beforehand", "behind", "being", 
             "below", "beside", "besides", "between", "beyond", "both", "but", "by", "can", "cannot", 
             "could", "couldn", "couldn't", "d", "didn", "didn't", "doesn", "doesn't", "don", "don't", 
             "down", "due", "during", "either", "else", "elsewhere", "empty", "enough", "even", "ever", 
             "everyone", "everything", "everywhere", "except", "first", "for", "former", "formerly",
             "from", "hadn", "hadn't", "hasn", "hasn't", "haven", "haven't", "he", "hence", "her", "here", 
             "hereafter", "hereby", "herein", "hereupon", "hers", "herself", "him", "himself", "his", "how", 
             "however", "hundred", "i", "if", "in", "indeed", "into", "is", "isn", "isn't", "it", "it's", 
             "its", "itself", "just", "latter", "latterly", "least", "ll", "may", "me", "meanwhile", 
             "mightn", "mightn't", "mine", "more", "moreover", "most", "mostly", "must", "mustn", "mustn't", 
             "my", "myself", "namely", "needn", "needn't", "neither", "never", "nevertheless", "next", "no",
             "nobody", "none", "noone", "nor", "not", "nothing", "now", "nowhere", "o", "of", "off", "on",
             "once", "one", "only", "onto", "or", "other", "others", "otherwise", "our", "ours", "ourselves", 
             "out", "over", "per", "please", "s", "same", "shan", "shan't", "she", "she's", "should've", 
             "shouldn", "shouldn't", "somehow", "something", "sometime", "somewhere", "such", "t", "than", 
             "that", "that'll", "the", "their", "theirs", "them", "themselves", "then", "thence", "there", 
             "thereafter", "thereby", "therefore", "therein", "thereupon", "these", "they", "this", "those",
             "through", "throughout", "thru", "thus", "to", "too", "toward", "towards", "under", "unless",
             "until", "up", "upon", "used", "ve", "was", "wasn", "wasn't", "we", "were", "weren", "weren't",
             "what", "whatever", "when", "whence", "whenever", "where", "whereafter", "whereas", "whereby", 
             "wherein", "whereupon", "wherever", "whether", "which", "while", "whither", "who", "whoever", 
             "whole", "whom", "whose", "why", "with", "within", "without", "won", "won't", "would", "wouldn",
             "wouldn't", "y", "yet", "you", "you'd", "you'll", "you're", "you've", "your", "yours", "yourself",
             "yourselves"]
        )
        # fmt: on
        constraints = [RepeatModification(), StopwordModification(stopwords=stopwords)]
        #
        # During entailment, we should only edit the hypothesis - keep the premise
        # the same.
        #
        input_column_modification = InputColumnModification(
            ["premise", "hypothesis"], {"premise"}
        )
        constraints.append(input_column_modification)
        # Minimum word embedding cosine similarity of 0.5.
        # (The paper claims 0.7, but analysis of the released code and some empirical
        # results show that it's 0.5.)
        
        ### constraints.append(WordEmbeddingDistance(min_cos_sim=0.5))
        constraints.append(WordEmbeddingDistance(min_cos_sim=sim))
        #
        # Only replace words with the same part of speech (or nouns with verbs)
        #
        constraints.append(PartOfSpeech(allow_verb_noun_swap=True))
        #
        # Universal Sentence Encoder with a minimum angular similarity of ε = 0.5.
        #
        # In the TextFooler code, they forget to divide the angle between the two
        # embeddings by pi. So if the original threshold was that 1 - sim >= 0.5, the
        # new threshold is 1 - (0.5) / pi = 0.840845057
        #
        use_constraint = UniversalSentenceEncoder(
            threshold = thre,
            metric="angular",
            compare_against_original=False,
            window_size=15,
            skip_text_shorter_than_window=True,
        )
        constraints.append(use_constraint)
        #
        # Goal is untargeted classification
        #
        goal_function = UntargetedClassification(model_wrapper)
        #
        # Greedily swap words with "Word Importance Ranking".
        #
        search_method = GreedyWordSwapWIR(wir_method="delete")

        return Attack(goal_function, constraints, transformation, search_method)


In [3]:
def runAttack(model_wrapper, n, path, target_ds, sim=0.5, thre=0.840845057):
    # used TFLepsilon
    attack = TFLepsilon.build(model_wrapper, sim, thre)
    attack_args = textattack.AttackArgs(num_examples=n, log_to_csv=path, shuffle=True, #parallel=True,
                                        checkpoint_interval=50, checkpoint_dir='checkpoints', 
                                        disable_stdout=True)
    attacker = textattack.Attacker(attack, target_ds, attack_args)
    attacker.attack_dataset()

In [7]:
# classifiers
def adaptation(train_set, test_set):
    lr1 = LogisticRegression(solver='saga', multi_class='multinomial') # default
    lr01 = LogisticRegression(solver='saga', multi_class='multinomial', C=0.1) # strong regularisation
    lr10 = LogisticRegression(solver='saga', multi_class='multinomial', C=10)  # weak regularisation
    
    rf7 = RandomForestClassifier(max_depth=7)
    rf14 = RandomForestClassifier(max_depth=14)
    rf30 = RandomForestClassifier(max_depth=30)
    
    knn7 = KNeighborsClassifier(n_neighbors=7)
    knn35 = KNeighborsClassifier(n_neighbors=35)
    knn175 = KNeighborsClassifier(n_neighbors=175)
    
    trainX = train_set.iloc[:,:-1]
    trainY = train_set.iloc[:,-1]
    testX = test_set.iloc[:,:-1]
    testY = test_set.iloc[:,-1]

      
    for key, clf in {'LR':lr1, 'LR C=0.1':lr01, 'LR C=10':lr10,  
                     'RF D=7':rf7, 'RF D=14':rf14, 'RF D=30':rf30,
                     '7-NN':knn7, '35-NN':knn35, '175-NN':knn175}.items():

        clf.fit(trainX, trainY) # fit train data
        pred = clf.predict(testX) # predict test set

        # print accuracy
        print(key, (pred==np.array(testY)).sum()/len(pred))

    return lr1, lr01, lr10, rf7, rf14, rf30, knn7, knn35, knn175

### BERT-based-uncased

In [5]:
# bert-based-uncased
model_path1 = 'bert-base-uncased'

bert_model = transformers.AutoModel.from_pretrained(model_path1)
bert_tokenizer = transformers.AutoTokenizer.from_pretrained(model_path1)

D:\anaconda3\envs\tf\lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
D:\anaconda3\envs\tf\lib\site-packages\transformers\utils\generic.py:260: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  torch.utils._pytree._register_pytree_node(


In [8]:
bertagtrain = pd.read_csv('../dataset_embeddings/bertagnewstrain.txt', header=None)
bertagtest = pd.read_csv('../dataset_embeddings/bertagnewstest.txt', header=None)
bert_lr1, bert_lr01, bert_lr10, bert_rf7, bert_rf14, bert_rf30, bert_knn7, bert_knn35, bert_knn175 = adaptation(bertagtrain, bertagtest)

D:\anaconda3\envs\tf\lib\site-packages\sklearn\linear_model\_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


LR 0.8942105263157895


D:\anaconda3\envs\tf\lib\site-packages\sklearn\linear_model\_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


LR C=0.1 0.8864473684210527


D:\anaconda3\envs\tf\lib\site-packages\sklearn\linear_model\_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


LR C=10 0.8940789473684211
RF D=7 0.7314473684210526
RF D=14 0.7997368421052632
RF D=30 0.81
7-NN 0.7902631578947369
35-NN 0.795
175-NN 0.763421052631579


In [9]:
# custom model wrapper for BERT
class BERTModelWrapper(HuggingFaceModelWrapper):
    def __init__(self, processor, text_encoder, classifier):
        self.processor = processor
        self.model = text_encoder
        self.classifier = classifier

    def __call__(self, text_input_list):
        inputs = self.processor(text_input_list, return_tensors='pt', padding=True, truncation=True)
        outputs = self.model(**inputs).pooler_output
        with torch.no_grad():
            preds = self.classifier.predict_proba(outputs)
        return preds

In [10]:
bert_lr1_ag = BERTModelWrapper(bert_tokenizer, bert_model, bert_lr1)
bert_lr01_ag = BERTModelWrapper(bert_tokenizer, bert_model, bert_lr01)
bert_lr10_ag = BERTModelWrapper(bert_tokenizer, bert_model, bert_lr10)

bert_rf7_ag = BERTModelWrapper(bert_tokenizer, bert_model, bert_rf7)
bert_rf14_ag = BERTModelWrapper(bert_tokenizer, bert_model, bert_rf14)
bert_rf30_ag = BERTModelWrapper(bert_tokenizer, bert_model, bert_rf30)

bert_knn7_ag = BERTModelWrapper(bert_tokenizer, bert_model, bert_knn7)
bert_knn35_ag = BERTModelWrapper(bert_tokenizer, bert_model, bert_knn35)
bert_knn175_ag = BERTModelWrapper(bert_tokenizer, bert_model, bert_knn175)

### CLIP

In [11]:
# Load CLIP model and processor
model_name = "openai/clip-vit-base-patch32"
clip_processor = CLIPProcessor.from_pretrained(model_name)
clip_model = CLIPModel.from_pretrained(model_name)

# Access text encoder
text_encoder = clip_model.text_model

D:\anaconda3\envs\tf\lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


In [12]:
clipagtrain = pd.read_csv('../dataset_embeddings/clipagnewstrain.txt', header=None)
clipagtest = pd.read_csv('../dataset_embeddings/clipagnewstest.txt', header=None)
clip_lr1, clip_lr01, clip_lr10, clip_rf7, clip_rf14, clip_rf30, clip_knn7, clip_knn35, clip_knn175 = adaptation(clipagtrain, clipagtest)

LR 0.915921052631579


D:\anaconda3\envs\tf\lib\site-packages\sklearn\linear_model\_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(


LR C=0.1 0.9163157894736842
LR C=10 0.915921052631579
RF D=7 0.8718421052631579
RF D=14 0.9028947368421053
RF D=30 0.9096052631578947
7-NN 0.9248684210526316
35-NN 0.9210526315789473
175-NN 0.9093421052631578


In [13]:
# custom model wrapper for CLIP
class CLIPModelWrapper(HuggingFaceModelWrapper):
    def __init__(self, processor, text_encoder, classifier):
        self.processor = processor
        self.model = text_encoder
        self.classifier = classifier

    def __call__(self, text_input_list):
        inputs = self.processor(text_input_list, return_tensors='pt', padding=True, truncation=True)
        outputs = self.model(**inputs).pooler_output
        with torch.no_grad():
            preds = self.classifier.predict_proba(outputs)
        return preds

In [14]:
clip_lr1_ag = CLIPModelWrapper(clip_processor, text_encoder, clip_lr1)
clip_lr01_ag = CLIPModelWrapper(clip_processor, text_encoder, clip_lr01)
clip_lr10_ag = CLIPModelWrapper(clip_processor, text_encoder, clip_lr10)

clip_rf7_ag = CLIPModelWrapper(clip_processor, text_encoder, clip_rf7)
clip_rf14_ag = CLIPModelWrapper(clip_processor, text_encoder, clip_rf14)
clip_rf30_ag = CLIPModelWrapper(clip_processor, text_encoder, clip_rf30)

clip_knn7_ag = CLIPModelWrapper(clip_processor, text_encoder, clip_knn7)
clip_knn35_ag = CLIPModelWrapper(clip_processor, text_encoder, clip_knn35)
clip_knn175_ag = CLIPModelWrapper(clip_processor, text_encoder, clip_knn175)

### Run Attacks

In [15]:
target_ds_ag = textattack.datasets.HuggingFaceDataset('ag_news', split='test')

textattack: Loading datasets dataset ag_news, split test.


In [16]:
n_samples = 300

### Default parameters, threshold = 1 - 0.5/$\pi$ = 0.841, minSim = 0.5

In [17]:
suffix = 'ep0841.csv'
thre = 1-0.5/np.pi

In [18]:
st = datetime.datetime.now()

#### BERT

In [19]:
runAttack(bert_lr1_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr1'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr1ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 43 / 2 / 5 / 50:  17%|████▏                    | 50/300 [09:35<47:57, 11.51s/it]textattack: Saving checkpoint under "checkpoints\1721956773856.ta.chkpt" at 2024-07-26 09:19:33 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 88 / 2 / 10 / 100:  33%|███████▎              | 100/300 [19:03<38:06, 11.43s/it]textattack: Saving checkpoint under "checkpoints\1721957341332.ta.chkpt" at 2024-07-26 09:29:01 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 132 / 3 / 15 / 150:  50%|██████████▌          | 150/300 [31:23<31:23, 12.55s/it]textattack: Saving checkpoint under "checkpoints\1721958081299.ta.chkpt" at 2024-07-26 09:41:21 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 175 / 4 / 21 / 200:  67%|██████████████       | 200/300 [43:06<21:33, 12.93s/it]textattack: Saving checkpoint under "checkpoints\1721958784772.ta.chkpt" at 2024-07-26 09:53:04 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 221 / 4 / 25 / 250:  83%|█████████████████▌   | 250/300 [54:28<10:53, 13.07s/it]textattack: Saving checkpoint under "checkpoints\1721959466347.ta.chkpt" at 2024-07-26 10:04:26 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 265 / 5 / 30 / 300: 100%|███████████████████| 300/300 [1:06:41<00:00, 13.34s/it]textattack: Saving checkpoint under "checkpoints\1721960199559.ta.chkpt" at 2024-07-26 10:16:39 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 265 / 5 / 30 / 300: 100%|███████████████████| 300/300 [1:06:41<00:00, 13.34s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 265    |
| Number of failed attacks:     | 5      |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 1.67%  |
| Attack success rate:          | 98.15% |
| Average perturbed word %:     | 15.36% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 191.89 |
+-------------------------------+--------+

In [21]:
runAttack(bert_lr01_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr01'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr01ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 44 / 1 / 5 / 50:  17%|████▏                    | 50/300 [09:27<47:19, 11.36s/it]textattack: Saving checkpoint under "checkpoints\1721990591817.ta.chkpt" at 2024-07-26 18:43:11 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 88 / 1 / 11 / 100:  33%|███████▎              | 100/300 [18:45<37:31, 11.26s/it]textattack: Saving checkpoint under "checkpoints\1721991149572.ta.chkpt" at 2024-07-26 18:52:29 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 129 / 5 / 16 / 150:  50%|██████████▌          | 150/300 [31:01<31:01, 12.41s/it]textattack: Saving checkpoint under "checkpoints\1721991884974.ta.chkpt" at 2024-07-26 19:04:44 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 172 / 5 / 23 / 200:  67%|██████████████       | 200/300 [42:22<21:11, 12.71s/it]textattack: Saving checkpoint under "checkpoints\1721992565902.ta.chkpt" at 2024-07-26 19:16:05 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 215 / 8 / 27 / 250:  83%|█████████████████▌   | 250/300 [54:25<10:53, 13.06s/it]textattack: Saving checkpoint under "checkpoints\1721993289010.ta.chkpt" at 2024-07-26 19:28:09 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 260 / 8 / 32 / 300: 100%|███████████████████| 300/300 [1:06:10<00:00, 13.24s/it]textattack: Saving checkpoint under "checkpoints\1721993994677.ta.chkpt" at 2024-07-26 19:39:54 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 260 / 8 / 32 / 300: 100%|███████████████████| 300/300 [1:06:10<00:00, 13.24s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 260    |
| Number of failed attacks:     | 8      |
| Number of skipped attacks:    | 32     |
| Original accuracy:            | 89.33% |
| Accuracy under attack:        | 2.67%  |
| Attack success rate:          | 97.01% |
| Average perturbed word %:     | 15.42% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 196.14 |
+-------------------------------+--------+


In [22]:
runAttack(bert_lr10_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr10'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr10ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 43 / 2 / 5 / 50:  17%|████▏                    | 50/300 [08:49<44:09, 10.60s/it]textattack: Saving checkpoint under "checkpoints\1721994524679.ta.chkpt" at 2024-07-26 19:48:44 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 86 / 3 / 11 / 100:  33%|███████▎              | 100/300 [17:52<35:44, 10.72s/it]textattack: Saving checkpoint under "checkpoints\1721995066942.ta.chkpt" at 2024-07-26 19:57:46 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 128 / 6 / 16 / 150:  50%|██████████▌          | 150/300 [30:12<30:12, 12.08s/it]textattack: Saving checkpoint under "checkpoints\1721995807033.ta.chkpt" at 2024-07-26 20:10:07 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 170 / 8 / 22 / 200:  67%|██████████████       | 200/300 [41:00<20:30, 12.30s/it]textattack: Saving checkpoint under "checkpoints\1721996455409.ta.chkpt" at 2024-07-26 20:20:55 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 214 / 10 / 26 / 250:  83%|████████████████▋   | 250/300 [52:26<10:29, 12.59s/it]textattack: Saving checkpoint under "checkpoints\1721997141082.ta.chkpt" at 2024-07-26 20:32:21 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 258 / 11 / 31 / 300: 100%|██████████████████| 300/300 [1:03:59<00:00, 12.80s/it]textattack: Saving checkpoint under "checkpoints\1721997834336.ta.chkpt" at 2024-07-26 20:43:54 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 258 / 11 / 31 / 300: 100%|██████████████████| 300/300 [1:03:59<00:00, 12.80s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 258    |
| Number of failed attacks:     | 11     |
| Number of skipped attacks:    | 31     |
| Original accuracy:            | 89.67% |
| Accuracy under attack:        | 3.67%  |
| Attack success rate:          | 95.91% |
| Average perturbed word %:     | 14.44% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 190.96 |
+-------------------------------+--------+


In [23]:
runAttack(bert_rf7_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf7ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 36 / 1 / 13 / 50:  17%|████                    | 50/300 [05:50<29:11,  7.01s/it]textattack: Saving checkpoint under "checkpoints\1721998184752.ta.chkpt" at 2024-07-26 20:49:44 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 68 / 3 / 29 / 100:  33%|███████▎              | 100/300 [11:04<22:09,  6.65s/it]textattack: Saving checkpoint under "checkpoints\1721998499348.ta.chkpt" at 2024-07-26 20:54:59 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 107 / 3 / 40 / 150:  50%|██████████▌          | 150/300 [17:17<17:17,  6.92s/it]textattack: Saving checkpoint under "checkpoints\1721998871755.ta.chkpt" at 2024-07-26 21:01:11 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 140 / 4 / 56 / 200:  67%|██████████████       | 200/300 [27:41<13:50,  8.31s/it]textattack: Saving checkpoint under "checkpoints\1721999495926.ta.chkpt" at 2024-07-26 21:11:35 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 182 / 5 / 63 / 250:  83%|█████████████████▌   | 250/300 [33:45<06:45,  8.10s/it]textattack: Saving checkpoint under "checkpoints\1721999859554.ta.chkpt" at 2024-07-26 21:17:39 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 221 / 5 / 74 / 300: 100%|█████████████████████| 300/300 [40:30<00:00,  8.10s/it]textattack: Saving checkpoint under "checkpoints\1722000265048.ta.chkpt" at 2024-07-26 21:24:25 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 221 / 5 / 74 / 300: 100%|█████████████████████| 300/300 [40:30<00:00,  8.10s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 221    |
| Number of failed attacks:     | 5      |
| Number of skipped attacks:    | 74     |
| Original accuracy:            | 75.33% |
| Accuracy under attack:        | 1.67%  |
| Attack success rate:          | 97.79% |
| Average perturbed word %:     | 8.53%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 133.38 |
+-------------------------------+--------+


In [24]:
runAttack(bert_rf14_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf14'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf14ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 38 / 3 / 9 / 50:  17%|████▏                    | 50/300 [07:29<37:27,  8.99s/it]textattack: Saving checkpoint under "checkpoints\1722000714612.ta.chkpt" at 2024-07-26 21:31:54 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 78 / 3 / 19 / 100:  33%|███████▎              | 100/300 [15:04<30:08,  9.04s/it]textattack: Saving checkpoint under "checkpoints\1722001169501.ta.chkpt" at 2024-07-26 21:39:29 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 116 / 7 / 27 / 150:  50%|██████████▌          | 150/300 [24:01<24:01,  9.61s/it]textattack: Saving checkpoint under "checkpoints\1722001706816.ta.chkpt" at 2024-07-26 21:48:26 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 145 / 12 / 43 / 200:  67%|█████████████▎      | 200/300 [37:26<18:43, 11.23s/it]textattack: Saving checkpoint under "checkpoints\1722002511634.ta.chkpt" at 2024-07-26 22:01:51 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 183 / 18 / 49 / 250:  83%|████████████████▋   | 250/300 [47:37<09:31, 11.43s/it]textattack: Saving checkpoint under "checkpoints\1722003122174.ta.chkpt" at 2024-07-26 22:12:02 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 225 / 18 / 57 / 300: 100%|████████████████████| 300/300 [58:45<00:00, 11.75s/it]textattack: Saving checkpoint under "checkpoints\1722003790812.ta.chkpt" at 2024-07-26 22:23:10 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 225 / 18 / 57 / 300: 100%|████████████████████| 300/300 [58:45<00:00, 11.75s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 225    |
| Number of failed attacks:     | 18     |
| Number of skipped attacks:    | 57     |
| Original accuracy:            | 81.0%  |
| Accuracy under attack:        | 6.0%   |
| Attack success rate:          | 92.59% |
| Average perturbed word %:     | 9.52%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 176.22 |
+-------------------------------+--------+


In [26]:
runAttack(bert_rf30_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf30'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf30ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:17<1:26:39, 17.39s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:17<1:26:51, 17.43s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                           | 2/300 [00:23<58:19, 11.74s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                           | 2/300 [00:23<58:21, 11.75s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [01:05<1:48:13, 21.86s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [01:05<1:48:16, 21.87s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:41<2:04:42, 25.28s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:41<2:04:44, 25.28s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 41 / 3 / 6 / 50:  17%|████▎                    | 51/300 [09:38<47:05, 11.35s/it]
[Succeeded / Failed / Skipped / Total] 42 / 3 / 6 / 51:  17%|████▎                    | 51/300 [09:38<47:05, 11.35s/it]
[Succeeded / Failed / Skipped / Total] 42 / 3 / 6 / 51:  17%|████▎                    | 52/300 [09:46<46:37, 11.28s/it]
[Succeeded / Failed / Skipped / Total] 43 / 3 / 6 / 52:  17%|████▎                    | 52/300 [09:46<46:38, 11.28s/it]
[Succeeded / Failed / Skipped / Total] 43 / 3 / 6 / 52:  18%|████▍                    | 53/300 [10:17<47:59, 11.66s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 6 / 53:  18%|████▍                    | 53/300 [10:17<47:59, 11.66s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 6 / 53:  18%|████▌                    | 54/300 [10:23<47:21, 11.55s/it]
[Succeeded / Failed / Skipped / Total] 45 / 3 / 6 / 54:  18%|████▌                    | 54/300 [10:23<47:21, 11.55s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 78 / 3 / 19 / 100:  34%|███████▍              | 101/300 [15:47<31:05,  9.38s/it]
[Succeeded / Failed / Skipped / Total] 79 / 3 / 19 / 101:  34%|███████▍              | 101/300 [15:47<31:05,  9.38s/it]
[Succeeded / Failed / Skipped / Total] 79 / 3 / 19 / 101:  34%|███████▍              | 102/300 [16:30<32:02,  9.71s/it]
[Succeeded / Failed / Skipped / Total] 79 / 4 / 19 / 102:  34%|███████▍              | 102/300 [16:30<32:02,  9.71s/it]
[Succeeded / Failed / Skipped / Total] 79 / 4 / 19 / 102:  34%|███████▌              | 103/300 [16:30<31:35,  9.62s/it]
[Succeeded / Failed / Skipped / Total] 79 / 4 / 20 / 103:  34%|███████▌              | 103/300 [16:30<31:35,  9.62s/it]
[Succeeded / Failed / Skipped / Total] 79 / 4 / 20 / 103:  35%|███████▋              | 104/300 [16:40<31:25,  9.62s/it]
[Succeeded / Failed / Skipped / Total] 80 / 4 / 20 / 104:  35%|███████▋              | 104/300 [16:40<31:25,  9.62s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 115 / 9 / 26 / 150:  50%|██████████▌          | 151/300 [26:05<25:44, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 116 / 9 / 26 / 151:  50%|██████████▌          | 151/300 [26:05<25:44, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 116 / 9 / 26 / 151:  51%|██████████▋          | 152/300 [26:43<26:01, 10.55s/it]
[Succeeded / Failed / Skipped / Total] 117 / 9 / 26 / 152:  51%|██████████▋          | 152/300 [26:43<26:01, 10.55s/it]
[Succeeded / Failed / Skipped / Total] 117 / 9 / 26 / 152:  51%|██████████▋          | 153/300 [26:52<25:48, 10.54s/it]
[Succeeded / Failed / Skipped / Total] 118 / 9 / 26 / 153:  51%|██████████▋          | 153/300 [26:52<25:48, 10.54s/it]
[Succeeded / Failed / Skipped / Total] 118 / 9 / 26 / 153:  51%|██████████▊          | 154/300 [26:57<25:33, 10.51s/it]
[Succeeded / Failed / Skipped / Total] 119 / 9 / 26 / 154:  51%|██████████▊          | 154/300 [26:58<25:33, 10.51s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 150 / 11 / 39 / 200:  67%|█████████████▍      | 201/300 [37:24<18:25, 11.17s/it]
[Succeeded / Failed / Skipped / Total] 151 / 11 / 39 / 201:  67%|█████████████▍      | 201/300 [37:24<18:25, 11.17s/it]
[Succeeded / Failed / Skipped / Total] 151 / 11 / 39 / 201:  67%|█████████████▍      | 202/300 [37:28<18:10, 11.13s/it]
[Succeeded / Failed / Skipped / Total] 152 / 11 / 39 / 202:  67%|█████████████▍      | 202/300 [37:28<18:10, 11.13s/it]
[Succeeded / Failed / Skipped / Total] 152 / 11 / 39 / 202:  68%|█████████████▌      | 203/300 [37:42<18:00, 11.14s/it]
[Succeeded / Failed / Skipped / Total] 153 / 11 / 39 / 203:  68%|█████████████▌      | 203/300 [37:42<18:01, 11.14s/it]
[Succeeded / Failed / Skipped / Total] 153 / 11 / 39 / 203:  68%|█████████████▌      | 204/300 [37:42<17:44, 11.09s/it]
[Succeeded / Failed / Skipped / Total] 153 / 11 / 40 / 204:  68%|█████████████▌      | 204/300 [37:42<17:44, 11.09s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 190 / 14 / 46 / 250:  84%|████████████████▋   | 251/300 [48:02<09:22, 11.48s/it]
[Succeeded / Failed / Skipped / Total] 191 / 14 / 46 / 251:  84%|████████████████▋   | 251/300 [48:02<09:22, 11.48s/it]
[Succeeded / Failed / Skipped / Total] 191 / 14 / 46 / 251:  84%|████████████████▊   | 252/300 [48:05<09:09, 11.45s/it]
[Succeeded / Failed / Skipped / Total] 192 / 14 / 46 / 252:  84%|████████████████▊   | 252/300 [48:05<09:09, 11.45s/it]
[Succeeded / Failed / Skipped / Total] 192 / 14 / 46 / 252:  84%|████████████████▊   | 253/300 [48:13<08:57, 11.44s/it]
[Succeeded / Failed / Skipped / Total] 193 / 14 / 46 / 253:  84%|████████████████▊   | 253/300 [48:13<08:57, 11.44s/it]
[Succeeded / Failed / Skipped / Total] 193 / 14 / 46 / 253:  85%|████████████████▉   | 254/300 [48:21<08:45, 11.42s/it]
[Succeeded / Failed / Skipped / Total] 194 / 14 / 46 / 254:  85%|████████████████▉   | 254/300 [48:21<08:45, 11.42s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 229    |
| Number of failed attacks:     | 18     |
| Number of skipped attacks:    | 53     |
| Original accuracy:            | 82.33% |
| Accuracy under attack:        | 6.0%   |
| Attack success rate:          | 92.71% |
| Average perturbed word %:     | 9.32%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 175.26 |
+-------------------------------+--------+


In [27]:
runAttack(bert_knn7_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn7ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                           | 1/300 [37:35<187:21:51, 2255.89s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                      | 1/300 [37:35<187:21:56, 2255.91s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                      | 2/300 [37:41<93:35:52, 1130.71s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                      | 2/300 [37:41<93:35:54, 1130.72s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                       | 3/300 [38:38<63:45:28, 772.82s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▏                       | 3/300 [38:38<63:45:30, 772.83s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                       | 4/300 [39:17<48:27:57, 589.45s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                       | 4/300 [39:17<48:27:58, 589.45s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 32 / 7 / 11 / 50:  17%|███▋                  | 51/300 [48:35<3:57:14, 57.17s/it]
[Succeeded / Failed / Skipped / Total] 33 / 7 / 11 / 51:  17%|███▋                  | 51/300 [48:35<3:57:14, 57.17s/it]
[Succeeded / Failed / Skipped / Total] 33 / 7 / 11 / 51:  17%|███▊                  | 52/300 [48:38<3:51:58, 56.12s/it]
[Succeeded / Failed / Skipped / Total] 34 / 7 / 11 / 52:  17%|███▊                  | 52/300 [48:38<3:51:58, 56.12s/it]
[Succeeded / Failed / Skipped / Total] 34 / 7 / 11 / 52:  18%|███▉                  | 53/300 [49:35<3:51:07, 56.14s/it]
[Succeeded / Failed / Skipped / Total] 34 / 8 / 11 / 53:  18%|███▉                  | 53/300 [49:35<3:51:07, 56.14s/it]
[Succeeded / Failed / Skipped / Total] 34 / 8 / 11 / 53:  18%|███▉                  | 54/300 [49:47<3:46:47, 55.32s/it]
[Succeeded / Failed / Skipped / Total] 35 / 8 / 11 / 54:  18%|███▉                  | 54/300 [49:47<3:46:47, 55.32s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 70 / 10 / 20 / 100:  34%|██████▍            | 101/300 [59:17<1:56:48, 35.22s/it]
[Succeeded / Failed / Skipped / Total] 71 / 10 / 20 / 101:  34%|██████▍            | 101/300 [59:17<1:56:48, 35.22s/it]
[Succeeded / Failed / Skipped / Total] 71 / 10 / 20 / 101:  34%|██████▍            | 102/300 [59:34<1:55:39, 35.05s/it]
[Succeeded / Failed / Skipped / Total] 72 / 10 / 20 / 102:  34%|██████▍            | 102/300 [59:34<1:55:39, 35.05s/it]
[Succeeded / Failed / Skipped / Total] 72 / 10 / 20 / 102:  34%|██████▌            | 103/300 [59:35<1:53:58, 34.71s/it]
[Succeeded / Failed / Skipped / Total] 72 / 10 / 21 / 103:  34%|██████▌            | 103/300 [59:35<1:53:58, 34.71s/it]
[Succeeded / Failed / Skipped / Total] 72 / 10 / 21 / 103:  35%|██████▌            | 104/300 [59:38<1:52:24, 34.41s/it]
[Succeeded / Failed / Skipped / Total] 73 / 10 / 21 / 104:  35%|██████▌            | 104/300 [59:38<1:52:24, 34.41s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 100 / 18 / 32 / 150:  50%|████████        | 151/300 [1:12:43<1:11:45, 28.90s/it]
[Succeeded / Failed / Skipped / Total] 101 / 18 / 32 / 151:  50%|████████        | 151/300 [1:12:43<1:11:45, 28.90s/it]
[Succeeded / Failed / Skipped / Total] 101 / 18 / 32 / 151:  51%|████████        | 152/300 [1:13:38<1:11:42, 29.07s/it]
[Succeeded / Failed / Skipped / Total] 101 / 19 / 32 / 152:  51%|████████        | 152/300 [1:13:38<1:11:42, 29.07s/it]
[Succeeded / Failed / Skipped / Total] 101 / 19 / 32 / 152:  51%|████████▏       | 153/300 [1:13:58<1:11:04, 29.01s/it]
[Succeeded / Failed / Skipped / Total] 102 / 19 / 32 / 153:  51%|████████▏       | 153/300 [1:13:58<1:11:04, 29.01s/it]
[Succeeded / Failed / Skipped / Total] 102 / 19 / 32 / 153:  51%|████████▏       | 154/300 [1:14:05<1:10:14, 28.87s/it]
[Succeeded / Failed / Skipped / Total] 103 / 19 / 32 / 154:  51%|████████▏       | 154/300 [1:14:05<1:10:14, 28.87s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 129 / 26 / 45 / 200:  67%|████████████      | 201/300 [1:27:50<43:15, 26.22s/it]
[Succeeded / Failed / Skipped / Total] 129 / 27 / 45 / 201:  67%|████████████      | 201/300 [1:27:50<43:15, 26.22s/it]
[Succeeded / Failed / Skipped / Total] 129 / 27 / 45 / 201:  67%|████████████      | 202/300 [1:27:55<42:39, 26.12s/it]
[Succeeded / Failed / Skipped / Total] 130 / 27 / 45 / 202:  67%|████████████      | 202/300 [1:27:55<42:39, 26.12s/it]
[Succeeded / Failed / Skipped / Total] 130 / 27 / 45 / 202:  68%|████████████▏     | 203/300 [1:28:50<42:26, 26.26s/it]
[Succeeded / Failed / Skipped / Total] 130 / 28 / 45 / 203:  68%|████████████▏     | 203/300 [1:28:50<42:26, 26.26s/it]
[Succeeded / Failed / Skipped / Total] 130 / 28 / 45 / 203:  68%|████████████▏     | 204/300 [1:28:55<41:50, 26.15s/it]
[Succeeded / Failed / Skipped / Total] 131 / 28 / 45 / 204:  68%|████████████▏     | 204/300 [1:28:55<41:50, 26.15s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 165 / 33 / 52 / 250:  84%|███████████████   | 251/300 [1:40:04<19:32, 23.92s/it]
[Succeeded / Failed / Skipped / Total] 166 / 33 / 52 / 251:  84%|███████████████   | 251/300 [1:40:04<19:32, 23.92s/it]
[Succeeded / Failed / Skipped / Total] 166 / 33 / 52 / 251:  84%|███████████████   | 252/300 [1:40:08<19:04, 23.85s/it]
[Succeeded / Failed / Skipped / Total] 167 / 33 / 52 / 252:  84%|███████████████   | 252/300 [1:40:08<19:04, 23.85s/it]
[Succeeded / Failed / Skipped / Total] 167 / 33 / 52 / 252:  84%|███████████████▏  | 253/300 [1:40:15<18:37, 23.78s/it]
[Succeeded / Failed / Skipped / Total] 168 / 33 / 52 / 253:  84%|███████████████▏  | 253/300 [1:40:15<18:37, 23.78s/it]
[Succeeded / Failed / Skipped / Total] 168 / 33 / 52 / 253:  85%|███████████████▏  | 254/300 [1:40:20<18:10, 23.70s/it]
[Succeeded / Failed / Skipped / Total] 169 / 33 / 52 / 254:  85%|███████████████▏  | 254/300 [1:40:20<18:10, 23.70s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 204    |
| Number of failed attacks:     | 38     |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 80.67% |
| Accuracy under attack:        | 12.67% |
| Attack success rate:          | 84.3%  |
| Average perturbed word %:     | 5.0%   |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 200.34 |
+-------------------------------+--------+


In [28]:
runAttack(bert_knn35_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn35'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn35ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:29<2:28:07, 29.72s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:29<2:28:11, 29.74s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:32<1:20:24, 16.19s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:32<1:20:24, 16.19s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:56<1:34:01, 19.00s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:57<1:34:03, 19.00s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:34<1:56:29, 23.61s/it]
[Succeeded / Failed / Skipped / Total] 4 / 0 / 0 / 4:   1%|▎                         | 4/300 [01:34<1:56:31, 23.62s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 37 / 4 / 9 / 50:  17%|████▎                    | 51/300 [11:41<57:07, 13.76s/it]
[Succeeded / Failed / Skipped / Total] 38 / 4 / 9 / 51:  17%|████▎                    | 51/300 [11:41<57:07, 13.76s/it]
[Succeeded / Failed / Skipped / Total] 38 / 4 / 9 / 51:  17%|████▎                    | 52/300 [11:45<56:02, 13.56s/it]
[Succeeded / Failed / Skipped / Total] 39 / 4 / 9 / 52:  17%|████▎                    | 52/300 [11:45<56:02, 13.56s/it]
[Succeeded / Failed / Skipped / Total] 39 / 4 / 9 / 52:  18%|████▍                    | 53/300 [11:58<55:49, 13.56s/it]
[Succeeded / Failed / Skipped / Total] 40 / 4 / 9 / 53:  18%|████▍                    | 53/300 [11:58<55:49, 13.56s/it]
[Succeeded / Failed / Skipped / Total] 40 / 4 / 9 / 53:  18%|████▌                    | 54/300 [12:37<57:30, 14.02s/it]
[Succeeded / Failed / Skipped / Total] 40 / 5 / 9 / 54:  18%|████▌                    | 54/300 [12:37<57:30, 14.02s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 74 / 7 / 19 / 100:  34%|███████▍              | 101/300 [20:47<40:57, 12.35s/it]
[Succeeded / Failed / Skipped / Total] 75 / 7 / 19 / 101:  34%|███████▍              | 101/300 [20:47<40:57, 12.35s/it]
[Succeeded / Failed / Skipped / Total] 75 / 7 / 19 / 101:  34%|███████▍              | 102/300 [20:53<40:33, 12.29s/it]
[Succeeded / Failed / Skipped / Total] 76 / 7 / 19 / 102:  34%|███████▍              | 102/300 [20:53<40:33, 12.29s/it]
[Succeeded / Failed / Skipped / Total] 76 / 7 / 19 / 102:  34%|███████▌              | 103/300 [20:54<39:58, 12.18s/it]
[Succeeded / Failed / Skipped / Total] 76 / 7 / 20 / 103:  34%|███████▌              | 103/300 [20:54<39:58, 12.18s/it]
[Succeeded / Failed / Skipped / Total] 76 / 7 / 20 / 103:  35%|███████▋              | 104/300 [20:57<39:30, 12.09s/it]
[Succeeded / Failed / Skipped / Total] 77 / 7 / 20 / 104:  35%|███████▋              | 104/300 [20:57<39:30, 12.09s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 110 / 12 / 28 / 150:  50%|██████████          | 151/300 [32:36<32:11, 12.96s/it]
[Succeeded / Failed / Skipped / Total] 111 / 12 / 28 / 151:  50%|██████████          | 151/300 [32:37<32:11, 12.96s/it]
[Succeeded / Failed / Skipped / Total] 111 / 12 / 28 / 151:  51%|██████████▏         | 152/300 [33:30<32:37, 13.23s/it]
[Succeeded / Failed / Skipped / Total] 111 / 13 / 28 / 152:  51%|██████████▏         | 152/300 [33:30<32:37, 13.23s/it]
[Succeeded / Failed / Skipped / Total] 111 / 13 / 28 / 152:  51%|██████████▏         | 153/300 [33:46<32:26, 13.24s/it]
[Succeeded / Failed / Skipped / Total] 112 / 13 / 28 / 153:  51%|██████████▏         | 153/300 [33:46<32:26, 13.24s/it]
[Succeeded / Failed / Skipped / Total] 112 / 13 / 28 / 153:  51%|██████████▎         | 154/300 [33:53<32:07, 13.20s/it]
[Succeeded / Failed / Skipped / Total] 113 / 13 / 28 / 154:  51%|██████████▎         | 154/300 [33:53<32:07, 13.20s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 140 / 17 / 43 / 200:  67%|█████████████▍      | 201/300 [47:35<23:26, 14.21s/it]
[Succeeded / Failed / Skipped / Total] 141 / 17 / 43 / 201:  67%|█████████████▍      | 201/300 [47:35<23:26, 14.21s/it]
[Succeeded / Failed / Skipped / Total] 141 / 17 / 43 / 201:  67%|█████████████▍      | 202/300 [47:42<23:08, 14.17s/it]
[Succeeded / Failed / Skipped / Total] 142 / 17 / 43 / 202:  67%|█████████████▍      | 202/300 [47:42<23:08, 14.17s/it]
[Succeeded / Failed / Skipped / Total] 142 / 17 / 43 / 202:  68%|█████████████▌      | 203/300 [47:51<22:52, 14.15s/it]
[Succeeded / Failed / Skipped / Total] 143 / 17 / 43 / 203:  68%|█████████████▌      | 203/300 [47:51<22:52, 14.15s/it]
[Succeeded / Failed / Skipped / Total] 143 / 17 / 43 / 203:  68%|█████████████▌      | 204/300 [47:56<22:33, 14.10s/it]
[Succeeded / Failed / Skipped / Total] 144 / 17 / 43 / 204:  68%|█████████████▌      | 204/300 [47:56<22:33, 14.10s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 177 / 22 / 51 / 250:  84%|████████████████▋   | 251/300 [59:47<11:40, 14.29s/it]
[Succeeded / Failed / Skipped / Total] 178 / 22 / 51 / 251:  84%|████████████████▋   | 251/300 [59:47<11:40, 14.29s/it]
[Succeeded / Failed / Skipped / Total] 178 / 22 / 51 / 251:  84%|████████████████▊   | 252/300 [59:49<11:23, 14.24s/it]
[Succeeded / Failed / Skipped / Total] 179 / 22 / 51 / 252:  84%|████████████████▊   | 252/300 [59:49<11:23, 14.24s/it]
[Succeeded / Failed / Skipped / Total] 179 / 22 / 51 / 252:  84%|████████████████▊   | 253/300 [59:58<11:08, 14.22s/it]
[Succeeded / Failed / Skipped / Total] 180 / 22 / 51 / 253:  84%|████████████████▊   | 253/300 [59:58<11:08, 14.22s/it]
[Succeeded / Failed / Skipped / Total] 180 / 22 / 51 / 253:  85%|███████████████▏  | 254/300 [1:00:06<10:53, 14.20s/it]
[Succeeded / Failed / Skipped / Total] 181 / 22 / 51 / 254:  85%|███████████████▏  | 254/300 [1:00:06<10:53, 14.20s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 219    |
| Number of failed attacks:     | 25     |
| Number of skipped attacks:    | 56     |
| Original accuracy:            | 81.33% |
| Accuracy under attack:        | 8.33%  |
| Attack success rate:          | 89.75% |
| Average perturbed word %:     | 7.68%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 187.45 |
+-------------------------------+--------+


In [29]:
runAttack(bert_knn175_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn175'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn175ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:19<1:36:37, 19.39s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:19<1:36:37, 19.39s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                           | 2/300 [00:22<55:22, 11.15s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                           | 2/300 [00:22<55:22, 11.15s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:42<1:09:52, 14.11s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:42<1:09:52, 14.11s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:16<1:33:46, 19.01s/it]
[Succeeded / Failed / Skipped / Total] 4 / 0 / 0 / 4:   1%|▎                         | 4/300 [01:16<1:33:47, 19.01s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 40 / 1 / 9 / 50:  17%|████▎                    | 51/300 [08:38<42:11, 10.17s/it]
[Succeeded / Failed / Skipped / Total] 41 / 1 / 9 / 51:  17%|████▎                    | 51/300 [08:38<42:11, 10.17s/it]
[Succeeded / Failed / Skipped / Total] 41 / 1 / 9 / 51:  17%|████▎                    | 52/300 [08:41<41:27, 10.03s/it]
[Succeeded / Failed / Skipped / Total] 42 / 1 / 9 / 52:  17%|████▎                    | 52/300 [08:41<41:27, 10.03s/it]
[Succeeded / Failed / Skipped / Total] 42 / 1 / 9 / 52:  18%|████▍                    | 53/300 [08:50<41:11, 10.01s/it]
[Succeeded / Failed / Skipped / Total] 43 / 1 / 9 / 53:  18%|████▍                    | 53/300 [08:50<41:12, 10.01s/it]
[Succeeded / Failed / Skipped / Total] 43 / 1 / 9 / 53:  18%|████▌                    | 54/300 [09:05<41:24, 10.10s/it]
[Succeeded / Failed / Skipped / Total] 44 / 1 / 9 / 54:  18%|████▌                    | 54/300 [09:05<41:24, 10.10s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 78 / 2 / 20 / 100:  34%|███████▍              | 101/300 [15:51<31:13,  9.42s/it]
[Succeeded / Failed / Skipped / Total] 78 / 2 / 21 / 101:  34%|███████▍              | 101/300 [15:51<31:13,  9.42s/it]
[Succeeded / Failed / Skipped / Total] 78 / 2 / 21 / 101:  34%|███████▍              | 102/300 [16:09<31:22,  9.51s/it]
[Succeeded / Failed / Skipped / Total] 79 / 2 / 21 / 102:  34%|███████▍              | 102/300 [16:09<31:22,  9.51s/it]
[Succeeded / Failed / Skipped / Total] 79 / 2 / 21 / 102:  34%|███████▌              | 103/300 [16:09<30:54,  9.42s/it]
[Succeeded / Failed / Skipped / Total] 79 / 2 / 22 / 103:  34%|███████▌              | 103/300 [16:09<30:54,  9.42s/it]
[Succeeded / Failed / Skipped / Total] 79 / 2 / 22 / 103:  35%|███████▋              | 104/300 [16:12<30:32,  9.35s/it]
[Succeeded / Failed / Skipped / Total] 80 / 2 / 22 / 104:  35%|███████▋              | 104/300 [16:12<30:32,  9.35s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 113 / 4 / 33 / 150:  50%|██████████▌          | 151/300 [26:03<25:42, 10.35s/it]
[Succeeded / Failed / Skipped / Total] 114 / 4 / 33 / 151:  50%|██████████▌          | 151/300 [26:03<25:42, 10.35s/it]
[Succeeded / Failed / Skipped / Total] 114 / 4 / 33 / 151:  51%|██████████▋          | 152/300 [26:16<25:35, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 115 / 4 / 33 / 152:  51%|██████████▋          | 152/300 [26:16<25:35, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 115 / 4 / 33 / 152:  51%|██████████▋          | 153/300 [26:25<25:23, 10.36s/it]
[Succeeded / Failed / Skipped / Total] 116 / 4 / 33 / 153:  51%|██████████▋          | 153/300 [26:25<25:23, 10.36s/it]
[Succeeded / Failed / Skipped / Total] 116 / 4 / 33 / 153:  51%|██████████▊          | 154/300 [26:33<25:10, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 117 / 4 / 33 / 154:  51%|██████████▊          | 154/300 [26:33<25:10, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 147 / 6 / 47 / 200:  67%|██████████████       | 201/300 [35:55<17:41, 10.72s/it]
[Succeeded / Failed / Skipped / Total] 148 / 6 / 47 / 201:  67%|██████████████       | 201/300 [35:55<17:41, 10.72s/it]
[Succeeded / Failed / Skipped / Total] 148 / 6 / 47 / 201:  67%|██████████████▏      | 202/300 [36:00<17:28, 10.70s/it]
[Succeeded / Failed / Skipped / Total] 149 / 6 / 47 / 202:  67%|██████████████▏      | 202/300 [36:00<17:28, 10.70s/it]
[Succeeded / Failed / Skipped / Total] 149 / 6 / 47 / 202:  68%|██████████████▏      | 203/300 [36:22<17:22, 10.75s/it]
[Succeeded / Failed / Skipped / Total] 150 / 6 / 47 / 203:  68%|██████████████▏      | 203/300 [36:22<17:22, 10.75s/it]
[Succeeded / Failed / Skipped / Total] 150 / 6 / 47 / 203:  68%|██████████████▎      | 204/300 [36:41<17:15, 10.79s/it]
[Succeeded / Failed / Skipped / Total] 151 / 6 / 47 / 204:  68%|██████████████▎      | 204/300 [36:41<17:15, 10.79s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 188 / 8 / 54 / 250:  84%|█████████████████▌   | 251/300 [45:54<08:57, 10.97s/it]
[Succeeded / Failed / Skipped / Total] 188 / 8 / 55 / 251:  84%|█████████████████▌   | 251/300 [45:54<08:57, 10.97s/it]
[Succeeded / Failed / Skipped / Total] 188 / 8 / 55 / 251:  84%|█████████████████▋   | 252/300 [45:56<08:45, 10.94s/it]
[Succeeded / Failed / Skipped / Total] 189 / 8 / 55 / 252:  84%|█████████████████▋   | 252/300 [45:56<08:45, 10.94s/it]
[Succeeded / Failed / Skipped / Total] 189 / 8 / 55 / 252:  84%|█████████████████▋   | 253/300 [46:04<08:33, 10.93s/it]
[Succeeded / Failed / Skipped / Total] 190 / 8 / 55 / 253:  84%|█████████████████▋   | 253/300 [46:04<08:33, 10.93s/it]
[Succeeded / Failed / Skipped / Total] 190 / 8 / 55 / 253:  85%|█████████████████▊   | 254/300 [46:12<08:22, 10.92s/it]
[Succeeded / Failed / Skipped / Total] 191 / 8 / 55 / 254:  85%|█████████████████▊   | 254/300 [46:12<08:22, 10.92s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 230    |
| Number of failed attacks:     | 10     |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 80.0%  |
| Accuracy under attack:        | 3.33%  |
| Attack success rate:          | 95.83% |
| Average perturbed word %:     | 9.09%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 150.35 |
+-------------------------------+--------+


#### CLIP

In [30]:
runAttack(clip_lr1_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr1'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr1ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:55<4:39:02, 56.00s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:56<4:39:21, 56.06s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [01:16<3:09:52, 38.23s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [01:16<3:09:54, 38.24s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [01:34<2:36:17, 31.57s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [01:34<2:36:18, 31.58s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:59<2:26:47, 29.76s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:59<2:26:49, 29.76s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 43 / 3 / 4 / 50:  17%|████▎                    | 51/300 [10:20<50:31, 12.18s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 4 / 51:  17%|████▎                    | 51/300 [10:20<50:31, 12.18s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 4 / 51:  17%|████▎                    | 52/300 [10:39<50:52, 12.31s/it]
[Succeeded / Failed / Skipped / Total] 44 / 4 / 4 / 52:  17%|████▎                    | 52/300 [10:39<50:52, 12.31s/it]
[Succeeded / Failed / Skipped / Total] 44 / 4 / 4 / 52:  18%|████▍                    | 53/300 [10:59<51:11, 12.44s/it]
[Succeeded / Failed / Skipped / Total] 45 / 4 / 4 / 53:  18%|████▍                    | 53/300 [10:59<51:12, 12.44s/it]
[Succeeded / Failed / Skipped / Total] 45 / 4 / 4 / 53:  18%|████▌                    | 54/300 [11:04<50:29, 12.31s/it]
[Succeeded / Failed / Skipped / Total] 46 / 4 / 4 / 54:  18%|████▌                    | 54/300 [11:04<50:29, 12.31s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 86 / 5 / 9 / 100:  34%|███████▋               | 101/300 [18:27<36:21, 10.96s/it]
[Succeeded / Failed / Skipped / Total] 87 / 5 / 9 / 101:  34%|███████▋               | 101/300 [18:27<36:21, 10.96s/it]
[Succeeded / Failed / Skipped / Total] 87 / 5 / 9 / 101:  34%|███████▊               | 102/300 [18:34<36:03, 10.93s/it]
[Succeeded / Failed / Skipped / Total] 88 / 5 / 9 / 102:  34%|███████▊               | 102/300 [18:34<36:03, 10.93s/it]
[Succeeded / Failed / Skipped / Total] 88 / 5 / 9 / 102:  34%|███████▉               | 103/300 [18:40<35:42, 10.87s/it]
[Succeeded / Failed / Skipped / Total] 89 / 5 / 9 / 103:  34%|███████▉               | 103/300 [18:40<35:42, 10.87s/it]
[Succeeded / Failed / Skipped / Total] 89 / 5 / 9 / 103:  35%|███████▉               | 104/300 [18:51<35:32, 10.88s/it]
[Succeeded / Failed / Skipped / Total] 90 / 5 / 9 / 104:  35%|███████▉               | 104/300 [18:51<35:32, 10.88s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 130 / 6 / 14 / 150:  50%|██████████▌          | 151/300 [27:01<26:39, 10.74s/it]
[Succeeded / Failed / Skipped / Total] 131 / 6 / 14 / 151:  50%|██████████▌          | 151/300 [27:01<26:39, 10.74s/it]
[Succeeded / Failed / Skipped / Total] 131 / 6 / 14 / 151:  51%|██████████▋          | 152/300 [27:09<26:26, 10.72s/it]
[Succeeded / Failed / Skipped / Total] 132 / 6 / 14 / 152:  51%|██████████▋          | 152/300 [27:09<26:26, 10.72s/it]
[Succeeded / Failed / Skipped / Total] 132 / 6 / 14 / 152:  51%|██████████▋          | 153/300 [27:12<26:08, 10.67s/it]
[Succeeded / Failed / Skipped / Total] 133 / 6 / 14 / 153:  51%|██████████▋          | 153/300 [27:12<26:08, 10.67s/it]
[Succeeded / Failed / Skipped / Total] 133 / 6 / 14 / 153:  51%|██████████▊          | 154/300 [27:13<25:48, 10.60s/it]
[Succeeded / Failed / Skipped / Total] 133 / 6 / 15 / 154:  51%|██████████▊          | 154/300 [27:13<25:48, 10.60s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 173 / 7 / 20 / 200:  67%|██████████████       | 201/300 [34:51<17:10, 10.41s/it]
[Succeeded / Failed / Skipped / Total] 174 / 7 / 20 / 201:  67%|██████████████       | 201/300 [34:51<17:10, 10.41s/it]
[Succeeded / Failed / Skipped / Total] 174 / 7 / 20 / 201:  67%|██████████████▏      | 202/300 [34:59<16:58, 10.40s/it]
[Succeeded / Failed / Skipped / Total] 175 / 7 / 20 / 202:  67%|██████████████▏      | 202/300 [34:59<16:58, 10.40s/it]
[Succeeded / Failed / Skipped / Total] 175 / 7 / 20 / 202:  68%|██████████████▏      | 203/300 [35:15<16:50, 10.42s/it]
[Succeeded / Failed / Skipped / Total] 176 / 7 / 20 / 203:  68%|██████████████▏      | 203/300 [35:15<16:50, 10.42s/it]
[Succeeded / Failed / Skipped / Total] 176 / 7 / 21 / 204:  68%|██████████████▎      | 204/300 [35:15<16:35, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 176 / 7 / 21 / 204:  68%|██████████████▎      | 205/300 [35:25<16:25, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 220 / 7 / 24 / 251:  84%|█████████████████▌   | 251/300 [43:16<08:26, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 220 / 7 / 24 / 251:  84%|█████████████████▌   | 251/300 [43:25<08:28, 10.38s/it]
[Succeeded / Failed / Skipped / Total] 220 / 7 / 24 / 251:  84%|█████████████████▋   | 252/300 [43:33<08:17, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 221 / 7 / 24 / 252:  84%|█████████████████▋   | 252/300 [43:33<08:17, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 221 / 7 / 24 / 252:  84%|█████████████████▋   | 253/300 [43:44<08:07, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 222 / 7 / 24 / 253:  84%|█████████████████▋   | 253/300 [43:44<08:07, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 222 / 7 / 24 / 253:  85%|█████████████████▊   | 254/300 [43:46<07:55, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 223 / 7 / 24 / 254:  85%|█████████████████▊   | 254/300 [43:46<07:55, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 262    |
| Number of failed attacks:     | 9      |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 3.0%   |
| Attack success rate:          | 96.68% |
| Average perturbed word %:     | 19.03% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 233.87 |
+-------------------------------+--------+


In [31]:
runAttack(clip_lr01_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr01'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr01ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:21<1:45:25, 21.16s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:21<1:45:34, 21.19s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:40<1:40:49, 20.30s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:40<1:40:51, 20.31s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:57<1:35:13, 19.24s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:57<1:35:14, 19.24s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:20<1:39:50, 20.24s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:20<1:39:51, 20.24s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 43 / 3 / 4 / 50:  17%|████▎                    | 51/300 [09:19<45:30, 10.97s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 4 / 51:  17%|████▎                    | 51/300 [09:19<45:30, 10.97s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 4 / 51:  17%|████▎                    | 52/300 [09:38<45:58, 11.12s/it]
[Succeeded / Failed / Skipped / Total] 44 / 4 / 4 / 52:  17%|████▎                    | 52/300 [09:38<45:58, 11.12s/it]
[Succeeded / Failed / Skipped / Total] 44 / 4 / 4 / 52:  18%|████▍                    | 53/300 [10:04<46:57, 11.41s/it]
[Succeeded / Failed / Skipped / Total] 45 / 4 / 4 / 53:  18%|████▍                    | 53/300 [10:04<46:57, 11.41s/it]
[Succeeded / Failed / Skipped / Total] 45 / 4 / 4 / 53:  18%|████▌                    | 54/300 [10:10<46:22, 11.31s/it]
[Succeeded / Failed / Skipped / Total] 46 / 4 / 4 / 54:  18%|████▌                    | 54/300 [10:10<46:22, 11.31s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 86 / 5 / 9 / 100:  34%|███████▋               | 101/300 [16:52<33:15, 10.03s/it]
[Succeeded / Failed / Skipped / Total] 87 / 5 / 9 / 101:  34%|███████▋               | 101/300 [16:52<33:15, 10.03s/it]
[Succeeded / Failed / Skipped / Total] 88 / 5 / 9 / 102:  34%|███████▊               | 102/300 [17:00<33:00, 10.00s/it]
[Succeeded / Failed / Skipped / Total] 88 / 5 / 9 / 102:  34%|███████▉               | 103/300 [17:05<32:42,  9.96s/it]
[Succeeded / Failed / Skipped / Total] 89 / 5 / 9 / 103:  34%|███████▉               | 103/300 [17:05<32:42,  9.96s/it]
[Succeeded / Failed / Skipped / Total] 89 / 5 / 9 / 103:  35%|███████▉               | 104/300 [17:16<32:33,  9.97s/it]
[Succeeded / Failed / Skipped / Total] 90 / 5 / 9 / 104:  35%|███████▉               | 104/300 [17:16<32:33,  9.97s/it]
[Succeeded / Failed / Skipped / Total] 90 / 5 / 9 / 104:  35%|████████               | 105/300 [17:18<32:09,  9.90s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 130 / 6 / 14 / 150:  50%|██████████▌          | 151/300 [25:05<24:45,  9.97s/it]
[Succeeded / Failed / Skipped / Total] 131 / 6 / 14 / 151:  50%|██████████▌          | 151/300 [25:05<24:45,  9.97s/it]
[Succeeded / Failed / Skipped / Total] 131 / 6 / 14 / 151:  51%|██████████▋          | 152/300 [25:14<24:34,  9.96s/it]
[Succeeded / Failed / Skipped / Total] 132 / 6 / 14 / 152:  51%|██████████▋          | 152/300 [25:14<24:34,  9.96s/it]
[Succeeded / Failed / Skipped / Total] 132 / 6 / 14 / 152:  51%|██████████▋          | 153/300 [25:17<24:18,  9.92s/it]
[Succeeded / Failed / Skipped / Total] 133 / 6 / 14 / 153:  51%|██████████▋          | 153/300 [25:17<24:18,  9.92s/it]
[Succeeded / Failed / Skipped / Total] 133 / 6 / 15 / 154:  51%|██████████▊          | 154/300 [25:17<23:58,  9.86s/it]
[Succeeded / Failed / Skipped / Total] 133 / 6 / 15 / 154:  52%|██████████▊          | 155/300 [25:24<23:46,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 173 / 7 / 20 / 200:  67%|██████████████       | 201/300 [32:42<16:06,  9.76s/it]
[Succeeded / Failed / Skipped / Total] 174 / 7 / 20 / 201:  67%|██████████████       | 201/300 [32:42<16:06,  9.76s/it]
[Succeeded / Failed / Skipped / Total] 174 / 7 / 20 / 201:  67%|██████████████▏      | 202/300 [32:50<15:55,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 175 / 7 / 20 / 202:  67%|██████████████▏      | 202/300 [32:50<15:55,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 175 / 7 / 20 / 202:  68%|██████████████▏      | 203/300 [33:06<15:48,  9.78s/it]
[Succeeded / Failed / Skipped / Total] 176 / 7 / 20 / 203:  68%|██████████████▏      | 203/300 [33:06<15:49,  9.78s/it]
[Succeeded / Failed / Skipped / Total] 176 / 7 / 21 / 204:  68%|██████████████▎      | 204/300 [33:06<15:34,  9.74s/it]
[Succeeded / Failed / Skipped / Total] 176 / 7 / 21 / 204:  68%|██████████████▎      | 205/300 [33:15<15:24,  9.73s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 220 / 7 / 24 / 251:  84%|█████████████████▌   | 251/300 [41:00<08:00,  9.80s/it]
[Succeeded / Failed / Skipped / Total] 220 / 7 / 24 / 251:  84%|█████████████████▌   | 251/300 [41:08<08:01,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 220 / 7 / 24 / 251:  84%|█████████████████▋   | 252/300 [41:18<07:52,  9.83s/it]
[Succeeded / Failed / Skipped / Total] 221 / 7 / 24 / 252:  84%|█████████████████▋   | 252/300 [41:18<07:52,  9.83s/it]
[Succeeded / Failed / Skipped / Total] 221 / 7 / 24 / 252:  84%|█████████████████▋   | 253/300 [41:27<07:42,  9.83s/it]
[Succeeded / Failed / Skipped / Total] 222 / 7 / 24 / 253:  84%|█████████████████▋   | 253/300 [41:27<07:42,  9.83s/it]
[Succeeded / Failed / Skipped / Total] 222 / 7 / 24 / 253:  85%|█████████████████▊   | 254/300 [41:30<07:31,  9.80s/it]
[Succeeded / Failed / Skipped / Total] 223 / 7 / 24 / 254:  85%|█████████████████▊   | 254/300 [41:30<07:31,  9.80s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 262    |
| Number of failed attacks:     | 9      |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 3.0%   |
| Attack success rate:          | 96.68% |
| Average perturbed word %:     | 19.19% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 234.7  |
+-------------------------------+--------+


In [32]:
runAttack(clip_lr10_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr10'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr10ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:22<1:50:49, 22.24s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:22<1:50:54, 22.26s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:43<1:46:53, 21.52s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:43<1:46:55, 21.53s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [01:00<1:40:00, 20.20s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [01:00<1:40:01, 20.21s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:24<1:44:08, 21.11s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:24<1:44:09, 21.11s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 43 / 3 / 4 / 50:  17%|████▎                    | 51/300 [09:50<48:03, 11.58s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 4 / 51:  17%|████▎                    | 51/300 [09:50<48:03, 11.58s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 4 / 51:  17%|████▎                    | 52/300 [10:20<49:18, 11.93s/it]
[Succeeded / Failed / Skipped / Total] 44 / 4 / 4 / 52:  17%|████▎                    | 52/300 [10:20<49:18, 11.93s/it]
[Succeeded / Failed / Skipped / Total] 44 / 4 / 4 / 52:  18%|████▍                    | 53/300 [10:42<49:53, 12.12s/it]
[Succeeded / Failed / Skipped / Total] 45 / 4 / 4 / 53:  18%|████▍                    | 53/300 [10:42<49:53, 12.12s/it]
[Succeeded / Failed / Skipped / Total] 45 / 4 / 4 / 53:  18%|████▌                    | 54/300 [10:48<49:12, 12.00s/it]
[Succeeded / Failed / Skipped / Total] 46 / 4 / 4 / 54:  18%|████▌                    | 54/300 [10:48<49:12, 12.00s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 86 / 5 / 9 / 100:  34%|███████▋               | 101/300 [17:27<34:23, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 87 / 5 / 9 / 101:  34%|███████▋               | 101/300 [17:27<34:23, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 87 / 5 / 9 / 101:  34%|███████▊               | 102/300 [17:34<34:06, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 88 / 5 / 9 / 102:  34%|███████▊               | 102/300 [17:34<34:06, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 88 / 5 / 9 / 102:  34%|███████▉               | 103/300 [17:39<33:47, 10.29s/it]
[Succeeded / Failed / Skipped / Total] 89 / 5 / 9 / 103:  34%|███████▉               | 103/300 [17:39<33:47, 10.29s/it]
[Succeeded / Failed / Skipped / Total] 89 / 5 / 9 / 103:  35%|███████▉               | 104/300 [17:50<33:36, 10.29s/it]
[Succeeded / Failed / Skipped / Total] 90 / 5 / 9 / 104:  35%|███████▉               | 104/300 [17:50<33:36, 10.29s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 130 / 6 / 14 / 150:  50%|██████████▌          | 151/300 [25:39<25:18, 10.19s/it]
[Succeeded / Failed / Skipped / Total] 131 / 6 / 14 / 151:  50%|██████████▌          | 151/300 [25:39<25:18, 10.19s/it]
[Succeeded / Failed / Skipped / Total] 131 / 6 / 14 / 151:  51%|██████████▋          | 152/300 [25:47<25:06, 10.18s/it]
[Succeeded / Failed / Skipped / Total] 132 / 6 / 14 / 152:  51%|██████████▋          | 152/300 [25:47<25:06, 10.18s/it]
[Succeeded / Failed / Skipped / Total] 132 / 6 / 14 / 152:  51%|██████████▋          | 153/300 [25:50<24:49, 10.13s/it]
[Succeeded / Failed / Skipped / Total] 133 / 6 / 14 / 153:  51%|██████████▋          | 153/300 [25:50<24:49, 10.13s/it]
[Succeeded / Failed / Skipped / Total] 133 / 6 / 15 / 154:  51%|██████████▊          | 154/300 [25:50<24:29, 10.07s/it]
[Succeeded / Failed / Skipped / Total] 133 / 6 / 15 / 154:  52%|██████████▊          | 155/300 [25:56<24:16, 10.04s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 173 / 7 / 20 / 200:  67%|██████████████       | 201/300 [33:10<16:20,  9.90s/it]
[Succeeded / Failed / Skipped / Total] 174 / 7 / 20 / 201:  67%|██████████████       | 201/300 [33:10<16:20,  9.90s/it]
[Succeeded / Failed / Skipped / Total] 174 / 7 / 20 / 201:  67%|██████████████▏      | 202/300 [33:18<16:09,  9.89s/it]
[Succeeded / Failed / Skipped / Total] 175 / 7 / 20 / 202:  67%|██████████████▏      | 202/300 [33:18<16:09,  9.89s/it]
[Succeeded / Failed / Skipped / Total] 175 / 7 / 20 / 202:  68%|██████████████▏      | 203/300 [33:33<16:02,  9.92s/it]
[Succeeded / Failed / Skipped / Total] 176 / 7 / 20 / 203:  68%|██████████████▏      | 203/300 [33:33<16:02,  9.92s/it]
[Succeeded / Failed / Skipped / Total] 176 / 7 / 21 / 204:  68%|██████████████▎      | 204/300 [33:33<15:47,  9.87s/it]
[Succeeded / Failed / Skipped / Total] 176 / 7 / 21 / 204:  68%|██████████████▎      | 205/300 [33:42<15:37,  9.87s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 220 / 7 / 24 / 251:  84%|█████████████████▌   | 251/300 [41:25<08:05,  9.90s/it]
[Succeeded / Failed / Skipped / Total] 220 / 7 / 24 / 251:  84%|█████████████████▌   | 251/300 [41:36<08:07,  9.95s/it]
[Succeeded / Failed / Skipped / Total] 220 / 7 / 24 / 251:  84%|█████████████████▋   | 252/300 [41:43<07:56,  9.93s/it]
[Succeeded / Failed / Skipped / Total] 221 / 7 / 24 / 252:  84%|█████████████████▋   | 252/300 [41:43<07:56,  9.93s/it]
[Succeeded / Failed / Skipped / Total] 221 / 7 / 24 / 252:  84%|█████████████████▋   | 253/300 [41:52<07:46,  9.93s/it]
[Succeeded / Failed / Skipped / Total] 222 / 7 / 24 / 253:  84%|█████████████████▋   | 253/300 [41:52<07:46,  9.93s/it]
[Succeeded / Failed / Skipped / Total] 222 / 7 / 24 / 253:  85%|█████████████████▊   | 254/300 [41:55<07:35,  9.90s/it]
[Succeeded / Failed / Skipped / Total] 223 / 7 / 24 / 254:  85%|█████████████████▊   | 254/300 [41:55<07:35,  9.90s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 262    |
| Number of failed attacks:     | 9      |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 3.0%   |
| Attack success rate:          | 96.68% |
| Average perturbed word %:     | 19.06% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 233.89 |
+-------------------------------+--------+


In [33]:
runAttack(clip_rf7_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf7ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:13<1:07:06, 13.46s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:13<1:07:10, 13.48s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:32<1:20:12, 16.15s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:32<1:20:16, 16.16s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:40<1:06:04, 13.35s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:40<1:06:06, 13.35s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:04<1:19:39, 16.15s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:04<1:19:42, 16.16s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 33 / 14 / 3 / 50:  17%|████                    | 51/300 [12:05<59:01, 14.22s/it]
[Succeeded / Failed / Skipped / Total] 33 / 15 / 3 / 51:  17%|████                    | 51/300 [12:05<59:01, 14.22s/it]
[Succeeded / Failed / Skipped / Total] 33 / 15 / 3 / 51:  17%|████▏                   | 52/300 [12:23<59:08, 14.31s/it]
[Succeeded / Failed / Skipped / Total] 33 / 16 / 3 / 52:  17%|████▏                   | 52/300 [12:23<59:08, 14.31s/it]
[Succeeded / Failed / Skipped / Total] 33 / 16 / 3 / 52:  18%|███▉                  | 53/300 [12:59<1:00:30, 14.70s/it]
[Succeeded / Failed / Skipped / Total] 33 / 17 / 3 / 53:  18%|███▉                  | 53/300 [12:59<1:00:30, 14.70s/it]
[Succeeded / Failed / Skipped / Total] 33 / 17 / 3 / 53:  18%|████▎                   | 54/300 [13:07<59:47, 14.59s/it]
[Succeeded / Failed / Skipped / Total] 34 / 17 / 3 / 54:  18%|████▎                   | 54/300 [13:07<59:48, 14.59s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 68 / 21 / 11 / 100:  34%|███████              | 101/300 [21:49<43:00, 12.97s/it]
[Succeeded / Failed / Skipped / Total] 69 / 21 / 11 / 101:  34%|███████              | 101/300 [21:49<43:00, 12.97s/it]
[Succeeded / Failed / Skipped / Total] 69 / 21 / 11 / 101:  34%|███████              | 101/300 [22:01<43:24, 13.09s/it]
[Succeeded / Failed / Skipped / Total] 69 / 21 / 11 / 101:  34%|███████▏             | 102/300 [22:15<43:12, 13.10s/it]
[Succeeded / Failed / Skipped / Total] 70 / 21 / 11 / 102:  34%|███████▏             | 102/300 [22:15<43:12, 13.10s/it]
[Succeeded / Failed / Skipped / Total] 70 / 21 / 11 / 102:  34%|███████▏             | 103/300 [22:23<42:48, 13.04s/it]
[Succeeded / Failed / Skipped / Total] 71 / 21 / 11 / 103:  34%|███████▏             | 103/300 [22:23<42:48, 13.04s/it]
[Succeeded / Failed / Skipped / Total] 71 / 21 / 11 / 103:  35%|███████▎             | 104/300 [22:42<42:48, 13.11s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 103 / 31 / 16 / 150:  50%|██████████          | 151/300 [33:10<32:44, 13.18s/it]
[Succeeded / Failed / Skipped / Total] 104 / 31 / 16 / 151:  50%|██████████          | 151/300 [33:10<32:44, 13.18s/it]
[Succeeded / Failed / Skipped / Total] 104 / 31 / 16 / 151:  51%|██████████▏         | 152/300 [33:27<32:34, 13.21s/it]
[Succeeded / Failed / Skipped / Total] 105 / 31 / 16 / 152:  51%|██████████▏         | 152/300 [33:27<32:34, 13.21s/it]
[Succeeded / Failed / Skipped / Total] 105 / 31 / 16 / 152:  51%|██████████▏         | 153/300 [33:38<32:19, 13.19s/it]
[Succeeded / Failed / Skipped / Total] 106 / 31 / 16 / 153:  51%|██████████▏         | 153/300 [33:38<32:19, 13.19s/it]
[Succeeded / Failed / Skipped / Total] 106 / 31 / 17 / 154:  51%|██████████▎         | 154/300 [33:38<31:53, 13.11s/it]
[Succeeded / Failed / Skipped / Total] 106 / 31 / 17 / 154:  52%|██████████▎         | 155/300 [33:47<31:37, 13.08s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 130 / 39 / 31 / 200:  67%|█████████████▍      | 201/300 [42:08<20:45, 12.58s/it]
[Succeeded / Failed / Skipped / Total] 131 / 39 / 31 / 201:  67%|█████████████▍      | 201/300 [42:08<20:45, 12.58s/it]
[Succeeded / Failed / Skipped / Total] 131 / 39 / 31 / 201:  67%|█████████████▍      | 202/300 [42:20<20:32, 12.58s/it]
[Succeeded / Failed / Skipped / Total] 132 / 39 / 31 / 202:  67%|█████████████▍      | 202/300 [42:20<20:32, 12.58s/it]
[Succeeded / Failed / Skipped / Total] 132 / 39 / 31 / 202:  68%|█████████████▌      | 203/300 [42:51<20:28, 12.67s/it]
[Succeeded / Failed / Skipped / Total] 132 / 40 / 31 / 203:  68%|█████████████▌      | 203/300 [42:51<20:28, 12.67s/it]
[Succeeded / Failed / Skipped / Total] 132 / 40 / 32 / 204:  68%|█████████████▌      | 204/300 [42:51<20:10, 12.61s/it]
[Succeeded / Failed / Skipped / Total] 132 / 40 / 32 / 204:  68%|█████████████▋      | 205/300 [43:09<20:00, 12.63s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 163 / 50 / 38 / 251:  84%|████████████████▋   | 251/300 [52:57<10:20, 12.66s/it]
[Succeeded / Failed / Skipped / Total] 163 / 50 / 38 / 251:  84%|████████████████▋   | 251/300 [53:12<10:23, 12.72s/it]
[Succeeded / Failed / Skipped / Total] 163 / 50 / 38 / 251:  84%|████████████████▊   | 252/300 [53:14<10:08, 12.68s/it]
[Succeeded / Failed / Skipped / Total] 164 / 50 / 38 / 252:  84%|████████████████▊   | 252/300 [53:14<10:08, 12.68s/it]
[Succeeded / Failed / Skipped / Total] 164 / 50 / 38 / 252:  84%|████████████████▊   | 253/300 [53:30<09:56, 12.69s/it]
[Succeeded / Failed / Skipped / Total] 165 / 50 / 38 / 253:  84%|████████████████▊   | 253/300 [53:30<09:56, 12.69s/it]
[Succeeded / Failed / Skipped / Total] 165 / 50 / 38 / 253:  85%|████████████████▉   | 254/300 [53:34<09:42, 12.66s/it]
[Succeeded / Failed / Skipped / Total] 166 / 50 / 38 / 254:  85%|████████████████▉   | 254/300 [53:34<09:42, 12.66s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 197    |
| Number of failed attacks:     | 60     |
| Number of skipped attacks:    | 43     |
| Original accuracy:            | 85.67% |
| Accuracy under attack:        | 20.0%  |
| Attack success rate:          | 76.65% |
| Average perturbed word %:     | 18.44% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 317.6  |
+-------------------------------+--------+


In [34]:
runAttack(clip_rf14_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf14'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf14ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:13<1:09:07, 13.87s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:13<1:09:12, 13.89s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:38<1:35:17, 19.19s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▏                         | 2/300 [00:38<1:35:20, 19.20s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▎                         | 3/300 [00:45<1:14:42, 15.09s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 3/300 [00:45<1:14:44, 15.10s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 4/300 [01:09<1:25:53, 17.41s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                         | 4/300 [01:09<1:25:54, 17.42s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 30 / 18 / 2 / 50:  17%|███▋                  | 51/300 [12:56<1:03:11, 15.23s/it]
[Succeeded / Failed / Skipped / Total] 31 / 18 / 2 / 51:  17%|███▋                  | 51/300 [12:56<1:03:11, 15.23s/it]
[Succeeded / Failed / Skipped / Total] 31 / 18 / 2 / 51:  17%|███▊                  | 52/300 [13:11<1:02:56, 15.23s/it]
[Succeeded / Failed / Skipped / Total] 32 / 18 / 2 / 52:  17%|███▊                  | 52/300 [13:11<1:02:56, 15.23s/it]
[Succeeded / Failed / Skipped / Total] 32 / 18 / 2 / 52:  18%|███▉                  | 53/300 [13:43<1:03:59, 15.55s/it]
[Succeeded / Failed / Skipped / Total] 32 / 19 / 2 / 53:  18%|███▉                  | 53/300 [13:43<1:04:00, 15.55s/it]
[Succeeded / Failed / Skipped / Total] 32 / 19 / 2 / 53:  18%|███▉                  | 54/300 [14:01<1:03:52, 15.58s/it]
[Succeeded / Failed / Skipped / Total] 33 / 19 / 2 / 54:  18%|███▉                  | 54/300 [14:01<1:03:52, 15.58s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 62 / 31 / 7 / 100:  34%|███████▍              | 101/300 [25:36<50:28, 15.22s/it]
[Succeeded / Failed / Skipped / Total] 63 / 31 / 7 / 101:  34%|███████▍              | 101/300 [25:36<50:28, 15.22s/it]
[Succeeded / Failed / Skipped / Total] 64 / 31 / 7 / 102:  34%|███████▍              | 102/300 [25:50<50:09, 15.20s/it]
[Succeeded / Failed / Skipped / Total] 64 / 31 / 7 / 102:  34%|███████▍              | 102/300 [25:51<50:11, 15.21s/it]
[Succeeded / Failed / Skipped / Total] 64 / 31 / 7 / 102:  34%|███████▌              | 103/300 [25:57<49:39, 15.13s/it]
[Succeeded / Failed / Skipped / Total] 65 / 31 / 7 / 103:  34%|███████▌              | 103/300 [25:57<49:39, 15.13s/it]
[Succeeded / Failed / Skipped / Total] 65 / 31 / 7 / 103:  35%|███████▋              | 104/300 [26:15<49:28, 15.14s/it]
[Succeeded / Failed / Skipped / Total] 65 / 32 / 7 / 104:  35%|███████▋              | 104/300 [26:15<49:28, 15.15s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 93 / 44 / 13 / 150:  50%|██████████▌          | 151/300 [38:11<37:40, 15.17s/it]
[Succeeded / Failed / Skipped / Total] 94 / 44 / 13 / 151:  50%|██████████▌          | 151/300 [38:11<37:40, 15.17s/it]
[Succeeded / Failed / Skipped / Total] 94 / 44 / 13 / 151:  51%|██████████▋          | 152/300 [38:45<37:44, 15.30s/it]
[Succeeded / Failed / Skipped / Total] 94 / 45 / 13 / 152:  51%|██████████▋          | 152/300 [38:45<37:44, 15.30s/it]
[Succeeded / Failed / Skipped / Total] 94 / 45 / 13 / 152:  51%|██████████▋          | 153/300 [38:53<37:21, 15.25s/it]
[Succeeded / Failed / Skipped / Total] 95 / 45 / 13 / 153:  51%|██████████▋          | 153/300 [38:53<37:21, 15.25s/it]
[Succeeded / Failed / Skipped / Total] 95 / 45 / 13 / 153:  51%|██████████▊          | 154/300 [38:58<36:56, 15.18s/it]
[Succeeded / Failed / Skipped / Total] 96 / 45 / 13 / 154:  51%|██████████▊          | 154/300 [38:58<36:56, 15.18s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 121 / 56 / 23 / 200:  67%|█████████████▍      | 201/300 [48:32<23:54, 14.49s/it]
[Succeeded / Failed / Skipped / Total] 122 / 56 / 23 / 201:  67%|█████████████▍      | 201/300 [48:32<23:54, 14.49s/it]
[Succeeded / Failed / Skipped / Total] 122 / 56 / 23 / 201:  67%|█████████████▍      | 202/300 [48:41<23:37, 14.46s/it]
[Succeeded / Failed / Skipped / Total] 123 / 56 / 23 / 202:  67%|█████████████▍      | 202/300 [48:41<23:37, 14.46s/it]
[Succeeded / Failed / Skipped / Total] 123 / 56 / 23 / 202:  68%|█████████████▌      | 203/300 [49:11<23:30, 14.54s/it]
[Succeeded / Failed / Skipped / Total] 123 / 57 / 23 / 203:  68%|█████████████▌      | 203/300 [49:11<23:30, 14.54s/it]
[Succeeded / Failed / Skipped / Total] 123 / 57 / 24 / 204:  68%|█████████████▌      | 204/300 [49:11<23:09, 14.47s/it]
[Succeeded / Failed / Skipped / Total] 123 / 57 / 24 / 204:  68%|█████████████▋      | 205/300 [49:28<22:55, 14.48s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 151 / 71 / 28 / 250:  83%|███████████████   | 250/300 [1:00:52<12:10, 14.61s/it]
[Succeeded / Failed / Skipped / Total] 151 / 71 / 28 / 250:  84%|███████████████   | 251/300 [1:00:52<11:52, 14.55s/it]
[Succeeded / Failed / Skipped / Total] 152 / 71 / 28 / 251:  84%|███████████████   | 251/300 [1:00:52<11:52, 14.55s/it]
[Succeeded / Failed / Skipped / Total] 152 / 71 / 28 / 251:  84%|███████████████   | 252/300 [1:01:10<11:39, 14.56s/it]
[Succeeded / Failed / Skipped / Total] 152 / 72 / 28 / 252:  84%|███████████████   | 252/300 [1:01:10<11:39, 14.56s/it]
[Succeeded / Failed / Skipped / Total] 152 / 72 / 28 / 252:  84%|███████████████▏  | 253/300 [1:01:39<11:27, 14.62s/it]
[Succeeded / Failed / Skipped / Total] 153 / 72 / 28 / 253:  84%|███████████████▏  | 253/300 [1:01:39<11:27, 14.62s/it]
[Succeeded / Failed / Skipped / Total] 153 / 72 / 28 / 253:  85%|███████████████▏  | 254/300 [1:01:43<11:10, 14.58s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 176    |
| Number of failed attacks:     | 91     |
| Number of skipped attacks:    | 33     |
| Original accuracy:            | 89.0%  |
| Accuracy under attack:        | 30.33% |
| Attack success rate:          | 65.92% |
| Average perturbed word %:     | 17.57% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 355.25 |
+-------------------------------+--------+


In [35]:
runAttack(clip_rf30_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf30'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf30ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:16<1:23:37, 16.78s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:16<1:23:46, 16.81s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:42<1:45:37, 21.27s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▏                         | 2/300 [00:42<1:45:37, 21.27s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▎                         | 3/300 [01:09<1:55:13, 23.28s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 3/300 [01:09<1:55:14, 23.28s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 4/300 [01:36<1:58:43, 24.07s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                         | 4/300 [01:36<1:58:47, 24.08s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 29 / 19 / 2 / 50:  17%|███▋                  | 51/300 [14:30<1:10:51, 17.08s/it]
[Succeeded / Failed / Skipped / Total] 29 / 20 / 2 / 51:  17%|███▋                  | 51/300 [14:30<1:10:52, 17.08s/it]
[Succeeded / Failed / Skipped / Total] 29 / 20 / 2 / 51:  17%|███▊                  | 52/300 [14:47<1:10:32, 17.07s/it]
[Succeeded / Failed / Skipped / Total] 30 / 20 / 2 / 52:  17%|███▊                  | 52/300 [14:47<1:10:32, 17.07s/it]
[Succeeded / Failed / Skipped / Total] 30 / 20 / 2 / 52:  18%|███▉                  | 53/300 [15:20<1:11:32, 17.38s/it]
[Succeeded / Failed / Skipped / Total] 30 / 21 / 2 / 53:  18%|███▉                  | 53/300 [15:20<1:11:32, 17.38s/it]
[Succeeded / Failed / Skipped / Total] 30 / 21 / 2 / 53:  18%|███▉                  | 54/300 [15:44<1:11:41, 17.49s/it]
[Succeeded / Failed / Skipped / Total] 30 / 22 / 2 / 54:  18%|███▉                  | 54/300 [15:44<1:11:42, 17.49s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 59 / 33 / 8 / 100:  34%|███████▍              | 101/300 [27:17<53:45, 16.21s/it]
[Succeeded / Failed / Skipped / Total] 60 / 33 / 8 / 101:  34%|███████▍              | 101/300 [27:17<53:45, 16.21s/it]
[Succeeded / Failed / Skipped / Total] 60 / 33 / 8 / 101:  34%|███████▍              | 101/300 [27:36<54:24, 16.40s/it]
[Succeeded / Failed / Skipped / Total] 60 / 33 / 8 / 101:  34%|███████▍              | 102/300 [27:41<53:45, 16.29s/it]
[Succeeded / Failed / Skipped / Total] 60 / 34 / 8 / 102:  34%|███████▍              | 102/300 [27:41<53:45, 16.29s/it]
[Succeeded / Failed / Skipped / Total] 60 / 34 / 8 / 102:  34%|███████▌              | 103/300 [27:59<53:32, 16.31s/it]
[Succeeded / Failed / Skipped / Total] 61 / 34 / 8 / 103:  34%|███████▌              | 103/300 [27:59<53:32, 16.31s/it]
[Succeeded / Failed / Skipped / Total] 61 / 34 / 8 / 103:  35%|███████▋              | 104/300 [28:17<53:19, 16.32s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 91 / 47 / 12 / 150:  50%|██████████▌          | 151/300 [39:42<39:11, 15.78s/it]
[Succeeded / Failed / Skipped / Total] 92 / 47 / 12 / 151:  50%|██████████▌          | 151/300 [39:42<39:11, 15.78s/it]
[Succeeded / Failed / Skipped / Total] 92 / 47 / 12 / 151:  51%|██████████▋          | 152/300 [40:01<38:57, 15.80s/it]
[Succeeded / Failed / Skipped / Total] 93 / 47 / 12 / 152:  51%|██████████▋          | 152/300 [40:01<38:57, 15.80s/it]
[Succeeded / Failed / Skipped / Total] 93 / 47 / 12 / 152:  51%|██████████▋          | 153/300 [40:22<38:47, 15.84s/it]
[Succeeded / Failed / Skipped / Total] 93 / 48 / 12 / 153:  51%|██████████▋          | 153/300 [40:22<38:47, 15.84s/it]
[Succeeded / Failed / Skipped / Total] 93 / 48 / 12 / 153:  51%|██████████▊          | 154/300 [40:26<38:20, 15.75s/it]
[Succeeded / Failed / Skipped / Total] 94 / 48 / 12 / 154:  51%|██████████▊          | 154/300 [40:26<38:20, 15.75s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 117 / 62 / 21 / 200:  67%|█████████████▍      | 201/300 [50:50<25:02, 15.18s/it]
[Succeeded / Failed / Skipped / Total] 117 / 63 / 21 / 201:  67%|█████████████▍      | 201/300 [50:50<25:02, 15.18s/it]
[Succeeded / Failed / Skipped / Total] 117 / 63 / 21 / 201:  67%|█████████████▍      | 202/300 [51:09<24:49, 15.20s/it]
[Succeeded / Failed / Skipped / Total] 118 / 63 / 21 / 202:  67%|█████████████▍      | 202/300 [51:09<24:49, 15.20s/it]
[Succeeded / Failed / Skipped / Total] 118 / 63 / 21 / 202:  68%|█████████████▌      | 203/300 [51:40<24:41, 15.27s/it]
[Succeeded / Failed / Skipped / Total] 118 / 64 / 21 / 203:  68%|█████████████▌      | 203/300 [51:40<24:41, 15.27s/it]
[Succeeded / Failed / Skipped / Total] 118 / 64 / 22 / 204:  68%|█████████████▌      | 204/300 [51:40<24:18, 15.20s/it]
[Succeeded / Failed / Skipped / Total] 118 / 64 / 22 / 204:  68%|█████████████▋      | 205/300 [52:03<24:07, 15.24s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 145 / 79 / 26 / 250:  84%|███████████████   | 251/300 [1:03:31<12:24, 15.18s/it]
[Succeeded / Failed / Skipped / Total] 146 / 79 / 26 / 251:  84%|███████████████   | 251/300 [1:03:31<12:24, 15.18s/it]
[Succeeded / Failed / Skipped / Total] 146 / 79 / 26 / 251:  84%|███████████████   | 252/300 [1:03:49<12:09, 15.20s/it]
[Succeeded / Failed / Skipped / Total] 146 / 80 / 26 / 252:  84%|███████████████   | 252/300 [1:03:49<12:09, 15.20s/it]
[Succeeded / Failed / Skipped / Total] 146 / 80 / 26 / 252:  84%|███████████████▏  | 253/300 [1:04:20<11:57, 15.26s/it]
[Succeeded / Failed / Skipped / Total] 147 / 80 / 26 / 253:  84%|███████████████▏  | 253/300 [1:04:20<11:57, 15.26s/it]
[Succeeded / Failed / Skipped / Total] 147 / 80 / 26 / 253:  85%|███████████████▏  | 254/300 [1:04:23<11:39, 15.21s/it]
[Succeeded / Failed / Skipped / Total] 148 / 80 / 26 / 254:  85%|███████████████▏  | 254/300 [1:04:23<11:39, 15.21s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 170    |
| Number of failed attacks:     | 100    |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 33.33% |
| Attack success rate:          | 62.96% |
| Average perturbed word %:     | 16.18% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 365.65 |
+-------------------------------+--------+


In [36]:
runAttack(clip_knn7_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn7ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                           | 1/300 [21:18<106:12:37, 1278.79s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|                      | 1/300 [21:18<106:12:41, 1278.80s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   1%|▏                       | 2/300 [21:43<53:56:33, 651.66s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▏                       | 2/300 [21:43<53:56:33, 651.66s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▏                       | 3/300 [22:22<36:55:40, 447.61s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▏                       | 3/300 [22:22<36:55:41, 447.62s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                       | 4/300 [22:50<28:10:18, 342.63s/it]
[Succeeded / Failed / Skipped / Total] 0 / 4 / 0 / 4:   1%|▎                       | 4/300 [22:50<28:10:19, 342.63s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 5 / 44 / 1 / 50:  17%|███▉                   | 51/300 [44:08<3:35:33, 51.94s/it]
[Succeeded / Failed / Skipped / Total] 5 / 45 / 1 / 51:  17%|███▉                   | 51/300 [44:09<3:35:33, 51.94s/it]
[Succeeded / Failed / Skipped / Total] 5 / 45 / 1 / 51:  17%|███▉                   | 52/300 [44:34<3:32:36, 51.44s/it]
[Succeeded / Failed / Skipped / Total] 5 / 46 / 1 / 52:  17%|███▉                   | 52/300 [44:34<3:32:36, 51.44s/it]
[Succeeded / Failed / Skipped / Total] 5 / 46 / 1 / 52:  18%|████                   | 53/300 [45:13<3:30:47, 51.20s/it]
[Succeeded / Failed / Skipped / Total] 5 / 47 / 1 / 53:  18%|████                   | 53/300 [45:13<3:30:47, 51.20s/it]
[Succeeded / Failed / Skipped / Total] 5 / 47 / 1 / 53:  18%|████▏                  | 54/300 [45:41<3:28:09, 50.77s/it]
[Succeeded / Failed / Skipped / Total] 5 / 48 / 1 / 54:  18%|████▏                  | 54/300 [45:41<3:28:09, 50.77s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 18 / 78 / 4 / 100:  34%|██████            | 101/300 [1:06:39<2:11:20, 39.60s/it]
[Succeeded / Failed / Skipped / Total] 18 / 79 / 4 / 101:  34%|██████            | 101/300 [1:06:39<2:11:20, 39.60s/it]
[Succeeded / Failed / Skipped / Total] 18 / 79 / 4 / 101:  34%|██████            | 102/300 [1:07:07<2:10:18, 39.49s/it]
[Succeeded / Failed / Skipped / Total] 18 / 80 / 4 / 102:  34%|██████            | 102/300 [1:07:07<2:10:18, 39.49s/it]
[Succeeded / Failed / Skipped / Total] 18 / 80 / 4 / 102:  34%|██████▏           | 103/300 [1:07:56<2:09:57, 39.58s/it]
[Succeeded / Failed / Skipped / Total] 18 / 81 / 4 / 103:  34%|██████▏           | 103/300 [1:07:56<2:09:57, 39.58s/it]
[Succeeded / Failed / Skipped / Total] 18 / 81 / 4 / 103:  35%|██████▏           | 104/300 [1:08:18<2:08:43, 39.41s/it]
[Succeeded / Failed / Skipped / Total] 18 / 82 / 4 / 104:  35%|██████▏           | 104/300 [1:08:18<2:08:43, 39.41s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 25 / 118 / 7 / 150:  50%|████████▌        | 151/300 [1:29:13<1:28:02, 35.46s/it]
[Succeeded / Failed / Skipped / Total] 26 / 118 / 7 / 151:  50%|████████▌        | 151/300 [1:29:13<1:28:02, 35.46s/it]
[Succeeded / Failed / Skipped / Total] 26 / 118 / 7 / 151:  51%|████████▌        | 152/300 [1:29:50<1:27:28, 35.46s/it]
[Succeeded / Failed / Skipped / Total] 26 / 119 / 7 / 152:  51%|████████▌        | 152/300 [1:29:50<1:27:28, 35.46s/it]
[Succeeded / Failed / Skipped / Total] 26 / 119 / 7 / 152:  51%|████████▋        | 153/300 [1:30:15<1:26:42, 35.39s/it]
[Succeeded / Failed / Skipped / Total] 26 / 120 / 7 / 153:  51%|████████▋        | 153/300 [1:30:15<1:26:42, 35.39s/it]
[Succeeded / Failed / Skipped / Total] 26 / 120 / 7 / 153:  51%|████████▋        | 154/300 [1:30:15<1:25:34, 35.16s/it]
[Succeeded / Failed / Skipped / Total] 26 / 120 / 8 / 154:  51%|████████▋        | 154/300 [1:30:15<1:25:34, 35.17s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 35 / 151 / 14 / 200:  67%|████████████      | 201/300 [1:48:30<53:26, 32.39s/it]
[Succeeded / Failed / Skipped / Total] 35 / 152 / 14 / 201:  67%|████████████      | 201/300 [1:48:30<53:26, 32.39s/it]
[Succeeded / Failed / Skipped / Total] 35 / 152 / 14 / 201:  67%|████████████      | 202/300 [1:48:52<52:49, 32.34s/it]
[Succeeded / Failed / Skipped / Total] 35 / 153 / 14 / 202:  67%|████████████      | 202/300 [1:48:52<52:49, 32.34s/it]
[Succeeded / Failed / Skipped / Total] 35 / 153 / 14 / 202:  68%|████████████▏     | 203/300 [1:49:27<52:18, 32.35s/it]
[Succeeded / Failed / Skipped / Total] 35 / 154 / 14 / 203:  68%|████████████▏     | 203/300 [1:49:27<52:18, 32.35s/it]
[Succeeded / Failed / Skipped / Total] 35 / 154 / 14 / 203:  68%|████████████▏     | 204/300 [1:49:33<51:33, 32.22s/it]
[Succeeded / Failed / Skipped / Total] 36 / 154 / 14 / 204:  68%|████████████▏     | 204/300 [1:49:33<51:33, 32.22s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 48 / 185 / 17 / 250:  84%|███████████████   | 251/300 [2:12:10<25:48, 31.60s/it]
[Succeeded / Failed / Skipped / Total] 48 / 186 / 17 / 251:  84%|███████████████   | 251/300 [2:12:10<25:48, 31.60s/it]
[Succeeded / Failed / Skipped / Total] 48 / 186 / 17 / 251:  84%|███████████████   | 252/300 [2:12:32<25:14, 31.56s/it]
[Succeeded / Failed / Skipped / Total] 48 / 187 / 17 / 252:  84%|███████████████   | 252/300 [2:12:32<25:14, 31.56s/it]
[Succeeded / Failed / Skipped / Total] 48 / 187 / 17 / 252:  84%|███████████████▏  | 253/300 [2:13:08<24:44, 31.57s/it]
[Succeeded / Failed / Skipped / Total] 48 / 188 / 17 / 253:  84%|███████████████▏  | 253/300 [2:13:08<24:44, 31.57s/it]
[Succeeded / Failed / Skipped / Total] 48 / 188 / 17 / 253:  85%|███████████████▏  | 254/300 [2:13:30<24:10, 31.54s/it]
[Succeeded / Failed / Skipped / Total] 48 / 189 / 17 / 254:  85%|███████████████▏  | 254/300 [2:13:30<24:10, 31.54s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 55     |
| Number of failed attacks:     | 223    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 74.33% |
| Attack success rate:          | 19.78% |
| Average perturbed word %:     | 5.75%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 524.86 |
+-------------------------------+--------+


In [37]:
runAttack(clip_knn35_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn35'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn35ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:30<2:32:32, 30.61s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|                          | 1/300 [00:30<2:32:42, 30.64s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   1%|▏                         | 2/300 [00:56<2:19:16, 28.04s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▏                         | 2/300 [00:56<2:19:18, 28.05s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▎                         | 3/300 [01:34<2:35:19, 31.38s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                         | 3/300 [01:34<2:35:21, 31.39s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                         | 4/300 [02:01<2:30:25, 30.49s/it]
[Succeeded / Failed / Skipped / Total] 0 / 4 / 0 / 4:   1%|▎                         | 4/300 [02:01<2:30:27, 30.50s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 14 / 36 / 0 / 50:  17%|███▋                  | 51/300 [21:37<1:45:36, 25.45s/it]
[Succeeded / Failed / Skipped / Total] 14 / 37 / 0 / 51:  17%|███▋                  | 51/300 [21:37<1:45:36, 25.45s/it]
[Succeeded / Failed / Skipped / Total] 14 / 37 / 0 / 51:  17%|███▊                  | 52/300 [22:00<1:44:56, 25.39s/it]
[Succeeded / Failed / Skipped / Total] 14 / 38 / 0 / 52:  17%|███▊                  | 52/300 [22:00<1:44:56, 25.39s/it]
[Succeeded / Failed / Skipped / Total] 14 / 38 / 0 / 52:  18%|███▉                  | 53/300 [22:35<1:45:17, 25.58s/it]
[Succeeded / Failed / Skipped / Total] 14 / 39 / 0 / 53:  18%|███▉                  | 53/300 [22:35<1:45:17, 25.58s/it]
[Succeeded / Failed / Skipped / Total] 14 / 39 / 0 / 53:  18%|███▉                  | 54/300 [22:53<1:44:15, 25.43s/it]
[Succeeded / Failed / Skipped / Total] 15 / 39 / 0 / 54:  18%|███▉                  | 54/300 [22:53<1:44:15, 25.43s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 32 / 65 / 3 / 100:  34%|██████▋             | 101/300 [41:29<1:21:45, 24.65s/it]
[Succeeded / Failed / Skipped / Total] 33 / 65 / 3 / 101:  34%|██████▋             | 101/300 [41:29<1:21:45, 24.65s/it]
[Succeeded / Failed / Skipped / Total] 33 / 65 / 3 / 101:  34%|██████▊             | 102/300 [41:39<1:20:51, 24.50s/it]
[Succeeded / Failed / Skipped / Total] 34 / 65 / 3 / 102:  34%|██████▊             | 102/300 [41:39<1:20:51, 24.50s/it]
[Succeeded / Failed / Skipped / Total] 34 / 65 / 3 / 102:  34%|██████▊             | 103/300 [41:41<1:19:44, 24.29s/it]
[Succeeded / Failed / Skipped / Total] 35 / 65 / 3 / 103:  34%|██████▊             | 103/300 [41:41<1:19:44, 24.29s/it]
[Succeeded / Failed / Skipped / Total] 35 / 65 / 3 / 103:  35%|██████▉             | 104/300 [42:03<1:19:15, 24.26s/it]
[Succeeded / Failed / Skipped / Total] 35 / 66 / 3 / 104:  35%|██████▉             | 104/300 [42:03<1:19:15, 24.26s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 51 / 93 / 6 / 150:  50%|█████████         | 151/300 [1:01:11<1:00:23, 24.32s/it]
[Succeeded / Failed / Skipped / Total] 51 / 94 / 6 / 151:  50%|█████████         | 151/300 [1:01:11<1:00:23, 24.32s/it]
[Succeeded / Failed / Skipped / Total] 51 / 94 / 6 / 151:  51%|█████████         | 152/300 [1:01:47<1:00:10, 24.39s/it]
[Succeeded / Failed / Skipped / Total] 51 / 95 / 6 / 152:  51%|█████████         | 152/300 [1:01:47<1:00:10, 24.39s/it]
[Succeeded / Failed / Skipped / Total] 51 / 95 / 6 / 152:  51%|██████████▏         | 153/300 [1:02:04<59:38, 24.34s/it]
[Succeeded / Failed / Skipped / Total] 52 / 95 / 6 / 153:  51%|██████████▏         | 153/300 [1:02:04<59:38, 24.34s/it]
[Succeeded / Failed / Skipped / Total] 52 / 95 / 6 / 153:  51%|██████████▎         | 154/300 [1:02:04<58:51, 24.19s/it]
[Succeeded / Failed / Skipped / Total] 52 / 95 / 7 / 154:  51%|██████████▎         | 154/300 [1:02:04<58:51, 24.19s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 66 / 121 / 13 / 200:  67%|████████████      | 201/300 [1:19:33<39:10, 23.75s/it]
[Succeeded / Failed / Skipped / Total] 66 / 122 / 13 / 201:  67%|████████████      | 201/300 [1:19:33<39:10, 23.75s/it]
[Succeeded / Failed / Skipped / Total] 66 / 122 / 13 / 201:  67%|████████████      | 202/300 [1:19:54<38:45, 23.73s/it]
[Succeeded / Failed / Skipped / Total] 66 / 123 / 13 / 202:  67%|████████████      | 202/300 [1:19:54<38:45, 23.73s/it]
[Succeeded / Failed / Skipped / Total] 66 / 123 / 13 / 202:  68%|████████████▏     | 203/300 [1:20:29<38:27, 23.79s/it]
[Succeeded / Failed / Skipped / Total] 66 / 124 / 13 / 203:  68%|████████████▏     | 203/300 [1:20:29<38:27, 23.79s/it]
[Succeeded / Failed / Skipped / Total] 66 / 124 / 13 / 203:  68%|████████████▏     | 204/300 [1:20:30<37:52, 23.68s/it]
[Succeeded / Failed / Skipped / Total] 66 / 124 / 14 / 204:  68%|████████████▏     | 204/300 [1:20:30<37:52, 23.68s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 82 / 152 / 16 / 250:  84%|███████████████   | 251/300 [1:41:33<19:49, 24.28s/it]
[Succeeded / Failed / Skipped / Total] 82 / 153 / 16 / 251:  84%|███████████████   | 251/300 [1:41:33<19:49, 24.28s/it]
[Succeeded / Failed / Skipped / Total] 82 / 153 / 16 / 251:  84%|███████████████   | 252/300 [1:41:55<19:24, 24.27s/it]
[Succeeded / Failed / Skipped / Total] 82 / 154 / 16 / 252:  84%|███████████████   | 252/300 [1:41:55<19:24, 24.27s/it]
[Succeeded / Failed / Skipped / Total] 82 / 154 / 16 / 252:  84%|███████████████▏  | 253/300 [1:42:31<19:02, 24.31s/it]
[Succeeded / Failed / Skipped / Total] 83 / 154 / 16 / 253:  84%|███████████████▏  | 253/300 [1:42:31<19:02, 24.31s/it]
[Succeeded / Failed / Skipped / Total] 83 / 154 / 16 / 253:  85%|███████████████▏  | 254/300 [1:42:52<18:37, 24.30s/it]
[Succeeded / Failed / Skipped / Total] 83 / 155 / 16 / 254:  85%|███████████████▏  | 254/300 [1:42:52<18:37, 24.30s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 93     |
| Number of failed attacks:     | 185    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 61.67% |
| Attack success rate:          | 33.45% |
| Average perturbed word %:     | 11.94% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 480.83 |
+-------------------------------+--------+


In [38]:
runAttack(clip_knn175_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn175'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn175ep0841.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:34<2:51:55, 34.50s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:34<2:52:00, 34.52s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:59<2:28:13, 29.85s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▏                         | 2/300 [00:59<2:28:16, 29.85s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▎                         | 3/300 [01:34<2:36:23, 31.59s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 3/300 [01:34<2:36:26, 31.60s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 4/300 [02:03<2:32:22, 30.89s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                         | 4/300 [02:03<2:32:23, 30.89s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 24 / 25 / 1 / 50:  17%|███▋                  | 51/300 [18:45<1:31:35, 22.07s/it]
[Succeeded / Failed / Skipped / Total] 25 / 25 / 1 / 51:  17%|███▋                  | 51/300 [18:45<1:31:35, 22.07s/it]
[Succeeded / Failed / Skipped / Total] 25 / 25 / 1 / 51:  17%|███▊                  | 52/300 [19:07<1:31:14, 22.07s/it]
[Succeeded / Failed / Skipped / Total] 25 / 26 / 1 / 52:  17%|███▊                  | 52/300 [19:07<1:31:14, 22.08s/it]
[Succeeded / Failed / Skipped / Total] 25 / 26 / 1 / 52:  18%|███▉                  | 53/300 [19:43<1:31:53, 22.32s/it]
[Succeeded / Failed / Skipped / Total] 25 / 27 / 1 / 53:  18%|███▉                  | 53/300 [19:43<1:31:53, 22.32s/it]
[Succeeded / Failed / Skipped / Total] 25 / 27 / 1 / 53:  18%|███▉                  | 54/300 [19:48<1:30:12, 22.00s/it]
[Succeeded / Failed / Skipped / Total] 26 / 27 / 1 / 54:  18%|███▉                  | 54/300 [19:48<1:30:12, 22.00s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 53 / 42 / 5 / 100:  34%|██████▋             | 101/300 [35:45<1:10:26, 21.24s/it]
[Succeeded / Failed / Skipped / Total] 54 / 42 / 5 / 101:  34%|██████▋             | 101/300 [35:45<1:10:26, 21.24s/it]
[Succeeded / Failed / Skipped / Total] 54 / 42 / 5 / 101:  34%|██████▊             | 102/300 [35:58<1:09:49, 21.16s/it]
[Succeeded / Failed / Skipped / Total] 55 / 42 / 5 / 102:  34%|██████▊             | 102/300 [35:58<1:09:49, 21.16s/it]
[Succeeded / Failed / Skipped / Total] 55 / 42 / 5 / 102:  34%|██████▊             | 103/300 [36:03<1:08:57, 21.00s/it]
[Succeeded / Failed / Skipped / Total] 56 / 42 / 5 / 103:  34%|██████▊             | 103/300 [36:03<1:08:57, 21.00s/it]
[Succeeded / Failed / Skipped / Total] 56 / 42 / 5 / 103:  35%|██████▉             | 104/300 [36:24<1:08:37, 21.01s/it]
[Succeeded / Failed / Skipped / Total] 56 / 43 / 5 / 104:  35%|██████▉             | 104/300 [36:24<1:08:37, 21.01s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 76 / 65 / 9 / 150:  50%|███████████           | 151/300 [52:59<52:17, 21.06s/it]
[Succeeded / Failed / Skipped / Total] 77 / 65 / 9 / 151:  50%|███████████           | 151/300 [52:59<52:17, 21.06s/it]
[Succeeded / Failed / Skipped / Total] 77 / 65 / 9 / 151:  51%|███████████▏          | 152/300 [53:36<52:11, 21.16s/it]
[Succeeded / Failed / Skipped / Total] 77 / 66 / 9 / 152:  51%|███████████▏          | 152/300 [53:36<52:11, 21.16s/it]
[Succeeded / Failed / Skipped / Total] 77 / 66 / 9 / 152:  51%|███████████▏          | 153/300 [54:03<51:56, 21.20s/it]
[Succeeded / Failed / Skipped / Total] 77 / 67 / 9 / 153:  51%|███████████▏          | 153/300 [54:03<51:56, 21.20s/it]
[Succeeded / Failed / Skipped / Total] 77 / 67 / 9 / 153:  51%|███████████▎          | 154/300 [54:03<51:15, 21.06s/it]
[Succeeded / Failed / Skipped / Total] 77 / 67 / 10 / 154:  51%|██████████▊          | 154/300 [54:03<51:15, 21.06s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 92 / 87 / 21 / 200:  67%|████████████▋      | 201/300 [1:08:52<33:55, 20.56s/it]
[Succeeded / Failed / Skipped / Total] 92 / 88 / 21 / 201:  67%|████████████▋      | 201/300 [1:08:52<33:55, 20.56s/it]
[Succeeded / Failed / Skipped / Total] 92 / 88 / 21 / 201:  67%|████████████▊      | 202/300 [1:09:14<33:35, 20.57s/it]
[Succeeded / Failed / Skipped / Total] 92 / 89 / 21 / 202:  67%|████████████▊      | 202/300 [1:09:14<33:35, 20.57s/it]
[Succeeded / Failed / Skipped / Total] 92 / 89 / 21 / 202:  68%|████████████▊      | 203/300 [1:09:49<33:21, 20.64s/it]
[Succeeded / Failed / Skipped / Total] 92 / 90 / 21 / 203:  68%|████████████▊      | 203/300 [1:09:49<33:21, 20.64s/it]
[Succeeded / Failed / Skipped / Total] 92 / 90 / 21 / 203:  68%|████████████▉      | 204/300 [1:09:49<32:51, 20.54s/it]
[Succeeded / Failed / Skipped / Total] 92 / 90 / 22 / 204:  68%|████████████▉      | 204/300 [1:09:49<32:51, 20.54s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 112 / 110 / 28 / 250:  84%|██████████████▏  | 251/300 [1:27:06<17:00, 20.82s/it]
[Succeeded / Failed / Skipped / Total] 112 / 111 / 28 / 251:  84%|██████████████▏  | 251/300 [1:27:06<17:00, 20.82s/it]
[Succeeded / Failed / Skipped / Total] 112 / 111 / 28 / 251:  84%|██████████████▎  | 252/300 [1:27:28<16:39, 20.83s/it]
[Succeeded / Failed / Skipped / Total] 112 / 112 / 28 / 252:  84%|██████████████▎  | 252/300 [1:27:28<16:39, 20.83s/it]
[Succeeded / Failed / Skipped / Total] 112 / 112 / 28 / 252:  84%|██████████████▎  | 253/300 [1:27:51<16:19, 20.83s/it]
[Succeeded / Failed / Skipped / Total] 113 / 112 / 28 / 253:  84%|██████████████▎  | 253/300 [1:27:51<16:19, 20.83s/it]
[Succeeded / Failed / Skipped / Total] 113 / 112 / 28 / 253:  85%|██████████████▍  | 254/300 [1:27:59<15:56, 20.78s/it]
[Succeeded / Failed / Skipped / Total] 114 / 112 / 28 / 254:  85%|██████████████▍  | 254/300 [1:27:59<15:56, 20.78s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 129    |
| Number of failed attacks:     | 137    |
| Number of skipped attacks:    | 34     |
| Original accuracy:            | 88.67% |
| Accuracy under attack:        | 45.67% |
| Attack success rate:          | 48.5%  |
| Average perturbed word %:     | 20.68% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 436.63 |
+-------------------------------+--------+


In [39]:
et = datetime.datetime.now()
et - st

datetime.timedelta(days=1, seconds=24622, microseconds=6146)

### Threshold = 1 - 0.4/$\pi$ = 0.873

In [40]:
suffix = 'ep0873.csv'
thre = 1-0.4/np.pi

#### BERT

In [41]:
runAttack(bert_lr1_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr1'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr1ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:29<2:25:47, 29.26s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:29<2:25:52, 29.27s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:39<1:37:57, 19.72s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:39<1:37:59, 19.73s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:57<1:34:56, 19.18s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:57<1:34:58, 19.19s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:28<1:49:37, 22.22s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:28<1:49:38, 22.22s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 42 / 3 / 5 / 50:  17%|████▎                    | 51/300 [09:29<46:19, 11.16s/it]
[Succeeded / Failed / Skipped / Total] 43 / 3 / 5 / 51:  17%|████▎                    | 51/300 [09:29<46:19, 11.16s/it]
[Succeeded / Failed / Skipped / Total] 43 / 3 / 5 / 51:  17%|████▎                    | 52/300 [09:38<45:56, 11.12s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 5 / 52:  17%|████▎                    | 52/300 [09:38<45:57, 11.12s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 5 / 52:  18%|████▍                    | 53/300 [10:07<47:11, 11.47s/it]
[Succeeded / Failed / Skipped / Total] 45 / 3 / 5 / 53:  18%|████▍                    | 53/300 [10:07<47:11, 11.47s/it]
[Succeeded / Failed / Skipped / Total] 45 / 3 / 5 / 53:  18%|████▌                    | 54/300 [10:17<46:52, 11.43s/it]
[Succeeded / Failed / Skipped / Total] 46 / 3 / 5 / 54:  18%|████▌                    | 54/300 [10:17<46:52, 11.43s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 87 / 3 / 10 / 100:  34%|███████▍              | 101/300 [18:34<36:35, 11.03s/it]
[Succeeded / Failed / Skipped / Total] 88 / 3 / 10 / 101:  34%|███████▍              | 101/300 [18:34<36:35, 11.03s/it]
[Succeeded / Failed / Skipped / Total] 88 / 3 / 10 / 101:  34%|███████▍              | 102/300 [18:38<36:12, 10.97s/it]
[Succeeded / Failed / Skipped / Total] 89 / 3 / 10 / 102:  34%|███████▍              | 102/300 [18:39<36:12, 10.97s/it]
[Succeeded / Failed / Skipped / Total] 89 / 3 / 10 / 102:  34%|███████▌              | 103/300 [18:47<35:56, 10.95s/it]
[Succeeded / Failed / Skipped / Total] 90 / 3 / 10 / 103:  34%|███████▌              | 103/300 [18:47<35:56, 10.95s/it]
[Succeeded / Failed / Skipped / Total] 90 / 3 / 10 / 103:  35%|███████▋              | 104/300 [18:56<35:41, 10.92s/it]
[Succeeded / Failed / Skipped / Total] 91 / 3 / 10 / 104:  35%|███████▋              | 104/300 [18:56<35:41, 10.92s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 128 / 7 / 15 / 150:  50%|██████████▌          | 151/300 [30:02<29:38, 11.94s/it]
[Succeeded / Failed / Skipped / Total] 129 / 7 / 15 / 151:  50%|██████████▌          | 151/300 [30:02<29:38, 11.94s/it]
[Succeeded / Failed / Skipped / Total] 129 / 7 / 15 / 151:  51%|██████████▋          | 152/300 [30:24<29:36, 12.00s/it]
[Succeeded / Failed / Skipped / Total] 130 / 7 / 15 / 152:  51%|██████████▋          | 152/300 [30:24<29:36, 12.00s/it]
[Succeeded / Failed / Skipped / Total] 130 / 7 / 15 / 152:  51%|██████████▋          | 153/300 [30:31<29:19, 11.97s/it]
[Succeeded / Failed / Skipped / Total] 131 / 7 / 15 / 153:  51%|██████████▋          | 153/300 [30:31<29:19, 11.97s/it]
[Succeeded / Failed / Skipped / Total] 131 / 7 / 15 / 153:  51%|██████████▊          | 154/300 [30:36<29:01, 11.93s/it]
[Succeeded / Failed / Skipped / Total] 132 / 7 / 15 / 154:  51%|██████████▊          | 154/300 [30:36<29:01, 11.93s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 170 / 9 / 21 / 200:  67%|██████████████       | 201/300 [41:39<20:30, 12.43s/it]
[Succeeded / Failed / Skipped / Total] 171 / 9 / 21 / 201:  67%|██████████████       | 201/300 [41:39<20:30, 12.43s/it]
[Succeeded / Failed / Skipped / Total] 171 / 9 / 21 / 201:  67%|██████████████▏      | 202/300 [41:51<20:18, 12.44s/it]
[Succeeded / Failed / Skipped / Total] 172 / 9 / 21 / 202:  67%|██████████████▏      | 202/300 [41:51<20:18, 12.44s/it]
[Succeeded / Failed / Skipped / Total] 172 / 9 / 21 / 202:  68%|██████████████▏      | 203/300 [42:23<20:15, 12.53s/it]
[Succeeded / Failed / Skipped / Total] 173 / 9 / 21 / 203:  68%|██████████████▏      | 203/300 [42:23<20:15, 12.53s/it]
[Succeeded / Failed / Skipped / Total] 173 / 9 / 21 / 203:  68%|██████████████▎      | 204/300 [42:26<19:58, 12.48s/it]
[Succeeded / Failed / Skipped / Total] 174 / 9 / 21 / 204:  68%|██████████████▎      | 204/300 [42:26<19:58, 12.48s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 214 / 11 / 25 / 250:  84%|████████████████▋   | 251/300 [52:56<10:20, 12.65s/it]
[Succeeded / Failed / Skipped / Total] 215 / 11 / 25 / 251:  84%|████████████████▋   | 251/300 [52:56<10:20, 12.65s/it]
[Succeeded / Failed / Skipped / Total] 215 / 11 / 25 / 251:  84%|████████████████▊   | 252/300 [53:12<10:08, 12.67s/it]
[Succeeded / Failed / Skipped / Total] 216 / 11 / 25 / 252:  84%|████████████████▊   | 252/300 [53:12<10:08, 12.67s/it]
[Succeeded / Failed / Skipped / Total] 216 / 11 / 25 / 252:  84%|████████████████▊   | 253/300 [53:33<09:57, 12.70s/it]
[Succeeded / Failed / Skipped / Total] 217 / 11 / 25 / 253:  84%|████████████████▊   | 253/300 [53:33<09:57, 12.70s/it]
[Succeeded / Failed / Skipped / Total] 217 / 11 / 25 / 253:  85%|████████████████▉   | 254/300 [53:44<09:44, 12.70s/it]
[Succeeded / Failed / Skipped / Total] 218 / 11 / 25 / 254:  85%|████████████████▉   | 254/300 [53:44<09:44, 12.70s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 258    |
| Number of failed attacks:     | 12     |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 4.0%   |
| Attack success rate:          | 95.56% |
| Average perturbed word %:     | 15.68% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 181.07 |
+-------------------------------+--------+


In [42]:
runAttack(bert_lr01_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr01'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr01ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:21<1:46:35, 21.39s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:21<1:46:39, 21.40s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:29<1:13:54, 14.88s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:29<1:13:57, 14.89s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:46<1:16:49, 15.52s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:46<1:16:52, 15.53s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:16<1:34:29, 19.15s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:16<1:34:30, 19.16s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 40 / 5 / 5 / 50:  17%|████▎                    | 51/300 [09:41<47:17, 11.40s/it]
[Succeeded / Failed / Skipped / Total] 41 / 5 / 5 / 51:  17%|████▎                    | 51/300 [09:41<47:17, 11.40s/it]
[Succeeded / Failed / Skipped / Total] 41 / 5 / 5 / 51:  17%|████▎                    | 52/300 [09:52<47:06, 11.40s/it]
[Succeeded / Failed / Skipped / Total] 42 / 5 / 5 / 52:  17%|████▎                    | 52/300 [09:52<47:06, 11.40s/it]
[Succeeded / Failed / Skipped / Total] 42 / 5 / 5 / 52:  18%|████▍                    | 53/300 [10:18<48:02, 11.67s/it]
[Succeeded / Failed / Skipped / Total] 43 / 5 / 5 / 53:  18%|████▍                    | 53/300 [10:18<48:02, 11.67s/it]
[Succeeded / Failed / Skipped / Total] 43 / 5 / 5 / 53:  18%|████▌                    | 54/300 [10:30<47:52, 11.68s/it]
[Succeeded / Failed / Skipped / Total] 44 / 5 / 5 / 54:  18%|████▌                    | 54/300 [10:30<47:52, 11.68s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 84 / 5 / 11 / 100:  34%|███████▍              | 101/300 [18:46<36:58, 11.15s/it]
[Succeeded / Failed / Skipped / Total] 85 / 5 / 11 / 101:  34%|███████▍              | 101/300 [18:46<36:58, 11.15s/it]
[Succeeded / Failed / Skipped / Total] 85 / 5 / 11 / 101:  34%|███████▍              | 102/300 [18:50<36:34, 11.08s/it]
[Succeeded / Failed / Skipped / Total] 86 / 5 / 11 / 102:  34%|███████▍              | 102/300 [18:50<36:34, 11.08s/it]
[Succeeded / Failed / Skipped / Total] 86 / 5 / 11 / 102:  34%|███████▌              | 103/300 [18:56<36:12, 11.03s/it]
[Succeeded / Failed / Skipped / Total] 87 / 5 / 11 / 103:  34%|███████▌              | 103/300 [18:56<36:12, 11.03s/it]
[Succeeded / Failed / Skipped / Total] 87 / 5 / 11 / 103:  35%|███████▋              | 104/300 [19:06<36:01, 11.03s/it]
[Succeeded / Failed / Skipped / Total] 88 / 5 / 11 / 104:  35%|███████▋              | 104/300 [19:06<36:01, 11.03s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 124 / 10 / 16 / 150:  50%|██████████          | 151/300 [30:51<30:26, 12.26s/it]
[Succeeded / Failed / Skipped / Total] 125 / 10 / 16 / 151:  50%|██████████          | 151/300 [30:51<30:26, 12.26s/it]
[Succeeded / Failed / Skipped / Total] 125 / 10 / 16 / 151:  51%|██████████▏         | 152/300 [31:15<30:25, 12.34s/it]
[Succeeded / Failed / Skipped / Total] 126 / 10 / 16 / 152:  51%|██████████▏         | 152/300 [31:15<30:25, 12.34s/it]
[Succeeded / Failed / Skipped / Total] 126 / 10 / 16 / 152:  51%|██████████▏         | 153/300 [31:23<30:09, 12.31s/it]
[Succeeded / Failed / Skipped / Total] 127 / 10 / 16 / 153:  51%|██████████▏         | 153/300 [31:23<30:09, 12.31s/it]
[Succeeded / Failed / Skipped / Total] 127 / 10 / 16 / 153:  51%|██████████▎         | 154/300 [31:27<29:49, 12.26s/it]
[Succeeded / Failed / Skipped / Total] 128 / 10 / 16 / 154:  51%|██████████▎         | 154/300 [31:27<29:49, 12.26s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 166 / 11 / 23 / 200:  67%|█████████████▍      | 201/300 [43:05<21:13, 12.86s/it]
[Succeeded / Failed / Skipped / Total] 167 / 11 / 23 / 201:  67%|█████████████▍      | 201/300 [43:05<21:13, 12.86s/it]
[Succeeded / Failed / Skipped / Total] 167 / 11 / 23 / 201:  67%|█████████████▍      | 202/300 [43:17<21:00, 12.86s/it]
[Succeeded / Failed / Skipped / Total] 168 / 11 / 23 / 202:  67%|█████████████▍      | 202/300 [43:17<21:00, 12.86s/it]
[Succeeded / Failed / Skipped / Total] 168 / 11 / 23 / 202:  68%|█████████████▌      | 203/300 [43:44<20:54, 12.93s/it]
[Succeeded / Failed / Skipped / Total] 169 / 11 / 23 / 203:  68%|█████████████▌      | 203/300 [43:44<20:54, 12.93s/it]
[Succeeded / Failed / Skipped / Total] 169 / 11 / 23 / 203:  68%|█████████████▌      | 204/300 [43:47<20:36, 12.88s/it]
[Succeeded / Failed / Skipped / Total] 170 / 11 / 23 / 204:  68%|█████████████▌      | 204/300 [43:47<20:36, 12.88s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 210 / 13 / 27 / 250:  84%|████████████████▋   | 251/300 [53:51<10:30, 12.87s/it]
[Succeeded / Failed / Skipped / Total] 211 / 13 / 27 / 251:  84%|████████████████▋   | 251/300 [53:51<10:30, 12.87s/it]
[Succeeded / Failed / Skipped / Total] 211 / 13 / 27 / 251:  84%|████████████████▊   | 252/300 [54:00<10:17, 12.86s/it]
[Succeeded / Failed / Skipped / Total] 212 / 13 / 27 / 252:  84%|████████████████▊   | 252/300 [54:00<10:17, 12.86s/it]
[Succeeded / Failed / Skipped / Total] 212 / 13 / 27 / 252:  84%|████████████████▊   | 253/300 [54:16<10:04, 12.87s/it]
[Succeeded / Failed / Skipped / Total] 213 / 13 / 27 / 253:  84%|████████████████▊   | 253/300 [54:16<10:04, 12.87s/it]
[Succeeded / Failed / Skipped / Total] 213 / 13 / 27 / 253:  85%|████████████████▉   | 254/300 [54:26<09:51, 12.86s/it]
[Succeeded / Failed / Skipped / Total] 214 / 13 / 27 / 254:  85%|████████████████▉   | 254/300 [54:26<09:51, 12.86s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 254    |
| Number of failed attacks:     | 14     |
| Number of skipped attacks:    | 32     |
| Original accuracy:            | 89.33% |
| Accuracy under attack:        | 4.67%  |
| Attack success rate:          | 94.78% |
| Average perturbed word %:     | 16.06% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 185.8  |
+-------------------------------+--------+


In [43]:
runAttack(bert_lr10_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr10'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr10ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:24<2:03:34, 24.80s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:24<2:03:39, 24.81s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:33<1:23:41, 16.85s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:33<1:23:41, 16.85s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:48<1:19:57, 16.15s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:48<1:19:58, 16.16s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:17<1:35:35, 19.38s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:17<1:35:36, 19.38s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 42 / 3 / 5 / 50:  17%|████▎                    | 51/300 [08:58<43:47, 10.55s/it]
[Succeeded / Failed / Skipped / Total] 43 / 3 / 5 / 51:  17%|████▎                    | 51/300 [08:58<43:47, 10.55s/it]
[Succeeded / Failed / Skipped / Total] 43 / 3 / 5 / 51:  17%|████▎                    | 52/300 [09:04<43:17, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 5 / 52:  17%|████▎                    | 52/300 [09:04<43:17, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 44 / 3 / 5 / 52:  18%|████▍                    | 53/300 [09:33<44:33, 10.82s/it]
[Succeeded / Failed / Skipped / Total] 45 / 3 / 5 / 53:  18%|████▍                    | 53/300 [09:33<44:33, 10.82s/it]
[Succeeded / Failed / Skipped / Total] 45 / 3 / 5 / 53:  18%|████▌                    | 54/300 [09:42<44:14, 10.79s/it]
[Succeeded / Failed / Skipped / Total] 46 / 3 / 5 / 54:  18%|████▌                    | 54/300 [09:42<44:14, 10.79s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 86 / 3 / 11 / 100:  34%|███████▍              | 101/300 [17:45<34:58, 10.55s/it]
[Succeeded / Failed / Skipped / Total] 87 / 3 / 11 / 101:  34%|███████▍              | 101/300 [17:45<34:58, 10.55s/it]
[Succeeded / Failed / Skipped / Total] 87 / 3 / 11 / 101:  34%|███████▍              | 102/300 [17:49<34:36, 10.49s/it]
[Succeeded / Failed / Skipped / Total] 88 / 3 / 11 / 102:  34%|███████▍              | 102/300 [17:49<34:36, 10.49s/it]
[Succeeded / Failed / Skipped / Total] 88 / 3 / 11 / 102:  34%|███████▌              | 103/300 [17:58<34:22, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 89 / 3 / 11 / 103:  34%|███████▌              | 103/300 [17:58<34:22, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 89 / 3 / 11 / 103:  35%|███████▋              | 104/300 [18:06<34:07, 10.45s/it]
[Succeeded / Failed / Skipped / Total] 90 / 3 / 11 / 104:  35%|███████▋              | 104/300 [18:06<34:08, 10.45s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 127 / 7 / 16 / 150:  50%|██████████▌          | 151/300 [28:53<28:30, 11.48s/it]
[Succeeded / Failed / Skipped / Total] 128 / 7 / 16 / 151:  50%|██████████▌          | 151/300 [28:53<28:30, 11.48s/it]
[Succeeded / Failed / Skipped / Total] 128 / 7 / 16 / 151:  51%|██████████▋          | 152/300 [29:13<28:26, 11.53s/it]
[Succeeded / Failed / Skipped / Total] 129 / 7 / 16 / 152:  51%|██████████▋          | 152/300 [29:13<28:26, 11.53s/it]
[Succeeded / Failed / Skipped / Total] 129 / 7 / 16 / 152:  51%|██████████▋          | 153/300 [29:23<28:14, 11.53s/it]
[Succeeded / Failed / Skipped / Total] 130 / 7 / 16 / 153:  51%|██████████▋          | 153/300 [29:23<28:14, 11.53s/it]
[Succeeded / Failed / Skipped / Total] 130 / 7 / 16 / 153:  51%|██████████▊          | 154/300 [29:29<27:57, 11.49s/it]
[Succeeded / Failed / Skipped / Total] 131 / 7 / 16 / 154:  51%|██████████▊          | 154/300 [29:29<27:57, 11.49s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 169 / 9 / 22 / 200:  67%|██████████████       | 201/300 [40:20<19:52, 12.04s/it]
[Succeeded / Failed / Skipped / Total] 170 / 9 / 22 / 201:  67%|██████████████       | 201/300 [40:20<19:52, 12.04s/it]
[Succeeded / Failed / Skipped / Total] 170 / 9 / 22 / 201:  67%|██████████████▏      | 202/300 [40:33<19:40, 12.04s/it]
[Succeeded / Failed / Skipped / Total] 171 / 9 / 22 / 202:  67%|██████████████▏      | 202/300 [40:33<19:40, 12.04s/it]
[Succeeded / Failed / Skipped / Total] 171 / 9 / 22 / 202:  68%|██████████████▏      | 203/300 [41:06<19:38, 12.15s/it]
[Succeeded / Failed / Skipped / Total] 172 / 9 / 22 / 203:  68%|██████████████▏      | 203/300 [41:06<19:38, 12.15s/it]
[Succeeded / Failed / Skipped / Total] 172 / 9 / 22 / 203:  68%|██████████████▎      | 204/300 [41:09<19:22, 12.11s/it]
[Succeeded / Failed / Skipped / Total] 173 / 9 / 22 / 204:  68%|██████████████▎      | 204/300 [41:09<19:22, 12.11s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 212 / 12 / 26 / 250:  84%|████████████████▋   | 251/300 [51:28<10:02, 12.30s/it]
[Succeeded / Failed / Skipped / Total] 213 / 12 / 26 / 251:  84%|████████████████▋   | 251/300 [51:28<10:02, 12.30s/it]
[Succeeded / Failed / Skipped / Total] 213 / 12 / 26 / 251:  84%|████████████████▊   | 252/300 [51:42<09:50, 12.31s/it]
[Succeeded / Failed / Skipped / Total] 214 / 12 / 26 / 252:  84%|████████████████▊   | 252/300 [51:42<09:50, 12.31s/it]
[Succeeded / Failed / Skipped / Total] 214 / 12 / 26 / 252:  84%|████████████████▊   | 253/300 [52:03<09:40, 12.35s/it]
[Succeeded / Failed / Skipped / Total] 215 / 12 / 26 / 253:  84%|████████████████▊   | 253/300 [52:03<09:40, 12.35s/it]
[Succeeded / Failed / Skipped / Total] 215 / 12 / 26 / 253:  85%|████████████████▉   | 254/300 [52:14<09:27, 12.34s/it]
[Succeeded / Failed / Skipped / Total] 216 / 12 / 26 / 254:  85%|████████████████▉   | 254/300 [52:14<09:27, 12.34s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 257    |
| Number of failed attacks:     | 12     |
| Number of skipped attacks:    | 31     |
| Original accuracy:            | 89.67% |
| Accuracy under attack:        | 4.0%   |
| Attack success rate:          | 95.54% |
| Average perturbed word %:     | 15.61% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 182.59 |
+-------------------------------+--------+


In [44]:
runAttack(bert_rf7_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf7ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:24<1:59:39, 24.01s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:24<1:59:44, 24.03s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:27<1:07:26, 13.58s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:27<1:07:28, 13.59s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                           | 3/300 [00:35<58:27, 11.81s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                           | 3/300 [00:35<58:29, 11.82s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:04<1:19:51, 16.19s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:04<1:19:52, 16.19s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 35 / 2 / 13 / 50:  17%|████                    | 51/300 [05:54<28:52,  6.96s/it]
[Succeeded / Failed / Skipped / Total] 36 / 2 / 13 / 51:  17%|████                    | 51/300 [05:54<28:52,  6.96s/it]
[Succeeded / Failed / Skipped / Total] 36 / 2 / 13 / 51:  17%|████▏                   | 52/300 [06:02<28:49,  6.98s/it]
[Succeeded / Failed / Skipped / Total] 37 / 2 / 13 / 52:  17%|████▏                   | 52/300 [06:02<28:50,  6.98s/it]
[Succeeded / Failed / Skipped / Total] 37 / 2 / 13 / 52:  18%|████▏                   | 53/300 [06:41<31:10,  7.57s/it]
[Succeeded / Failed / Skipped / Total] 37 / 3 / 13 / 53:  18%|████▏                   | 53/300 [06:41<31:10,  7.57s/it]
[Succeeded / Failed / Skipped / Total] 37 / 3 / 13 / 53:  18%|████▎                   | 54/300 [06:49<31:03,  7.58s/it]
[Succeeded / Failed / Skipped / Total] 38 / 3 / 13 / 54:  18%|████▎                   | 54/300 [06:49<31:03,  7.58s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 67 / 4 / 30 / 101:  34%|███████▍              | 102/300 [10:58<21:17,  6.45s/it]
[Succeeded / Failed / Skipped / Total] 68 / 4 / 30 / 102:  34%|███████▍              | 102/300 [10:58<21:17,  6.45s/it]
[Succeeded / Failed / Skipped / Total] 69 / 4 / 30 / 103:  34%|███████▌              | 103/300 [11:03<21:09,  6.44s/it]
[Succeeded / Failed / Skipped / Total] 69 / 4 / 30 / 103:  35%|███████▋              | 104/300 [11:05<20:54,  6.40s/it]
[Succeeded / Failed / Skipped / Total] 70 / 4 / 30 / 104:  35%|███████▋              | 104/300 [11:05<20:54,  6.40s/it]
[Succeeded / Failed / Skipped / Total] 71 / 4 / 30 / 105:  35%|███████▋              | 105/300 [11:18<21:00,  6.46s/it]
[Succeeded / Failed / Skipped / Total] 71 / 4 / 30 / 105:  35%|███████▊              | 106/300 [11:18<20:42,  6.40s/it]
[Succeeded / Failed / Skipped / Total] 71 / 4 / 31 / 106:  35%|███████▊              | 106/300 [11:18<20:42,  6.40s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 106 / 4 / 40 / 150:  50%|██████████▌          | 151/300 [17:57<17:43,  7.14s/it]
[Succeeded / Failed / Skipped / Total] 107 / 4 / 40 / 151:  50%|██████████▌          | 151/300 [17:57<17:43,  7.14s/it]
[Succeeded / Failed / Skipped / Total] 107 / 4 / 40 / 151:  51%|██████████▋          | 152/300 [18:13<17:44,  7.19s/it]
[Succeeded / Failed / Skipped / Total] 108 / 4 / 40 / 152:  51%|██████████▋          | 152/300 [18:13<17:44,  7.19s/it]
[Succeeded / Failed / Skipped / Total] 108 / 4 / 40 / 152:  51%|██████████▋          | 153/300 [18:16<17:33,  7.16s/it]
[Succeeded / Failed / Skipped / Total] 109 / 4 / 40 / 153:  51%|██████████▋          | 153/300 [18:16<17:33,  7.16s/it]
[Succeeded / Failed / Skipped / Total] 109 / 4 / 40 / 153:  51%|██████████▊          | 154/300 [18:22<17:25,  7.16s/it]
[Succeeded / Failed / Skipped / Total] 110 / 4 / 40 / 154:  51%|██████████▊          | 154/300 [18:22<17:25,  7.16s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 137 / 7 / 56 / 200:  67%|██████████████       | 201/300 [27:47<13:41,  8.30s/it]
[Succeeded / Failed / Skipped / Total] 138 / 7 / 56 / 201:  67%|██████████████       | 201/300 [27:47<13:41,  8.30s/it]
[Succeeded / Failed / Skipped / Total] 138 / 7 / 56 / 201:  67%|██████████████▏      | 202/300 [27:51<13:30,  8.27s/it]
[Succeeded / Failed / Skipped / Total] 139 / 7 / 56 / 202:  67%|██████████████▏      | 202/300 [27:51<13:30,  8.27s/it]
[Succeeded / Failed / Skipped / Total] 139 / 7 / 56 / 202:  68%|██████████████▏      | 203/300 [28:06<13:26,  8.31s/it]
[Succeeded / Failed / Skipped / Total] 140 / 7 / 56 / 203:  68%|██████████████▏      | 203/300 [28:06<13:26,  8.31s/it]
[Succeeded / Failed / Skipped / Total] 140 / 7 / 56 / 203:  68%|██████████████▎      | 204/300 [28:06<13:13,  8.27s/it]
[Succeeded / Failed / Skipped / Total] 140 / 7 / 57 / 204:  68%|██████████████▎      | 204/300 [28:06<13:13,  8.27s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 179 / 8 / 63 / 250:  84%|█████████████████▌   | 251/300 [33:43<06:35,  8.06s/it]
[Succeeded / Failed / Skipped / Total] 180 / 8 / 63 / 251:  84%|█████████████████▌   | 251/300 [33:43<06:35,  8.06s/it]
[Succeeded / Failed / Skipped / Total] 180 / 8 / 63 / 251:  84%|█████████████████▋   | 252/300 [33:44<06:25,  8.04s/it]
[Succeeded / Failed / Skipped / Total] 181 / 8 / 63 / 252:  84%|█████████████████▋   | 252/300 [33:44<06:25,  8.04s/it]
[Succeeded / Failed / Skipped / Total] 181 / 8 / 63 / 252:  84%|█████████████████▋   | 253/300 [33:53<06:17,  8.04s/it]
[Succeeded / Failed / Skipped / Total] 182 / 8 / 63 / 253:  84%|█████████████████▋   | 253/300 [33:53<06:17,  8.04s/it]
[Succeeded / Failed / Skipped / Total] 182 / 8 / 63 / 253:  85%|█████████████████▊   | 254/300 [34:00<06:09,  8.03s/it]
[Succeeded / Failed / Skipped / Total] 183 / 8 / 63 / 254:  85%|█████████████████▊   | 254/300 [34:00<06:09,  8.03s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 216    |
| Number of failed attacks:     | 10     |
| Number of skipped attacks:    | 74     |
| Original accuracy:            | 75.33% |
| Accuracy under attack:        | 3.33%  |
| Attack success rate:          | 95.58% |
| Average perturbed word %:     | 8.43%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 127.41 |
+-------------------------------+--------+


In [45]:
runAttack(bert_rf14_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf14'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf14ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:27<2:15:02, 27.10s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:27<2:15:08, 27.12s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:30<1:16:11, 15.34s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:30<1:16:13, 15.35s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:59<1:37:48, 19.76s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:59<1:37:51, 19.77s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:28<1:49:38, 22.22s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:28<1:49:39, 22.23s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 40 / 1 / 9 / 50:  17%|████▎                    | 51/300 [07:33<36:52,  8.89s/it]
[Succeeded / Failed / Skipped / Total] 41 / 1 / 9 / 51:  17%|████▎                    | 51/300 [07:33<36:52,  8.89s/it]
[Succeeded / Failed / Skipped / Total] 41 / 1 / 9 / 51:  17%|████▎                    | 52/300 [07:41<36:42,  8.88s/it]
[Succeeded / Failed / Skipped / Total] 42 / 1 / 9 / 52:  17%|████▎                    | 52/300 [07:41<36:42,  8.88s/it]
[Succeeded / Failed / Skipped / Total] 42 / 1 / 9 / 52:  18%|████▍                    | 53/300 [08:15<38:29,  9.35s/it]
[Succeeded / Failed / Skipped / Total] 42 / 2 / 9 / 53:  18%|████▍                    | 53/300 [08:15<38:30,  9.35s/it]
[Succeeded / Failed / Skipped / Total] 42 / 2 / 9 / 53:  18%|████▌                    | 54/300 [08:26<38:25,  9.37s/it]
[Succeeded / Failed / Skipped / Total] 43 / 2 / 9 / 54:  18%|████▌                    | 54/300 [08:26<38:25,  9.37s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 79 / 2 / 19 / 100:  34%|███████▍              | 101/300 [13:28<26:33,  8.01s/it]
[Succeeded / Failed / Skipped / Total] 80 / 2 / 19 / 101:  34%|███████▍              | 101/300 [13:28<26:33,  8.01s/it]
[Succeeded / Failed / Skipped / Total] 80 / 2 / 19 / 101:  34%|███████▍              | 102/300 [13:36<26:24,  8.00s/it]
[Succeeded / Failed / Skipped / Total] 81 / 2 / 19 / 102:  34%|███████▍              | 102/300 [13:36<26:24,  8.00s/it]
[Succeeded / Failed / Skipped / Total] 81 / 2 / 19 / 102:  34%|███████▌              | 103/300 [13:36<26:01,  7.93s/it]
[Succeeded / Failed / Skipped / Total] 81 / 2 / 20 / 103:  34%|███████▌              | 103/300 [13:36<26:01,  7.93s/it]
[Succeeded / Failed / Skipped / Total] 81 / 2 / 20 / 103:  35%|███████▋              | 104/300 [13:40<25:46,  7.89s/it]
[Succeeded / Failed / Skipped / Total] 82 / 2 / 20 / 104:  35%|███████▋              | 104/300 [13:40<25:46,  7.89s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 117 / 6 / 27 / 150:  50%|██████████▌          | 151/300 [21:43<21:26,  8.63s/it]
[Succeeded / Failed / Skipped / Total] 118 / 6 / 27 / 151:  50%|██████████▌          | 151/300 [21:43<21:26,  8.63s/it]
[Succeeded / Failed / Skipped / Total] 118 / 6 / 27 / 151:  51%|██████████▋          | 152/300 [21:56<21:21,  8.66s/it]
[Succeeded / Failed / Skipped / Total] 119 / 6 / 27 / 152:  51%|██████████▋          | 152/300 [21:56<21:21,  8.66s/it]
[Succeeded / Failed / Skipped / Total] 119 / 6 / 27 / 152:  51%|██████████▋          | 153/300 [22:02<21:11,  8.65s/it]
[Succeeded / Failed / Skipped / Total] 120 / 6 / 27 / 153:  51%|██████████▋          | 153/300 [22:02<21:11,  8.65s/it]
[Succeeded / Failed / Skipped / Total] 120 / 6 / 27 / 153:  51%|██████████▊          | 154/300 [22:08<20:59,  8.63s/it]
[Succeeded / Failed / Skipped / Total] 121 / 6 / 27 / 154:  51%|██████████▊          | 154/300 [22:08<20:59,  8.63s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 146 / 11 / 43 / 200:  67%|█████████████▍      | 201/300 [32:08<15:49,  9.59s/it]
[Succeeded / Failed / Skipped / Total] 147 / 11 / 43 / 201:  67%|█████████████▍      | 201/300 [32:08<15:49,  9.59s/it]
[Succeeded / Failed / Skipped / Total] 147 / 11 / 43 / 201:  67%|█████████████▍      | 202/300 [32:17<15:40,  9.59s/it]
[Succeeded / Failed / Skipped / Total] 148 / 11 / 43 / 202:  67%|█████████████▍      | 202/300 [32:17<15:40,  9.59s/it]
[Succeeded / Failed / Skipped / Total] 148 / 11 / 43 / 202:  68%|█████████████▌      | 203/300 [32:39<15:36,  9.65s/it]
[Succeeded / Failed / Skipped / Total] 149 / 11 / 43 / 203:  68%|█████████████▌      | 203/300 [32:39<15:36,  9.65s/it]
[Succeeded / Failed / Skipped / Total] 149 / 11 / 43 / 203:  68%|█████████████▌      | 204/300 [32:39<15:22,  9.61s/it]
[Succeeded / Failed / Skipped / Total] 149 / 11 / 44 / 204:  68%|█████████████▌      | 204/300 [32:39<15:22,  9.61s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 187 / 14 / 49 / 250:  84%|████████████████▋   | 251/300 [40:53<07:58,  9.77s/it]
[Succeeded / Failed / Skipped / Total] 188 / 14 / 49 / 251:  84%|████████████████▋   | 251/300 [40:53<07:58,  9.77s/it]
[Succeeded / Failed / Skipped / Total] 188 / 14 / 49 / 251:  84%|████████████████▊   | 252/300 [40:56<07:47,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 189 / 14 / 49 / 252:  84%|████████████████▊   | 252/300 [40:56<07:47,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 189 / 14 / 49 / 252:  84%|████████████████▊   | 253/300 [41:10<07:38,  9.76s/it]
[Succeeded / Failed / Skipped / Total] 190 / 14 / 49 / 253:  84%|████████████████▊   | 253/300 [41:10<07:38,  9.76s/it]
[Succeeded / Failed / Skipped / Total] 190 / 14 / 49 / 253:  85%|████████████████▉   | 254/300 [41:17<07:28,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 191 / 14 / 49 / 254:  85%|████████████████▉   | 254/300 [41:17<07:28,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 228    |
| Number of failed attacks:     | 15     |
| Number of skipped attacks:    | 57     |
| Original accuracy:            | 81.0%  |
| Accuracy under attack:        | 5.0%   |
| Attack success rate:          | 93.83% |
| Average perturbed word %:     | 9.98%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 157.21 |
+-------------------------------+--------+


In [46]:
runAttack(bert_rf30_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf30'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf30ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:32<2:39:37, 32.03s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:32<2:39:46, 32.06s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:42<1:45:37, 21.27s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:42<1:45:47, 21.30s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [01:04<1:46:36, 21.54s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [01:04<1:46:37, 21.54s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:37<1:59:59, 24.32s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:37<2:00:01, 24.33s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 41 / 3 / 6 / 50:  17%|████▎                    | 51/300 [08:25<41:10,  9.92s/it]
[Succeeded / Failed / Skipped / Total] 42 / 3 / 6 / 51:  17%|████▎                    | 51/300 [08:25<41:10,  9.92s/it]
[Succeeded / Failed / Skipped / Total] 42 / 3 / 6 / 51:  17%|████▎                    | 52/300 [08:33<40:51,  9.88s/it]
[Succeeded / Failed / Skipped / Total] 43 / 3 / 6 / 52:  17%|████▎                    | 52/300 [08:34<40:51,  9.88s/it]
[Succeeded / Failed / Skipped / Total] 43 / 3 / 6 / 52:  18%|████▍                    | 53/300 [09:06<42:25, 10.30s/it]
[Succeeded / Failed / Skipped / Total] 43 / 4 / 6 / 53:  18%|████▍                    | 53/300 [09:06<42:25, 10.31s/it]
[Succeeded / Failed / Skipped / Total] 43 / 4 / 6 / 53:  18%|████▌                    | 54/300 [09:13<42:03, 10.26s/it]
[Succeeded / Failed / Skipped / Total] 44 / 4 / 6 / 54:  18%|████▌                    | 54/300 [09:13<42:03, 10.26s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 77 / 4 / 19 / 100:  34%|███████▍              | 101/300 [14:28<28:30,  8.60s/it]
[Succeeded / Failed / Skipped / Total] 78 / 4 / 19 / 101:  34%|███████▍              | 101/300 [14:28<28:30,  8.60s/it]
[Succeeded / Failed / Skipped / Total] 78 / 4 / 19 / 101:  34%|███████▍              | 102/300 [15:02<29:12,  8.85s/it]
[Succeeded / Failed / Skipped / Total] 78 / 5 / 19 / 102:  34%|███████▍              | 102/300 [15:02<29:12,  8.85s/it]
[Succeeded / Failed / Skipped / Total] 78 / 5 / 19 / 102:  34%|███████▌              | 103/300 [15:02<28:46,  8.77s/it]
[Succeeded / Failed / Skipped / Total] 78 / 5 / 20 / 103:  34%|███████▌              | 103/300 [15:02<28:46,  8.77s/it]
[Succeeded / Failed / Skipped / Total] 78 / 5 / 20 / 103:  35%|███████▋              | 104/300 [15:09<28:34,  8.75s/it]
[Succeeded / Failed / Skipped / Total] 79 / 5 / 20 / 104:  35%|███████▋              | 104/300 [15:10<28:35,  8.75s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 114 / 10 / 26 / 150:  50%|██████████          | 151/300 [23:25<23:07,  9.31s/it]
[Succeeded / Failed / Skipped / Total] 115 / 10 / 26 / 151:  50%|██████████          | 151/300 [23:25<23:07,  9.31s/it]
[Succeeded / Failed / Skipped / Total] 115 / 10 / 26 / 151:  51%|██████████▏         | 152/300 [24:03<23:25,  9.50s/it]
[Succeeded / Failed / Skipped / Total] 116 / 10 / 26 / 152:  51%|██████████▏         | 152/300 [24:03<23:25,  9.50s/it]
[Succeeded / Failed / Skipped / Total] 116 / 10 / 26 / 152:  51%|██████████▏         | 153/300 [24:11<23:14,  9.49s/it]
[Succeeded / Failed / Skipped / Total] 117 / 10 / 26 / 153:  51%|██████████▏         | 153/300 [24:11<23:14,  9.49s/it]
[Succeeded / Failed / Skipped / Total] 117 / 10 / 26 / 153:  51%|██████████▎         | 154/300 [24:17<23:01,  9.46s/it]
[Succeeded / Failed / Skipped / Total] 118 / 10 / 26 / 154:  51%|██████████▎         | 154/300 [24:17<23:01,  9.46s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 149 / 12 / 39 / 200:  67%|█████████████▍      | 201/300 [32:49<16:09,  9.80s/it]
[Succeeded / Failed / Skipped / Total] 150 / 12 / 39 / 201:  67%|█████████████▍      | 201/300 [32:49<16:09,  9.80s/it]
[Succeeded / Failed / Skipped / Total] 150 / 12 / 39 / 201:  67%|█████████████▍      | 202/300 [33:04<16:02,  9.82s/it]
[Succeeded / Failed / Skipped / Total] 151 / 12 / 39 / 202:  67%|█████████████▍      | 202/300 [33:04<16:02,  9.82s/it]
[Succeeded / Failed / Skipped / Total] 151 / 12 / 39 / 202:  68%|█████████████▌      | 203/300 [33:17<15:54,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 152 / 12 / 39 / 203:  68%|█████████████▌      | 203/300 [33:17<15:54,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 152 / 12 / 39 / 203:  68%|█████████████▌      | 204/300 [33:17<15:40,  9.79s/it]
[Succeeded / Failed / Skipped / Total] 152 / 12 / 40 / 204:  68%|█████████████▌      | 204/300 [33:17<15:40,  9.79s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 187 / 17 / 46 / 250:  84%|████████████████▋   | 251/300 [43:36<08:30, 10.43s/it]
[Succeeded / Failed / Skipped / Total] 188 / 17 / 46 / 251:  84%|████████████████▋   | 251/300 [43:36<08:30, 10.43s/it]
[Succeeded / Failed / Skipped / Total] 188 / 17 / 46 / 251:  84%|████████████████▊   | 252/300 [43:40<08:19, 10.40s/it]
[Succeeded / Failed / Skipped / Total] 189 / 17 / 46 / 252:  84%|████████████████▊   | 252/300 [43:40<08:19, 10.40s/it]
[Succeeded / Failed / Skipped / Total] 189 / 17 / 46 / 252:  84%|████████████████▊   | 253/300 [43:47<08:08, 10.39s/it]
[Succeeded / Failed / Skipped / Total] 190 / 17 / 46 / 253:  84%|████████████████▊   | 253/300 [43:47<08:08, 10.39s/it]
[Succeeded / Failed / Skipped / Total] 190 / 17 / 46 / 253:  85%|████████████████▉   | 254/300 [43:54<07:57, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 191 / 17 / 46 / 254:  85%|████████████████▉   | 254/300 [43:54<07:57, 10.37s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 225    |
| Number of failed attacks:     | 22     |
| Number of skipped attacks:    | 53     |
| Original accuracy:            | 82.33% |
| Accuracy under attack:        | 7.33%  |
| Attack success rate:          | 91.09% |
| Average perturbed word %:     | 9.62%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 161.47 |
+-------------------------------+--------+


In [47]:
runAttack(bert_knn7_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn7ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                           | 1/300 [24:56<124:15:29, 1496.09s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                      | 1/300 [24:56<124:15:29, 1496.09s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                       | 2/300 [25:07<62:24:48, 753.99s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                       | 2/300 [25:07<62:24:51, 754.00s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                       | 3/300 [25:45<42:30:34, 515.27s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▏                       | 3/300 [25:45<42:30:37, 515.28s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                       | 4/300 [26:19<32:28:34, 394.98s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                       | 4/300 [26:19<32:28:35, 394.99s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 32 / 7 / 11 / 50:  17%|███▋                  | 51/300 [35:20<2:52:35, 41.59s/it]
[Succeeded / Failed / Skipped / Total] 33 / 7 / 11 / 51:  17%|███▋                  | 51/300 [35:20<2:52:35, 41.59s/it]
[Succeeded / Failed / Skipped / Total] 33 / 7 / 11 / 51:  17%|███▊                  | 52/300 [35:24<2:48:50, 40.85s/it]
[Succeeded / Failed / Skipped / Total] 34 / 7 / 11 / 52:  17%|███▊                  | 52/300 [35:24<2:48:50, 40.85s/it]
[Succeeded / Failed / Skipped / Total] 34 / 7 / 11 / 52:  18%|███▉                  | 53/300 [36:03<2:48:01, 40.82s/it]
[Succeeded / Failed / Skipped / Total] 34 / 8 / 11 / 53:  18%|███▉                  | 53/300 [36:03<2:48:01, 40.82s/it]
[Succeeded / Failed / Skipped / Total] 34 / 8 / 11 / 53:  18%|███▉                  | 54/300 [36:12<2:44:58, 40.24s/it]
[Succeeded / Failed / Skipped / Total] 35 / 8 / 11 / 54:  18%|███▉                  | 54/300 [36:12<2:44:58, 40.24s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 70 / 10 / 20 / 100:  34%|██████▍            | 101/300 [45:14<1:29:08, 26.88s/it]
[Succeeded / Failed / Skipped / Total] 71 / 10 / 20 / 101:  34%|██████▍            | 101/300 [45:14<1:29:08, 26.88s/it]
[Succeeded / Failed / Skipped / Total] 71 / 10 / 20 / 101:  34%|██████▍            | 102/300 [45:30<1:28:21, 26.77s/it]
[Succeeded / Failed / Skipped / Total] 72 / 10 / 20 / 102:  34%|██████▍            | 102/300 [45:30<1:28:21, 26.77s/it]
[Succeeded / Failed / Skipped / Total] 72 / 10 / 20 / 102:  34%|██████▌            | 103/300 [45:31<1:27:03, 26.52s/it]
[Succeeded / Failed / Skipped / Total] 72 / 10 / 21 / 103:  34%|██████▌            | 103/300 [45:31<1:27:03, 26.52s/it]
[Succeeded / Failed / Skipped / Total] 72 / 10 / 21 / 103:  35%|██████▌            | 104/300 [45:34<1:25:54, 26.30s/it]
[Succeeded / Failed / Skipped / Total] 73 / 10 / 21 / 104:  35%|██████▌            | 104/300 [45:34<1:25:54, 26.30s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 99 / 19 / 32 / 150:  50%|██████████▌          | 151/300 [56:43<55:57, 22.54s/it]
[Succeeded / Failed / Skipped / Total] 100 / 19 / 32 / 151:  50%|██████████          | 151/300 [56:43<55:57, 22.54s/it]
[Succeeded / Failed / Skipped / Total] 100 / 19 / 32 / 151:  51%|██████████▏         | 152/300 [57:32<56:01, 22.71s/it]
[Succeeded / Failed / Skipped / Total] 100 / 20 / 32 / 152:  51%|██████████▏         | 152/300 [57:32<56:01, 22.71s/it]
[Succeeded / Failed / Skipped / Total] 100 / 20 / 32 / 152:  51%|██████████▏         | 153/300 [57:50<55:34, 22.68s/it]
[Succeeded / Failed / Skipped / Total] 101 / 20 / 32 / 153:  51%|██████████▏         | 153/300 [57:50<55:34, 22.68s/it]
[Succeeded / Failed / Skipped / Total] 101 / 20 / 32 / 153:  51%|██████████▎         | 154/300 [57:56<54:56, 22.58s/it]
[Succeeded / Failed / Skipped / Total] 102 / 20 / 32 / 154:  51%|██████████▎         | 154/300 [57:56<54:56, 22.58s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 129 / 26 / 45 / 200:  67%|████████████      | 201/300 [1:09:34<34:15, 20.77s/it]
[Succeeded / Failed / Skipped / Total] 130 / 26 / 45 / 201:  67%|████████████      | 201/300 [1:09:34<34:15, 20.77s/it]
[Succeeded / Failed / Skipped / Total] 130 / 26 / 45 / 201:  67%|████████████      | 202/300 [1:09:38<33:47, 20.69s/it]
[Succeeded / Failed / Skipped / Total] 131 / 26 / 45 / 202:  67%|████████████      | 202/300 [1:09:38<33:47, 20.69s/it]
[Succeeded / Failed / Skipped / Total] 131 / 26 / 45 / 202:  68%|████████████▏     | 203/300 [1:10:32<33:42, 20.85s/it]
[Succeeded / Failed / Skipped / Total] 131 / 27 / 45 / 203:  68%|████████████▏     | 203/300 [1:10:33<33:42, 20.85s/it]
[Succeeded / Failed / Skipped / Total] 131 / 27 / 45 / 203:  68%|████████████▏     | 204/300 [1:10:37<33:14, 20.77s/it]
[Succeeded / Failed / Skipped / Total] 132 / 27 / 45 / 204:  68%|████████████▏     | 204/300 [1:10:37<33:14, 20.77s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 166 / 32 / 52 / 250:  84%|███████████████   | 251/300 [1:22:35<16:07, 19.74s/it]
[Succeeded / Failed / Skipped / Total] 167 / 32 / 52 / 251:  84%|███████████████   | 251/300 [1:22:35<16:07, 19.74s/it]
[Succeeded / Failed / Skipped / Total] 167 / 32 / 52 / 251:  84%|███████████████   | 252/300 [1:22:39<15:44, 19.68s/it]
[Succeeded / Failed / Skipped / Total] 168 / 32 / 52 / 252:  84%|███████████████   | 252/300 [1:22:39<15:44, 19.68s/it]
[Succeeded / Failed / Skipped / Total] 168 / 32 / 52 / 252:  84%|███████████████▏  | 253/300 [1:22:45<15:22, 19.63s/it]
[Succeeded / Failed / Skipped / Total] 169 / 32 / 52 / 253:  84%|███████████████▏  | 253/300 [1:22:45<15:22, 19.63s/it]
[Succeeded / Failed / Skipped / Total] 169 / 32 / 52 / 253:  85%|███████████████▏  | 254/300 [1:22:51<15:00, 19.57s/it]
[Succeeded / Failed / Skipped / Total] 170 / 32 / 52 / 254:  85%|███████████████▏  | 254/300 [1:22:51<15:00, 19.57s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 206    |
| Number of failed attacks:     | 36     |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 80.67% |
| Accuracy under attack:        | 12.0%  |
| Attack success rate:          | 85.12% |
| Average perturbed word %:     | 5.22%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 178.29 |
+-------------------------------+--------+


In [48]:
runAttack(bert_knn35_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn35'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn35ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:21<1:46:39, 21.40s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:21<1:46:44, 21.42s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                           | 2/300 [00:24<59:51, 12.05s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                           | 2/300 [00:24<59:51, 12.05s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:43<1:11:04, 14.36s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:43<1:11:06, 14.36s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:18<1:36:37, 19.59s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:18<1:36:40, 19.59s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 34 / 7 / 9 / 50:  17%|████▎                    | 51/300 [10:59<53:37, 12.92s/it]
[Succeeded / Failed / Skipped / Total] 35 / 7 / 9 / 51:  17%|████▎                    | 51/300 [10:59<53:37, 12.92s/it]
[Succeeded / Failed / Skipped / Total] 35 / 7 / 9 / 51:  17%|████▎                    | 52/300 [11:02<52:38, 12.73s/it]
[Succeeded / Failed / Skipped / Total] 36 / 7 / 9 / 52:  17%|████▎                    | 52/300 [11:02<52:38, 12.73s/it]
[Succeeded / Failed / Skipped / Total] 36 / 7 / 9 / 52:  18%|████▍                    | 53/300 [11:19<52:45, 12.82s/it]
[Succeeded / Failed / Skipped / Total] 37 / 7 / 9 / 53:  18%|████▍                    | 53/300 [11:19<52:45, 12.82s/it]
[Succeeded / Failed / Skipped / Total] 37 / 7 / 9 / 53:  18%|████▌                    | 54/300 [11:51<53:59, 13.17s/it]
[Succeeded / Failed / Skipped / Total] 37 / 8 / 9 / 54:  18%|████▌                    | 54/300 [11:51<53:59, 13.17s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 72 / 9 / 19 / 100:  34%|███████▍              | 101/300 [19:20<38:07, 11.49s/it]
[Succeeded / Failed / Skipped / Total] 73 / 9 / 19 / 101:  34%|███████▍              | 101/300 [19:20<38:07, 11.49s/it]
[Succeeded / Failed / Skipped / Total] 73 / 9 / 19 / 101:  34%|███████▍              | 102/300 [19:27<37:46, 11.45s/it]
[Succeeded / Failed / Skipped / Total] 74 / 9 / 19 / 102:  34%|███████▍              | 102/300 [19:27<37:46, 11.45s/it]
[Succeeded / Failed / Skipped / Total] 74 / 9 / 19 / 102:  34%|███████▌              | 103/300 [19:27<37:13, 11.34s/it]
[Succeeded / Failed / Skipped / Total] 74 / 9 / 20 / 103:  34%|███████▌              | 103/300 [19:27<37:13, 11.34s/it]
[Succeeded / Failed / Skipped / Total] 74 / 9 / 20 / 103:  35%|███████▋              | 104/300 [19:30<36:46, 11.26s/it]
[Succeeded / Failed / Skipped / Total] 75 / 9 / 20 / 104:  35%|███████▋              | 104/300 [19:30<36:46, 11.26s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 108 / 14 / 28 / 150:  50%|██████████          | 151/300 [30:28<30:04, 12.11s/it]
[Succeeded / Failed / Skipped / Total] 109 / 14 / 28 / 151:  50%|██████████          | 151/300 [30:28<30:04, 12.11s/it]
[Succeeded / Failed / Skipped / Total] 109 / 14 / 28 / 151:  51%|██████████▏         | 152/300 [31:18<30:28, 12.36s/it]
[Succeeded / Failed / Skipped / Total] 109 / 15 / 28 / 152:  51%|██████████▏         | 152/300 [31:18<30:28, 12.36s/it]
[Succeeded / Failed / Skipped / Total] 109 / 15 / 28 / 152:  51%|██████████▏         | 153/300 [31:30<30:15, 12.35s/it]
[Succeeded / Failed / Skipped / Total] 110 / 15 / 28 / 153:  51%|██████████▏         | 153/300 [31:30<30:16, 12.35s/it]
[Succeeded / Failed / Skipped / Total] 110 / 15 / 28 / 153:  51%|██████████▎         | 154/300 [31:36<29:58, 12.32s/it]
[Succeeded / Failed / Skipped / Total] 111 / 15 / 28 / 154:  51%|██████████▎         | 154/300 [31:36<29:58, 12.32s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 137 / 20 / 43 / 200:  67%|█████████████▍      | 201/300 [43:41<21:31, 13.04s/it]
[Succeeded / Failed / Skipped / Total] 138 / 20 / 43 / 201:  67%|█████████████▍      | 201/300 [43:41<21:31, 13.04s/it]
[Succeeded / Failed / Skipped / Total] 138 / 20 / 43 / 201:  67%|█████████████▍      | 202/300 [43:46<21:14, 13.00s/it]
[Succeeded / Failed / Skipped / Total] 139 / 20 / 43 / 202:  67%|█████████████▍      | 202/300 [43:46<21:14, 13.00s/it]
[Succeeded / Failed / Skipped / Total] 139 / 20 / 43 / 202:  68%|█████████████▌      | 203/300 [43:55<20:59, 12.98s/it]
[Succeeded / Failed / Skipped / Total] 140 / 20 / 43 / 203:  68%|█████████████▌      | 203/300 [43:55<20:59, 12.98s/it]
[Succeeded / Failed / Skipped / Total] 140 / 20 / 43 / 203:  68%|█████████████▌      | 204/300 [44:07<20:45, 12.98s/it]
[Succeeded / Failed / Skipped / Total] 141 / 20 / 43 / 204:  68%|█████████████▌      | 204/300 [44:07<20:45, 12.98s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 173 / 26 / 51 / 250:  84%|████████████████▋   | 251/300 [54:54<10:43, 13.13s/it]
[Succeeded / Failed / Skipped / Total] 174 / 26 / 51 / 251:  84%|████████████████▋   | 251/300 [54:54<10:43, 13.13s/it]
[Succeeded / Failed / Skipped / Total] 174 / 26 / 51 / 251:  84%|████████████████▊   | 252/300 [54:56<10:27, 13.08s/it]
[Succeeded / Failed / Skipped / Total] 175 / 26 / 51 / 252:  84%|████████████████▊   | 252/300 [54:56<10:27, 13.08s/it]
[Succeeded / Failed / Skipped / Total] 175 / 26 / 51 / 252:  84%|████████████████▊   | 253/300 [55:04<10:13, 13.06s/it]
[Succeeded / Failed / Skipped / Total] 176 / 26 / 51 / 253:  84%|████████████████▊   | 253/300 [55:04<10:13, 13.06s/it]
[Succeeded / Failed / Skipped / Total] 176 / 26 / 51 / 253:  85%|████████████████▉   | 254/300 [55:13<10:00, 13.05s/it]
[Succeeded / Failed / Skipped / Total] 177 / 26 / 51 / 254:  85%|████████████████▉   | 254/300 [55:13<10:00, 13.05s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 214    |
| Number of failed attacks:     | 30     |
| Number of skipped attacks:    | 56     |
| Original accuracy:            | 81.33% |
| Accuracy under attack:        | 10.0%  |
| Attack success rate:          | 87.7%  |
| Average perturbed word %:     | 7.65%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 170.29 |
+-------------------------------+--------+


In [49]:
runAttack(bert_knn175_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn175'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn175ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:20<1:43:58, 20.87s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:20<1:44:06, 20.89s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                           | 2/300 [00:23<59:18, 11.94s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                           | 2/300 [00:23<59:21, 11.95s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [01:00<1:39:40, 20.14s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [01:00<1:39:42, 20.14s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:35<1:57:13, 23.76s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:35<1:57:14, 23.77s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 37 / 4 / 9 / 50:  17%|████▎                    | 51/300 [09:38<47:03, 11.34s/it]
[Succeeded / Failed / Skipped / Total] 38 / 4 / 9 / 51:  17%|████▎                    | 51/300 [09:38<47:03, 11.34s/it]
[Succeeded / Failed / Skipped / Total] 38 / 4 / 9 / 51:  17%|████▎                    | 52/300 [09:41<46:12, 11.18s/it]
[Succeeded / Failed / Skipped / Total] 39 / 4 / 9 / 52:  17%|████▎                    | 52/300 [09:41<46:12, 11.18s/it]
[Succeeded / Failed / Skipped / Total] 39 / 4 / 9 / 52:  18%|████▍                    | 53/300 [09:48<45:44, 11.11s/it]
[Succeeded / Failed / Skipped / Total] 40 / 4 / 9 / 53:  18%|████▍                    | 53/300 [09:48<45:44, 11.11s/it]
[Succeeded / Failed / Skipped / Total] 40 / 4 / 9 / 53:  18%|████▌                    | 54/300 [10:02<45:45, 11.16s/it]
[Succeeded / Failed / Skipped / Total] 41 / 4 / 9 / 54:  18%|████▌                    | 54/300 [10:02<45:45, 11.16s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 75 / 5 / 20 / 100:  34%|███████▍              | 101/300 [16:11<31:54,  9.62s/it]
[Succeeded / Failed / Skipped / Total] 75 / 5 / 21 / 101:  34%|███████▍              | 101/300 [16:11<31:54,  9.62s/it]
[Succeeded / Failed / Skipped / Total] 75 / 5 / 21 / 101:  34%|███████▍              | 102/300 [16:38<32:18,  9.79s/it]
[Succeeded / Failed / Skipped / Total] 76 / 5 / 21 / 102:  34%|███████▍              | 102/300 [16:38<32:18,  9.79s/it]
[Succeeded / Failed / Skipped / Total] 76 / 5 / 21 / 102:  34%|███████▌              | 103/300 [16:39<31:50,  9.70s/it]
[Succeeded / Failed / Skipped / Total] 76 / 5 / 22 / 103:  34%|███████▌              | 103/300 [16:39<31:50,  9.70s/it]
[Succeeded / Failed / Skipped / Total] 76 / 5 / 22 / 103:  35%|███████▋              | 104/300 [16:41<31:27,  9.63s/it]
[Succeeded / Failed / Skipped / Total] 77 / 5 / 22 / 104:  35%|███████▋              | 104/300 [16:41<31:27,  9.63s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 109 / 8 / 33 / 150:  50%|██████████▌          | 151/300 [26:34<26:13, 10.56s/it]
[Succeeded / Failed / Skipped / Total] 110 / 8 / 33 / 151:  50%|██████████▌          | 151/300 [26:34<26:13, 10.56s/it]
[Succeeded / Failed / Skipped / Total] 110 / 8 / 33 / 151:  51%|██████████▋          | 152/300 [26:50<26:07, 10.59s/it]
[Succeeded / Failed / Skipped / Total] 111 / 8 / 33 / 152:  51%|██████████▋          | 152/300 [26:50<26:07, 10.59s/it]
[Succeeded / Failed / Skipped / Total] 111 / 8 / 33 / 152:  51%|██████████▋          | 153/300 [26:59<25:56, 10.59s/it]
[Succeeded / Failed / Skipped / Total] 112 / 8 / 33 / 153:  51%|██████████▋          | 153/300 [26:59<25:56, 10.59s/it]
[Succeeded / Failed / Skipped / Total] 112 / 8 / 33 / 153:  51%|██████████▊          | 154/300 [27:06<25:41, 10.56s/it]
[Succeeded / Failed / Skipped / Total] 113 / 8 / 33 / 154:  51%|██████████▊          | 154/300 [27:06<25:41, 10.56s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 142 / 11 / 47 / 200:  67%|█████████████▍      | 201/300 [37:20<18:23, 11.15s/it]
[Succeeded / Failed / Skipped / Total] 143 / 11 / 47 / 201:  67%|█████████████▍      | 201/300 [37:20<18:23, 11.15s/it]
[Succeeded / Failed / Skipped / Total] 143 / 11 / 47 / 201:  67%|█████████████▍      | 202/300 [37:27<18:10, 11.13s/it]
[Succeeded / Failed / Skipped / Total] 144 / 11 / 47 / 202:  67%|█████████████▍      | 202/300 [37:27<18:10, 11.13s/it]
[Succeeded / Failed / Skipped / Total] 144 / 11 / 47 / 202:  68%|█████████████▌      | 203/300 [37:47<18:03, 11.17s/it]
[Succeeded / Failed / Skipped / Total] 145 / 11 / 47 / 203:  68%|█████████████▌      | 203/300 [37:47<18:03, 11.17s/it]
[Succeeded / Failed / Skipped / Total] 145 / 11 / 47 / 203:  68%|█████████████▌      | 204/300 [38:13<17:59, 11.24s/it]
[Succeeded / Failed / Skipped / Total] 146 / 11 / 47 / 204:  68%|█████████████▌      | 204/300 [38:13<17:59, 11.24s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 183 / 13 / 54 / 250:  84%|████████████████▋   | 251/300 [46:59<09:10, 11.23s/it]
[Succeeded / Failed / Skipped / Total] 183 / 13 / 55 / 251:  84%|████████████████▋   | 251/300 [46:59<09:10, 11.23s/it]
[Succeeded / Failed / Skipped / Total] 183 / 13 / 55 / 251:  84%|████████████████▊   | 252/300 [47:01<08:57, 11.20s/it]
[Succeeded / Failed / Skipped / Total] 184 / 13 / 55 / 252:  84%|████████████████▊   | 252/300 [47:01<08:57, 11.20s/it]
[Succeeded / Failed / Skipped / Total] 184 / 13 / 55 / 252:  84%|████████████████▊   | 253/300 [47:08<08:45, 11.18s/it]
[Succeeded / Failed / Skipped / Total] 185 / 13 / 55 / 253:  84%|████████████████▊   | 253/300 [47:08<08:45, 11.18s/it]
[Succeeded / Failed / Skipped / Total] 185 / 13 / 55 / 253:  85%|████████████████▉   | 254/300 [47:16<08:33, 11.17s/it]
[Succeeded / Failed / Skipped / Total] 186 / 13 / 55 / 254:  85%|████████████████▉   | 254/300 [47:16<08:33, 11.17s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 227    |
| Number of failed attacks:     | 13     |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 80.0%  |
| Accuracy under attack:        | 4.33%  |
| Attack success rate:          | 94.58% |
| Average perturbed word %:     | 9.15%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 142.61 |
+-------------------------------+--------+


#### CLIP

In [50]:
runAttack(clip_lr1_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr1'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr1ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:41<3:27:21, 41.61s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:41<3:27:21, 41.61s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [01:02<2:34:49, 31.17s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▏                         | 2/300 [01:02<2:34:51, 31.18s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▎                         | 3/300 [01:23<2:17:03, 27.69s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 3/300 [01:23<2:17:05, 27.69s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 4/300 [01:47<2:12:57, 26.95s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                         | 4/300 [01:47<2:12:58, 26.96s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 41 / 5 / 4 / 50:  17%|████▎                    | 51/300 [10:01<48:55, 11.79s/it]
[Succeeded / Failed / Skipped / Total] 42 / 5 / 4 / 51:  17%|████▎                    | 51/300 [10:01<48:55, 11.79s/it]
[Succeeded / Failed / Skipped / Total] 42 / 5 / 4 / 51:  17%|████▎                    | 52/300 [10:19<49:16, 11.92s/it]
[Succeeded / Failed / Skipped / Total] 42 / 6 / 4 / 52:  17%|████▎                    | 52/300 [10:19<49:16, 11.92s/it]
[Succeeded / Failed / Skipped / Total] 42 / 6 / 4 / 52:  18%|████▍                    | 53/300 [10:40<49:46, 12.09s/it]
[Succeeded / Failed / Skipped / Total] 43 / 6 / 4 / 53:  18%|████▍                    | 53/300 [10:40<49:46, 12.09s/it]
[Succeeded / Failed / Skipped / Total] 43 / 6 / 4 / 53:  18%|████▌                    | 54/300 [10:46<49:04, 11.97s/it]
[Succeeded / Failed / Skipped / Total] 44 / 6 / 4 / 54:  18%|████▌                    | 54/300 [10:46<49:04, 11.97s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 84 / 7 / 9 / 100:  34%|███████▋               | 101/300 [17:15<34:00, 10.25s/it]
[Succeeded / Failed / Skipped / Total] 85 / 7 / 9 / 101:  34%|███████▋               | 101/300 [17:15<34:00, 10.25s/it]
[Succeeded / Failed / Skipped / Total] 86 / 7 / 9 / 102:  34%|███████▊               | 102/300 [17:22<33:43, 10.22s/it]
[Succeeded / Failed / Skipped / Total] 86 / 7 / 9 / 102:  34%|███████▉               | 103/300 [17:27<33:24, 10.17s/it]
[Succeeded / Failed / Skipped / Total] 87 / 7 / 9 / 103:  34%|███████▉               | 103/300 [17:27<33:24, 10.17s/it]
[Succeeded / Failed / Skipped / Total] 87 / 7 / 9 / 103:  35%|███████▉               | 104/300 [17:45<33:27, 10.24s/it]
[Succeeded / Failed / Skipped / Total] 88 / 7 / 9 / 104:  35%|███████▉               | 104/300 [17:45<33:27, 10.24s/it]
[Succeeded / Failed / Skipped / Total] 88 / 7 / 9 / 104:  35%|████████               | 105/300 [17:47<33:03, 10.17s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 126 / 10 / 14 / 150:  50%|██████████          | 151/300 [25:53<25:32, 10.29s/it]
[Succeeded / Failed / Skipped / Total] 127 / 10 / 14 / 151:  50%|██████████          | 151/300 [25:53<25:32, 10.29s/it]
[Succeeded / Failed / Skipped / Total] 127 / 10 / 14 / 151:  51%|██████████▏         | 152/300 [26:01<25:20, 10.27s/it]
[Succeeded / Failed / Skipped / Total] 128 / 10 / 14 / 152:  51%|██████████▏         | 152/300 [26:01<25:20, 10.27s/it]
[Succeeded / Failed / Skipped / Total] 128 / 10 / 14 / 152:  51%|██████████▏         | 153/300 [26:04<25:03, 10.23s/it]
[Succeeded / Failed / Skipped / Total] 129 / 10 / 14 / 153:  51%|██████████▏         | 153/300 [26:04<25:03, 10.23s/it]
[Succeeded / Failed / Skipped / Total] 129 / 10 / 15 / 154:  51%|██████████▎         | 154/300 [26:04<24:43, 10.16s/it]
[Succeeded / Failed / Skipped / Total] 129 / 10 / 15 / 154:  52%|██████████▎         | 155/300 [26:10<24:29, 10.14s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 166 / 14 / 20 / 200:  67%|█████████████▍      | 201/300 [33:53<16:41, 10.12s/it]
[Succeeded / Failed / Skipped / Total] 167 / 14 / 20 / 201:  67%|█████████████▍      | 201/300 [33:53<16:41, 10.12s/it]
[Succeeded / Failed / Skipped / Total] 167 / 14 / 20 / 201:  67%|█████████████▍      | 202/300 [34:01<16:30, 10.10s/it]
[Succeeded / Failed / Skipped / Total] 168 / 14 / 20 / 202:  67%|█████████████▍      | 202/300 [34:01<16:30, 10.10s/it]
[Succeeded / Failed / Skipped / Total] 168 / 14 / 20 / 202:  68%|█████████████▌      | 203/300 [34:16<16:22, 10.13s/it]
[Succeeded / Failed / Skipped / Total] 169 / 14 / 20 / 203:  68%|█████████████▌      | 203/300 [34:16<16:22, 10.13s/it]
[Succeeded / Failed / Skipped / Total] 169 / 14 / 21 / 204:  68%|█████████████▌      | 204/300 [34:16<16:07, 10.08s/it]
[Succeeded / Failed / Skipped / Total] 169 / 14 / 21 / 204:  68%|█████████████▋      | 205/300 [34:25<15:57, 10.07s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 213 / 14 / 24 / 251:  84%|████████████████▋   | 251/300 [41:58<08:11, 10.03s/it]
[Succeeded / Failed / Skipped / Total] 213 / 14 / 24 / 251:  84%|████████████████▋   | 251/300 [42:11<08:14, 10.08s/it]
[Succeeded / Failed / Skipped / Total] 213 / 14 / 24 / 251:  84%|████████████████▊   | 252/300 [42:14<08:02, 10.06s/it]
[Succeeded / Failed / Skipped / Total] 214 / 14 / 24 / 252:  84%|████████████████▊   | 252/300 [42:14<08:02, 10.06s/it]
[Succeeded / Failed / Skipped / Total] 214 / 14 / 24 / 252:  84%|████████████████▊   | 253/300 [42:23<07:52, 10.05s/it]
[Succeeded / Failed / Skipped / Total] 215 / 14 / 24 / 253:  84%|████████████████▊   | 253/300 [42:23<07:52, 10.05s/it]
[Succeeded / Failed / Skipped / Total] 215 / 14 / 24 / 253:  85%|████████████████▉   | 254/300 [42:25<07:41, 10.02s/it]
[Succeeded / Failed / Skipped / Total] 216 / 14 / 24 / 254:  85%|████████████████▉   | 254/300 [42:25<07:41, 10.02s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 250    |
| Number of failed attacks:     | 21     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 7.0%   |
| Attack success rate:          | 92.25% |
| Average perturbed word %:     | 20.42% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 227.05 |
+-------------------------------+--------+


In [51]:
runAttack(clip_lr01_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr01'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr01ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:22<1:53:33, 22.79s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:22<1:53:38, 22.80s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:42<1:45:12, 21.18s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▏                         | 2/300 [00:42<1:45:15, 21.19s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▎                         | 3/300 [01:03<1:44:42, 21.15s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 3/300 [01:03<1:44:44, 21.16s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 4/300 [01:26<1:47:10, 21.73s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                         | 4/300 [01:26<1:47:13, 21.73s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 42 / 4 / 4 / 50:  17%|████▎                    | 51/300 [09:21<45:41, 11.01s/it]
[Succeeded / Failed / Skipped / Total] 43 / 4 / 4 / 51:  17%|████▎                    | 51/300 [09:21<45:41, 11.01s/it]
[Succeeded / Failed / Skipped / Total] 43 / 4 / 4 / 51:  17%|████▎                    | 52/300 [09:39<46:05, 11.15s/it]
[Succeeded / Failed / Skipped / Total] 43 / 5 / 4 / 52:  17%|████▎                    | 52/300 [09:39<46:05, 11.15s/it]
[Succeeded / Failed / Skipped / Total] 43 / 5 / 4 / 52:  18%|████▍                    | 53/300 [10:00<46:38, 11.33s/it]
[Succeeded / Failed / Skipped / Total] 43 / 6 / 4 / 53:  18%|████▍                    | 53/300 [10:00<46:39, 11.33s/it]
[Succeeded / Failed / Skipped / Total] 43 / 6 / 4 / 53:  18%|████▌                    | 54/300 [10:06<46:01, 11.22s/it]
[Succeeded / Failed / Skipped / Total] 44 / 6 / 4 / 54:  18%|████▌                    | 54/300 [10:06<46:01, 11.22s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 84 / 7 / 9 / 100:  34%|███████▋               | 101/300 [16:31<32:32,  9.81s/it]
[Succeeded / Failed / Skipped / Total] 85 / 7 / 9 / 101:  34%|███████▋               | 101/300 [16:31<32:32,  9.81s/it]
[Succeeded / Failed / Skipped / Total] 86 / 7 / 9 / 102:  34%|███████▊               | 102/300 [16:38<32:17,  9.79s/it]
[Succeeded / Failed / Skipped / Total] 86 / 7 / 9 / 102:  34%|███████▉               | 103/300 [16:43<31:59,  9.74s/it]
[Succeeded / Failed / Skipped / Total] 87 / 7 / 9 / 103:  34%|███████▉               | 103/300 [16:43<31:59,  9.74s/it]
[Succeeded / Failed / Skipped / Total] 87 / 7 / 9 / 103:  35%|███████▉               | 104/300 [16:59<32:01,  9.80s/it]
[Succeeded / Failed / Skipped / Total] 87 / 8 / 9 / 104:  35%|███████▉               | 104/300 [16:59<32:01,  9.80s/it]
[Succeeded / Failed / Skipped / Total] 87 / 8 / 9 / 104:  35%|████████               | 105/300 [17:02<31:38,  9.74s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 124 / 12 / 14 / 150:  50%|██████████          | 151/300 [25:06<24:46,  9.97s/it]
[Succeeded / Failed / Skipped / Total] 125 / 12 / 14 / 151:  50%|██████████          | 151/300 [25:06<24:46,  9.97s/it]
[Succeeded / Failed / Skipped / Total] 125 / 12 / 14 / 151:  51%|██████████▏         | 152/300 [25:14<24:34,  9.97s/it]
[Succeeded / Failed / Skipped / Total] 126 / 12 / 14 / 152:  51%|██████████▏         | 152/300 [25:14<24:34,  9.97s/it]
[Succeeded / Failed / Skipped / Total] 126 / 12 / 14 / 152:  51%|██████████▏         | 153/300 [25:17<24:18,  9.92s/it]
[Succeeded / Failed / Skipped / Total] 127 / 12 / 14 / 153:  51%|██████████▏         | 153/300 [25:17<24:18,  9.92s/it]
[Succeeded / Failed / Skipped / Total] 127 / 12 / 15 / 154:  51%|██████████▎         | 154/300 [25:17<23:58,  9.86s/it]
[Succeeded / Failed / Skipped / Total] 127 / 12 / 15 / 154:  52%|██████████▎         | 155/300 [25:24<23:45,  9.83s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 165 / 15 / 20 / 200:  67%|█████████████▍      | 201/300 [33:00<16:15,  9.85s/it]
[Succeeded / Failed / Skipped / Total] 166 / 15 / 20 / 201:  67%|█████████████▍      | 201/300 [33:00<16:15,  9.85s/it]
[Succeeded / Failed / Skipped / Total] 166 / 15 / 20 / 201:  67%|█████████████▍      | 202/300 [33:07<16:04,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 167 / 15 / 20 / 202:  67%|█████████████▍      | 202/300 [33:07<16:04,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 167 / 15 / 20 / 202:  68%|█████████████▌      | 203/300 [33:22<15:57,  9.87s/it]
[Succeeded / Failed / Skipped / Total] 168 / 15 / 20 / 203:  68%|█████████████▌      | 203/300 [33:22<15:57,  9.87s/it]
[Succeeded / Failed / Skipped / Total] 168 / 15 / 20 / 203:  68%|█████████████▌      | 204/300 [33:22<15:42,  9.82s/it]
[Succeeded / Failed / Skipped / Total] 168 / 15 / 21 / 204:  68%|█████████████▌      | 204/300 [33:22<15:42,  9.82s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 211 / 16 / 24 / 251:  84%|████████████████▋   | 251/300 [41:02<08:00,  9.81s/it]
[Succeeded / Failed / Skipped / Total] 211 / 16 / 24 / 251:  84%|████████████████▋   | 251/300 [41:13<08:02,  9.86s/it]
[Succeeded / Failed / Skipped / Total] 211 / 16 / 24 / 251:  84%|████████████████▊   | 252/300 [41:19<07:52,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 212 / 16 / 24 / 252:  84%|████████████████▊   | 252/300 [41:19<07:52,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 212 / 16 / 24 / 252:  84%|████████████████▊   | 253/300 [41:30<07:42,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 213 / 16 / 24 / 253:  84%|████████████████▊   | 253/300 [41:30<07:42,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 213 / 16 / 24 / 253:  85%|████████████████▉   | 254/300 [41:32<07:31,  9.81s/it]
[Succeeded / Failed / Skipped / Total] 214 / 16 / 24 / 254:  85%|████████████████▉   | 254/300 [41:33<07:31,  9.82s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 247    |
| Number of failed attacks:     | 24     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 8.0%   |
| Attack success rate:          | 91.14% |
| Average perturbed word %:     | 20.46% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 228.87 |
+-------------------------------+--------+


In [52]:
runAttack(clip_lr10_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr10'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr10ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:18<1:34:09, 18.90s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:18<1:34:14, 18.91s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:38<1:34:55, 19.11s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▏                         | 2/300 [00:38<1:34:58, 19.12s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▎                         | 3/300 [00:58<1:36:47, 19.56s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 3/300 [00:58<1:36:51, 19.57s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 4/300 [01:21<1:40:19, 20.34s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                         | 4/300 [01:21<1:40:20, 20.34s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 41 / 5 / 4 / 50:  17%|████▎                    | 51/300 [09:17<45:23, 10.94s/it]
[Succeeded / Failed / Skipped / Total] 42 / 5 / 4 / 51:  17%|████▎                    | 51/300 [09:17<45:23, 10.94s/it]
[Succeeded / Failed / Skipped / Total] 42 / 5 / 4 / 51:  17%|████▎                    | 52/300 [09:36<45:47, 11.08s/it]
[Succeeded / Failed / Skipped / Total] 42 / 6 / 4 / 52:  17%|████▎                    | 52/300 [09:36<45:47, 11.08s/it]
[Succeeded / Failed / Skipped / Total] 42 / 6 / 4 / 52:  18%|████▍                    | 53/300 [09:56<46:22, 11.26s/it]
[Succeeded / Failed / Skipped / Total] 43 / 6 / 4 / 53:  18%|████▍                    | 53/300 [09:56<46:22, 11.26s/it]
[Succeeded / Failed / Skipped / Total] 43 / 6 / 4 / 53:  18%|████▌                    | 54/300 [10:02<45:45, 11.16s/it]
[Succeeded / Failed / Skipped / Total] 44 / 6 / 4 / 54:  18%|████▌                    | 54/300 [10:02<45:45, 11.16s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 84 / 7 / 9 / 100:  34%|███████▋               | 101/300 [16:25<32:20,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 85 / 7 / 9 / 101:  34%|███████▋               | 101/300 [16:25<32:20,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 86 / 7 / 9 / 102:  34%|███████▊               | 102/300 [16:32<32:06,  9.73s/it]
[Succeeded / Failed / Skipped / Total] 86 / 7 / 9 / 102:  34%|███████▉               | 103/300 [16:37<31:47,  9.69s/it]
[Succeeded / Failed / Skipped / Total] 87 / 7 / 9 / 103:  34%|███████▉               | 103/300 [16:37<31:48,  9.69s/it]
[Succeeded / Failed / Skipped / Total] 87 / 7 / 9 / 103:  35%|███████▉               | 104/300 [16:54<31:51,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 88 / 7 / 9 / 104:  35%|███████▉               | 104/300 [16:54<31:51,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 88 / 7 / 9 / 104:  35%|████████               | 105/300 [16:56<31:27,  9.68s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 126 / 10 / 14 / 150:  50%|██████████          | 151/300 [24:57<24:38,  9.92s/it]
[Succeeded / Failed / Skipped / Total] 127 / 10 / 14 / 151:  50%|██████████          | 151/300 [24:57<24:38,  9.92s/it]
[Succeeded / Failed / Skipped / Total] 127 / 10 / 14 / 151:  51%|██████████▏         | 152/300 [25:06<24:26,  9.91s/it]
[Succeeded / Failed / Skipped / Total] 128 / 10 / 14 / 152:  51%|██████████▏         | 152/300 [25:06<24:26,  9.91s/it]
[Succeeded / Failed / Skipped / Total] 128 / 10 / 14 / 152:  51%|██████████▏         | 153/300 [25:08<24:09,  9.86s/it]
[Succeeded / Failed / Skipped / Total] 129 / 10 / 14 / 153:  51%|██████████▏         | 153/300 [25:09<24:09,  9.86s/it]
[Succeeded / Failed / Skipped / Total] 129 / 10 / 15 / 154:  51%|██████████▎         | 154/300 [25:09<23:50,  9.80s/it]
[Succeeded / Failed / Skipped / Total] 129 / 10 / 15 / 154:  52%|██████████▎         | 155/300 [25:15<23:37,  9.78s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 166 / 14 / 20 / 200:  67%|█████████████▍      | 201/300 [32:43<16:06,  9.77s/it]
[Succeeded / Failed / Skipped / Total] 167 / 14 / 20 / 201:  67%|█████████████▍      | 201/300 [32:43<16:06,  9.77s/it]
[Succeeded / Failed / Skipped / Total] 167 / 14 / 20 / 201:  67%|█████████████▍      | 202/300 [32:50<15:56,  9.76s/it]
[Succeeded / Failed / Skipped / Total] 168 / 14 / 20 / 202:  67%|█████████████▍      | 202/300 [32:50<15:56,  9.76s/it]
[Succeeded / Failed / Skipped / Total] 168 / 14 / 20 / 202:  68%|█████████████▌      | 203/300 [33:05<15:48,  9.78s/it]
[Succeeded / Failed / Skipped / Total] 169 / 14 / 20 / 203:  68%|█████████████▌      | 203/300 [33:05<15:48,  9.78s/it]
[Succeeded / Failed / Skipped / Total] 169 / 14 / 21 / 204:  68%|█████████████▌      | 204/300 [33:05<15:34,  9.73s/it]
[Succeeded / Failed / Skipped / Total] 169 / 14 / 21 / 204:  68%|█████████████▋      | 205/300 [33:14<15:24,  9.73s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 212 / 15 / 24 / 251:  84%|████████████████▋   | 251/300 [40:43<07:56,  9.73s/it]
[Succeeded / Failed / Skipped / Total] 212 / 15 / 24 / 251:  84%|████████████████▋   | 251/300 [40:52<07:58,  9.77s/it]
[Succeeded / Failed / Skipped / Total] 212 / 15 / 24 / 251:  84%|████████████████▊   | 252/300 [40:58<07:48,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 213 / 15 / 24 / 252:  84%|████████████████▊   | 252/300 [40:58<07:48,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 213 / 15 / 24 / 252:  84%|████████████████▊   | 253/300 [41:07<07:38,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 214 / 15 / 24 / 253:  84%|████████████████▊   | 253/300 [41:07<07:38,  9.75s/it]
[Succeeded / Failed / Skipped / Total] 214 / 15 / 24 / 253:  85%|████████████████▉   | 254/300 [41:10<07:27,  9.73s/it]
[Succeeded / Failed / Skipped / Total] 215 / 15 / 24 / 254:  85%|████████████████▉   | 254/300 [41:10<07:27,  9.73s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 249    |
| Number of failed attacks:     | 22     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 7.33%  |
| Attack success rate:          | 91.88% |
| Average perturbed word %:     | 20.32% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 226.87 |
+-------------------------------+--------+


In [53]:
runAttack(clip_rf7_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf7ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:14<1:10:28, 14.14s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:14<1:10:33, 14.16s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:33<1:23:02, 16.72s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▏                         | 2/300 [00:33<1:23:05, 16.73s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▎                         | 3/300 [00:41<1:07:42, 13.68s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 3/300 [00:41<1:07:44, 13.68s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 4/300 [01:02<1:16:43, 15.55s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                         | 4/300 [01:02<1:16:45, 15.56s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 31 / 16 / 3 / 50:  17%|████                    | 51/300 [10:34<51:36, 12.44s/it]
[Succeeded / Failed / Skipped / Total] 31 / 17 / 3 / 51:  17%|████                    | 51/300 [10:34<51:36, 12.44s/it]
[Succeeded / Failed / Skipped / Total] 31 / 17 / 3 / 51:  17%|████▏                   | 52/300 [10:51<51:47, 12.53s/it]
[Succeeded / Failed / Skipped / Total] 31 / 18 / 3 / 52:  17%|████▏                   | 52/300 [10:51<51:47, 12.53s/it]
[Succeeded / Failed / Skipped / Total] 31 / 18 / 3 / 52:  18%|████▏                   | 53/300 [11:10<52:03, 12.65s/it]
[Succeeded / Failed / Skipped / Total] 32 / 18 / 3 / 53:  18%|████▏                   | 53/300 [11:10<52:03, 12.65s/it]
[Succeeded / Failed / Skipped / Total] 32 / 18 / 3 / 53:  18%|████▎                   | 54/300 [11:16<51:21, 12.53s/it]
[Succeeded / Failed / Skipped / Total] 33 / 18 / 3 / 54:  18%|████▎                   | 54/300 [11:16<51:21, 12.53s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 65 / 24 / 11 / 100:  34%|███████              | 101/300 [19:32<38:30, 11.61s/it]
[Succeeded / Failed / Skipped / Total] 66 / 24 / 11 / 101:  34%|███████              | 101/300 [19:32<38:30, 11.61s/it]
[Succeeded / Failed / Skipped / Total] 66 / 24 / 11 / 101:  34%|███████▏             | 102/300 [19:57<38:44, 11.74s/it]
[Succeeded / Failed / Skipped / Total] 67 / 24 / 11 / 102:  34%|███████▏             | 102/300 [19:57<38:44, 11.74s/it]
[Succeeded / Failed / Skipped / Total] 67 / 24 / 11 / 102:  34%|███████▏             | 103/300 [20:09<38:33, 11.74s/it]
[Succeeded / Failed / Skipped / Total] 68 / 24 / 11 / 103:  34%|███████▏             | 103/300 [20:09<38:33, 11.74s/it]
[Succeeded / Failed / Skipped / Total] 68 / 24 / 11 / 103:  35%|███████▎             | 104/300 [20:27<38:33, 11.80s/it]
[Succeeded / Failed / Skipped / Total] 68 / 25 / 11 / 104:  35%|███████▎             | 104/300 [20:27<38:33, 11.80s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 97 / 37 / 16 / 150:  50%|██████████▌          | 151/300 [30:46<30:22, 12.23s/it]
[Succeeded / Failed / Skipped / Total] 98 / 37 / 16 / 151:  50%|██████████▌          | 151/300 [30:46<30:22, 12.23s/it]
[Succeeded / Failed / Skipped / Total] 98 / 37 / 16 / 151:  51%|██████████▋          | 152/300 [31:01<30:12, 12.25s/it]
[Succeeded / Failed / Skipped / Total] 99 / 37 / 16 / 152:  51%|██████████▋          | 152/300 [31:01<30:12, 12.25s/it]
[Succeeded / Failed / Skipped / Total] 99 / 37 / 16 / 152:  51%|██████████▋          | 153/300 [31:16<30:03, 12.27s/it]
[Succeeded / Failed / Skipped / Total] 100 / 37 / 16 / 153:  51%|██████████▏         | 153/300 [31:17<30:03, 12.27s/it]
[Succeeded / Failed / Skipped / Total] 100 / 37 / 17 / 154:  51%|██████████▎         | 154/300 [31:17<29:39, 12.19s/it]
[Succeeded / Failed / Skipped / Total] 100 / 37 / 17 / 154:  52%|██████████▎         | 155/300 [31:35<29:33, 12.23s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 122 / 47 / 31 / 200:  67%|█████████████▍      | 201/300 [39:40<19:32, 11.84s/it]
[Succeeded / Failed / Skipped / Total] 123 / 47 / 31 / 201:  67%|█████████████▍      | 201/300 [39:40<19:32, 11.84s/it]
[Succeeded / Failed / Skipped / Total] 123 / 47 / 31 / 201:  67%|█████████████▍      | 202/300 [39:53<19:21, 11.85s/it]
[Succeeded / Failed / Skipped / Total] 124 / 47 / 31 / 202:  67%|█████████████▍      | 202/300 [39:53<19:21, 11.85s/it]
[Succeeded / Failed / Skipped / Total] 124 / 47 / 31 / 202:  68%|█████████████▌      | 203/300 [40:23<19:18, 11.94s/it]
[Succeeded / Failed / Skipped / Total] 124 / 48 / 31 / 203:  68%|█████████████▌      | 203/300 [40:23<19:18, 11.94s/it]
[Succeeded / Failed / Skipped / Total] 124 / 48 / 32 / 204:  68%|█████████████▌      | 204/300 [40:23<19:00, 11.88s/it]
[Succeeded / Failed / Skipped / Total] 124 / 48 / 32 / 204:  68%|█████████████▋      | 205/300 [40:42<18:51, 11.91s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 152 / 61 / 38 / 251:  84%|████████████████▋   | 251/300 [50:05<09:46, 11.97s/it]
[Succeeded / Failed / Skipped / Total] 152 / 61 / 38 / 251:  84%|████████████████▊   | 252/300 [50:19<09:35, 11.98s/it]
[Succeeded / Failed / Skipped / Total] 153 / 61 / 38 / 252:  84%|████████████████▊   | 252/300 [50:19<09:35, 11.98s/it]
[Succeeded / Failed / Skipped / Total] 153 / 61 / 38 / 252:  84%|████████████████▊   | 253/300 [50:46<09:25, 12.04s/it]
[Succeeded / Failed / Skipped / Total] 153 / 62 / 38 / 253:  84%|████████████████▊   | 253/300 [50:46<09:25, 12.04s/it]
[Succeeded / Failed / Skipped / Total] 153 / 62 / 38 / 253:  85%|████████████████▉   | 254/300 [50:50<09:12, 12.01s/it]
[Succeeded / Failed / Skipped / Total] 154 / 62 / 38 / 254:  85%|████████████████▉   | 254/300 [50:50<09:12, 12.01s/it]
[Succeeded / Failed / Skipped / Total] 154 / 62 / 38 / 254:  85%|█████████████████   | 255/300 [51:10<09:01, 12.04s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 181    |
| Number of failed attacks:     | 76     |
| Number of skipped attacks:    | 43     |
| Original accuracy:            | 85.67% |
| Accuracy under attack:        | 25.33% |
| Attack success rate:          | 70.43% |
| Average perturbed word %:     | 19.14% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 293.05 |
+-------------------------------+--------+


In [54]:
runAttack(clip_rf14_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf14'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf14ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:13<1:08:36, 13.77s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:13<1:08:46, 13.80s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:36<1:31:21, 18.39s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:36<1:31:26, 18.41s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:47<1:17:58, 15.75s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:47<1:18:00, 15.76s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:11<1:28:45, 17.99s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:11<1:28:46, 18.00s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 27 / 21 / 2 / 50:  17%|███▋                  | 51/300 [12:38<1:01:42, 14.87s/it]
[Succeeded / Failed / Skipped / Total] 27 / 22 / 2 / 51:  17%|███▋                  | 51/300 [12:38<1:01:42, 14.87s/it]
[Succeeded / Failed / Skipped / Total] 27 / 22 / 2 / 51:  17%|███▊                  | 52/300 [12:52<1:01:23, 14.85s/it]
[Succeeded / Failed / Skipped / Total] 28 / 22 / 2 / 52:  17%|███▊                  | 52/300 [12:52<1:01:23, 14.85s/it]
[Succeeded / Failed / Skipped / Total] 28 / 22 / 2 / 52:  18%|███▉                  | 53/300 [13:12<1:01:33, 14.95s/it]
[Succeeded / Failed / Skipped / Total] 28 / 23 / 2 / 53:  18%|███▉                  | 53/300 [13:12<1:01:33, 14.95s/it]
[Succeeded / Failed / Skipped / Total] 28 / 23 / 2 / 53:  18%|███▉                  | 54/300 [13:26<1:01:11, 14.93s/it]
[Succeeded / Failed / Skipped / Total] 29 / 23 / 2 / 54:  18%|███▉                  | 54/300 [13:26<1:01:11, 14.93s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 57 / 36 / 7 / 100:  34%|███████▍              | 101/300 [24:45<48:47, 14.71s/it]
[Succeeded / Failed / Skipped / Total] 58 / 36 / 7 / 101:  34%|███████▍              | 101/300 [24:45<48:47, 14.71s/it]
[Succeeded / Failed / Skipped / Total] 58 / 36 / 7 / 101:  34%|███████▍              | 101/300 [24:58<49:11, 14.83s/it]
[Succeeded / Failed / Skipped / Total] 58 / 36 / 7 / 101:  34%|███████▍              | 102/300 [24:58<48:29, 14.70s/it]
[Succeeded / Failed / Skipped / Total] 59 / 36 / 7 / 102:  34%|███████▍              | 102/300 [24:58<48:29, 14.70s/it]
[Succeeded / Failed / Skipped / Total] 59 / 36 / 7 / 102:  34%|███████▌              | 103/300 [25:05<47:59, 14.62s/it]
[Succeeded / Failed / Skipped / Total] 60 / 36 / 7 / 103:  34%|███████▌              | 103/300 [25:05<47:59, 14.62s/it]
[Succeeded / Failed / Skipped / Total] 60 / 36 / 7 / 103:  35%|███████▋              | 104/300 [25:21<47:47, 14.63s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 83 / 54 / 13 / 150:  50%|██████████▌          | 151/300 [37:13<36:43, 14.79s/it]
[Succeeded / Failed / Skipped / Total] 83 / 55 / 13 / 151:  50%|██████████▌          | 151/300 [37:13<36:43, 14.79s/it]
[Succeeded / Failed / Skipped / Total] 83 / 55 / 13 / 151:  51%|██████████▋          | 152/300 [37:41<36:41, 14.88s/it]
[Succeeded / Failed / Skipped / Total] 83 / 56 / 13 / 152:  51%|██████████▋          | 152/300 [37:41<36:41, 14.88s/it]
[Succeeded / Failed / Skipped / Total] 83 / 56 / 13 / 152:  51%|██████████▋          | 153/300 [37:52<36:23, 14.85s/it]
[Succeeded / Failed / Skipped / Total] 84 / 56 / 13 / 153:  51%|██████████▋          | 153/300 [37:52<36:23, 14.85s/it]
[Succeeded / Failed / Skipped / Total] 84 / 56 / 13 / 153:  51%|██████████▊          | 154/300 [37:56<35:58, 14.78s/it]
[Succeeded / Failed / Skipped / Total] 85 / 56 / 13 / 154:  51%|██████████▊          | 154/300 [37:56<35:58, 14.78s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 107 / 70 / 23 / 200:  67%|█████████████▍      | 201/300 [47:50<23:33, 14.28s/it]
[Succeeded / Failed / Skipped / Total] 107 / 71 / 23 / 201:  67%|█████████████▍      | 201/300 [47:50<23:33, 14.28s/it]
[Succeeded / Failed / Skipped / Total] 107 / 71 / 23 / 201:  67%|█████████████▍      | 202/300 [48:05<23:19, 14.28s/it]
[Succeeded / Failed / Skipped / Total] 107 / 72 / 23 / 202:  67%|█████████████▍      | 202/300 [48:05<23:19, 14.28s/it]
[Succeeded / Failed / Skipped / Total] 107 / 72 / 23 / 202:  68%|█████████████▌      | 203/300 [48:34<23:12, 14.36s/it]
[Succeeded / Failed / Skipped / Total] 107 / 73 / 23 / 203:  68%|█████████████▌      | 203/300 [48:34<23:12, 14.36s/it]
[Succeeded / Failed / Skipped / Total] 107 / 73 / 23 / 203:  68%|█████████████▌      | 204/300 [48:34<22:51, 14.29s/it]
[Succeeded / Failed / Skipped / Total] 107 / 73 / 24 / 204:  68%|█████████████▌      | 204/300 [48:34<22:51, 14.29s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 135 / 87 / 28 / 250:  84%|████████████████▋   | 251/300 [59:33<11:37, 14.24s/it]
[Succeeded / Failed / Skipped / Total] 136 / 87 / 28 / 251:  84%|████████████████▋   | 251/300 [59:33<11:37, 14.24s/it]
[Succeeded / Failed / Skipped / Total] 136 / 87 / 28 / 251:  84%|████████████████▊   | 252/300 [59:49<11:23, 14.25s/it]
[Succeeded / Failed / Skipped / Total] 136 / 88 / 28 / 252:  84%|████████████████▊   | 252/300 [59:50<11:23, 14.25s/it]
[Succeeded / Failed / Skipped / Total] 136 / 88 / 28 / 252:  84%|███████████████▏  | 253/300 [1:00:14<11:11, 14.29s/it]
[Succeeded / Failed / Skipped / Total] 137 / 88 / 28 / 253:  84%|███████████████▏  | 253/300 [1:00:14<11:11, 14.29s/it]
[Succeeded / Failed / Skipped / Total] 137 / 88 / 28 / 253:  85%|███████████████▏  | 254/300 [1:00:17<10:55, 14.24s/it]
[Succeeded / Failed / Skipped / Total] 138 / 88 / 28 / 254:  85%|███████████████▏  | 254/300 [1:00:17<10:55, 14.24s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 160    |
| Number of failed attacks:     | 107    |
| Number of skipped attacks:    | 33     |
| Original accuracy:            | 89.0%  |
| Accuracy under attack:        | 35.67% |
| Attack success rate:          | 59.93% |
| Average perturbed word %:     | 18.35% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 330.94 |
+-------------------------------+--------+


In [55]:
runAttack(clip_rf30_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf30'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf30ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:22<1:52:03, 22.49s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|                          | 1/300 [00:22<1:52:13, 22.52s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   1%|▏                         | 2/300 [00:44<1:51:32, 22.46s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▏                         | 2/300 [00:44<1:51:34, 22.47s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▎                         | 3/300 [01:12<1:59:30, 24.14s/it]
[Succeeded / Failed / Skipped / Total] 1 / 2 / 0 / 3:   1%|▎                         | 3/300 [01:12<1:59:32, 24.15s/it]
[Succeeded / Failed / Skipped / Total] 1 / 2 / 0 / 3:   1%|▎                         | 4/300 [01:38<2:00:57, 24.52s/it]
[Succeeded / Failed / Skipped / Total] 1 / 3 / 0 / 4:   1%|▎                         | 4/300 [01:38<2:00:58, 24.52s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 26 / 22 / 2 / 50:  17%|███▋                  | 51/300 [13:16<1:04:49, 15.62s/it]
[Succeeded / Failed / Skipped / Total] 26 / 23 / 2 / 51:  17%|███▋                  | 51/300 [13:16<1:04:50, 15.62s/it]
[Succeeded / Failed / Skipped / Total] 26 / 23 / 2 / 51:  17%|███▊                  | 52/300 [13:31<1:04:32, 15.61s/it]
[Succeeded / Failed / Skipped / Total] 27 / 23 / 2 / 52:  17%|███▊                  | 52/300 [13:31<1:04:32, 15.61s/it]
[Succeeded / Failed / Skipped / Total] 27 / 23 / 2 / 52:  18%|███▉                  | 53/300 [13:55<1:04:55, 15.77s/it]
[Succeeded / Failed / Skipped / Total] 27 / 24 / 2 / 53:  18%|███▉                  | 53/300 [13:55<1:04:55, 15.77s/it]
[Succeeded / Failed / Skipped / Total] 27 / 24 / 2 / 53:  18%|███▉                  | 54/300 [14:14<1:04:54, 15.83s/it]
[Succeeded / Failed / Skipped / Total] 27 / 25 / 2 / 54:  18%|███▉                  | 54/300 [14:14<1:04:54, 15.83s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 53 / 39 / 8 / 100:  34%|███████▍              | 101/300 [24:51<48:59, 14.77s/it]
[Succeeded / Failed / Skipped / Total] 54 / 39 / 8 / 101:  34%|███████▍              | 101/300 [24:51<48:59, 14.77s/it]
[Succeeded / Failed / Skipped / Total] 54 / 39 / 8 / 101:  34%|███████▍              | 102/300 [25:14<48:59, 14.85s/it]
[Succeeded / Failed / Skipped / Total] 54 / 40 / 8 / 102:  34%|███████▍              | 102/300 [25:14<48:59, 14.85s/it]
[Succeeded / Failed / Skipped / Total] 54 / 40 / 8 / 102:  34%|███████▌              | 103/300 [25:23<48:32, 14.79s/it]
[Succeeded / Failed / Skipped / Total] 55 / 40 / 8 / 103:  34%|███████▌              | 103/300 [25:23<48:32, 14.79s/it]
[Succeeded / Failed / Skipped / Total] 55 / 40 / 8 / 103:  35%|███████▋              | 104/300 [25:38<48:19, 14.79s/it]
[Succeeded / Failed / Skipped / Total] 55 / 41 / 8 / 104:  35%|███████▋              | 104/300 [25:38<48:19, 14.79s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 79 / 59 / 12 / 150:  50%|██████████▌          | 151/300 [35:53<35:25, 14.26s/it]
[Succeeded / Failed / Skipped / Total] 80 / 59 / 12 / 151:  50%|██████████▌          | 151/300 [35:53<35:25, 14.26s/it]
[Succeeded / Failed / Skipped / Total] 80 / 59 / 12 / 151:  51%|██████████▋          | 152/300 [36:22<35:24, 14.36s/it]
[Succeeded / Failed / Skipped / Total] 80 / 60 / 12 / 152:  51%|██████████▋          | 152/300 [36:22<35:24, 14.36s/it]
[Succeeded / Failed / Skipped / Total] 80 / 60 / 12 / 152:  51%|██████████▋          | 153/300 [36:40<35:14, 14.38s/it]
[Succeeded / Failed / Skipped / Total] 81 / 60 / 12 / 153:  51%|██████████▋          | 153/300 [36:40<35:14, 14.38s/it]
[Succeeded / Failed / Skipped / Total] 81 / 60 / 12 / 153:  51%|██████████▊          | 154/300 [36:43<34:48, 14.31s/it]
[Succeeded / Failed / Skipped / Total] 82 / 60 / 12 / 154:  51%|██████████▊          | 154/300 [36:43<34:48, 14.31s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 102 / 77 / 21 / 200:  67%|█████████████▍      | 201/300 [46:16<22:47, 13.81s/it]
[Succeeded / Failed / Skipped / Total] 103 / 77 / 21 / 201:  67%|█████████████▍      | 201/300 [46:16<22:47, 13.81s/it]
[Succeeded / Failed / Skipped / Total] 103 / 77 / 21 / 201:  67%|█████████████▍      | 202/300 [46:31<22:34, 13.82s/it]
[Succeeded / Failed / Skipped / Total] 103 / 78 / 21 / 202:  67%|█████████████▍      | 202/300 [46:31<22:34, 13.82s/it]
[Succeeded / Failed / Skipped / Total] 103 / 78 / 21 / 202:  68%|█████████████▌      | 203/300 [47:03<22:29, 13.91s/it]
[Succeeded / Failed / Skipped / Total] 103 / 79 / 21 / 203:  68%|█████████████▌      | 203/300 [47:03<22:29, 13.91s/it]
[Succeeded / Failed / Skipped / Total] 103 / 79 / 21 / 203:  68%|█████████████▌      | 204/300 [47:03<22:08, 13.84s/it]
[Succeeded / Failed / Skipped / Total] 103 / 79 / 22 / 204:  68%|█████████████▌      | 204/300 [47:03<22:08, 13.84s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 128 / 96 / 26 / 250:  84%|████████████████▋   | 251/300 [57:45<11:16, 13.81s/it]
[Succeeded / Failed / Skipped / Total] 129 / 96 / 26 / 251:  84%|████████████████▋   | 251/300 [57:45<11:16, 13.81s/it]
[Succeeded / Failed / Skipped / Total] 129 / 96 / 26 / 251:  84%|████████████████▊   | 252/300 [58:02<11:03, 13.82s/it]
[Succeeded / Failed / Skipped / Total] 129 / 97 / 26 / 252:  84%|████████████████▊   | 252/300 [58:02<11:03, 13.82s/it]
[Succeeded / Failed / Skipped / Total] 129 / 97 / 26 / 252:  84%|████████████████▊   | 253/300 [58:26<10:51, 13.86s/it]
[Succeeded / Failed / Skipped / Total] 129 / 98 / 26 / 253:  84%|████████████████▊   | 253/300 [58:26<10:51, 13.86s/it]
[Succeeded / Failed / Skipped / Total] 129 / 98 / 26 / 253:  85%|████████████████▉   | 254/300 [58:29<10:35, 13.82s/it]
[Succeeded / Failed / Skipped / Total] 130 / 98 / 26 / 254:  85%|████████████████▉   | 254/300 [58:29<10:35, 13.82s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 149    |
| Number of failed attacks:     | 121    |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 40.33% |
| Attack success rate:          | 55.19% |
| Average perturbed word %:     | 15.47% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 324.27 |
+-------------------------------+--------+


In [56]:
runAttack(clip_knn7_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn7ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                           | 1/300 [36:28<181:47:51, 2188.87s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|                      | 1/300 [36:28<181:47:55, 2188.88s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   1%|▏                      | 2/300 [36:51<91:31:17, 1105.63s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▏                      | 2/300 [36:51<91:31:17, 1105.63s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▏                       | 3/300 [37:17<61:31:46, 745.81s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▏                       | 3/300 [37:17<61:31:47, 745.82s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                       | 4/300 [37:42<46:30:47, 565.70s/it]
[Succeeded / Failed / Skipped / Total] 0 / 4 / 0 / 4:   1%|▎                       | 4/300 [37:42<46:30:48, 565.70s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 3 / 46 / 1 / 50:  17%|███▉                   | 51/300 [56:27<4:35:38, 66.42s/it]
[Succeeded / Failed / Skipped / Total] 3 / 47 / 1 / 51:  17%|███▉                   | 51/300 [56:27<4:35:38, 66.42s/it]
[Succeeded / Failed / Skipped / Total] 3 / 47 / 1 / 51:  17%|███▉                   | 52/300 [56:48<4:30:57, 65.55s/it]
[Succeeded / Failed / Skipped / Total] 3 / 48 / 1 / 52:  17%|███▉                   | 52/300 [56:48<4:30:57, 65.55s/it]
[Succeeded / Failed / Skipped / Total] 3 / 48 / 1 / 52:  18%|████                   | 53/300 [57:13<4:26:43, 64.79s/it]
[Succeeded / Failed / Skipped / Total] 3 / 49 / 1 / 53:  18%|████                   | 53/300 [57:13<4:26:43, 64.79s/it]
[Succeeded / Failed / Skipped / Total] 3 / 49 / 1 / 53:  18%|████▏                  | 54/300 [57:36<4:22:28, 64.02s/it]
[Succeeded / Failed / Skipped / Total] 3 / 50 / 1 / 54:  18%|████▏                  | 54/300 [57:36<4:22:28, 64.02s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 15 / 81 / 4 / 100:  34%|██████            | 101/300 [1:16:02<2:29:49, 45.17s/it]
[Succeeded / Failed / Skipped / Total] 15 / 82 / 4 / 101:  34%|██████            | 101/300 [1:16:02<2:29:49, 45.17s/it]
[Succeeded / Failed / Skipped / Total] 15 / 82 / 4 / 101:  34%|██████            | 102/300 [1:16:28<2:28:27, 44.99s/it]
[Succeeded / Failed / Skipped / Total] 15 / 83 / 4 / 102:  34%|██████            | 102/300 [1:16:28<2:28:28, 44.99s/it]
[Succeeded / Failed / Skipped / Total] 15 / 83 / 4 / 102:  34%|██████▏           | 103/300 [1:17:01<2:27:19, 44.87s/it]
[Succeeded / Failed / Skipped / Total] 16 / 83 / 4 / 103:  34%|██████▏           | 103/300 [1:17:01<2:27:19, 44.87s/it]
[Succeeded / Failed / Skipped / Total] 16 / 83 / 4 / 103:  35%|██████▏           | 104/300 [1:17:23<2:25:50, 44.65s/it]
[Succeeded / Failed / Skipped / Total] 16 / 84 / 4 / 104:  35%|██████▏           | 104/300 [1:17:23<2:25:50, 44.65s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 22 / 121 / 7 / 150:  50%|████████▌        | 151/300 [1:35:44<1:34:28, 38.04s/it]
[Succeeded / Failed / Skipped / Total] 23 / 121 / 7 / 151:  50%|████████▌        | 151/300 [1:35:44<1:34:28, 38.04s/it]
[Succeeded / Failed / Skipped / Total] 23 / 121 / 7 / 151:  51%|████████▌        | 152/300 [1:36:18<1:33:46, 38.02s/it]
[Succeeded / Failed / Skipped / Total] 23 / 122 / 7 / 152:  51%|████████▌        | 152/300 [1:36:18<1:33:46, 38.02s/it]
[Succeeded / Failed / Skipped / Total] 23 / 122 / 7 / 152:  51%|████████▋        | 153/300 [1:36:41<1:32:54, 37.92s/it]
[Succeeded / Failed / Skipped / Total] 23 / 123 / 7 / 153:  51%|████████▋        | 153/300 [1:36:41<1:32:54, 37.92s/it]
[Succeeded / Failed / Skipped / Total] 23 / 123 / 7 / 153:  51%|████████▋        | 154/300 [1:36:42<1:31:40, 37.68s/it]
[Succeeded / Failed / Skipped / Total] 23 / 123 / 8 / 154:  51%|████████▋        | 154/300 [1:36:42<1:31:40, 37.68s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 31 / 155 / 14 / 200:  67%|████████████      | 201/300 [1:53:23<55:50, 33.85s/it]
[Succeeded / Failed / Skipped / Total] 31 / 156 / 14 / 201:  67%|████████████      | 201/300 [1:53:23<55:50, 33.85s/it]
[Succeeded / Failed / Skipped / Total] 31 / 156 / 14 / 201:  67%|████████████      | 202/300 [1:53:41<55:09, 33.77s/it]
[Succeeded / Failed / Skipped / Total] 31 / 157 / 14 / 202:  67%|████████████      | 202/300 [1:53:41<55:09, 33.77s/it]
[Succeeded / Failed / Skipped / Total] 31 / 157 / 14 / 202:  68%|████████████▏     | 203/300 [1:54:15<54:35, 33.77s/it]
[Succeeded / Failed / Skipped / Total] 31 / 158 / 14 / 203:  68%|████████████▏     | 203/300 [1:54:15<54:35, 33.77s/it]
[Succeeded / Failed / Skipped / Total] 31 / 158 / 14 / 203:  68%|████████████▏     | 204/300 [1:54:25<53:50, 33.65s/it]
[Succeeded / Failed / Skipped / Total] 32 / 158 / 14 / 204:  68%|████████████▏     | 204/300 [1:54:25<53:50, 33.65s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 42 / 191 / 17 / 250:  84%|███████████████   | 251/300 [2:14:21<26:13, 32.12s/it]
[Succeeded / Failed / Skipped / Total] 42 / 192 / 17 / 251:  84%|███████████████   | 251/300 [2:14:21<26:13, 32.12s/it]
[Succeeded / Failed / Skipped / Total] 42 / 192 / 17 / 251:  84%|███████████████   | 252/300 [2:14:41<25:39, 32.07s/it]
[Succeeded / Failed / Skipped / Total] 42 / 193 / 17 / 252:  84%|███████████████   | 252/300 [2:14:41<25:39, 32.07s/it]
[Succeeded / Failed / Skipped / Total] 42 / 193 / 17 / 252:  84%|███████████████▏  | 253/300 [2:15:09<25:06, 32.05s/it]
[Succeeded / Failed / Skipped / Total] 42 / 194 / 17 / 253:  84%|███████████████▏  | 253/300 [2:15:09<25:06, 32.05s/it]
[Succeeded / Failed / Skipped / Total] 42 / 194 / 17 / 253:  85%|███████████████▏  | 254/300 [2:15:29<24:32, 32.01s/it]
[Succeeded / Failed / Skipped / Total] 42 / 195 / 17 / 254:  85%|███████████████▏  | 254/300 [2:15:29<24:32, 32.01s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 49     |
| Number of failed attacks:     | 229    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 76.33% |
| Attack success rate:          | 17.63% |
| Average perturbed word %:     | 5.25%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 452.25 |
+-------------------------------+--------+


In [57]:
runAttack(clip_knn35_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn35'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn35ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:22<1:51:47, 22.43s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|                          | 1/300 [00:22<1:51:52, 22.45s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   1%|▏                         | 2/300 [00:45<1:52:18, 22.61s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▏                         | 2/300 [00:45<1:52:20, 22.62s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▎                         | 3/300 [01:12<2:00:07, 24.27s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                         | 3/300 [01:12<2:00:09, 24.27s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                         | 4/300 [01:38<2:01:35, 24.65s/it]
[Succeeded / Failed / Skipped / Total] 0 / 4 / 0 / 4:   1%|▎                         | 4/300 [01:38<2:01:36, 24.65s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 8 / 42 / 0 / 50:  17%|███▉                   | 51/300 [19:01<1:32:55, 22.39s/it]
[Succeeded / Failed / Skipped / Total] 8 / 43 / 0 / 51:  17%|███▉                   | 51/300 [19:01<1:32:55, 22.39s/it]
[Succeeded / Failed / Skipped / Total] 8 / 43 / 0 / 51:  17%|███▉                   | 52/300 [19:23<1:32:29, 22.38s/it]
[Succeeded / Failed / Skipped / Total] 8 / 44 / 0 / 52:  17%|███▉                   | 52/300 [19:23<1:32:29, 22.38s/it]
[Succeeded / Failed / Skipped / Total] 8 / 44 / 0 / 52:  18%|████                   | 53/300 [19:48<1:32:20, 22.43s/it]
[Succeeded / Failed / Skipped / Total] 8 / 45 / 0 / 53:  18%|████                   | 53/300 [19:48<1:32:20, 22.43s/it]
[Succeeded / Failed / Skipped / Total] 8 / 45 / 0 / 53:  18%|████▏                  | 54/300 [20:03<1:31:21, 22.28s/it]
[Succeeded / Failed / Skipped / Total] 9 / 45 / 0 / 54:  18%|████▏                  | 54/300 [20:03<1:31:21, 22.28s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 22 / 75 / 3 / 100:  34%|██████▋             | 101/300 [37:29<1:13:52, 22.27s/it]
[Succeeded / Failed / Skipped / Total] 23 / 75 / 3 / 101:  34%|██████▋             | 101/300 [37:29<1:13:52, 22.27s/it]
[Succeeded / Failed / Skipped / Total] 23 / 75 / 3 / 101:  34%|██████▊             | 102/300 [37:38<1:13:04, 22.14s/it]
[Succeeded / Failed / Skipped / Total] 24 / 75 / 3 / 102:  34%|██████▊             | 102/300 [37:38<1:13:04, 22.14s/it]
[Succeeded / Failed / Skipped / Total] 24 / 75 / 3 / 102:  34%|██████▊             | 103/300 [37:41<1:12:05, 21.95s/it]
[Succeeded / Failed / Skipped / Total] 25 / 75 / 3 / 103:  34%|██████▊             | 103/300 [37:41<1:12:05, 21.95s/it]
[Succeeded / Failed / Skipped / Total] 25 / 75 / 3 / 103:  35%|██████▉             | 104/300 [38:02<1:11:42, 21.95s/it]
[Succeeded / Failed / Skipped / Total] 25 / 76 / 3 / 104:  35%|██████▉             | 104/300 [38:02<1:11:42, 21.95s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 39 / 105 / 6 / 150:  50%|██████████▌          | 151/300 [55:14<54:30, 21.95s/it]
[Succeeded / Failed / Skipped / Total] 39 / 106 / 6 / 151:  50%|██████████▌          | 151/300 [55:14<54:30, 21.95s/it]
[Succeeded / Failed / Skipped / Total] 39 / 106 / 6 / 151:  51%|██████████▋          | 152/300 [55:48<54:20, 22.03s/it]
[Succeeded / Failed / Skipped / Total] 39 / 107 / 6 / 152:  51%|██████████▋          | 152/300 [55:48<54:20, 22.03s/it]
[Succeeded / Failed / Skipped / Total] 39 / 107 / 6 / 152:  51%|██████████▋          | 153/300 [56:03<53:51, 21.99s/it]
[Succeeded / Failed / Skipped / Total] 40 / 107 / 6 / 153:  51%|██████████▋          | 153/300 [56:03<53:51, 21.99s/it]
[Succeeded / Failed / Skipped / Total] 40 / 107 / 6 / 153:  51%|██████████▊          | 154/300 [56:03<53:09, 21.84s/it]
[Succeeded / Failed / Skipped / Total] 40 / 107 / 7 / 154:  51%|██████████▊          | 154/300 [56:03<53:09, 21.84s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 52 / 135 / 13 / 200:  67%|████████████      | 201/300 [1:11:51<35:23, 21.45s/it]
[Succeeded / Failed / Skipped / Total] 52 / 136 / 13 / 201:  67%|████████████      | 201/300 [1:11:51<35:23, 21.45s/it]
[Succeeded / Failed / Skipped / Total] 52 / 136 / 13 / 201:  67%|████████████      | 202/300 [1:12:09<35:00, 21.43s/it]
[Succeeded / Failed / Skipped / Total] 52 / 137 / 13 / 202:  67%|████████████      | 202/300 [1:12:09<35:00, 21.43s/it]
[Succeeded / Failed / Skipped / Total] 52 / 137 / 13 / 202:  68%|████████████▏     | 203/300 [1:12:42<34:44, 21.49s/it]
[Succeeded / Failed / Skipped / Total] 52 / 138 / 13 / 203:  68%|████████████▏     | 203/300 [1:12:42<34:44, 21.49s/it]
[Succeeded / Failed / Skipped / Total] 52 / 138 / 13 / 203:  68%|████████████▏     | 204/300 [1:12:42<34:12, 21.38s/it]
[Succeeded / Failed / Skipped / Total] 52 / 138 / 14 / 204:  68%|████████████▏     | 204/300 [1:12:42<34:12, 21.38s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 67 / 167 / 16 / 250:  84%|███████████████   | 251/300 [1:32:12<17:59, 22.04s/it]
[Succeeded / Failed / Skipped / Total] 67 / 168 / 16 / 251:  84%|███████████████   | 251/300 [1:32:12<17:59, 22.04s/it]
[Succeeded / Failed / Skipped / Total] 67 / 168 / 16 / 251:  84%|███████████████   | 252/300 [1:32:32<17:37, 22.03s/it]
[Succeeded / Failed / Skipped / Total] 67 / 169 / 16 / 252:  84%|███████████████   | 252/300 [1:32:32<17:37, 22.03s/it]
[Succeeded / Failed / Skipped / Total] 67 / 169 / 16 / 252:  84%|███████████████▏  | 253/300 [1:33:02<17:16, 22.06s/it]
[Succeeded / Failed / Skipped / Total] 67 / 170 / 16 / 253:  84%|███████████████▏  | 253/300 [1:33:02<17:16, 22.06s/it]
[Succeeded / Failed / Skipped / Total] 67 / 170 / 16 / 253:  85%|███████████████▏  | 254/300 [1:33:21<16:54, 22.05s/it]
[Succeeded / Failed / Skipped / Total] 67 / 171 / 16 / 254:  85%|███████████████▏  | 254/300 [1:33:21<16:54, 22.05s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 72     |
| Number of failed attacks:     | 206    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 68.67% |
| Attack success rate:          | 25.9%  |
| Average perturbed word %:     | 11.32% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 423.31 |
+-------------------------------+--------+


In [58]:
runAttack(clip_knn175_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn175'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn175ep0873.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8726760455264837
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']



  0%|▎                                                                               | 1/300 [00:22<1:51:41, 22.41s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|                          | 1/300 [00:22<1:51:46, 22.43s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   1%|▏                         | 2/300 [00:45<1:51:58, 22.54s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▏                         | 2/300 [00:45<1:52:00, 22.55s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▎                         | 3/300 [01:12<1:58:53, 24.02s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                         | 3/300 [01:12<1:58:55, 24.02s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                         | 4/300 [01:39<2:02:59, 24.93s/it]
[Succeeded / Failed / Skipped / Total] 0 / 4 / 0 / 4:   1%|▎                         | 4/300 [01:39<2:03:00, 24.93s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 18 / 31 / 1 / 50:  17%|███▋                  | 51/300 [16:52<1:22:22, 19.85s/it]
[Succeeded / Failed / Skipped / Total] 19 / 31 / 1 / 51:  17%|███▋                  | 51/300 [16:52<1:22:22, 19.85s/it]
[Succeeded / Failed / Skipped / Total] 19 / 31 / 1 / 51:  17%|███▊                  | 52/300 [17:13<1:22:07, 19.87s/it]
[Succeeded / Failed / Skipped / Total] 19 / 32 / 1 / 52:  17%|███▊                  | 52/300 [17:13<1:22:07, 19.87s/it]
[Succeeded / Failed / Skipped / Total] 19 / 32 / 1 / 52:  18%|███▉                  | 53/300 [17:39<1:22:15, 19.98s/it]
[Succeeded / Failed / Skipped / Total] 19 / 33 / 1 / 53:  18%|███▉                  | 53/300 [17:39<1:22:15, 19.98s/it]
[Succeeded / Failed / Skipped / Total] 19 / 33 / 1 / 53:  18%|███▉                  | 54/300 [17:44<1:20:48, 19.71s/it]
[Succeeded / Failed / Skipped / Total] 20 / 33 / 1 / 54:  18%|███▉                  | 54/300 [17:44<1:20:48, 19.71s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 41 / 54 / 5 / 100:  34%|██████▋             | 101/300 [32:39<1:04:20, 19.40s/it]
[Succeeded / Failed / Skipped / Total] 42 / 54 / 5 / 101:  34%|██████▋             | 101/300 [32:39<1:04:21, 19.40s/it]
[Succeeded / Failed / Skipped / Total] 42 / 54 / 5 / 101:  34%|██████▊             | 102/300 [32:53<1:03:50, 19.35s/it]
[Succeeded / Failed / Skipped / Total] 43 / 54 / 5 / 102:  34%|██████▊             | 102/300 [32:53<1:03:50, 19.35s/it]
[Succeeded / Failed / Skipped / Total] 43 / 54 / 5 / 102:  34%|██████▊             | 103/300 [32:58<1:03:05, 19.21s/it]
[Succeeded / Failed / Skipped / Total] 44 / 54 / 5 / 103:  34%|██████▊             | 103/300 [32:58<1:03:05, 19.21s/it]
[Succeeded / Failed / Skipped / Total] 44 / 54 / 5 / 103:  35%|██████▉             | 104/300 [33:21<1:02:52, 19.25s/it]
[Succeeded / Failed / Skipped / Total] 44 / 55 / 5 / 104:  35%|██████▉             | 104/300 [33:21<1:02:52, 19.25s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 64 / 77 / 9 / 150:  50%|███████████           | 151/300 [49:07<48:28, 19.52s/it]
[Succeeded / Failed / Skipped / Total] 65 / 77 / 9 / 151:  50%|███████████           | 151/300 [49:07<48:28, 19.52s/it]
[Succeeded / Failed / Skipped / Total] 65 / 77 / 9 / 151:  51%|███████████▏          | 152/300 [49:42<48:24, 19.62s/it]
[Succeeded / Failed / Skipped / Total] 65 / 78 / 9 / 152:  51%|███████████▏          | 152/300 [49:42<48:24, 19.62s/it]
[Succeeded / Failed / Skipped / Total] 65 / 78 / 9 / 152:  51%|███████████▏          | 153/300 [50:06<48:08, 19.65s/it]
[Succeeded / Failed / Skipped / Total] 65 / 79 / 9 / 153:  51%|███████████▏          | 153/300 [50:06<48:08, 19.65s/it]
[Succeeded / Failed / Skipped / Total] 65 / 79 / 9 / 153:  51%|███████████▎          | 154/300 [50:06<47:30, 19.52s/it]
[Succeeded / Failed / Skipped / Total] 65 / 79 / 10 / 154:  51%|██████████▊          | 154/300 [50:06<47:30, 19.52s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 78 / 101 / 21 / 200:  67%|████████████      | 201/300 [1:04:06<31:34, 19.14s/it]
[Succeeded / Failed / Skipped / Total] 78 / 102 / 21 / 201:  67%|████████████      | 201/300 [1:04:06<31:34, 19.14s/it]
[Succeeded / Failed / Skipped / Total] 78 / 102 / 21 / 201:  67%|████████████      | 202/300 [1:04:23<31:14, 19.13s/it]
[Succeeded / Failed / Skipped / Total] 78 / 103 / 21 / 202:  67%|████████████      | 202/300 [1:04:23<31:14, 19.13s/it]
[Succeeded / Failed / Skipped / Total] 78 / 103 / 21 / 202:  68%|████████████▏     | 203/300 [1:04:56<31:01, 19.20s/it]
[Succeeded / Failed / Skipped / Total] 78 / 104 / 21 / 203:  68%|████████████▏     | 203/300 [1:04:56<31:01, 19.20s/it]
[Succeeded / Failed / Skipped / Total] 78 / 104 / 21 / 203:  68%|████████████▏     | 204/300 [1:04:56<30:33, 19.10s/it]
[Succeeded / Failed / Skipped / Total] 78 / 104 / 22 / 204:  68%|████████████▏     | 204/300 [1:04:56<30:33, 19.10s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 97 / 125 / 28 / 250:  84%|███████████████   | 251/300 [1:20:36<15:44, 19.27s/it]
[Succeeded / Failed / Skipped / Total] 97 / 126 / 28 / 251:  84%|███████████████   | 251/300 [1:20:36<15:44, 19.27s/it]
[Succeeded / Failed / Skipped / Total] 97 / 126 / 28 / 251:  84%|███████████████   | 252/300 [1:20:55<15:24, 19.27s/it]
[Succeeded / Failed / Skipped / Total] 97 / 127 / 28 / 252:  84%|███████████████   | 252/300 [1:20:55<15:24, 19.27s/it]
[Succeeded / Failed / Skipped / Total] 97 / 127 / 28 / 252:  84%|███████████████▏  | 253/300 [1:21:25<15:07, 19.31s/it]
[Succeeded / Failed / Skipped / Total] 97 / 128 / 28 / 253:  84%|███████████████▏  | 253/300 [1:21:25<15:07, 19.31s/it]
[Succeeded / Failed / Skipped / Total] 97 / 128 / 28 / 253:  85%|███████████████▏  | 254/300 [1:21:32<14:46, 19.26s/it]
[Succeeded / Failed / Skipped / Total] 98 / 128 / 28 / 254:  85%|███████████████▏  | 254/300 [1:21:32<14:46, 19.26s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 111    |
| Number of failed attacks:     | 155    |
| Number of skipped attacks:    | 34     |
| Original accuracy:            | 88.67% |
| Accuracy under attack:        | 51.67% |
| Attack success rate:          | 41.73% |
| Average perturbed word %:     | 20.33% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 384.23 |
+-------------------------------+--------+


In [59]:
et2 = datetime.datetime.now()
et2 - et

datetime.timedelta(seconds=76041, microseconds=997276)

### Threshold = 0.9

In [60]:
suffix = 'ep09.csv'
thre = 0.9

#### BERT

In [61]:
runAttack(bert_lr1_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr1'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr1ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                               | 1/300 [00:18<1:32:07, 18.49s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:18<1:32:11, 18.50s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:27<1:09:27, 13.99s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:27<1:09:27, 13.99s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:47<1:18:29, 15.86s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:47<1:18:32, 15.87s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:11<1:27:52, 17.81s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:11<1:27:53, 17.82s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 40 / 5 / 5 / 50:  17%|████▎                    | 51/300 [08:46<42:50, 10.32s/it]
[Succeeded / Failed / Skipped / Total] 41 / 5 / 5 / 51:  17%|████▎                    | 51/300 [08:46<42:50, 10.32s/it]
[Succeeded / Failed / Skipped / Total] 41 / 5 / 5 / 51:  17%|████▎                    | 52/300 [08:56<42:39, 10.32s/it]
[Succeeded / Failed / Skipped / Total] 42 / 5 / 5 / 52:  17%|████▎                    | 52/300 [08:56<42:39, 10.32s/it]
[Succeeded / Failed / Skipped / Total] 42 / 5 / 5 / 52:  18%|████▍                    | 53/300 [09:14<43:05, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 42 / 6 / 5 / 53:  18%|████▍                    | 53/300 [09:14<43:05, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 42 / 6 / 5 / 53:  18%|████▌                    | 54/300 [09:21<42:36, 10.39s/it]
[Succeeded / Failed / Skipped / Total] 43 / 6 / 5 / 54:  18%|████▌                    | 54/300 [09:21<42:36, 10.39s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 81 / 9 / 10 / 100:  34%|███████▍              | 101/300 [18:12<35:51, 10.81s/it]
[Succeeded / Failed / Skipped / Total] 82 / 9 / 10 / 101:  34%|███████▍              | 101/300 [18:12<35:52, 10.81s/it]
[Succeeded / Failed / Skipped / Total] 82 / 9 / 10 / 101:  34%|███████▍              | 102/300 [18:16<35:28, 10.75s/it]
[Succeeded / Failed / Skipped / Total] 83 / 9 / 10 / 102:  34%|███████▍              | 102/300 [18:16<35:28, 10.75s/it]
[Succeeded / Failed / Skipped / Total] 83 / 9 / 10 / 102:  34%|███████▌              | 103/300 [18:22<35:08, 10.70s/it]
[Succeeded / Failed / Skipped / Total] 84 / 9 / 10 / 103:  34%|███████▌              | 103/300 [18:22<35:08, 10.70s/it]
[Succeeded / Failed / Skipped / Total] 84 / 9 / 10 / 103:  35%|███████▋              | 104/300 [18:37<35:05, 10.74s/it]
[Succeeded / Failed / Skipped / Total] 85 / 9 / 10 / 104:  35%|███████▋              | 104/300 [18:37<35:05, 10.74s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 119 / 16 / 15 / 150:  50%|██████████          | 151/300 [28:12<27:49, 11.21s/it]
[Succeeded / Failed / Skipped / Total] 120 / 16 / 15 / 151:  50%|██████████          | 151/300 [28:12<27:49, 11.21s/it]
[Succeeded / Failed / Skipped / Total] 120 / 16 / 15 / 151:  51%|██████████▏         | 152/300 [28:38<27:53, 11.30s/it]
[Succeeded / Failed / Skipped / Total] 121 / 16 / 15 / 152:  51%|██████████▏         | 152/300 [28:38<27:53, 11.31s/it]
[Succeeded / Failed / Skipped / Total] 121 / 16 / 15 / 152:  51%|██████████▏         | 153/300 [28:44<27:36, 11.27s/it]
[Succeeded / Failed / Skipped / Total] 122 / 16 / 15 / 153:  51%|██████████▏         | 153/300 [28:44<27:36, 11.27s/it]
[Succeeded / Failed / Skipped / Total] 122 / 16 / 15 / 153:  51%|██████████▎         | 154/300 [28:49<27:19, 11.23s/it]
[Succeeded / Failed / Skipped / Total] 123 / 16 / 15 / 154:  51%|██████████▎         | 154/300 [28:49<27:19, 11.23s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 158 / 21 / 21 / 200:  67%|█████████████▍      | 201/300 [39:27<19:26, 11.78s/it]
[Succeeded / Failed / Skipped / Total] 159 / 21 / 21 / 201:  67%|█████████████▍      | 201/300 [39:27<19:26, 11.78s/it]
[Succeeded / Failed / Skipped / Total] 159 / 21 / 21 / 201:  67%|█████████████▍      | 202/300 [39:35<19:12, 11.76s/it]
[Succeeded / Failed / Skipped / Total] 160 / 21 / 21 / 202:  67%|█████████████▍      | 202/300 [39:35<19:12, 11.76s/it]
[Succeeded / Failed / Skipped / Total] 160 / 21 / 21 / 202:  68%|█████████████▌      | 203/300 [40:02<19:07, 11.83s/it]
[Succeeded / Failed / Skipped / Total] 161 / 21 / 21 / 203:  68%|█████████████▌      | 203/300 [40:02<19:08, 11.84s/it]
[Succeeded / Failed / Skipped / Total] 161 / 21 / 21 / 203:  68%|█████████████▌      | 204/300 [40:05<18:52, 11.79s/it]
[Succeeded / Failed / Skipped / Total] 162 / 21 / 21 / 204:  68%|█████████████▌      | 204/300 [40:05<18:52, 11.79s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 201 / 24 / 25 / 250:  84%|████████████████▋   | 251/300 [49:29<09:39, 11.83s/it]
[Succeeded / Failed / Skipped / Total] 202 / 24 / 25 / 251:  84%|████████████████▋   | 251/300 [49:29<09:39, 11.83s/it]
[Succeeded / Failed / Skipped / Total] 202 / 24 / 25 / 251:  84%|████████████████▊   | 252/300 [49:49<09:29, 11.86s/it]
[Succeeded / Failed / Skipped / Total] 203 / 24 / 25 / 252:  84%|████████████████▊   | 252/300 [49:49<09:29, 11.86s/it]
[Succeeded / Failed / Skipped / Total] 203 / 24 / 25 / 252:  84%|████████████████▊   | 253/300 [50:04<09:18, 11.88s/it]
[Succeeded / Failed / Skipped / Total] 204 / 24 / 25 / 253:  84%|████████████████▊   | 253/300 [50:04<09:18, 11.88s/it]
[Succeeded / Failed / Skipped / Total] 204 / 24 / 25 / 253:  85%|████████████████▉   | 254/300 [50:14<09:05, 11.87s/it]
[Succeeded / Failed / Skipped / Total] 205 / 24 / 25 / 254:  85%|████████████████▉   | 254/300 [50:14<09:05, 11.87s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 240    |
| Number of failed attacks:     | 30     |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 10.0%  |
| Attack success rate:          | 88.89% |
| Average perturbed word %:     | 17.87% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 161.2  |
+-------------------------------+--------+


In [62]:
runAttack(bert_lr01_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr01'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr01ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                               | 1/300 [00:36<3:02:46, 36.68s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:36<3:02:51, 36.69s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:47<1:57:36, 23.68s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:47<1:57:36, 23.68s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [01:00<1:39:22, 20.08s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [01:00<1:39:24, 20.08s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:26<1:46:57, 21.68s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:26<1:47:01, 21.69s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 38 / 7 / 5 / 50:  17%|████▏                    | 50/300 [08:28<42:24, 10.18s/it]
[Succeeded / Failed / Skipped / Total] 38 / 7 / 5 / 50:  17%|████▎                    | 51/300 [08:36<42:03, 10.13s/it]
[Succeeded / Failed / Skipped / Total] 39 / 7 / 5 / 51:  17%|████▎                    | 51/300 [08:36<42:03, 10.13s/it]
[Succeeded / Failed / Skipped / Total] 39 / 7 / 5 / 51:  17%|████▎                    | 52/300 [08:46<41:51, 10.13s/it]
[Succeeded / Failed / Skipped / Total] 40 / 7 / 5 / 52:  17%|████▎                    | 52/300 [08:46<41:51, 10.13s/it]
[Succeeded / Failed / Skipped / Total] 40 / 7 / 5 / 52:  18%|████▍                    | 53/300 [09:04<42:19, 10.28s/it]
[Succeeded / Failed / Skipped / Total] 40 / 8 / 5 / 53:  18%|████▍                    | 53/300 [09:04<42:19, 10.28s/it]
[Succeeded / Failed / Skipped / Total] 40 / 8 / 5 / 53:  18%|████▌                    | 54/300 [09:12<41:57, 10.24s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 77 / 12 / 11 / 100:  34%|███████              | 101/300 [17:23<34:16, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 78 / 12 / 11 / 101:  34%|███████              | 101/300 [17:23<34:16, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 78 / 12 / 11 / 101:  34%|███████▏             | 102/300 [17:27<33:54, 10.27s/it]
[Succeeded / Failed / Skipped / Total] 79 / 12 / 11 / 102:  34%|███████▏             | 102/300 [17:27<33:54, 10.27s/it]
[Succeeded / Failed / Skipped / Total] 79 / 12 / 11 / 102:  34%|███████▏             | 103/300 [17:32<33:33, 10.22s/it]
[Succeeded / Failed / Skipped / Total] 80 / 12 / 11 / 103:  34%|███████▏             | 103/300 [17:32<33:33, 10.22s/it]
[Succeeded / Failed / Skipped / Total] 80 / 12 / 11 / 103:  35%|███████▎             | 104/300 [17:43<33:25, 10.23s/it]
[Succeeded / Failed / Skipped / Total] 81 / 12 / 11 / 104:  35%|███████▎             | 104/300 [17:43<33:25, 10.23s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 112 / 22 / 16 / 150:  50%|██████████          | 151/300 [27:14<26:52, 10.82s/it]
[Succeeded / Failed / Skipped / Total] 113 / 22 / 16 / 151:  50%|██████████          | 151/300 [27:14<26:52, 10.82s/it]
[Succeeded / Failed / Skipped / Total] 113 / 22 / 16 / 151:  51%|██████████▏         | 152/300 [27:41<26:57, 10.93s/it]
[Succeeded / Failed / Skipped / Total] 114 / 22 / 16 / 152:  51%|██████████▏         | 152/300 [27:41<26:57, 10.93s/it]
[Succeeded / Failed / Skipped / Total] 114 / 22 / 16 / 152:  51%|██████████▏         | 153/300 [27:54<26:48, 10.94s/it]
[Succeeded / Failed / Skipped / Total] 115 / 22 / 16 / 153:  51%|██████████▏         | 153/300 [27:54<26:48, 10.94s/it]
[Succeeded / Failed / Skipped / Total] 115 / 22 / 16 / 153:  51%|██████████▎         | 154/300 [27:59<26:32, 10.91s/it]
[Succeeded / Failed / Skipped / Total] 116 / 22 / 16 / 154:  51%|██████████▎         | 154/300 [27:59<26:32, 10.91s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 151 / 26 / 23 / 200:  67%|█████████████▍      | 201/300 [38:25<18:55, 11.47s/it]
[Succeeded / Failed / Skipped / Total] 152 / 26 / 23 / 201:  67%|█████████████▍      | 201/300 [38:25<18:55, 11.47s/it]
[Succeeded / Failed / Skipped / Total] 152 / 26 / 23 / 201:  67%|█████████████▍      | 202/300 [38:33<18:42, 11.45s/it]
[Succeeded / Failed / Skipped / Total] 153 / 26 / 23 / 202:  67%|█████████████▍      | 202/300 [38:33<18:42, 11.45s/it]
[Succeeded / Failed / Skipped / Total] 153 / 26 / 23 / 202:  68%|█████████████▌      | 203/300 [39:01<18:38, 11.53s/it]
[Succeeded / Failed / Skipped / Total] 154 / 26 / 23 / 203:  68%|█████████████▌      | 203/300 [39:01<18:38, 11.53s/it]
[Succeeded / Failed / Skipped / Total] 154 / 26 / 23 / 203:  68%|█████████████▌      | 204/300 [39:04<18:23, 11.49s/it]
[Succeeded / Failed / Skipped / Total] 155 / 26 / 23 / 204:  68%|█████████████▌      | 204/300 [39:04<18:23, 11.49s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 193 / 30 / 27 / 250:  84%|████████████████▋   | 251/300 [48:47<09:31, 11.66s/it]
[Succeeded / Failed / Skipped / Total] 194 / 30 / 27 / 251:  84%|████████████████▋   | 251/300 [48:47<09:31, 11.66s/it]
[Succeeded / Failed / Skipped / Total] 194 / 30 / 27 / 251:  84%|████████████████▊   | 252/300 [49:03<09:20, 11.68s/it]
[Succeeded / Failed / Skipped / Total] 195 / 30 / 27 / 252:  84%|████████████████▊   | 252/300 [49:03<09:20, 11.68s/it]
[Succeeded / Failed / Skipped / Total] 195 / 30 / 27 / 252:  84%|████████████████▊   | 253/300 [49:20<09:09, 11.70s/it]
[Succeeded / Failed / Skipped / Total] 196 / 30 / 27 / 253:  84%|████████████████▊   | 253/300 [49:20<09:09, 11.70s/it]
[Succeeded / Failed / Skipped / Total] 196 / 30 / 27 / 253:  85%|████████████████▉   | 254/300 [49:29<08:57, 11.69s/it]
[Succeeded / Failed / Skipped / Total] 197 / 30 / 27 / 254:  85%|████████████████▉   | 254/300 [49:29<08:57, 11.69s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 233    |
| Number of failed attacks:     | 35     |
| Number of skipped attacks:    | 32     |
| Original accuracy:            | 89.33% |
| Accuracy under attack:        | 11.67% |
| Attack success rate:          | 86.94% |
| Average perturbed word %:     | 17.62% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 164.59 |
+-------------------------------+--------+


In [63]:
runAttack(bert_lr10_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr10'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr10ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                               | 1/300 [00:30<2:31:34, 30.42s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:30<2:31:39, 30.43s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:41<1:42:48, 20.70s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:41<1:42:50, 20.71s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:56<1:33:42, 18.93s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:56<1:33:43, 18.94s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:19<1:37:39, 19.80s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:19<1:37:40, 19.80s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 40 / 5 / 5 / 50:  17%|████▎                    | 51/300 [08:22<40:51,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 41 / 5 / 5 / 51:  17%|████▎                    | 51/300 [08:22<40:51,  9.84s/it]
[Succeeded / Failed / Skipped / Total] 41 / 5 / 5 / 51:  17%|████▎                    | 52/300 [08:29<40:30,  9.80s/it]
[Succeeded / Failed / Skipped / Total] 42 / 5 / 5 / 52:  17%|████▎                    | 52/300 [08:29<40:30,  9.80s/it]
[Succeeded / Failed / Skipped / Total] 42 / 5 / 5 / 52:  18%|████▍                    | 53/300 [08:47<40:58,  9.95s/it]
[Succeeded / Failed / Skipped / Total] 42 / 6 / 5 / 53:  18%|████▍                    | 53/300 [08:47<40:58,  9.95s/it]
[Succeeded / Failed / Skipped / Total] 42 / 6 / 5 / 53:  18%|████▌                    | 54/300 [08:53<40:32,  9.89s/it]
[Succeeded / Failed / Skipped / Total] 43 / 6 / 5 / 54:  18%|████▌                    | 54/300 [08:53<40:32,  9.89s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 80 / 9 / 11 / 100:  34%|███████▍              | 101/300 [17:10<33:50, 10.20s/it]
[Succeeded / Failed / Skipped / Total] 81 / 9 / 11 / 101:  34%|███████▍              | 101/300 [17:10<33:50, 10.20s/it]
[Succeeded / Failed / Skipped / Total] 81 / 9 / 11 / 101:  34%|███████▍              | 102/300 [17:14<33:28, 10.14s/it]
[Succeeded / Failed / Skipped / Total] 82 / 9 / 11 / 102:  34%|███████▍              | 102/300 [17:14<33:28, 10.14s/it]
[Succeeded / Failed / Skipped / Total] 82 / 9 / 11 / 102:  34%|███████▌              | 103/300 [17:20<33:10, 10.10s/it]
[Succeeded / Failed / Skipped / Total] 83 / 9 / 11 / 103:  34%|███████▌              | 103/300 [17:20<33:10, 10.10s/it]
[Succeeded / Failed / Skipped / Total] 83 / 9 / 11 / 103:  35%|███████▋              | 104/300 [17:32<33:03, 10.12s/it]
[Succeeded / Failed / Skipped / Total] 84 / 9 / 11 / 104:  35%|███████▋              | 104/300 [17:32<33:03, 10.12s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 117 / 17 / 16 / 150:  50%|██████████          | 151/300 [26:36<26:14, 10.57s/it]
[Succeeded / Failed / Skipped / Total] 118 / 17 / 16 / 151:  50%|██████████          | 151/300 [26:36<26:14, 10.57s/it]
[Succeeded / Failed / Skipped / Total] 118 / 17 / 16 / 151:  51%|██████████▏         | 152/300 [27:00<26:17, 10.66s/it]
[Succeeded / Failed / Skipped / Total] 119 / 17 / 16 / 152:  51%|██████████▏         | 152/300 [27:00<26:17, 10.66s/it]
[Succeeded / Failed / Skipped / Total] 119 / 17 / 16 / 152:  51%|██████████▏         | 153/300 [27:06<26:03, 10.63s/it]
[Succeeded / Failed / Skipped / Total] 120 / 17 / 16 / 153:  51%|██████████▏         | 153/300 [27:06<26:03, 10.63s/it]
[Succeeded / Failed / Skipped / Total] 120 / 17 / 16 / 153:  51%|██████████▎         | 154/300 [27:12<25:47, 10.60s/it]
[Succeeded / Failed / Skipped / Total] 121 / 17 / 16 / 154:  51%|██████████▎         | 154/300 [27:12<25:47, 10.60s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 157 / 21 / 22 / 200:  67%|█████████████▍      | 201/300 [37:24<18:25, 11.17s/it]
[Succeeded / Failed / Skipped / Total] 158 / 21 / 22 / 201:  67%|█████████████▍      | 201/300 [37:24<18:25, 11.17s/it]
[Succeeded / Failed / Skipped / Total] 158 / 21 / 22 / 201:  67%|█████████████▍      | 202/300 [37:32<18:12, 11.15s/it]
[Succeeded / Failed / Skipped / Total] 159 / 21 / 22 / 202:  67%|█████████████▍      | 202/300 [37:32<18:12, 11.15s/it]
[Succeeded / Failed / Skipped / Total] 159 / 21 / 22 / 202:  68%|█████████████▌      | 203/300 [38:03<18:11, 11.25s/it]
[Succeeded / Failed / Skipped / Total] 160 / 21 / 22 / 203:  68%|█████████████▌      | 203/300 [38:03<18:11, 11.25s/it]
[Succeeded / Failed / Skipped / Total] 160 / 21 / 22 / 203:  68%|█████████████▌      | 204/300 [38:06<17:56, 11.21s/it]
[Succeeded / Failed / Skipped / Total] 161 / 21 / 22 / 204:  68%|█████████████▌      | 204/300 [38:06<17:56, 11.21s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 200 / 24 / 26 / 250:  84%|████████████████▋   | 251/300 [47:48<09:20, 11.43s/it]
[Succeeded / Failed / Skipped / Total] 201 / 24 / 26 / 251:  84%|████████████████▋   | 251/300 [47:48<09:20, 11.43s/it]
[Succeeded / Failed / Skipped / Total] 201 / 24 / 26 / 251:  84%|████████████████▊   | 252/300 [48:10<09:10, 11.47s/it]
[Succeeded / Failed / Skipped / Total] 202 / 24 / 26 / 252:  84%|████████████████▊   | 252/300 [48:10<09:10, 11.47s/it]
[Succeeded / Failed / Skipped / Total] 202 / 24 / 26 / 252:  84%|████████████████▊   | 253/300 [48:28<09:00, 11.50s/it]
[Succeeded / Failed / Skipped / Total] 203 / 24 / 26 / 253:  84%|████████████████▊   | 253/300 [48:28<09:00, 11.50s/it]
[Succeeded / Failed / Skipped / Total] 203 / 24 / 26 / 253:  85%|████████████████▉   | 254/300 [48:38<08:48, 11.49s/it]
[Succeeded / Failed / Skipped / Total] 204 / 24 / 26 / 254:  85%|████████████████▉   | 254/300 [48:38<08:48, 11.49s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 239    |
| Number of failed attacks:     | 30     |
| Number of skipped attacks:    | 31     |
| Original accuracy:            | 89.67% |
| Accuracy under attack:        | 10.0%  |
| Attack success rate:          | 88.85% |
| Average perturbed word %:     | 17.65% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 159.37 |
+-------------------------------+--------+


In [64]:
runAttack(bert_rf7_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf7ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                               | 1/300 [00:31<2:37:30, 31.61s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:31<2:37:35, 31.62s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:34<1:26:09, 17.35s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:34<1:26:11, 17.35s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:46<1:17:04, 15.57s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:46<1:17:05, 15.57s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:08<1:24:34, 17.14s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:08<1:24:35, 17.15s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 34 / 3 / 13 / 50:  17%|████                    | 51/300 [05:39<27:38,  6.66s/it]
[Succeeded / Failed / Skipped / Total] 34 / 4 / 13 / 51:  17%|████                    | 51/300 [05:39<27:38,  6.66s/it]
[Succeeded / Failed / Skipped / Total] 34 / 4 / 13 / 51:  17%|████▏                   | 52/300 [05:47<27:35,  6.68s/it]
[Succeeded / Failed / Skipped / Total] 35 / 4 / 13 / 52:  17%|████▏                   | 52/300 [05:47<27:35,  6.68s/it]
[Succeeded / Failed / Skipped / Total] 35 / 4 / 13 / 52:  18%|████▏                   | 53/300 [06:05<28:21,  6.89s/it]
[Succeeded / Failed / Skipped / Total] 35 / 5 / 13 / 53:  18%|████▏                   | 53/300 [06:05<28:21,  6.89s/it]
[Succeeded / Failed / Skipped / Total] 35 / 5 / 13 / 53:  18%|████▎                   | 54/300 [06:12<28:15,  6.89s/it]
[Succeeded / Failed / Skipped / Total] 36 / 5 / 13 / 54:  18%|████▎                   | 54/300 [06:12<28:15,  6.89s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 65 / 6 / 30 / 101:  34%|███████▍              | 102/300 [10:03<19:30,  5.91s/it]
[Succeeded / Failed / Skipped / Total] 66 / 6 / 30 / 102:  34%|███████▍              | 102/300 [10:03<19:30,  5.91s/it]
[Succeeded / Failed / Skipped / Total] 66 / 6 / 30 / 102:  34%|███████▌              | 103/300 [10:11<19:30,  5.94s/it]
[Succeeded / Failed / Skipped / Total] 67 / 6 / 30 / 103:  34%|███████▌              | 103/300 [10:11<19:30,  5.94s/it]
[Succeeded / Failed / Skipped / Total] 67 / 6 / 30 / 103:  35%|███████▋              | 104/300 [10:13<19:16,  5.90s/it]
[Succeeded / Failed / Skipped / Total] 68 / 6 / 30 / 104:  35%|███████▋              | 104/300 [10:13<19:16,  5.90s/it]
[Succeeded / Failed / Skipped / Total] 68 / 6 / 30 / 104:  35%|███████▋              | 105/300 [10:27<19:26,  5.98s/it]
[Succeeded / Failed / Skipped / Total] 69 / 6 / 30 / 105:  35%|███████▋              | 105/300 [10:27<19:26,  5.98s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 100 / 10 / 40 / 150:  50%|██████████          | 151/300 [16:03<15:50,  6.38s/it]
[Succeeded / Failed / Skipped / Total] 100 / 11 / 40 / 151:  50%|██████████          | 151/300 [16:03<15:50,  6.38s/it]
[Succeeded / Failed / Skipped / Total] 100 / 11 / 40 / 151:  51%|██████████▏         | 152/300 [16:16<15:50,  6.42s/it]
[Succeeded / Failed / Skipped / Total] 101 / 11 / 40 / 152:  51%|██████████▏         | 152/300 [16:16<15:50,  6.42s/it]
[Succeeded / Failed / Skipped / Total] 101 / 11 / 40 / 152:  51%|██████████▏         | 153/300 [16:20<15:42,  6.41s/it]
[Succeeded / Failed / Skipped / Total] 102 / 11 / 40 / 153:  51%|██████████▏         | 153/300 [16:20<15:42,  6.41s/it]
[Succeeded / Failed / Skipped / Total] 102 / 11 / 40 / 153:  51%|██████████▎         | 154/300 [16:23<15:32,  6.39s/it]
[Succeeded / Failed / Skipped / Total] 103 / 11 / 40 / 154:  51%|██████████▎         | 154/300 [16:23<15:32,  6.39s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 129 / 15 / 56 / 200:  67%|█████████████▍      | 201/300 [24:20<11:59,  7.27s/it]
[Succeeded / Failed / Skipped / Total] 130 / 15 / 56 / 201:  67%|█████████████▍      | 201/300 [24:20<11:59,  7.27s/it]
[Succeeded / Failed / Skipped / Total] 130 / 15 / 56 / 201:  67%|█████████████▍      | 202/300 [24:26<11:51,  7.26s/it]
[Succeeded / Failed / Skipped / Total] 131 / 15 / 56 / 202:  67%|█████████████▍      | 202/300 [24:26<11:51,  7.26s/it]
[Succeeded / Failed / Skipped / Total] 131 / 15 / 56 / 202:  68%|█████████████▌      | 203/300 [24:35<11:44,  7.27s/it]
[Succeeded / Failed / Skipped / Total] 132 / 15 / 56 / 203:  68%|█████████████▌      | 203/300 [24:35<11:44,  7.27s/it]
[Succeeded / Failed / Skipped / Total] 132 / 15 / 56 / 203:  68%|█████████████▌      | 204/300 [24:35<11:34,  7.23s/it]
[Succeeded / Failed / Skipped / Total] 132 / 15 / 57 / 204:  68%|█████████████▌      | 204/300 [24:35<11:34,  7.23s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 170 / 17 / 63 / 250:  84%|████████████████▋   | 251/300 [29:49<05:49,  7.13s/it]
[Succeeded / Failed / Skipped / Total] 171 / 17 / 63 / 251:  84%|████████████████▋   | 251/300 [29:49<05:49,  7.13s/it]
[Succeeded / Failed / Skipped / Total] 171 / 17 / 63 / 251:  84%|████████████████▊   | 252/300 [29:50<05:41,  7.11s/it]
[Succeeded / Failed / Skipped / Total] 172 / 17 / 63 / 252:  84%|████████████████▊   | 252/300 [29:50<05:41,  7.11s/it]
[Succeeded / Failed / Skipped / Total] 172 / 17 / 63 / 252:  84%|████████████████▊   | 253/300 [30:00<05:34,  7.12s/it]
[Succeeded / Failed / Skipped / Total] 173 / 17 / 63 / 253:  84%|████████████████▊   | 253/300 [30:00<05:34,  7.12s/it]
[Succeeded / Failed / Skipped / Total] 173 / 17 / 63 / 253:  85%|████████████████▉   | 254/300 [30:05<05:26,  7.11s/it]
[Succeeded / Failed / Skipped / Total] 174 / 17 / 63 / 254:  85%|████████████████▉   | 254/300 [30:05<05:26,  7.11s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 208    |
| Number of failed attacks:     | 18     |
| Number of skipped attacks:    | 74     |
| Original accuracy:            | 75.33% |
| Accuracy under attack:        | 6.0%   |
| Attack success rate:          | 92.04% |
| Average perturbed word %:     | 9.01%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 109.11 |
+-------------------------------+--------+


In [65]:
runAttack(bert_rf14_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf14'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf14ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                               | 1/300 [00:19<1:37:20, 19.53s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:19<1:37:33, 19.58s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:24<1:00:35, 12.20s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:24<1:00:41, 12.22s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:37<1:01:54, 12.51s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:37<1:01:57, 12.52s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:00<1:14:43, 15.15s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:00<1:14:43, 15.15s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 37 / 4 / 9 / 50:  17%|████▎                    | 51/300 [06:39<32:29,  7.83s/it]
[Succeeded / Failed / Skipped / Total] 38 / 4 / 9 / 51:  17%|████▎                    | 51/300 [06:39<32:29,  7.83s/it]
[Succeeded / Failed / Skipped / Total] 38 / 4 / 9 / 51:  17%|████▎                    | 52/300 [06:46<32:17,  7.81s/it]
[Succeeded / Failed / Skipped / Total] 39 / 4 / 9 / 52:  17%|████▎                    | 52/300 [06:46<32:17,  7.81s/it]
[Succeeded / Failed / Skipped / Total] 39 / 4 / 9 / 52:  18%|████▍                    | 53/300 [07:03<32:54,  7.99s/it]
[Succeeded / Failed / Skipped / Total] 39 / 5 / 9 / 53:  18%|████▍                    | 53/300 [07:03<32:54,  7.99s/it]
[Succeeded / Failed / Skipped / Total] 39 / 5 / 9 / 53:  18%|████▌                    | 54/300 [07:10<32:39,  7.97s/it]
[Succeeded / Failed / Skipped / Total] 40 / 5 / 9 / 54:  18%|████▌                    | 54/300 [07:10<32:39,  7.97s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 73 / 8 / 19 / 100:  34%|███████▍              | 101/300 [12:36<24:50,  7.49s/it]
[Succeeded / Failed / Skipped / Total] 74 / 8 / 19 / 101:  34%|███████▍              | 101/300 [12:36<24:50,  7.49s/it]
[Succeeded / Failed / Skipped / Total] 74 / 8 / 19 / 101:  34%|███████▍              | 102/300 [12:44<24:43,  7.49s/it]
[Succeeded / Failed / Skipped / Total] 75 / 8 / 19 / 102:  34%|███████▍              | 102/300 [12:44<24:43,  7.49s/it]
[Succeeded / Failed / Skipped / Total] 75 / 8 / 19 / 102:  34%|███████▌              | 103/300 [12:44<24:21,  7.42s/it]
[Succeeded / Failed / Skipped / Total] 75 / 8 / 20 / 103:  34%|███████▌              | 103/300 [12:44<24:21,  7.42s/it]
[Succeeded / Failed / Skipped / Total] 75 / 8 / 20 / 103:  35%|███████▋              | 104/300 [12:50<24:11,  7.41s/it]
[Succeeded / Failed / Skipped / Total] 76 / 8 / 20 / 104:  35%|███████▋              | 104/300 [12:50<24:11,  7.41s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 108 / 15 / 27 / 150:  50%|██████████          | 151/300 [20:02<19:46,  7.96s/it]
[Succeeded / Failed / Skipped / Total] 109 / 15 / 27 / 151:  50%|██████████          | 151/300 [20:02<19:46,  7.96s/it]
[Succeeded / Failed / Skipped / Total] 109 / 15 / 27 / 151:  51%|██████████▏         | 152/300 [20:31<19:58,  8.10s/it]
[Succeeded / Failed / Skipped / Total] 110 / 15 / 27 / 152:  51%|██████████▏         | 152/300 [20:31<19:58,  8.10s/it]
[Succeeded / Failed / Skipped / Total] 110 / 15 / 27 / 152:  51%|██████████▏         | 153/300 [20:35<19:47,  8.08s/it]
[Succeeded / Failed / Skipped / Total] 111 / 15 / 27 / 153:  51%|██████████▏         | 153/300 [20:35<19:47,  8.08s/it]
[Succeeded / Failed / Skipped / Total] 111 / 15 / 27 / 153:  51%|██████████▎         | 154/300 [20:38<19:34,  8.05s/it]
[Succeeded / Failed / Skipped / Total] 112 / 15 / 27 / 154:  51%|██████████▎         | 154/300 [20:38<19:34,  8.05s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 136 / 21 / 43 / 200:  67%|█████████████▍      | 201/300 [29:28<14:30,  8.80s/it]
[Succeeded / Failed / Skipped / Total] 137 / 21 / 43 / 201:  67%|█████████████▍      | 201/300 [29:28<14:30,  8.80s/it]
[Succeeded / Failed / Skipped / Total] 137 / 21 / 43 / 201:  67%|█████████████▍      | 202/300 [29:40<14:23,  8.81s/it]
[Succeeded / Failed / Skipped / Total] 137 / 22 / 43 / 202:  67%|█████████████▍      | 202/300 [29:40<14:23,  8.81s/it]
[Succeeded / Failed / Skipped / Total] 137 / 22 / 43 / 202:  68%|█████████████▌      | 203/300 [30:02<14:21,  8.88s/it]
[Succeeded / Failed / Skipped / Total] 138 / 22 / 43 / 203:  68%|█████████████▌      | 203/300 [30:02<14:21,  8.88s/it]
[Succeeded / Failed / Skipped / Total] 138 / 22 / 44 / 204:  68%|█████████████▌      | 204/300 [30:02<14:08,  8.84s/it]
[Succeeded / Failed / Skipped / Total] 138 / 22 / 44 / 204:  68%|█████████████▋      | 205/300 [30:08<13:58,  8.82s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 175 / 26 / 49 / 250:  84%|████████████████▋   | 251/300 [38:17<07:28,  9.15s/it]
[Succeeded / Failed / Skipped / Total] 176 / 26 / 49 / 251:  84%|████████████████▋   | 251/300 [38:17<07:28,  9.15s/it]
[Succeeded / Failed / Skipped / Total] 176 / 26 / 49 / 251:  84%|████████████████▊   | 252/300 [38:20<07:18,  9.13s/it]
[Succeeded / Failed / Skipped / Total] 177 / 26 / 49 / 252:  84%|████████████████▊   | 252/300 [38:21<07:18,  9.13s/it]
[Succeeded / Failed / Skipped / Total] 177 / 26 / 49 / 252:  84%|████████████████▊   | 253/300 [38:27<07:08,  9.12s/it]
[Succeeded / Failed / Skipped / Total] 178 / 26 / 49 / 253:  84%|████████████████▊   | 253/300 [38:27<07:08,  9.12s/it]
[Succeeded / Failed / Skipped / Total] 178 / 26 / 49 / 253:  85%|████████████████▉   | 254/300 [38:34<06:59,  9.11s/it]
[Succeeded / Failed / Skipped / Total] 179 / 26 / 49 / 254:  85%|████████████████▉   | 254/300 [38:34<06:59,  9.11s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 213    |
| Number of failed attacks:     | 30     |
| Number of skipped attacks:    | 57     |
| Original accuracy:            | 81.0%  |
| Accuracy under attack:        | 10.0%  |
| Attack success rate:          | 87.65% |
| Average perturbed word %:     | 10.75% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 137.12 |
+-------------------------------+--------+


In [66]:
runAttack(bert_rf30_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf30'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf30ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                               | 1/300 [00:33<2:47:51, 33.68s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|                          | 1/300 [00:33<2:47:56, 33.70s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   1%|▏                         | 2/300 [00:42<1:46:25, 21.43s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▏                         | 2/300 [00:42<1:46:29, 21.44s/it]
[Succeeded / Failed / Skipped / Total] 1 / 1 / 0 / 2:   1%|▎                         | 3/300 [01:06<1:49:11, 22.06s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 3/300 [01:06<1:49:12, 22.06s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 4/300 [01:32<1:53:57, 23.10s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                         | 4/300 [01:32<1:53:58, 23.10s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 36 / 8 / 6 / 50:  17%|████▎                    | 51/300 [08:42<42:28, 10.24s/it]
[Succeeded / Failed / Skipped / Total] 37 / 8 / 6 / 51:  17%|████▎                    | 51/300 [08:42<42:28, 10.24s/it]
[Succeeded / Failed / Skipped / Total] 37 / 8 / 6 / 51:  17%|████▎                    | 52/300 [08:49<42:03, 10.17s/it]
[Succeeded / Failed / Skipped / Total] 38 / 8 / 6 / 52:  17%|████▎                    | 52/300 [08:49<42:03, 10.17s/it]
[Succeeded / Failed / Skipped / Total] 38 / 8 / 6 / 52:  18%|████▍                    | 53/300 [09:00<41:57, 10.19s/it]
[Succeeded / Failed / Skipped / Total] 39 / 8 / 6 / 53:  18%|████▍                    | 53/300 [09:00<41:57, 10.19s/it]
[Succeeded / Failed / Skipped / Total] 39 / 8 / 6 / 53:  18%|████▌                    | 54/300 [09:18<42:22, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 39 / 9 / 6 / 54:  18%|████▌                    | 54/300 [09:18<42:22, 10.34s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 70 / 11 / 19 / 100:  34%|███████              | 101/300 [14:39<28:53,  8.71s/it]
[Succeeded / Failed / Skipped / Total] 71 / 11 / 19 / 101:  34%|███████              | 101/300 [14:39<28:53,  8.71s/it]
[Succeeded / Failed / Skipped / Total] 71 / 11 / 19 / 101:  34%|███████▏             | 102/300 [14:48<28:45,  8.71s/it]
[Succeeded / Failed / Skipped / Total] 72 / 11 / 19 / 102:  34%|███████▏             | 102/300 [14:48<28:45,  8.71s/it]
[Succeeded / Failed / Skipped / Total] 72 / 11 / 19 / 102:  34%|███████▏             | 103/300 [14:48<28:20,  8.63s/it]
[Succeeded / Failed / Skipped / Total] 72 / 11 / 20 / 103:  34%|███████▏             | 103/300 [14:48<28:20,  8.63s/it]
[Succeeded / Failed / Skipped / Total] 72 / 11 / 20 / 103:  35%|███████▎             | 104/300 [15:11<28:37,  8.76s/it]
[Succeeded / Failed / Skipped / Total] 72 / 12 / 20 / 104:  35%|███████▎             | 104/300 [15:11<28:37,  8.76s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 105 / 19 / 26 / 150:  50%|██████████          | 151/300 [22:49<22:31,  9.07s/it]
[Succeeded / Failed / Skipped / Total] 106 / 19 / 26 / 151:  50%|██████████          | 151/300 [22:49<22:31,  9.07s/it]
[Succeeded / Failed / Skipped / Total] 106 / 19 / 26 / 151:  51%|██████████▏         | 152/300 [23:15<22:38,  9.18s/it]
[Succeeded / Failed / Skipped / Total] 107 / 19 / 26 / 152:  51%|██████████▏         | 152/300 [23:15<22:38,  9.18s/it]
[Succeeded / Failed / Skipped / Total] 107 / 19 / 26 / 152:  51%|██████████▏         | 153/300 [23:20<22:25,  9.16s/it]
[Succeeded / Failed / Skipped / Total] 108 / 19 / 26 / 153:  51%|██████████▏         | 153/300 [23:20<22:25,  9.16s/it]
[Succeeded / Failed / Skipped / Total] 108 / 19 / 26 / 153:  51%|██████████▎         | 154/300 [23:25<22:12,  9.13s/it]
[Succeeded / Failed / Skipped / Total] 109 / 19 / 26 / 154:  51%|██████████▎         | 154/300 [23:25<22:12,  9.13s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 133 / 28 / 39 / 200:  67%|█████████████▍      | 201/300 [32:47<16:09,  9.79s/it]
[Succeeded / Failed / Skipped / Total] 134 / 28 / 39 / 201:  67%|█████████████▍      | 201/300 [32:47<16:09,  9.79s/it]
[Succeeded / Failed / Skipped / Total] 134 / 28 / 39 / 201:  67%|█████████████▍      | 202/300 [32:52<15:57,  9.77s/it]
[Succeeded / Failed / Skipped / Total] 135 / 28 / 39 / 202:  67%|█████████████▍      | 202/300 [32:52<15:57,  9.77s/it]
[Succeeded / Failed / Skipped / Total] 135 / 28 / 39 / 202:  68%|█████████████▌      | 203/300 [33:05<15:48,  9.78s/it]
[Succeeded / Failed / Skipped / Total] 136 / 28 / 39 / 203:  68%|█████████████▌      | 203/300 [33:05<15:48,  9.78s/it]
[Succeeded / Failed / Skipped / Total] 136 / 28 / 39 / 203:  68%|█████████████▌      | 204/300 [33:05<15:34,  9.73s/it]
[Succeeded / Failed / Skipped / Total] 136 / 28 / 40 / 204:  68%|█████████████▌      | 204/300 [33:05<15:34,  9.73s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 166 / 38 / 46 / 250:  84%|████████████████▋   | 251/300 [42:44<08:20, 10.22s/it]
[Succeeded / Failed / Skipped / Total] 167 / 38 / 46 / 251:  84%|████████████████▋   | 251/300 [42:44<08:20, 10.22s/it]
[Succeeded / Failed / Skipped / Total] 167 / 38 / 46 / 251:  84%|████████████████▊   | 252/300 [42:47<08:09, 10.19s/it]
[Succeeded / Failed / Skipped / Total] 168 / 38 / 46 / 252:  84%|████████████████▊   | 252/300 [42:47<08:09, 10.19s/it]
[Succeeded / Failed / Skipped / Total] 168 / 38 / 46 / 252:  84%|████████████████▊   | 253/300 [42:53<07:57, 10.17s/it]
[Succeeded / Failed / Skipped / Total] 169 / 38 / 46 / 253:  84%|████████████████▊   | 253/300 [42:53<07:58, 10.17s/it]
[Succeeded / Failed / Skipped / Total] 169 / 38 / 46 / 253:  85%|████████████████▉   | 254/300 [42:58<07:46, 10.15s/it]
[Succeeded / Failed / Skipped / Total] 170 / 38 / 46 / 254:  85%|████████████████▉   | 254/300 [42:58<07:46, 10.15s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 201    |
| Number of failed attacks:     | 46     |
| Number of skipped attacks:    | 53     |
| Original accuracy:            | 82.33% |
| Accuracy under attack:        | 15.33% |
| Attack success rate:          | 81.38% |
| Average perturbed word %:     | 9.59%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 148.72 |
+-------------------------------+--------+


In [67]:
runAttack(bert_knn7_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn7ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                           | 1/300 [25:34<127:24:57, 1534.10s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                      | 1/300 [25:34<127:25:02, 1534.12s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                       | 2/300 [25:44<63:55:30, 772.25s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                       | 2/300 [25:44<63:55:32, 772.26s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                       | 3/300 [26:06<43:05:14, 522.27s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▏                       | 3/300 [26:06<43:05:17, 522.28s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                       | 4/300 [26:31<32:42:18, 397.77s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                       | 4/300 [26:31<32:42:19, 397.77s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 28 / 11 / 11 / 50:  17%|███▌                 | 51/300 [34:10<2:46:51, 40.21s/it]
[Succeeded / Failed / Skipped / Total] 29 / 11 / 11 / 51:  17%|███▌                 | 51/300 [34:10<2:46:51, 40.21s/it]
[Succeeded / Failed / Skipped / Total] 29 / 11 / 11 / 51:  17%|███▋                 | 52/300 [34:13<2:43:13, 39.49s/it]
[Succeeded / Failed / Skipped / Total] 30 / 11 / 11 / 52:  17%|███▋                 | 52/300 [34:13<2:43:13, 39.49s/it]
[Succeeded / Failed / Skipped / Total] 30 / 11 / 11 / 52:  18%|███▋                 | 53/300 [34:31<2:40:56, 39.09s/it]
[Succeeded / Failed / Skipped / Total] 31 / 11 / 11 / 53:  18%|███▋                 | 53/300 [34:31<2:40:56, 39.09s/it]
[Succeeded / Failed / Skipped / Total] 31 / 11 / 11 / 53:  18%|███▊                 | 54/300 [34:55<2:39:04, 38.80s/it]
[Succeeded / Failed / Skipped / Total] 31 / 12 / 11 / 54:  18%|███▊                 | 54/300 [34:55<2:39:04, 38.80s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 64 / 16 / 20 / 100:  34%|██████▍            | 101/300 [41:56<1:22:38, 24.92s/it]
[Succeeded / Failed / Skipped / Total] 65 / 16 / 20 / 101:  34%|██████▍            | 101/300 [41:56<1:22:38, 24.92s/it]
[Succeeded / Failed / Skipped / Total] 65 / 16 / 20 / 101:  34%|██████▍            | 102/300 [42:26<1:22:23, 24.97s/it]
[Succeeded / Failed / Skipped / Total] 65 / 17 / 20 / 102:  34%|██████▍            | 102/300 [42:26<1:22:23, 24.97s/it]
[Succeeded / Failed / Skipped / Total] 65 / 17 / 20 / 102:  34%|██████▌            | 103/300 [42:26<1:21:11, 24.73s/it]
[Succeeded / Failed / Skipped / Total] 65 / 17 / 21 / 103:  34%|██████▌            | 103/300 [42:26<1:21:11, 24.73s/it]
[Succeeded / Failed / Skipped / Total] 65 / 17 / 21 / 103:  35%|██████▌            | 104/300 [42:33<1:20:13, 24.56s/it]
[Succeeded / Failed / Skipped / Total] 66 / 17 / 21 / 104:  35%|██████▌            | 104/300 [42:33<1:20:13, 24.56s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 91 / 27 / 32 / 150:  50%|██████████▌          | 151/300 [51:54<51:13, 20.63s/it]
[Succeeded / Failed / Skipped / Total] 92 / 27 / 32 / 151:  50%|██████████▌          | 151/300 [51:54<51:13, 20.63s/it]
[Succeeded / Failed / Skipped / Total] 92 / 27 / 32 / 151:  51%|██████████▋          | 152/300 [52:33<51:10, 20.75s/it]
[Succeeded / Failed / Skipped / Total] 92 / 28 / 32 / 152:  51%|██████████▋          | 152/300 [52:33<51:10, 20.75s/it]
[Succeeded / Failed / Skipped / Total] 92 / 28 / 32 / 152:  51%|██████████▋          | 153/300 [53:00<50:55, 20.79s/it]
[Succeeded / Failed / Skipped / Total] 92 / 29 / 32 / 153:  51%|██████████▋          | 153/300 [53:00<50:55, 20.79s/it]
[Succeeded / Failed / Skipped / Total] 92 / 29 / 32 / 153:  51%|██████████▊          | 154/300 [53:04<50:18, 20.68s/it]
[Succeeded / Failed / Skipped / Total] 93 / 29 / 32 / 154:  51%|██████████▊          | 154/300 [53:04<50:18, 20.68s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 118 / 37 / 45 / 200:  67%|████████████      | 201/300 [1:04:02<31:32, 19.12s/it]
[Succeeded / Failed / Skipped / Total] 118 / 38 / 45 / 201:  67%|████████████      | 201/300 [1:04:02<31:32, 19.12s/it]
[Succeeded / Failed / Skipped / Total] 118 / 38 / 45 / 201:  67%|████████████      | 202/300 [1:04:07<31:06, 19.05s/it]
[Succeeded / Failed / Skipped / Total] 119 / 38 / 45 / 202:  67%|████████████      | 202/300 [1:04:07<31:06, 19.05s/it]
[Succeeded / Failed / Skipped / Total] 119 / 38 / 45 / 202:  68%|████████████▏     | 203/300 [1:04:57<31:02, 19.20s/it]
[Succeeded / Failed / Skipped / Total] 119 / 39 / 45 / 203:  68%|████████████▏     | 203/300 [1:04:57<31:02, 19.20s/it]
[Succeeded / Failed / Skipped / Total] 119 / 39 / 45 / 203:  68%|████████████▏     | 204/300 [1:05:01<30:36, 19.13s/it]
[Succeeded / Failed / Skipped / Total] 120 / 39 / 45 / 204:  68%|████████████▏     | 204/300 [1:05:01<30:36, 19.13s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 153 / 45 / 52 / 250:  84%|███████████████   | 251/300 [1:14:33<14:33, 17.82s/it]
[Succeeded / Failed / Skipped / Total] 154 / 45 / 52 / 251:  84%|███████████████   | 251/300 [1:14:33<14:33, 17.82s/it]
[Succeeded / Failed / Skipped / Total] 154 / 45 / 52 / 251:  84%|███████████████   | 252/300 [1:14:37<14:12, 17.77s/it]
[Succeeded / Failed / Skipped / Total] 155 / 45 / 52 / 252:  84%|███████████████   | 252/300 [1:14:37<14:12, 17.77s/it]
[Succeeded / Failed / Skipped / Total] 155 / 45 / 52 / 252:  84%|███████████████▏  | 253/300 [1:14:45<13:53, 17.73s/it]
[Succeeded / Failed / Skipped / Total] 156 / 45 / 52 / 253:  84%|███████████████▏  | 253/300 [1:14:45<13:53, 17.73s/it]
[Succeeded / Failed / Skipped / Total] 156 / 45 / 52 / 253:  85%|███████████████▏  | 254/300 [1:14:51<13:33, 17.68s/it]
[Succeeded / Failed / Skipped / Total] 157 / 45 / 52 / 254:  85%|███████████████▏  | 254/300 [1:14:51<13:33, 17.68s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 189    |
| Number of failed attacks:     | 53     |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 80.67% |
| Accuracy under attack:        | 17.67% |
| Attack success rate:          | 78.1%  |
| Average perturbed word %:     | 5.23%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 147.14 |
+-------------------------------+--------+


In [68]:
runAttack(bert_knn35_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn35'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn35ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                               | 1/300 [00:30<2:32:36, 30.62s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:30<2:32:36, 30.62s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:33<1:22:45, 16.66s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:33<1:22:45, 16.66s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:55<1:31:23, 18.46s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 3/300 [00:55<1:31:25, 18.47s/it]
[Succeeded / Failed / Skipped / Total] 2 / 1 / 0 / 3:   1%|▎                         | 4/300 [01:20<1:39:36, 20.19s/it]
[Succeeded / Failed / Skipped / Total] 2 / 2 / 0 / 4:   1%|▎                         | 4/300 [01:20<1:39:37, 20.20s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 33 / 8 / 9 / 50:  17%|████▎                    | 51/300 [08:57<43:43, 10.53s/it]
[Succeeded / Failed / Skipped / Total] 34 / 8 / 9 / 51:  17%|████▎                    | 51/300 [08:57<43:43, 10.53s/it]
[Succeeded / Failed / Skipped / Total] 34 / 8 / 9 / 51:  17%|████▎                    | 52/300 [09:00<42:56, 10.39s/it]
[Succeeded / Failed / Skipped / Total] 35 / 8 / 9 / 52:  17%|████▎                    | 52/300 [09:00<42:56, 10.39s/it]
[Succeeded / Failed / Skipped / Total] 35 / 8 / 9 / 52:  18%|████▍                    | 53/300 [09:23<43:44, 10.62s/it]
[Succeeded / Failed / Skipped / Total] 35 / 9 / 9 / 53:  18%|████▍                    | 53/300 [09:23<43:44, 10.63s/it]
[Succeeded / Failed / Skipped / Total] 35 / 9 / 9 / 53:  18%|████▌                    | 54/300 [09:45<44:25, 10.83s/it]
[Succeeded / Failed / Skipped / Total] 35 / 10 / 9 / 54:  18%|████▎                   | 54/300 [09:45<44:25, 10.83s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 63 / 18 / 19 / 100:  34%|███████              | 101/300 [17:52<35:13, 10.62s/it]
[Succeeded / Failed / Skipped / Total] 64 / 18 / 19 / 101:  34%|███████              | 101/300 [17:52<35:13, 10.62s/it]
[Succeeded / Failed / Skipped / Total] 64 / 18 / 19 / 101:  34%|███████▏             | 102/300 [17:57<34:52, 10.57s/it]
[Succeeded / Failed / Skipped / Total] 65 / 18 / 19 / 102:  34%|███████▏             | 102/300 [17:57<34:52, 10.57s/it]
[Succeeded / Failed / Skipped / Total] 65 / 18 / 19 / 102:  34%|███████▏             | 103/300 [17:58<34:22, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 65 / 18 / 20 / 103:  34%|███████▏             | 103/300 [17:58<34:22, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 65 / 18 / 20 / 103:  35%|███████▎             | 104/300 [18:02<34:00, 10.41s/it]
[Succeeded / Failed / Skipped / Total] 66 / 18 / 20 / 104:  35%|███████▎             | 104/300 [18:02<34:00, 10.41s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 98 / 24 / 28 / 150:  50%|██████████▌          | 151/300 [26:59<26:38, 10.73s/it]
[Succeeded / Failed / Skipped / Total] 99 / 24 / 28 / 151:  50%|██████████▌          | 151/300 [26:59<26:38, 10.73s/it]
[Succeeded / Failed / Skipped / Total] 99 / 24 / 28 / 151:  51%|██████████▋          | 152/300 [27:36<26:53, 10.90s/it]
[Succeeded / Failed / Skipped / Total] 99 / 25 / 28 / 152:  51%|██████████▋          | 152/300 [27:36<26:53, 10.90s/it]
[Succeeded / Failed / Skipped / Total] 99 / 25 / 28 / 152:  51%|██████████▋          | 153/300 [27:49<26:44, 10.91s/it]
[Succeeded / Failed / Skipped / Total] 100 / 25 / 28 / 153:  51%|██████████▏         | 153/300 [27:49<26:44, 10.91s/it]
[Succeeded / Failed / Skipped / Total] 100 / 25 / 28 / 153:  51%|██████████▎         | 154/300 [27:54<26:27, 10.87s/it]
[Succeeded / Failed / Skipped / Total] 101 / 25 / 28 / 154:  51%|██████████▎         | 154/300 [27:54<26:27, 10.87s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 124 / 33 / 43 / 200:  67%|█████████████▍      | 201/300 [38:51<19:08, 11.60s/it]
[Succeeded / Failed / Skipped / Total] 125 / 33 / 43 / 201:  67%|█████████████▍      | 201/300 [38:51<19:08, 11.60s/it]
[Succeeded / Failed / Skipped / Total] 125 / 33 / 43 / 201:  67%|█████████████▍      | 202/300 [38:54<18:52, 11.56s/it]
[Succeeded / Failed / Skipped / Total] 126 / 33 / 43 / 202:  67%|█████████████▍      | 202/300 [38:54<18:52, 11.56s/it]
[Succeeded / Failed / Skipped / Total] 126 / 33 / 43 / 202:  68%|█████████████▌      | 203/300 [39:04<18:40, 11.55s/it]
[Succeeded / Failed / Skipped / Total] 127 / 33 / 43 / 203:  68%|█████████████▌      | 203/300 [39:04<18:40, 11.55s/it]
[Succeeded / Failed / Skipped / Total] 127 / 33 / 43 / 203:  68%|█████████████▌      | 204/300 [39:20<18:30, 11.57s/it]
[Succeeded / Failed / Skipped / Total] 128 / 33 / 43 / 204:  68%|█████████████▌      | 204/300 [39:20<18:30, 11.57s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 160 / 39 / 51 / 250:  84%|████████████████▋   | 251/300 [47:48<09:19, 11.43s/it]
[Succeeded / Failed / Skipped / Total] 161 / 39 / 51 / 251:  84%|████████████████▋   | 251/300 [47:48<09:19, 11.43s/it]
[Succeeded / Failed / Skipped / Total] 161 / 39 / 51 / 251:  84%|████████████████▊   | 252/300 [47:53<09:07, 11.40s/it]
[Succeeded / Failed / Skipped / Total] 162 / 39 / 51 / 252:  84%|████████████████▊   | 252/300 [47:53<09:07, 11.40s/it]
[Succeeded / Failed / Skipped / Total] 162 / 39 / 51 / 252:  84%|████████████████▊   | 253/300 [48:00<08:55, 11.39s/it]
[Succeeded / Failed / Skipped / Total] 163 / 39 / 51 / 253:  84%|████████████████▊   | 253/300 [48:00<08:55, 11.39s/it]
[Succeeded / Failed / Skipped / Total] 163 / 39 / 51 / 253:  85%|████████████████▉   | 254/300 [48:08<08:43, 11.37s/it]
[Succeeded / Failed / Skipped / Total] 164 / 39 / 51 / 254:  85%|████████████████▉   | 254/300 [48:08<08:43, 11.37s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 195    |
| Number of failed attacks:     | 49     |
| Number of skipped attacks:    | 56     |
| Original accuracy:            | 81.33% |
| Accuracy under attack:        | 16.33% |
| Attack success rate:          | 79.92% |
| Average perturbed word %:     | 8.14%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 143.03 |
+-------------------------------+--------+


In [69]:
runAttack(bert_knn175_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn175'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn175ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                               | 1/300 [00:25<2:06:51, 25.46s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:25<2:06:55, 25.47s/it]
[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:27<1:08:27, 13.78s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:27<1:08:29, 13.79s/it]
[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [00:40<1:07:19, 13.60s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [00:40<1:07:19, 13.60s/it]
[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:04<1:19:55, 16.20s/it]
[Succeeded / Failed / Skipped / Total] 3 / 1 / 0 / 4:   1%|▎                         | 4/300 [01:04<1:19:56, 16.20s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 36 / 5 / 9 / 50:  17%|████▎                    | 51/300 [07:51<38:21,  9.24s/it]
[Succeeded / Failed / Skipped / Total] 37 / 5 / 9 / 51:  17%|████▎                    | 51/300 [07:51<38:21,  9.24s/it]
[Succeeded / Failed / Skipped / Total] 37 / 5 / 9 / 51:  17%|████▎                    | 52/300 [07:54<37:42,  9.12s/it]
[Succeeded / Failed / Skipped / Total] 38 / 5 / 9 / 52:  17%|████▎                    | 52/300 [07:54<37:42,  9.12s/it]
[Succeeded / Failed / Skipped / Total] 38 / 5 / 9 / 52:  18%|████▍                    | 53/300 [08:08<37:55,  9.21s/it]
[Succeeded / Failed / Skipped / Total] 39 / 5 / 9 / 53:  18%|████▍                    | 53/300 [08:08<37:55,  9.21s/it]
[Succeeded / Failed / Skipped / Total] 39 / 5 / 9 / 53:  18%|████▌                    | 54/300 [08:22<38:08,  9.30s/it]
[Succeeded / Failed / Skipped / Total] 40 / 5 / 9 / 54:  18%|████▌                    | 54/300 [08:22<38:08,  9.30s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 73 / 7 / 20 / 100:  34%|███████▍              | 101/300 [14:11<27:58,  8.43s/it]
[Succeeded / Failed / Skipped / Total] 73 / 7 / 21 / 101:  34%|███████▍              | 101/300 [14:11<27:58,  8.43s/it]
[Succeeded / Failed / Skipped / Total] 73 / 7 / 21 / 101:  34%|███████▍              | 102/300 [14:29<28:08,  8.53s/it]
[Succeeded / Failed / Skipped / Total] 74 / 7 / 21 / 102:  34%|███████▍              | 102/300 [14:29<28:08,  8.53s/it]
[Succeeded / Failed / Skipped / Total] 74 / 7 / 21 / 102:  34%|███████▌              | 103/300 [14:30<27:44,  8.45s/it]
[Succeeded / Failed / Skipped / Total] 74 / 7 / 22 / 103:  34%|███████▌              | 103/300 [14:30<27:44,  8.45s/it]
[Succeeded / Failed / Skipped / Total] 74 / 7 / 22 / 103:  35%|███████▋              | 104/300 [14:34<27:27,  8.41s/it]
[Succeeded / Failed / Skipped / Total] 75 / 7 / 22 / 104:  35%|███████▋              | 104/300 [14:34<27:27,  8.41s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 105 / 12 / 33 / 150:  50%|██████████          | 151/300 [22:32<22:14,  8.96s/it]
[Succeeded / Failed / Skipped / Total] 106 / 12 / 33 / 151:  50%|██████████          | 151/300 [22:32<22:14,  8.96s/it]
[Succeeded / Failed / Skipped / Total] 106 / 12 / 33 / 151:  51%|██████████▏         | 152/300 [22:44<22:08,  8.98s/it]
[Succeeded / Failed / Skipped / Total] 107 / 12 / 33 / 152:  51%|██████████▏         | 152/300 [22:44<22:08,  8.98s/it]
[Succeeded / Failed / Skipped / Total] 107 / 12 / 33 / 152:  51%|██████████▏         | 153/300 [22:51<21:57,  8.97s/it]
[Succeeded / Failed / Skipped / Total] 108 / 12 / 33 / 153:  51%|██████████▏         | 153/300 [22:51<21:57,  8.97s/it]
[Succeeded / Failed / Skipped / Total] 108 / 12 / 33 / 153:  51%|██████████▎         | 154/300 [22:55<21:44,  8.93s/it]
[Succeeded / Failed / Skipped / Total] 109 / 12 / 33 / 154:  51%|██████████▎         | 154/300 [22:55<21:44,  8.93s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 137 / 16 / 47 / 200:  67%|█████████████▍      | 201/300 [31:42<15:37,  9.47s/it]
[Succeeded / Failed / Skipped / Total] 138 / 16 / 47 / 201:  67%|█████████████▍      | 201/300 [31:42<15:37,  9.47s/it]
[Succeeded / Failed / Skipped / Total] 138 / 16 / 47 / 201:  67%|█████████████▍      | 202/300 [31:51<15:27,  9.46s/it]
[Succeeded / Failed / Skipped / Total] 139 / 16 / 47 / 202:  67%|█████████████▍      | 202/300 [31:51<15:27,  9.46s/it]
[Succeeded / Failed / Skipped / Total] 139 / 16 / 47 / 202:  68%|█████████████▌      | 203/300 [32:07<15:20,  9.49s/it]
[Succeeded / Failed / Skipped / Total] 140 / 16 / 47 / 203:  68%|█████████████▌      | 203/300 [32:07<15:20,  9.49s/it]
[Succeeded / Failed / Skipped / Total] 140 / 16 / 47 / 203:  68%|█████████████▌      | 204/300 [32:30<15:17,  9.56s/it]
[Succeeded / Failed / Skipped / Total] 141 / 16 / 47 / 204:  68%|█████████████▌      | 204/300 [32:30<15:17,  9.56s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 176 / 20 / 54 / 250:  84%|████████████████▋   | 251/300 [42:00<08:12, 10.04s/it]
[Succeeded / Failed / Skipped / Total] 176 / 20 / 55 / 251:  84%|████████████████▋   | 251/300 [42:00<08:12, 10.04s/it]
[Succeeded / Failed / Skipped / Total] 176 / 20 / 55 / 251:  84%|████████████████▊   | 252/300 [42:06<08:01, 10.03s/it]
[Succeeded / Failed / Skipped / Total] 177 / 20 / 55 / 252:  84%|████████████████▊   | 252/300 [42:06<08:01, 10.03s/it]
[Succeeded / Failed / Skipped / Total] 177 / 20 / 55 / 252:  84%|████████████████▊   | 253/300 [42:12<07:50, 10.01s/it]
[Succeeded / Failed / Skipped / Total] 178 / 20 / 55 / 253:  84%|████████████████▊   | 253/300 [42:12<07:50, 10.01s/it]
[Succeeded / Failed / Skipped / Total] 178 / 20 / 55 / 253:  85%|████████████████▉   | 254/300 [42:18<07:39,  9.99s/it]
[Succeeded / Failed / Skipped / Total] 179 / 20 / 55 / 254:  85%|████████████████▉   | 254/300 [42:18<07:39,  9.99s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 218    |
| Number of failed attacks:     | 22     |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 80.0%  |
| Accuracy under attack:        | 7.33%  |
| Attack success rate:          | 90.83% |
| Average perturbed word %:     | 9.84%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 123.09 |
+-------------------------------+--------+

#### CLIP

In [70]:
runAttack(clip_lr1_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr1'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr1ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                               | 1/300 [00:24<2:01:38, 24.41s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|                          | 1/300 [00:24<2:01:43, 24.43s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   1%|▏                         | 2/300 [00:39<1:38:53, 19.91s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▏                         | 2/300 [00:39<1:38:55, 19.92s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▎                         | 3/300 [00:53<1:28:39, 17.91s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                         | 3/300 [00:53<1:28:42, 17.92s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                         | 4/300 [01:11<1:27:44, 17.79s/it]
[Succeeded / Failed / Skipped / Total] 0 / 4 / 0 / 4:   1%|▎                         | 4/300 [01:11<1:27:45, 17.79s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 26 / 20 / 4 / 50:  17%|████                    | 51/300 [08:53<43:23, 10.46s/it]
[Succeeded / Failed / Skipped / Total] 27 / 20 / 4 / 51:  17%|████                    | 51/300 [08:53<43:23, 10.46s/it]
[Succeeded / Failed / Skipped / Total] 27 / 20 / 4 / 51:  17%|████▏                   | 52/300 [09:07<43:28, 10.52s/it]
[Succeeded / Failed / Skipped / Total] 28 / 20 / 4 / 52:  17%|████▏                   | 52/300 [09:07<43:29, 10.52s/it]
[Succeeded / Failed / Skipped / Total] 28 / 20 / 4 / 52:  18%|████▏                   | 53/300 [09:19<43:27, 10.56s/it]
[Succeeded / Failed / Skipped / Total] 28 / 21 / 4 / 53:  18%|████▏                   | 53/300 [09:19<43:28, 10.56s/it]
[Succeeded / Failed / Skipped / Total] 28 / 21 / 4 / 53:  18%|████▎                   | 54/300 [09:26<43:01, 10.49s/it]
[Succeeded / Failed / Skipped / Total] 29 / 21 / 4 / 54:  18%|████▎                   | 54/300 [09:26<43:01, 10.50s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 63 / 28 / 9 / 100:  34%|███████▍              | 101/300 [16:10<31:52,  9.61s/it]
[Succeeded / Failed / Skipped / Total] 64 / 28 / 9 / 101:  34%|███████▍              | 101/300 [16:10<31:52,  9.61s/it]
[Succeeded / Failed / Skipped / Total] 65 / 28 / 9 / 102:  34%|███████▍              | 102/300 [16:17<31:37,  9.58s/it]
[Succeeded / Failed / Skipped / Total] 65 / 28 / 9 / 102:  34%|███████▍              | 102/300 [16:22<31:47,  9.64s/it]
[Succeeded / Failed / Skipped / Total] 65 / 28 / 9 / 102:  34%|███████▌              | 103/300 [16:23<31:20,  9.54s/it]
[Succeeded / Failed / Skipped / Total] 66 / 28 / 9 / 103:  34%|███████▌              | 103/300 [16:23<31:20,  9.54s/it]
[Succeeded / Failed / Skipped / Total] 66 / 28 / 9 / 103:  35%|███████▋              | 104/300 [16:34<31:14,  9.56s/it]
[Succeeded / Failed / Skipped / Total] 67 / 28 / 9 / 104:  35%|███████▋              | 104/300 [16:34<31:14,  9.56s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 97 / 39 / 14 / 150:  50%|██████████▌          | 151/300 [23:56<23:37,  9.51s/it]
[Succeeded / Failed / Skipped / Total] 98 / 39 / 14 / 151:  50%|██████████▌          | 151/300 [23:56<23:37,  9.51s/it]
[Succeeded / Failed / Skipped / Total] 98 / 39 / 14 / 151:  51%|██████████▋          | 152/300 [24:11<23:33,  9.55s/it]
[Succeeded / Failed / Skipped / Total] 99 / 39 / 14 / 152:  51%|██████████▋          | 152/300 [24:11<23:33,  9.55s/it]
[Succeeded / Failed / Skipped / Total] 99 / 39 / 14 / 152:  51%|██████████▋          | 153/300 [24:22<23:24,  9.56s/it]
[Succeeded / Failed / Skipped / Total] 100 / 39 / 14 / 153:  51%|██████████▏         | 153/300 [24:22<23:24,  9.56s/it]
[Succeeded / Failed / Skipped / Total] 100 / 39 / 15 / 154:  51%|██████████▎         | 154/300 [24:22<23:06,  9.49s/it]
[Succeeded / Failed / Skipped / Total] 100 / 39 / 15 / 154:  52%|██████████▎         | 155/300 [24:31<22:56,  9.49s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 136 / 44 / 20 / 200:  67%|█████████████▍      | 201/300 [31:24<15:28,  9.38s/it]
[Succeeded / Failed / Skipped / Total] 136 / 45 / 20 / 201:  67%|█████████████▍      | 201/300 [31:24<15:28,  9.38s/it]
[Succeeded / Failed / Skipped / Total] 136 / 45 / 20 / 201:  67%|█████████████▍      | 202/300 [31:33<15:18,  9.37s/it]
[Succeeded / Failed / Skipped / Total] 136 / 46 / 20 / 202:  67%|█████████████▍      | 202/300 [31:33<15:18,  9.37s/it]
[Succeeded / Failed / Skipped / Total] 136 / 46 / 20 / 202:  68%|█████████████▌      | 203/300 [31:53<15:14,  9.43s/it]
[Succeeded / Failed / Skipped / Total] 137 / 46 / 20 / 203:  68%|█████████████▌      | 203/300 [31:53<15:14,  9.43s/it]
[Succeeded / Failed / Skipped / Total] 137 / 46 / 20 / 203:  68%|█████████████▌      | 204/300 [31:54<15:00,  9.38s/it]
[Succeeded / Failed / Skipped / Total] 137 / 46 / 21 / 204:  68%|█████████████▌      | 204/300 [31:54<15:00,  9.38s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 171 / 55 / 24 / 250:  84%|████████████████▋   | 251/300 [39:26<07:42,  9.43s/it]
[Succeeded / Failed / Skipped / Total] 172 / 55 / 24 / 251:  84%|████████████████▋   | 251/300 [39:26<07:42,  9.43s/it]
[Succeeded / Failed / Skipped / Total] 172 / 55 / 24 / 251:  84%|████████████████▊   | 252/300 [39:41<07:33,  9.45s/it]
[Succeeded / Failed / Skipped / Total] 172 / 56 / 24 / 252:  84%|████████████████▊   | 252/300 [39:41<07:33,  9.45s/it]
[Succeeded / Failed / Skipped / Total] 172 / 56 / 24 / 252:  84%|████████████████▊   | 253/300 [39:51<07:24,  9.45s/it]
[Succeeded / Failed / Skipped / Total] 173 / 56 / 24 / 253:  84%|████████████████▊   | 253/300 [39:51<07:24,  9.45s/it]
[Succeeded / Failed / Skipped / Total] 173 / 56 / 24 / 253:  85%|████████████████▉   | 254/300 [39:53<07:13,  9.42s/it]
[Succeeded / Failed / Skipped / Total] 174 / 56 / 24 / 254:  85%|████████████████▉   | 254/300 [39:53<07:13,  9.42s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 202    |
| Number of failed attacks:     | 69     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 23.0%  |
| Attack success rate:          | 74.54% |
| Average perturbed word %:     | 22.6%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 195.53 |
+-------------------------------+--------+


In [72]:
runAttack(clip_lr01_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr01'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr01ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column


  0%|▎                                                                               | 1/300 [00:32<2:43:06, 32.73s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   0%|                          | 1/300 [00:32<2:43:14, 32.76s/it]
[Succeeded / Failed / Skipped / Total] 0 / 1 / 0 / 1:   1%|▏                         | 2/300 [00:44<1:50:42, 22.29s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▏                         | 2/300 [00:44<1:50:46, 22.30s/it]
[Succeeded / Failed / Skipped / Total] 0 / 2 / 0 / 2:   1%|▎                         | 3/300 [00:56<1:33:34, 18.90s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                         | 3/300 [00:56<1:33:37, 18.91s/it]
[Succeeded / Failed / Skipped / Total] 0 / 3 / 0 / 3:   1%|▎                         | 4/300 [01:11<1:28:15, 17.89s/it]
[Succeeded / Failed / Skipped / Total] 0 / 4 / 0 / 4:   1%|▎                         | 4/300 [01:11<1:28:16, 17.90s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 26 / 20 / 4 / 50:  17%|████                    | 51/300 [08:50<43:09, 10.40s/it]
[Succeeded / Failed / Skipped / Total] 27 / 20 / 4 / 51:  17%|████                    | 51/300 [08:50<43:09, 10.40s/it]
[Succeeded / Failed / Skipped / Total] 27 / 20 / 4 / 51:  17%|████▏                   | 52/300 [09:04<43:16, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 28 / 20 / 4 / 52:  17%|████▏                   | 52/300 [09:04<43:16, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 28 / 20 / 4 / 52:  18%|████▏                   | 53/300 [09:18<43:20, 10.53s/it]
[Succeeded / Failed / Skipped / Total] 28 / 21 / 4 / 53:  18%|████▏                   | 53/300 [09:18<43:21, 10.53s/it]
[Succeeded / Failed / Skipped / Total] 28 / 21 / 4 / 53:  18%|████▎                   | 54/300 [09:25<42:55, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 29 / 21 / 4 / 54:  18%|████▎                   | 54/300 [09:25<42:55, 10.47s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 63 / 28 / 9 / 100:  34%|███████▍              | 101/300 [16:15<32:02,  9.66s/it]
[Succeeded / Failed / Skipped / Total] 64 / 28 / 9 / 101:  34%|███████▍              | 101/300 [16:15<32:02,  9.66s/it]
[Succeeded / Failed / Skipped / Total] 64 / 28 / 9 / 101:  34%|███████▍              | 102/300 [16:23<31:48,  9.64s/it]
[Succeeded / Failed / Skipped / Total] 65 / 28 / 9 / 102:  34%|███████▍              | 102/300 [16:23<31:48,  9.64s/it]
[Succeeded / Failed / Skipped / Total] 65 / 28 / 9 / 102:  34%|███████▌              | 103/300 [16:29<31:31,  9.60s/it]
[Succeeded / Failed / Skipped / Total] 66 / 28 / 9 / 103:  34%|███████▌              | 103/300 [16:29<31:31,  9.60s/it]
[Succeeded / Failed / Skipped / Total] 66 / 28 / 9 / 103:  35%|███████▋              | 104/300 [16:41<31:28,  9.63s/it]
[Succeeded / Failed / Skipped / Total] 66 / 29 / 9 / 104:  35%|███████▋              | 104/300 [16:41<31:28,  9.63s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 95 / 41 / 14 / 150:  50%|██████████▌          | 151/300 [23:56<23:37,  9.51s/it]
[Succeeded / Failed / Skipped / Total] 96 / 41 / 14 / 151:  50%|██████████▌          | 151/300 [23:56<23:37,  9.51s/it]
[Succeeded / Failed / Skipped / Total] 96 / 41 / 14 / 151:  51%|██████████▋          | 152/300 [24:09<23:31,  9.54s/it]
[Succeeded / Failed / Skipped / Total] 97 / 41 / 14 / 152:  51%|██████████▋          | 152/300 [24:09<23:31,  9.54s/it]
[Succeeded / Failed / Skipped / Total] 97 / 41 / 14 / 152:  51%|██████████▋          | 153/300 [24:20<23:22,  9.54s/it]
[Succeeded / Failed / Skipped / Total] 98 / 41 / 14 / 153:  51%|██████████▋          | 153/300 [24:20<23:22,  9.54s/it]
[Succeeded / Failed / Skipped / Total] 98 / 41 / 14 / 153:  51%|██████████▊          | 154/300 [24:20<23:04,  9.48s/it]
[Succeeded / Failed / Skipped / Total] 98 / 41 / 15 / 154:  51%|██████████▊          | 154/300 [24:20<23:04,  9.48s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 133 / 47 / 20 / 200:  67%|█████████████▍      | 201/300 [31:24<15:28,  9.37s/it]
[Succeeded / Failed / Skipped / Total] 133 / 48 / 20 / 201:  67%|█████████████▍      | 201/300 [31:24<15:28,  9.37s/it]
[Succeeded / Failed / Skipped / Total] 133 / 48 / 20 / 201:  67%|█████████████▍      | 202/300 [31:32<15:18,  9.37s/it]
[Succeeded / Failed / Skipped / Total] 133 / 49 / 20 / 202:  67%|█████████████▍      | 202/300 [31:33<15:18,  9.37s/it]
[Succeeded / Failed / Skipped / Total] 133 / 49 / 20 / 202:  68%|█████████████▌      | 203/300 [31:50<15:13,  9.41s/it]
[Succeeded / Failed / Skipped / Total] 134 / 49 / 20 / 203:  68%|█████████████▌      | 203/300 [31:50<15:13,  9.41s/it]
[Succeeded / Failed / Skipped / Total] 134 / 49 / 21 / 204:  68%|█████████████▌      | 204/300 [31:50<14:59,  9.37s/it]
[Succeeded / Failed / Skipped / Total] 134 / 49 / 21 / 204:  68%|█████████████▋      | 205/300 [32:04<14:52,  9.39s/it]
[Succeeded / Failed / Skipped / Total] 


[Succeeded / Failed / Skipped / Total] 169 / 58 / 24 / 251:  84%|████████████████▋   | 251/300 [39:33<07:43,  9.46s/it]
[Succeeded / Failed / Skipped / Total] 169 / 58 / 24 / 251:  84%|████████████████▋   | 251/300 [39:43<07:45,  9.49s/it]
[Succeeded / Failed / Skipped / Total] 169 / 58 / 24 / 251:  84%|████████████████▊   | 252/300 [39:47<07:34,  9.47s/it]
[Succeeded / Failed / Skipped / Total] 169 / 59 / 24 / 252:  84%|████████████████▊   | 252/300 [39:47<07:34,  9.47s/it]
[Succeeded / Failed / Skipped / Total] 169 / 59 / 24 / 252:  84%|████████████████▊   | 253/300 [39:57<07:25,  9.48s/it]
[Succeeded / Failed / Skipped / Total] 170 / 59 / 24 / 253:  84%|████████████████▊   | 253/300 [39:57<07:25,  9.48s/it]
[Succeeded / Failed / Skipped / Total] 170 / 59 / 24 / 253:  85%|████████████████▉   | 254/300 [39:59<07:14,  9.45s/it]
[Succeeded / Failed / Skipped / Total] 171 / 59 / 24 / 254:  85%|████████████████▉   | 254/300 [39:59<07:14,  9.45s/it]
[Succeeded / Failed / Skipped / Total] 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 198    |
| Number of failed attacks:     | 73     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 24.33% |
| Attack success rate:          | 73.06% |
| Average perturbed word %:     | 22.23% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 197.08 |
+-------------------------------+--------+


In [73]:
runAttack(clip_lr10_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr10'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr10ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column

[Succeeded / Failed / Skipped / Total] 26 / 20 / 4 / 50:  17%|████                    | 50/300 [07:48<39:02,  9.37s/it]textattack: Saving checkpoint under "checkpoints\1722185521126.ta.chkpt" at 2024-07-29 00:52:01 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 62 / 29 / 9 / 100:  33%|███████▎              | 100/300 [15:29<30:59,  9.30s/it]textattack: Saving checkpoint under "checkpoints\1722185982544.ta.chkpt" at 2024-07-29 00:59:42 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 96 / 40 / 14 / 150:  50%|██████████▌          | 150/300 [22:50<22:50,  9.14s/it]textattack: Saving checkpoint under "checkpoints\1722186423314.ta.chkpt" at 2024-07-29 01:07:03 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 135 / 45 / 20 / 200:  67%|█████████████▎      | 200/300 [30:06<15:03,  9.03s/it]textattack: Saving checkpoint under "checkpoints\1722186859162.ta.chkpt" at 2024-07-29 01:14:19 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 170 / 56 / 24 / 250:  83%|████████████████▋   | 250/300 [38:19<07:39,  9.20s/it]textattack: Saving checkpoint under "checkpoints\1722187351914.ta.chkpt" at 2024-07-29 01:22:31 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 201 / 70 / 29 / 300: 100%|████████████████████| 300/300 [46:33<00:00,  9.31s/it]textattack: Saving checkpoint under "checkpoints\1722187845925.ta.chkpt" at 2024-07-29 01:30:45 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 201 / 70 / 29 / 300: 100%|████████████████████| 300/300 [46:33<00:00,  9.31s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 201    |
| Number of failed attacks:     | 70     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 23.33% |
| Attack success rate:          | 74.17% |
| Average perturbed word %:     | 22.4%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 195.89 |
+-------------------------------+--------+


In [74]:
runAttack(clip_rf7_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf7ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column

[Succeeded / Failed / Skipped / Total] 24 / 23 / 3 / 50:  17%|████                    | 50/300 [08:08<40:41,  9.76s/it]textattack: Saving checkpoint under "checkpoints\1722188334333.ta.chkpt" at 2024-07-29 01:38:54 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 47 / 42 / 11 / 100:  33%|███████              | 100/300 [16:59<33:58, 10.19s/it]textattack: Saving checkpoint under "checkpoints\1722188865491.ta.chkpt" at 2024-07-29 01:47:45 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 71 / 63 / 16 / 150:  50%|██████████▌          | 150/300 [26:08<26:08, 10.46s/it]textattack: Saving checkpoint under "checkpoints\1722189415105.ta.chkpt" at 2024-07-29 01:56:55 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 89 / 80 / 31 / 200:  67%|██████████████       | 200/300 [32:55<16:27,  9.88s/it]textattack: Saving checkpoint under "checkpoints\1722189821632.ta.chkpt" at 2024-07-29 02:03:41 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 111 / 101 / 38 / 250:  83%|███████████████▊   | 250/300 [41:52<08:22, 10.05s/it]textattack: Saving checkpoint under "checkpoints\1722190358461.ta.chkpt" at 2024-07-29 02:12:38 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 131 / 126 / 43 / 300: 100%|███████████████████| 300/300 [51:36<00:00, 10.32s/it]textattack: Saving checkpoint under "checkpoints\1722190942371.ta.chkpt" at 2024-07-29 02:22:22 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 131 / 126 / 43 / 300: 100%|███████████████████| 300/300 [51:36<00:00, 10.32s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 131    |
| Number of failed attacks:     | 126    |
| Number of skipped attacks:    | 43     |
| Original accuracy:            | 85.67% |
| Accuracy under attack:        | 42.0%  |
| Attack success rate:          | 50.97% |
| Average perturbed word %:     | 16.67% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 227.47 |
+-------------------------------+--------+


In [75]:
runAttack(clip_rf14_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf14'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf14ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column

[Succeeded / Failed / Skipped / Total] 13 / 35 / 2 / 50:  17%|████                    | 50/300 [09:46<48:54, 11.74s/it]textattack: Saving checkpoint under "checkpoints\1722191529464.ta.chkpt" at 2024-07-29 02:32:09 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 30 / 63 / 7 / 100:  33%|███████▎              | 100/300 [20:04<40:08, 12.04s/it]textattack: Saving checkpoint under "checkpoints\1722192146955.ta.chkpt" at 2024-07-29 02:42:26 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 44 / 93 / 13 / 150:  50%|██████████▌          | 150/300 [30:33<30:33, 12.22s/it]textattack: Saving checkpoint under "checkpoints\1722192775536.ta.chkpt" at 2024-07-29 02:52:55 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 67 / 110 / 23 / 200:  67%|█████████████▎      | 200/300 [37:59<18:59, 11.40s/it]textattack: Saving checkpoint under "checkpoints\1722193222396.ta.chkpt" at 2024-07-29 03:00:22 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 88 / 134 / 28 / 250:  83%|████████████████▋   | 250/300 [47:32<09:30, 11.41s/it]textattack: Saving checkpoint under "checkpoints\1722193794875.ta.chkpt" at 2024-07-29 03:09:54 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 99 / 168 / 33 / 300: 100%|████████████████████| 300/300 [58:20<00:00, 11.67s/it]textattack: Saving checkpoint under "checkpoints\1722194442943.ta.chkpt" at 2024-07-29 03:20:42 after 300 attacks.


[Succeeded / Failed / Skipped / Total] 99 / 168 / 33 / 300: 100%|████████████████████| 300/300 [58:21<00:00, 11.67s/it]


+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 99     |
| Number of failed attacks:     | 168    |
| Number of skipped attacks:    | 33     |
| Original accuracy:            | 89.0%  |
| Accuracy under attack:        | 56.0%  |
| Attack success rate:          | 37.08% |
| Average perturbed word %:     | 14.95% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 244.35 |
+-------------------------------+--------+


In [76]:
runAttack(clip_rf30_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf30'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf30ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column

[Succeeded / Failed / Skipped / Total] 15 / 33 / 2 / 50:  17%|████                    | 50/300 [11:03<55:18, 13.27s/it]textattack: Saving checkpoint under "checkpoints\1722195107551.ta.chkpt" at 2024-07-29 03:31:47 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 36 / 56 / 8 / 100:  33%|███████▎              | 100/300 [20:08<40:17, 12.09s/it]textattack: Saving checkpoint under "checkpoints\1722195652461.ta.chkpt" at 2024-07-29 03:40:52 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 56 / 82 / 12 / 150:  50%|██████████▌          | 150/300 [30:06<30:06, 12.04s/it]textattack: Saving checkpoint under "checkpoints\1722196250018.ta.chkpt" at 2024-07-29 03:50:50 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 77 / 102 / 21 / 200:  67%|█████████████▎      | 200/300 [38:06<19:03, 11.43s/it]textattack: Saving checkpoint under "checkpoints\1722196730077.ta.chkpt" at 2024-07-29 03:58:50 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 95 / 129 / 26 / 250:  83%|████████████████▋   | 250/300 [47:53<09:34, 11.49s/it]textattack: Saving checkpoint under "checkpoints\1722197317285.ta.chkpt" at 2024-07-29 04:08:37 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 110 / 160 / 30 / 300: 100%|███████████████████| 300/300 [58:41<00:00, 11.74s/it]textattack: Saving checkpoint under "checkpoints\1722197965389.ta.chkpt" at 2024-07-29 04:19:25 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 110 / 160 / 30 / 300: 100%|███████████████████| 300/300 [58:41<00:00, 11.74s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 110    |
| Number of failed attacks:     | 160    |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 53.33% |
| Attack success rate:          | 40.74% |
| Average perturbed word %:     | 14.87% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 241.69 |
+-------------------------------+--------+


In [77]:
runAttack(clip_knn7_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn7ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column

[Succeeded / Failed / Skipped / Total] 2 / 47 / 1 / 50:  17%|███▊                   | 50/300 [49:09<4:05:47, 58.99s/it]textattack: Saving checkpoint under "checkpoints\1722200915430.ta.chkpt" at 2024-07-29 05:08:35 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 10 / 86 / 4 / 100:  33%|██████            | 100/300 [1:04:21<2:08:42, 38.61s/it]textattack: Saving checkpoint under "checkpoints\1722201827150.ta.chkpt" at 2024-07-29 05:23:47 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 14 / 129 / 7 / 150:  50%|████████▌        | 150/300 [1:18:59<1:18:59, 31.60s/it]textattack: Saving checkpoint under "checkpoints\1722202705516.ta.chkpt" at 2024-07-29 05:38:25 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 21 / 165 / 14 / 200:  67%|████████████      | 200/300 [1:32:30<46:15, 27.75s/it]textattack: Saving checkpoint under "checkpoints\1722203516030.ta.chkpt" at 2024-07-29 05:51:56 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 29 / 204 / 17 / 250:  83%|███████████████   | 250/300 [1:48:05<21:37, 25.94s/it]textattack: Saving checkpoint under "checkpoints\1722204451177.ta.chkpt" at 2024-07-29 06:07:31 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 35 / 243 / 22 / 300: 100%|██████████████████| 300/300 [2:02:20<00:00, 24.47s/it]textattack: Saving checkpoint under "checkpoints\1722205306053.ta.chkpt" at 2024-07-29 06:21:46 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 35 / 243 / 22 / 300: 100%|██████████████████| 300/300 [2:02:20<00:00, 24.47s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 35     |
| Number of failed attacks:     | 243    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 81.0%  |
| Attack success rate:          | 12.59% |
| Average perturbed word %:     | 5.3%   |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 304.76 |
+-------------------------------+--------+


In [78]:
runAttack(clip_knn35_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn35'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn35ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column

[Succeeded / Failed / Skipped / Total] 7 / 43 / 0 / 50:  17%|███▊                   | 50/300 [13:04<1:05:20, 15.68s/it]textattack: Saving checkpoint under "checkpoints\1722206090282.ta.chkpt" at 2024-07-29 06:34:50 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 13 / 84 / 3 / 100:  33%|███████▎              | 100/300 [28:15<56:31, 16.96s/it]textattack: Saving checkpoint under "checkpoints\1722207001918.ta.chkpt" at 2024-07-29 06:50:01 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 26 / 118 / 6 / 150:  50%|██████████▌          | 150/300 [41:33<41:33, 16.62s/it]textattack: Saving checkpoint under "checkpoints\1722207799435.ta.chkpt" at 2024-07-29 07:03:19 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 37 / 150 / 13 / 200:  67%|█████████████▎      | 200/300 [54:04<27:02, 16.22s/it]textattack: Saving checkpoint under "checkpoints\1722208550429.ta.chkpt" at 2024-07-29 07:15:50 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 46 / 188 / 16 / 250:  83%|███████████████   | 250/300 [1:09:25<13:53, 16.66s/it]textattack: Saving checkpoint under "checkpoints\1722209471258.ta.chkpt" at 2024-07-29 07:31:11 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 50 / 228 / 22 / 300: 100%|██████████████████| 300/300 [1:23:16<00:00, 16.65s/it]textattack: Saving checkpoint under "checkpoints\1722210302646.ta.chkpt" at 2024-07-29 07:45:02 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 50 / 228 / 22 / 300: 100%|██████████████████| 300/300 [1:23:16<00:00, 16.65s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 50     |
| Number of failed attacks:     | 228    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 76.0%  |
| Attack success rate:          | 17.99% |
| Average perturbed word %:     | 10.28% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 290.03 |
+-------------------------------+--------+


In [79]:
runAttack(clip_knn175_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn175'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn175ep09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.9
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (column

[Succeeded / Failed / Skipped / Total] 10 / 39 / 1 / 50:  17%|███▋                  | 50/300 [12:26<1:02:12, 14.93s/it]textattack: Saving checkpoint under "checkpoints\1722211049365.ta.chkpt" at 2024-07-29 07:57:29 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 30 / 65 / 5 / 100:  33%|███████▎              | 100/300 [25:30<51:01, 15.31s/it]textattack: Saving checkpoint under "checkpoints\1722211833674.ta.chkpt" at 2024-07-29 08:10:33 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 48 / 93 / 9 / 150:  50%|███████████           | 150/300 [37:39<37:39, 15.07s/it]textattack: Saving checkpoint under "checkpoints\1722212562731.ta.chkpt" at 2024-07-29 08:22:42 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 58 / 121 / 21 / 200:  67%|█████████████▎      | 200/300 [48:46<24:23, 14.63s/it]textattack: Saving checkpoint under "checkpoints\1722213229340.ta.chkpt" at 2024-07-29 08:33:49 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 72 / 150 / 28 / 250:  83%|███████████████   | 250/300 [1:02:10<12:26, 14.92s/it]textattack: Saving checkpoint under "checkpoints\1722214033751.ta.chkpt" at 2024-07-29 08:47:13 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 84 / 182 / 34 / 300: 100%|██████████████████| 300/300 [1:15:16<00:00, 15.05s/it]textattack: Saving checkpoint under "checkpoints\1722214818868.ta.chkpt" at 2024-07-29 09:00:18 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 84 / 182 / 34 / 300: 100%|██████████████████| 300/300 [1:15:16<00:00, 15.05s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 84     |
| Number of failed attacks:     | 182    |
| Number of skipped attacks:    | 34     |
| Original accuracy:            | 88.67% |
| Accuracy under attack:        | 60.67% |
| Attack success rate:          | 31.58% |
| Average perturbed word %:     | 21.12% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 273.47 |
+-------------------------------+--------+


In [80]:
et3 = datetime.datetime.now()
et3 - et2

datetime.timedelta(seconds=71563, microseconds=607867)

### Threshold = 0.95

In [81]:
suffix = 'ep095.csv'
thre = 0.95

#### BERT

In [82]:
runAttack(bert_lr1_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr1'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr1ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 0 / 45 / 5 / 50:  17%|████▏                    | 50/300 [04:31<22:36,  5.42s/it]textattack: Saving checkpoint under "checkpoints\1722215090438.ta.chkpt" at 2024-07-29 09:04:50 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 87 / 10 / 100:  33%|███████▎              | 100/300 [09:06<18:13,  5.47s/it]textattack: Saving checkpoint under "checkpoints\1722215365723.ta.chkpt" at 2024-07-29 09:09:25 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 6 / 129 / 15 / 150:  50%|██████████▌          | 150/300 [13:43<13:43,  5.49s/it]textattack: Saving checkpoint under "checkpoints\1722215642832.ta.chkpt" at 2024-07-29 09:14:02 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 7 / 172 / 21 / 200:  67%|██████████████       | 200/300 [18:36<09:18,  5.58s/it]textattack: Saving checkpoint under "checkpoints\1722215935985.ta.chkpt" at 2024-07-29 09:18:55 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 9 / 216 / 25 / 250:  83%|█████████████████▌   | 250/300 [23:26<04:41,  5.62s/it]textattack: Saving checkpoint under "checkpoints\1722216225350.ta.chkpt" at 2024-07-29 09:23:45 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 11 / 259 / 30 / 300: 100%|████████████████████| 300/300 [28:09<00:00,  5.63s/it]textattack: Saving checkpoint under "checkpoints\1722216509146.ta.chkpt" at 2024-07-29 09:28:29 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 11 / 259 / 30 / 300: 100%|████████████████████| 300/300 [28:09<00:00,  5.63s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 11     |
| Number of failed attacks:     | 259    |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 86.33% |
| Attack success rate:          | 4.07%  |
| Average perturbed word %:     | 7.07%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.54  |
+-------------------------------+--------+


In [83]:
runAttack(bert_lr01_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr01'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr01ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 0 / 45 / 5 / 50:  17%|████▏                    | 50/300 [04:06<20:32,  4.93s/it]textattack: Saving checkpoint under "checkpoints\1722216755787.ta.chkpt" at 2024-07-29 09:32:35 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 2 / 87 / 11 / 100:  33%|███████▎              | 100/300 [08:26<16:52,  5.06s/it]textattack: Saving checkpoint under "checkpoints\1722217015772.ta.chkpt" at 2024-07-29 09:36:55 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 5 / 129 / 16 / 150:  50%|██████████▌          | 150/300 [12:56<12:56,  5.17s/it]textattack: Saving checkpoint under "checkpoints\1722217285442.ta.chkpt" at 2024-07-29 09:41:25 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 5 / 172 / 23 / 200:  67%|██████████████       | 200/300 [17:34<08:47,  5.27s/it]textattack: Saving checkpoint under "checkpoints\1722217563422.ta.chkpt" at 2024-07-29 09:46:03 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 6 / 217 / 27 / 250:  83%|█████████████████▌   | 250/300 [22:20<04:28,  5.36s/it]textattack: Saving checkpoint under "checkpoints\1722217850185.ta.chkpt" at 2024-07-29 09:50:50 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 6 / 262 / 32 / 300: 100%|█████████████████████| 300/300 [27:01<00:00,  5.41s/it]textattack: Saving checkpoint under "checkpoints\1722218130819.ta.chkpt" at 2024-07-29 09:55:30 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 6 / 262 / 32 / 300: 100%|█████████████████████| 300/300 [27:01<00:00,  5.41s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 6      |
| Number of failed attacks:     | 262    |
| Number of skipped attacks:    | 32     |
| Original accuracy:            | 89.33% |
| Accuracy under attack:        | 87.33% |
| Attack success rate:          | 2.24%  |
| Average perturbed word %:     | 5.27%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.54  |
+-------------------------------+--------+


In [84]:
runAttack(bert_lr10_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr10'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr10ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 1 / 44 / 5 / 50:  17%|████▏                    | 50/300 [04:01<20:09,  4.84s/it]textattack: Saving checkpoint under "checkpoints\1722218372725.ta.chkpt" at 2024-07-29 09:59:32 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 2 / 87 / 11 / 100:  33%|███████▎              | 100/300 [08:24<16:49,  5.05s/it]textattack: Saving checkpoint under "checkpoints\1722218635469.ta.chkpt" at 2024-07-29 10:03:55 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 5 / 129 / 16 / 150:  50%|██████████▌          | 150/300 [12:48<12:48,  5.13s/it]textattack: Saving checkpoint under "checkpoints\1722218899898.ta.chkpt" at 2024-07-29 10:08:19 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 6 / 172 / 22 / 200:  67%|██████████████       | 200/300 [17:29<08:44,  5.25s/it]textattack: Saving checkpoint under "checkpoints\1722219179942.ta.chkpt" at 2024-07-29 10:12:59 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 8 / 216 / 26 / 250:  83%|█████████████████▌   | 250/300 [22:15<04:27,  5.34s/it]textattack: Saving checkpoint under "checkpoints\1722219466378.ta.chkpt" at 2024-07-29 10:17:46 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 10 / 259 / 31 / 300: 100%|████████████████████| 300/300 [26:55<00:00,  5.38s/it]textattack: Saving checkpoint under "checkpoints\1722219746197.ta.chkpt" at 2024-07-29 10:22:26 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 10 / 259 / 31 / 300: 100%|████████████████████| 300/300 [26:55<00:00,  5.38s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 10     |
| Number of failed attacks:     | 259    |
| Number of skipped attacks:    | 31     |
| Original accuracy:            | 89.67% |
| Accuracy under attack:        | 86.33% |
| Attack success rate:          | 3.72%  |
| Average perturbed word %:     | 6.48%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.43  |
+-------------------------------+--------+


In [85]:
runAttack(bert_rf7_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf7ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 11 / 26 / 13 / 50:  17%|███▊                   | 50/300 [02:55<14:36,  3.51s/it]textattack: Saving checkpoint under "checkpoints\1722219922094.ta.chkpt" at 2024-07-29 10:25:22 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 16 / 55 / 29 / 100:  33%|███████              | 100/300 [06:04<12:08,  3.64s/it]textattack: Saving checkpoint under "checkpoints\1722220110839.ta.chkpt" at 2024-07-29 10:28:30 after 100 attacks.
[Succeeded / Failed / Skipped / Total] 16 / 55 / 30 / 101:  34%|███████              | 101/300 [06:04<11:57,  3.61s/it]

[Succeeded / Failed / Skipped / Total] 22 / 88 / 40 / 150:  50%|██████████▌          | 150/300 [09:53<09:53,  3.95s/it]textattack: Saving checkpoint under "checkpoints\1722220339832.ta.chkpt" at 2024-07-29 10:32:19 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 27 / 117 / 56 / 200:  67%|█████████████▎      | 200/300 [13:40<06:50,  4.10s/it]textattack: Saving checkpoint under "checkpoints\1722220567084.ta.chkpt" at 2024-07-29 10:36:07 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 34 / 153 / 63 / 250:  83%|████████████████▋   | 250/300 [17:51<03:34,  4.29s/it]textattack: Saving checkpoint under "checkpoints\1722220818162.ta.chkpt" at 2024-07-29 10:40:18 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 40 / 186 / 74 / 300: 100%|████████████████████| 300/300 [21:51<00:00,  4.37s/it]textattack: Saving checkpoint under "checkpoints\1722221058256.ta.chkpt" at 2024-07-29 10:44:18 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 40 / 186 / 74 / 300: 100%|████████████████████| 300/300 [21:51<00:00,  4.37s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 40     |
| Number of failed attacks:     | 186    |
| Number of skipped attacks:    | 74     |
| Original accuracy:            | 75.33% |
| Accuracy under attack:        | 62.0%  |
| Attack success rate:          | 17.7%  |
| Average perturbed word %:     | 4.74%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 36.94  |
+-------------------------------+--------+


In [86]:
runAttack(bert_rf14_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf14'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf14ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 6 / 35 / 9 / 50:  17%|████▏                    | 50/300 [04:20<21:40,  5.20s/it]textattack: Saving checkpoint under "checkpoints\1722221318443.ta.chkpt" at 2024-07-29 10:48:38 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 10 / 71 / 19 / 100:  33%|███████              | 100/300 [08:07<16:14,  4.87s/it]textattack: Saving checkpoint under "checkpoints\1722221545803.ta.chkpt" at 2024-07-29 10:52:25 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 18 / 105 / 27 / 150:  50%|██████████          | 150/300 [12:02<12:02,  4.82s/it]textattack: Saving checkpoint under "checkpoints\1722221781242.ta.chkpt" at 2024-07-29 10:56:21 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 21 / 136 / 43 / 200:  67%|█████████████▎      | 200/300 [15:53<07:56,  4.77s/it]textattack: Saving checkpoint under "checkpoints\1722222012305.ta.chkpt" at 2024-07-29 11:00:12 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 27 / 174 / 49 / 250:  83%|████████████████▋   | 250/300 [20:16<04:03,  4.87s/it]textattack: Saving checkpoint under "checkpoints\1722222274846.ta.chkpt" at 2024-07-29 11:04:34 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 30 / 213 / 57 / 300: 100%|████████████████████| 300/300 [24:39<00:00,  4.93s/it]textattack: Saving checkpoint under "checkpoints\1722222538310.ta.chkpt" at 2024-07-29 11:08:58 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 30 / 213 / 57 / 300: 100%|████████████████████| 300/300 [24:39<00:00,  4.93s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 30     |
| Number of failed attacks:     | 213    |
| Number of skipped attacks:    | 57     |
| Original accuracy:            | 81.0%  |
| Accuracy under attack:        | 71.0%  |
| Attack success rate:          | 12.35% |
| Average perturbed word %:     | 5.26%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.54  |
+-------------------------------+--------+


In [87]:
runAttack(bert_rf30_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf30'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf30ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 4 / 40 / 6 / 50:  17%|████▏                    | 50/300 [04:35<22:58,  5.51s/it]textattack: Saving checkpoint under "checkpoints\1722222814096.ta.chkpt" at 2024-07-29 11:13:34 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 10 / 71 / 19 / 100:  33%|███████              | 100/300 [08:14<16:29,  4.95s/it]textattack: Saving checkpoint under "checkpoints\1722223033084.ta.chkpt" at 2024-07-29 11:17:13 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 18 / 106 / 26 / 150:  50%|██████████          | 150/300 [12:20<12:20,  4.94s/it]textattack: Saving checkpoint under "checkpoints\1722223278817.ta.chkpt" at 2024-07-29 11:21:18 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 23 / 138 / 39 / 200:  67%|█████████████▎      | 200/300 [16:23<08:11,  4.92s/it]textattack: Saving checkpoint under "checkpoints\1722223521896.ta.chkpt" at 2024-07-29 11:25:21 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 26 / 178 / 46 / 250:  83%|████████████████▋   | 250/300 [20:52<04:10,  5.01s/it]textattack: Saving checkpoint under "checkpoints\1722223790987.ta.chkpt" at 2024-07-29 11:29:50 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 29 / 218 / 53 / 300: 100%|████████████████████| 300/300 [25:25<00:00,  5.08s/it]textattack: Saving checkpoint under "checkpoints\1722224063684.ta.chkpt" at 2024-07-29 11:34:23 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 29 / 218 / 53 / 300: 100%|████████████████████| 300/300 [25:25<00:00,  5.08s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 29     |
| Number of failed attacks:     | 218    |
| Number of skipped attacks:    | 53     |
| Original accuracy:            | 82.33% |
| Accuracy under attack:        | 72.67% |
| Attack success rate:          | 11.74% |
| Average perturbed word %:     | 3.98%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.67  |
+-------------------------------+--------+


In [88]:
runAttack(bert_knn7_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn7ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 6 / 33 / 11 / 50:  17%|███▋                  | 50/300 [33:55<2:49:35, 40.70s/it]textattack: Saving checkpoint under "checkpoints\1722226098841.ta.chkpt" at 2024-07-29 12:08:18 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 18 / 62 / 20 / 100:  33%|██████▎            | 100/300 [38:05<1:16:11, 22.86s/it]textattack: Saving checkpoint under "checkpoints\1722226349472.ta.chkpt" at 2024-07-29 12:12:29 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 28 / 90 / 32 / 150:  50%|██████████▌          | 150/300 [42:15<42:15, 16.90s/it]textattack: Saving checkpoint under "checkpoints\1722226598847.ta.chkpt" at 2024-07-29 12:16:38 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 36 / 119 / 45 / 200:  67%|█████████████▎      | 200/300 [47:03<23:31, 14.12s/it]textattack: Saving checkpoint under "checkpoints\1722226886926.ta.chkpt" at 2024-07-29 12:21:26 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 44 / 154 / 52 / 250:  83%|████████████████▋   | 250/300 [51:53<10:22, 12.45s/it]textattack: Saving checkpoint under "checkpoints\1722227177467.ta.chkpt" at 2024-07-29 12:26:17 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 46 / 196 / 58 / 300: 100%|████████████████████| 300/300 [57:10<00:00, 11.44s/it]textattack: Saving checkpoint under "checkpoints\1722227494633.ta.chkpt" at 2024-07-29 12:31:34 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 46 / 196 / 58 / 300: 100%|████████████████████| 300/300 [57:10<00:00, 11.44s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 46     |
| Number of failed attacks:     | 196    |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 80.67% |
| Accuracy under attack:        | 65.33% |
| Attack success rate:          | 19.01% |
| Average perturbed word %:     | 4.01%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.34  |
+-------------------------------+--------+


In [89]:
runAttack(bert_knn35_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn35'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn35ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 8 / 33 / 9 / 50:  17%|████▏                    | 50/300 [04:04<20:23,  4.90s/it]textattack: Saving checkpoint under "checkpoints\1722227739519.ta.chkpt" at 2024-07-29 12:35:39 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 16 / 65 / 19 / 100:  33%|███████              | 100/300 [08:25<16:51,  5.06s/it]textattack: Saving checkpoint under "checkpoints\1722228000500.ta.chkpt" at 2024-07-29 12:40:00 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 24 / 98 / 28 / 150:  50%|██████████▌          | 150/300 [12:57<12:57,  5.18s/it]textattack: Saving checkpoint under "checkpoints\1722228271837.ta.chkpt" at 2024-07-29 12:44:31 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 28 / 129 / 43 / 200:  67%|█████████████▎      | 200/300 [17:30<08:45,  5.25s/it]textattack: Saving checkpoint under "checkpoints\1722228545444.ta.chkpt" at 2024-07-29 12:49:05 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 32 / 167 / 51 / 250:  83%|████████████████▋   | 250/300 [22:30<04:30,  5.40s/it]textattack: Saving checkpoint under "checkpoints\1722228845300.ta.chkpt" at 2024-07-29 12:54:05 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 36 / 208 / 56 / 300: 100%|████████████████████| 300/300 [27:48<00:00,  5.56s/it]textattack: Saving checkpoint under "checkpoints\1722229163530.ta.chkpt" at 2024-07-29 12:59:23 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 36 / 208 / 56 / 300: 100%|████████████████████| 300/300 [27:48<00:00,  5.56s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 36     |
| Number of failed attacks:     | 208    |
| Number of skipped attacks:    | 56     |
| Original accuracy:            | 81.33% |
| Accuracy under attack:        | 69.33% |
| Attack success rate:          | 14.75% |
| Average perturbed word %:     | 4.2%   |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.42  |
+-------------------------------+--------+


In [90]:
runAttack(bert_knn175_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn175'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn175ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 5 / 36 / 9 / 50:  17%|████▏                    | 50/300 [03:58<19:54,  4.78s/it]textattack: Saving checkpoint under "checkpoints\1722229402524.ta.chkpt" at 2024-07-29 13:03:22 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 9 / 71 / 20 / 100:  33%|███████▎              | 100/300 [08:17<16:34,  4.97s/it]textattack: Saving checkpoint under "checkpoints\1722229660835.ta.chkpt" at 2024-07-29 13:07:40 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 16 / 101 / 33 / 150:  50%|██████████          | 150/300 [12:29<12:29,  4.99s/it]textattack: Saving checkpoint under "checkpoints\1722229912720.ta.chkpt" at 2024-07-29 13:11:52 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 19 / 134 / 47 / 200:  67%|█████████████▎      | 200/300 [17:06<08:33,  5.13s/it]textattack: Saving checkpoint under "checkpoints\1722230190306.ta.chkpt" at 2024-07-29 13:16:30 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 26 / 170 / 54 / 250:  83%|████████████████▋   | 250/300 [22:02<04:24,  5.29s/it]textattack: Saving checkpoint under "checkpoints\1722230486599.ta.chkpt" at 2024-07-29 13:21:26 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 34 / 206 / 60 / 300: 100%|████████████████████| 300/300 [27:00<00:00,  5.40s/it]textattack: Saving checkpoint under "checkpoints\1722230784047.ta.chkpt" at 2024-07-29 13:26:24 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 34 / 206 / 60 / 300: 100%|████████████████████| 300/300 [27:00<00:00,  5.40s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 34     |
| Number of failed attacks:     | 206    |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 80.0%  |
| Accuracy under attack:        | 68.67% |
| Attack success rate:          | 14.17% |
| Average perturbed word %:     | 5.95%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 36.94  |
+-------------------------------+--------+


#### CLIP

In [91]:
runAttack(clip_lr1_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr1'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr1ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 0 / 46 / 4 / 50:  17%|████▏                    | 50/300 [03:42<18:34,  4.46s/it]textattack: Saving checkpoint under "checkpoints\1722231007105.ta.chkpt" at 2024-07-29 13:30:07 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 0 / 91 / 9 / 100:  33%|███████▋               | 100/300 [07:30<15:00,  4.50s/it]textattack: Saving checkpoint under "checkpoints\1722231234396.ta.chkpt" at 2024-07-29 13:33:54 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 1 / 135 / 14 / 150:  50%|██████████▌          | 150/300 [11:22<11:22,  4.55s/it]textattack: Saving checkpoint under "checkpoints\1722231466545.ta.chkpt" at 2024-07-29 13:37:46 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 177 / 20 / 200:  67%|██████████████       | 200/300 [15:10<07:35,  4.55s/it]textattack: Saving checkpoint under "checkpoints\1722231695053.ta.chkpt" at 2024-07-29 13:41:35 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 223 / 24 / 250:  83%|█████████████████▌   | 250/300 [19:14<03:50,  4.62s/it]textattack: Saving checkpoint under "checkpoints\1722231938383.ta.chkpt" at 2024-07-29 13:45:38 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 268 / 29 / 300: 100%|█████████████████████| 300/300 [23:08<00:00,  4.63s/it]textattack: Saving checkpoint under "checkpoints\1722232172569.ta.chkpt" at 2024-07-29 13:49:32 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 3 / 268 / 29 / 300: 100%|█████████████████████| 300/300 [23:08<00:00,  4.63s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 3      |
| Number of failed attacks:     | 268    |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 89.33% |
| Attack success rate:          | 1.11%  |
| Average perturbed word %:     | 7.5%   |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.79  |
+-------------------------------+--------+


In [92]:
runAttack(clip_lr01_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr01'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr01ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 0 / 46 / 4 / 50:  17%|████▏                    | 50/300 [03:30<17:34,  4.22s/it]textattack: Saving checkpoint under "checkpoints\1722232383661.ta.chkpt" at 2024-07-29 13:53:03 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 0 / 91 / 9 / 100:  33%|███████▋               | 100/300 [07:14<14:28,  4.34s/it]textattack: Saving checkpoint under "checkpoints\1722232606734.ta.chkpt" at 2024-07-29 13:56:46 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 1 / 135 / 14 / 150:  50%|██████████▌          | 150/300 [11:01<11:01,  4.41s/it]textattack: Saving checkpoint under "checkpoints\1722232834333.ta.chkpt" at 2024-07-29 14:00:34 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 177 / 20 / 200:  67%|██████████████       | 200/300 [14:45<07:22,  4.43s/it]textattack: Saving checkpoint under "checkpoints\1722233058237.ta.chkpt" at 2024-07-29 14:04:18 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 223 / 24 / 250:  83%|█████████████████▌   | 250/300 [18:49<03:45,  4.52s/it]textattack: Saving checkpoint under "checkpoints\1722233302297.ta.chkpt" at 2024-07-29 14:08:22 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 268 / 29 / 300: 100%|█████████████████████| 300/300 [22:40<00:00,  4.54s/it]textattack: Saving checkpoint under "checkpoints\1722233533617.ta.chkpt" at 2024-07-29 14:12:13 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 3 / 268 / 29 / 300: 100%|█████████████████████| 300/300 [22:40<00:00,  4.54s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 3      |
| Number of failed attacks:     | 268    |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 89.33% |
| Attack success rate:          | 1.11%  |
| Average perturbed word %:     | 7.5%   |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.78  |
+-------------------------------+--------+


In [93]:
runAttack(clip_lr10_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr10'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr10ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 0 / 46 / 4 / 50:  17%|████▏                    | 50/300 [03:26<17:13,  4.14s/it]textattack: Saving checkpoint under "checkpoints\1722233740669.ta.chkpt" at 2024-07-29 14:15:40 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 0 / 91 / 9 / 100:  33%|███████▋               | 100/300 [07:10<14:21,  4.31s/it]textattack: Saving checkpoint under "checkpoints\1722233964849.ta.chkpt" at 2024-07-29 14:19:24 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 1 / 135 / 14 / 150:  50%|██████████▌          | 150/300 [11:00<11:00,  4.40s/it]textattack: Saving checkpoint under "checkpoints\1722234194082.ta.chkpt" at 2024-07-29 14:23:14 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 177 / 20 / 200:  67%|██████████████       | 200/300 [14:42<07:21,  4.41s/it]textattack: Saving checkpoint under "checkpoints\1722234416689.ta.chkpt" at 2024-07-29 14:26:56 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 223 / 24 / 250:  83%|█████████████████▌   | 250/300 [18:45<03:45,  4.50s/it]textattack: Saving checkpoint under "checkpoints\1722234658961.ta.chkpt" at 2024-07-29 14:30:58 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 268 / 29 / 300: 100%|█████████████████████| 300/300 [22:37<00:00,  4.53s/it]textattack: Saving checkpoint under "checkpoints\1722234891645.ta.chkpt" at 2024-07-29 14:34:51 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 3 / 268 / 29 / 300: 100%|█████████████████████| 300/300 [22:37<00:00,  4.53s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 3      |
| Number of failed attacks:     | 268    |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 89.33% |
| Attack success rate:          | 1.11%  |
| Average perturbed word %:     | 7.5%   |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.79  |
+-------------------------------+--------+


In [94]:
runAttack(clip_rf7_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf7ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 1 / 46 / 3 / 50:  17%|████▏                    | 50/300 [03:30<17:30,  4.20s/it]textattack: Saving checkpoint under "checkpoints\1722235101820.ta.chkpt" at 2024-07-29 14:38:21 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 1 / 88 / 11 / 100:  33%|███████▎              | 100/300 [07:07<14:14,  4.27s/it]textattack: Saving checkpoint under "checkpoints\1722235319112.ta.chkpt" at 2024-07-29 14:41:59 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 131 / 16 / 150:  50%|██████████▌          | 150/300 [10:45<10:45,  4.30s/it]textattack: Saving checkpoint under "checkpoints\1722235537211.ta.chkpt" at 2024-07-29 14:45:37 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 6 / 163 / 31 / 200:  67%|██████████████       | 200/300 [13:32<06:46,  4.06s/it]textattack: Saving checkpoint under "checkpoints\1722235703972.ta.chkpt" at 2024-07-29 14:48:23 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 8 / 204 / 38 / 250:  83%|█████████████████▌   | 250/300 [17:21<03:28,  4.17s/it]textattack: Saving checkpoint under "checkpoints\1722235933146.ta.chkpt" at 2024-07-29 14:52:13 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 8 / 249 / 43 / 300: 100%|█████████████████████| 300/300 [21:13<00:00,  4.25s/it]textattack: Saving checkpoint under "checkpoints\1722236165646.ta.chkpt" at 2024-07-29 14:56:05 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 8 / 249 / 43 / 300: 100%|█████████████████████| 300/300 [21:13<00:00,  4.25s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 8      |
| Number of failed attacks:     | 249    |
| Number of skipped attacks:    | 43     |
| Original accuracy:            | 85.67% |
| Accuracy under attack:        | 83.0%  |
| Attack success rate:          | 3.11%  |
| Average perturbed word %:     | 4.56%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.19  |
+-------------------------------+--------+


In [95]:
runAttack(clip_rf14_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf14'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf14ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 1 / 47 / 2 / 50:  17%|████▏                    | 50/300 [03:44<18:41,  4.48s/it]textattack: Saving checkpoint under "checkpoints\1722236390045.ta.chkpt" at 2024-07-29 14:59:50 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 1 / 92 / 7 / 100:  33%|███████▋               | 100/300 [07:34<15:08,  4.54s/it]textattack: Saving checkpoint under "checkpoints\1722236619865.ta.chkpt" at 2024-07-29 15:03:39 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 2 / 135 / 13 / 150:  50%|██████████▌          | 150/300 [11:16<11:16,  4.51s/it]textattack: Saving checkpoint under "checkpoints\1722236842196.ta.chkpt" at 2024-07-29 15:07:22 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 5 / 172 / 23 / 200:  67%|██████████████       | 200/300 [14:27<07:13,  4.34s/it]textattack: Saving checkpoint under "checkpoints\1722237033021.ta.chkpt" at 2024-07-29 15:10:33 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 6 / 216 / 28 / 250:  83%|█████████████████▌   | 250/300 [18:26<03:41,  4.43s/it]textattack: Saving checkpoint under "checkpoints\1722237272085.ta.chkpt" at 2024-07-29 15:14:32 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 7 / 260 / 33 / 300: 100%|█████████████████████| 300/300 [22:17<00:00,  4.46s/it]textattack: Saving checkpoint under "checkpoints\1722237502847.ta.chkpt" at 2024-07-29 15:18:22 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 7 / 260 / 33 / 300: 100%|█████████████████████| 300/300 [22:17<00:00,  4.46s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 7      |
| Number of failed attacks:     | 260    |
| Number of skipped attacks:    | 33     |
| Original accuracy:            | 89.0%  |
| Accuracy under attack:        | 86.67% |
| Attack success rate:          | 2.62%  |
| Average perturbed word %:     | 3.01%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.45  |
+-------------------------------+--------+


In [96]:
runAttack(clip_rf30_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf30'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf30ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 1 / 47 / 2 / 50:  17%|████▏                    | 50/300 [04:07<20:38,  4.95s/it]textattack: Saving checkpoint under "checkpoints\1722237750710.ta.chkpt" at 2024-07-29 15:22:30 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 1 / 91 / 8 / 100:  33%|███████▋               | 100/300 [08:08<16:17,  4.89s/it]textattack: Saving checkpoint under "checkpoints\1722237991897.ta.chkpt" at 2024-07-29 15:26:31 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 4 / 134 / 12 / 150:  50%|██████████▌          | 150/300 [12:02<12:02,  4.82s/it]textattack: Saving checkpoint under "checkpoints\1722238225848.ta.chkpt" at 2024-07-29 15:30:25 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 7 / 172 / 21 / 200:  67%|██████████████       | 200/300 [15:22<07:41,  4.61s/it]textattack: Saving checkpoint under "checkpoints\1722238425824.ta.chkpt" at 2024-07-29 15:33:45 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 8 / 216 / 26 / 250:  83%|█████████████████▌   | 250/300 [19:26<03:53,  4.67s/it]textattack: Saving checkpoint under "checkpoints\1722238669879.ta.chkpt" at 2024-07-29 15:37:49 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 9 / 261 / 30 / 300: 100%|█████████████████████| 300/300 [23:35<00:00,  4.72s/it]textattack: Saving checkpoint under "checkpoints\1722238918718.ta.chkpt" at 2024-07-29 15:41:58 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 9 / 261 / 30 / 300: 100%|█████████████████████| 300/300 [23:35<00:00,  4.72s/it]





+-------------------------------+-------+
| Attack Results                |       |
+-------------------------------+-------+
| Number of successful attacks: | 9     |
| Number of failed attacks:     | 261   |
| Number of skipped attacks:    | 30    |
| Original accuracy:            | 90.0% |
| Accuracy under attack:        | 87.0% |
| Attack success rate:          | 3.33% |
| Average perturbed word %:     | 3.33% |
| Average num. words per input: | 39.3  |
| Avg num queries:              | 37.24 |
+-------------------------------+-------+


In [97]:
runAttack(clip_knn7_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn7ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 0 / 49 / 1 / 50:  17%|███▊                   | 50/300 [31:00<2:35:02, 37.21s/it]textattack: Saving checkpoint under "checkpoints\1722240779437.ta.chkpt" at 2024-07-29 16:12:59 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 1 / 95 / 4 / 100:  33%|███████              | 100/300 [35:22<1:10:45, 21.23s/it]textattack: Saving checkpoint under "checkpoints\1722241041633.ta.chkpt" at 2024-07-29 16:17:21 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 140 / 7 / 150:  50%|███████████           | 150/300 [39:44<39:44, 15.90s/it]textattack: Saving checkpoint under "checkpoints\1722241303156.ta.chkpt" at 2024-07-29 16:21:43 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 4 / 182 / 14 / 200:  67%|██████████████       | 200/300 [43:59<21:59, 13.20s/it]textattack: Saving checkpoint under "checkpoints\1722241557965.ta.chkpt" at 2024-07-29 16:25:57 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 4 / 229 / 17 / 250:  83%|█████████████████▌   | 250/300 [48:36<09:43, 11.67s/it]textattack: Saving checkpoint under "checkpoints\1722241835695.ta.chkpt" at 2024-07-29 16:30:35 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 4 / 274 / 22 / 300: 100%|█████████████████████| 300/300 [52:51<00:00, 10.57s/it]textattack: Saving checkpoint under "checkpoints\1722242090217.ta.chkpt" at 2024-07-29 16:34:50 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 4 / 274 / 22 / 300: 100%|█████████████████████| 300/300 [52:51<00:00, 10.57s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 4      |
| Number of failed attacks:     | 274    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 91.33% |
| Attack success rate:          | 1.44%  |
| Average perturbed word %:     | 4.62%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.44  |
+-------------------------------+--------+


In [98]:
runAttack(clip_knn35_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn35'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn35ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 0 / 50 / 0 / 50:  17%|████▏                    | 50/300 [04:17<21:27,  5.15s/it]textattack: Saving checkpoint under "checkpoints\1722242347886.ta.chkpt" at 2024-07-29 16:39:07 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 0 / 97 / 3 / 100:  33%|███████▋               | 100/300 [08:50<17:41,  5.31s/it]textattack: Saving checkpoint under "checkpoints\1722242621168.ta.chkpt" at 2024-07-29 16:43:41 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 1 / 143 / 6 / 150:  50%|███████████           | 150/300 [13:18<13:18,  5.33s/it]textattack: Saving checkpoint under "checkpoints\1722242889251.ta.chkpt" at 2024-07-29 16:48:09 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 2 / 185 / 13 / 200:  67%|██████████████       | 200/300 [17:35<08:47,  5.28s/it]textattack: Saving checkpoint under "checkpoints\1722243145398.ta.chkpt" at 2024-07-29 16:52:25 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 2 / 232 / 16 / 250:  83%|█████████████████▌   | 250/300 [22:15<04:27,  5.34s/it]textattack: Saving checkpoint under "checkpoints\1722243425971.ta.chkpt" at 2024-07-29 16:57:05 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 275 / 22 / 300: 100%|█████████████████████| 300/300 [26:27<00:00,  5.29s/it]textattack: Saving checkpoint under "checkpoints\1722243678043.ta.chkpt" at 2024-07-29 17:01:18 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 3 / 275 / 22 / 300: 100%|█████████████████████| 300/300 [26:27<00:00,  5.29s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 3      |
| Number of failed attacks:     | 275    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 91.67% |
| Attack success rate:          | 1.08%  |
| Average perturbed word %:     | 4.35%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.71  |
+-------------------------------+--------+


In [99]:
runAttack(clip_knn175_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn175'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn175ep095.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.95
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']
        (colum

[Succeeded / Failed / Skipped / Total] 0 / 49 / 1 / 50:  17%|████▏                    | 50/300 [04:08<20:44,  4.98s/it]textattack: Saving checkpoint under "checkpoints\1722243927005.ta.chkpt" at 2024-07-29 17:05:27 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 1 / 94 / 5 / 100:  33%|███████▋               | 100/300 [08:32<17:05,  5.13s/it]textattack: Saving checkpoint under "checkpoints\1722244190914.ta.chkpt" at 2024-07-29 17:09:50 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 138 / 9 / 150:  50%|███████████           | 150/300 [12:53<12:53,  5.16s/it]textattack: Saving checkpoint under "checkpoints\1722244451579.ta.chkpt" at 2024-07-29 17:14:11 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 4 / 175 / 21 / 200:  67%|██████████████       | 200/300 [16:25<08:12,  4.93s/it]textattack: Saving checkpoint under "checkpoints\1722244663253.ta.chkpt" at 2024-07-29 17:17:43 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 4 / 218 / 28 / 250:  83%|█████████████████▌   | 250/300 [20:43<04:08,  4.97s/it]textattack: Saving checkpoint under "checkpoints\1722244921919.ta.chkpt" at 2024-07-29 17:22:01 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 4 / 262 / 34 / 300: 100%|█████████████████████| 300/300 [24:53<00:00,  4.98s/it]textattack: Saving checkpoint under "checkpoints\1722245171780.ta.chkpt" at 2024-07-29 17:26:11 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 4 / 262 / 34 / 300: 100%|█████████████████████| 300/300 [24:53<00:00,  4.98s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 4      |
| Number of failed attacks:     | 262    |
| Number of skipped attacks:    | 34     |
| Original accuracy:            | 88.67% |
| Accuracy under attack:        | 87.33% |
| Attack success rate:          | 1.5%   |
| Average perturbed word %:     | 5.28%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 37.63  |
+-------------------------------+--------+


In [100]:
et4 = datetime.datetime.now()
et4 - et3

datetime.timedelta(seconds=30352, microseconds=865045)

### Threshold = 1 - 0.6/$\pi$ = 0.809

In [101]:
suffix = 'ep0809.csv'
thre = 1-0.6/np.pi

#### BERT

In [102]:
runAttack(bert_lr1_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr1'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr1ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 43 / 2 / 5 / 50:  17%|████▏                    | 50/300 [09:11<45:58, 11.03s/it]textattack: Saving checkpoint under "checkpoints\1722245723727.ta.chkpt" at 2024-07-29 17:35:23 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 88 / 2 / 10 / 100:  33%|███████▎              | 100/300 [18:41<37:23, 11.22s/it]textattack: Saving checkpoint under "checkpoints\1722246294009.ta.chkpt" at 2024-07-29 17:44:54 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 133 / 2 / 15 / 150:  50%|██████████▌          | 150/300 [31:03<31:03, 12.42s/it]textattack: Saving checkpoint under "checkpoints\1722247035342.ta.chkpt" at 2024-07-29 17:57:15 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 176 / 3 / 21 / 200:  67%|██████████████       | 200/300 [42:14<21:07, 12.67s/it]textattack: Saving checkpoint under "checkpoints\1722247706914.ta.chkpt" at 2024-07-29 18:08:26 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 222 / 3 / 25 / 250:  83%|█████████████████▌   | 250/300 [53:45<10:45, 12.90s/it]textattack: Saving checkpoint under "checkpoints\1722248397178.ta.chkpt" at 2024-07-29 18:19:57 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 267 / 3 / 30 / 300: 100%|███████████████████| 300/300 [1:06:06<00:00, 13.22s/it]textattack: Saving checkpoint under "checkpoints\1722249138454.ta.chkpt" at 2024-07-29 18:32:18 after 300 attacks.


[Succeeded / Failed / Skipped / Total] 267 / 3 / 30 / 300: 100%|███████████████████| 300/300 [1:06:06<00:00, 13.22s/it]


+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 267    |
| Number of failed attacks:     | 3      |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 1.0%   |
| Attack success rate:          | 98.89% |
| Average perturbed word %:     | 15.33% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 193.23 |
+-------------------------------+--------+


In [103]:
runAttack(bert_lr01_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr01'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr01ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 44 / 1 / 5 / 50:  17%|████▏                    | 50/300 [09:35<47:57, 11.51s/it]textattack: Saving checkpoint under "checkpoints\1722249714195.ta.chkpt" at 2024-07-29 18:41:54 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 88 / 1 / 11 / 100:  33%|███████▎              | 100/300 [19:02<38:05, 11.43s/it]textattack: Saving checkpoint under "checkpoints\1722250281703.ta.chkpt" at 2024-07-29 18:51:21 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 132 / 2 / 16 / 150:  50%|██████████▌          | 150/300 [31:11<31:11, 12.47s/it]textattack: Saving checkpoint under "checkpoints\1722251009967.ta.chkpt" at 2024-07-29 19:03:29 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 175 / 2 / 23 / 200:  67%|██████████████       | 200/300 [42:05<21:02, 12.63s/it]textattack: Saving checkpoint under "checkpoints\1722251663997.ta.chkpt" at 2024-07-29 19:14:23 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 219 / 4 / 27 / 250:  83%|█████████████████▌   | 250/300 [54:13<10:50, 13.02s/it]textattack: Saving checkpoint under "checkpoints\1722252392562.ta.chkpt" at 2024-07-29 19:26:32 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 264 / 4 / 32 / 300: 100%|███████████████████| 300/300 [1:05:43<00:00, 13.15s/it]textattack: Saving checkpoint under "checkpoints\1722253082586.ta.chkpt" at 2024-07-29 19:38:02 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 264 / 4 / 32 / 300: 100%|███████████████████| 300/300 [1:05:43<00:00, 13.15s/it]






+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 264    |
| Number of failed attacks:     | 4      |
| Number of skipped attacks:    | 32     |
| Original accuracy:            | 89.33% |
| Accuracy under attack:        | 1.33%  |
| Attack success rate:          | 98.51% |
| Average perturbed word %:     | 15.45% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 197.41 |
+-------------------------------+--------+


In [104]:
runAttack(bert_lr10_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr10'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr10ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 44 / 1 / 5 / 50:  17%|████▏                    | 50/300 [08:41<43:28, 10.43s/it]textattack: Saving checkpoint under "checkpoints\1722253604560.ta.chkpt" at 2024-07-29 19:46:44 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 88 / 1 / 11 / 100:  33%|███████▎              | 100/300 [17:52<35:45, 10.73s/it]textattack: Saving checkpoint under "checkpoints\1722254155422.ta.chkpt" at 2024-07-29 19:55:55 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 133 / 1 / 16 / 150:  50%|██████████▌          | 150/300 [30:28<30:28, 12.19s/it]textattack: Saving checkpoint under "checkpoints\1722254911798.ta.chkpt" at 2024-07-29 20:08:31 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 175 / 3 / 22 / 200:  67%|██████████████       | 200/300 [41:45<20:52, 12.53s/it]textattack: Saving checkpoint under "checkpoints\1722255587984.ta.chkpt" at 2024-07-29 20:19:47 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 219 / 5 / 26 / 250:  83%|█████████████████▌   | 250/300 [52:52<10:34, 12.69s/it]textattack: Saving checkpoint under "checkpoints\1722256255761.ta.chkpt" at 2024-07-29 20:30:55 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 264 / 5 / 31 / 300: 100%|███████████████████| 300/300 [1:03:55<00:00, 12.78s/it]textattack: Saving checkpoint under "checkpoints\1722256917955.ta.chkpt" at 2024-07-29 20:41:57 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 264 / 5 / 31 / 300: 100%|███████████████████| 300/300 [1:03:55<00:00, 12.78s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 264    |
| Number of failed attacks:     | 5      |
| Number of skipped attacks:    | 31     |
| Original accuracy:            | 89.67% |
| Accuracy under attack:        | 1.67%  |
| Attack success rate:          | 98.14% |
| Average perturbed word %:     | 14.89% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 193.51 |
+-------------------------------+--------+


In [105]:
runAttack(bert_rf7_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf7ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 36 / 1 / 13 / 50:  17%|████                    | 50/300 [05:36<28:03,  6.74s/it]textattack: Saving checkpoint under "checkpoints\1722257255015.ta.chkpt" at 2024-07-29 20:47:35 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 67 / 4 / 29 / 100:  33%|███████▎              | 100/300 [11:10<22:20,  6.70s/it]textattack: Saving checkpoint under "checkpoints\1722257588666.ta.chkpt" at 2024-07-29 20:53:08 after 100 attacks.
[Succeeded / Failed / Skipped / Total] 67 / 4 / 30 / 101:  34%|███████▍              | 101/300 [11:10<22:01,  6.64s/it]

[Succeeded / Failed / Skipped / Total] 105 / 5 / 40 / 150:  50%|██████████▌          | 150/300 [17:15<17:15,  6.90s/it]textattack: Saving checkpoint under "checkpoints\1722257953588.ta.chkpt" at 2024-07-29 20:59:13 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 137 / 7 / 56 / 200:  67%|██████████████       | 200/300 [27:39<13:49,  8.30s/it]textattack: Saving checkpoint under "checkpoints\1722258577652.ta.chkpt" at 2024-07-29 21:09:37 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 179 / 8 / 63 / 250:  83%|█████████████████▌   | 250/300 [33:41<06:44,  8.09s/it]textattack: Saving checkpoint under "checkpoints\1722258939513.ta.chkpt" at 2024-07-29 21:15:39 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 218 / 8 / 74 / 300: 100%|█████████████████████| 300/300 [40:21<00:00,  8.07s/it]textattack: Saving checkpoint under "checkpoints\1722259339667.ta.chkpt" at 2024-07-29 21:22:19 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 218 / 8 / 74 / 300: 100%|█████████████████████| 300/300 [40:21<00:00,  8.07s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 218    |
| Number of failed attacks:     | 8      |
| Number of skipped attacks:    | 74     |
| Original accuracy:            | 75.33% |
| Accuracy under attack:        | 2.67%  |
| Attack success rate:          | 96.46% |
| Average perturbed word %:     | 8.21%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 140.46 |
+-------------------------------+--------+


In [106]:
runAttack(bert_rf14_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf14'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf14ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 38 / 3 / 9 / 50:  17%|████▏                    | 50/300 [07:59<39:58,  9.59s/it]textattack: Saving checkpoint under "checkpoints\1722259819433.ta.chkpt" at 2024-07-29 21:30:19 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 78 / 3 / 19 / 100:  33%|███████▎              | 100/300 [15:11<30:23,  9.12s/it]textattack: Saving checkpoint under "checkpoints\1722260251772.ta.chkpt" at 2024-07-29 21:37:31 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 117 / 6 / 27 / 150:  50%|██████████▌          | 150/300 [23:36<23:36,  9.45s/it]textattack: Saving checkpoint under "checkpoints\1722260756573.ta.chkpt" at 2024-07-29 21:45:56 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 147 / 10 / 43 / 200:  67%|█████████████▎      | 200/300 [36:00<18:00, 10.80s/it]textattack: Saving checkpoint under "checkpoints\1722261500263.ta.chkpt" at 2024-07-29 21:58:20 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 187 / 14 / 49 / 250:  83%|████████████████▋   | 250/300 [45:47<09:09, 10.99s/it]textattack: Saving checkpoint under "checkpoints\1722262087390.ta.chkpt" at 2024-07-29 22:08:07 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 229 / 14 / 57 / 300: 100%|████████████████████| 300/300 [54:47<00:00, 10.96s/it]textattack: Saving checkpoint under "checkpoints\1722262627009.ta.chkpt" at 2024-07-29 22:17:07 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 229 / 14 / 57 / 300: 100%|████████████████████| 300/300 [54:47<00:00, 10.96s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 229    |
| Number of failed attacks:     | 14     |
| Number of skipped attacks:    | 57     |
| Original accuracy:            | 81.0%  |
| Accuracy under attack:        | 4.67%  |
| Attack success rate:          | 94.24% |
| Average perturbed word %:     | 9.52%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 174.67 |
+-------------------------------+--------+


In [107]:
runAttack(bert_rf30_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf30'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf30ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 40 / 4 / 6 / 50:  17%|████▏                    | 50/300 [10:03<50:15, 12.06s/it]textattack: Saving checkpoint under "checkpoints\1722263230169.ta.chkpt" at 2024-07-29 22:27:10 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 77 / 4 / 19 / 100:  33%|███████▎              | 100/300 [15:48<31:37,  9.49s/it]textattack: Saving checkpoint under "checkpoints\1722263575760.ta.chkpt" at 2024-07-29 22:32:55 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 114 / 10 / 26 / 150:  50%|██████████          | 150/300 [25:04<25:04, 10.03s/it]textattack: Saving checkpoint under "checkpoints\1722264131245.ta.chkpt" at 2024-07-29 22:42:11 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 149 / 12 / 39 / 200:  67%|█████████████▎      | 200/300 [35:36<17:48, 10.68s/it]textattack: Saving checkpoint under "checkpoints\1722264763740.ta.chkpt" at 2024-07-29 22:52:43 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 189 / 15 / 46 / 250:  83%|████████████████▋   | 250/300 [46:08<09:13, 11.07s/it]textattack: Saving checkpoint under "checkpoints\1722265395442.ta.chkpt" at 2024-07-29 23:03:15 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 229 / 18 / 53 / 300: 100%|████████████████████| 300/300 [56:32<00:00, 11.31s/it]textattack: Saving checkpoint under "checkpoints\1722266019947.ta.chkpt" at 2024-07-29 23:13:39 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 229 / 18 / 53 / 300: 100%|████████████████████| 300/300 [56:32<00:00, 11.31s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 229    |
| Number of failed attacks:     | 18     |
| Number of skipped attacks:    | 53     |
| Original accuracy:            | 82.33% |
| Accuracy under attack:        | 6.0%   |
| Attack success rate:          | 92.71% |
| Average perturbed word %:     | 9.15%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 179.36 |
+-------------------------------+--------+


In [108]:
runAttack(bert_knn7_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn7ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 32 / 7 / 11 / 50:  17%|███▋                  | 50/300 [35:08<2:55:41, 42.17s/it]textattack: Saving checkpoint under "checkpoints\1722268128323.ta.chkpt" at 2024-07-29 23:48:48 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 71 / 9 / 20 / 100:  33%|██████▋             | 100/300 [45:51<1:31:42, 27.51s/it]textattack: Saving checkpoint under "checkpoints\1722268771250.ta.chkpt" at 2024-07-29 23:59:31 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 101 / 17 / 32 / 150:  50%|██████████          | 150/300 [59:13<59:13, 23.69s/it]textattack: Saving checkpoint under "checkpoints\1722269573839.ta.chkpt" at 2024-07-30 00:12:53 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 130 / 25 / 45 / 200:  67%|████████████      | 200/300 [1:14:48<37:24, 22.44s/it]textattack: Saving checkpoint under "checkpoints\1722270508798.ta.chkpt" at 2024-07-30 00:28:28 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 166 / 32 / 52 / 250:  83%|███████████████   | 250/300 [1:27:51<17:34, 21.08s/it]textattack: Saving checkpoint under "checkpoints\1722271291290.ta.chkpt" at 2024-07-30 00:41:31 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 205 / 37 / 58 / 300: 100%|██████████████████| 300/300 [1:40:22<00:00, 20.07s/it]textattack: Saving checkpoint under "checkpoints\1722272042517.ta.chkpt" at 2024-07-30 00:54:02 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 205 / 37 / 58 / 300: 100%|██████████████████| 300/300 [1:40:22<00:00, 20.07s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 205    |
| Number of failed attacks:     | 37     |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 80.67% |
| Accuracy under attack:        | 12.33% |
| Attack success rate:          | 84.71% |
| Average perturbed word %:     | 5.06%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 205.13 |
+-------------------------------+--------+


In [109]:
runAttack(bert_knn35_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn35'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn35ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 37 / 4 / 9 / 50:  17%|████▏                    | 50/300 [11:13<56:07, 13.47s/it]textattack: Saving checkpoint under "checkpoints\1722272716040.ta.chkpt" at 2024-07-30 01:05:16 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 73 / 8 / 19 / 100:  33%|███████▎              | 100/300 [21:51<43:42, 13.11s/it]textattack: Saving checkpoint under "checkpoints\1722273354047.ta.chkpt" at 2024-07-30 01:15:54 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 111 / 11 / 28 / 150:  50%|██████████          | 150/300 [33:37<33:37, 13.45s/it]textattack: Saving checkpoint under "checkpoints\1722274059862.ta.chkpt" at 2024-07-30 01:27:39 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 141 / 16 / 43 / 200:  67%|█████████████▎      | 200/300 [49:13<24:36, 14.77s/it]textattack: Saving checkpoint under "checkpoints\1722274996026.ta.chkpt" at 2024-07-30 01:43:16 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 178 / 21 / 51 / 250:  83%|███████████████   | 250/300 [1:02:20<12:28, 14.96s/it]textattack: Saving checkpoint under "checkpoints\1722275783296.ta.chkpt" at 2024-07-30 01:56:23 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 221 / 23 / 56 / 300: 100%|██████████████████| 300/300 [1:13:53<00:00, 14.78s/it]textattack: Saving checkpoint under "checkpoints\1722276476545.ta.chkpt" at 2024-07-30 02:07:56 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 221 / 23 / 56 / 300: 100%|██████████████████| 300/300 [1:13:53<00:00, 14.78s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 221    |
| Number of failed attacks:     | 23     |
| Number of skipped attacks:    | 56     |
| Original accuracy:            | 81.33% |
| Accuracy under attack:        | 7.67%  |
| Attack success rate:          | 90.57% |
| Average perturbed word %:     | 7.74%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 192.71 |
+-------------------------------+--------+


In [110]:
runAttack(bert_knn175_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn175'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn175ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 40 / 1 / 9 / 50:  17%|████▏                    | 50/300 [08:52<44:24, 10.66s/it]textattack: Saving checkpoint under "checkpoints\1722277009492.ta.chkpt" at 2024-07-30 02:16:49 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 78 / 2 / 20 / 100:  33%|███████▎              | 100/300 [16:25<32:51,  9.86s/it]textattack: Saving checkpoint under "checkpoints\1722277462513.ta.chkpt" at 2024-07-30 02:24:22 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 113 / 4 / 33 / 150:  50%|██████████▌          | 150/300 [25:48<25:48, 10.32s/it]textattack: Saving checkpoint under "checkpoints\1722278025323.ta.chkpt" at 2024-07-30 02:33:45 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 147 / 6 / 47 / 200:  67%|██████████████       | 200/300 [36:49<18:24, 11.05s/it]textattack: Saving checkpoint under "checkpoints\1722278686367.ta.chkpt" at 2024-07-30 02:44:46 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 189 / 7 / 54 / 250:  83%|█████████████████▌   | 250/300 [46:55<09:23, 11.26s/it]textattack: Saving checkpoint under "checkpoints\1722279292038.ta.chkpt" at 2024-07-30 02:54:52 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 232 / 8 / 60 / 300: 100%|█████████████████████| 300/300 [56:57<00:00, 11.39s/it]textattack: Saving checkpoint under "checkpoints\1722279894513.ta.chkpt" at 2024-07-30 03:04:54 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 232 / 8 / 60 / 300: 100%|█████████████████████| 300/300 [56:57<00:00, 11.39s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 232    |
| Number of failed attacks:     | 8      |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 80.0%  |
| Accuracy under attack:        | 2.67%  |
| Attack success rate:          | 96.67% |
| Average perturbed word %:     | 9.19%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 154.3  |
+-------------------------------+--------+


#### CLIP

In [111]:
runAttack(clip_lr1_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr1'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr1ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 44 / 2 / 4 / 50:  17%|████▏                    | 50/300 [09:57<49:46, 11.94s/it]textattack: Saving checkpoint under "checkpoints\1722280491797.ta.chkpt" at 2024-07-30 03:14:51 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 87 / 4 / 9 / 100:  33%|███████▋               | 100/300 [17:22<34:45, 10.43s/it]textattack: Saving checkpoint under "checkpoints\1722280937524.ta.chkpt" at 2024-07-30 03:22:17 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 131 / 5 / 14 / 150:  50%|██████████▌          | 150/300 [25:41<25:41, 10.28s/it]textattack: Saving checkpoint under "checkpoints\1722281435891.ta.chkpt" at 2024-07-30 03:30:35 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 174 / 6 / 20 / 200:  67%|██████████████       | 200/300 [33:21<16:40, 10.01s/it]textattack: Saving checkpoint under "checkpoints\1722281895607.ta.chkpt" at 2024-07-30 03:38:15 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 220 / 6 / 24 / 250:  83%|█████████████████▌   | 250/300 [41:26<08:17,  9.94s/it]textattack: Saving checkpoint under "checkpoints\1722282380781.ta.chkpt" at 2024-07-30 03:46:20 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 263 / 8 / 29 / 300: 100%|█████████████████████| 300/300 [51:06<00:00, 10.22s/it]textattack: Saving checkpoint under "checkpoints\1722282961295.ta.chkpt" at 2024-07-30 03:56:01 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 263 / 8 / 29 / 300: 100%|█████████████████████| 300/300 [51:06<00:00, 10.22s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 263    |
| Number of failed attacks:     | 8      |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 2.67%  |
| Attack success rate:          | 97.05% |
| Average perturbed word %:     | 18.42% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 234.08 |
+-------------------------------+--------+


In [112]:
runAttack(clip_lr01_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr01'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr01ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 44 / 2 / 4 / 50:  17%|████▏                    | 50/300 [09:14<46:10, 11.08s/it]textattack: Saving checkpoint under "checkpoints\1722283515609.ta.chkpt" at 2024-07-30 04:05:15 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 87 / 4 / 9 / 100:  33%|███████▋               | 100/300 [16:39<33:18,  9.99s/it]textattack: Saving checkpoint under "checkpoints\1722283960605.ta.chkpt" at 2024-07-30 04:12:40 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 131 / 5 / 14 / 150:  50%|██████████▌          | 150/300 [24:51<24:51,  9.94s/it]textattack: Saving checkpoint under "checkpoints\1722284452717.ta.chkpt" at 2024-07-30 04:20:52 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 174 / 6 / 20 / 200:  67%|██████████████       | 200/300 [32:20<16:10,  9.70s/it]textattack: Saving checkpoint under "checkpoints\1722284902200.ta.chkpt" at 2024-07-30 04:28:22 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 220 / 6 / 24 / 250:  83%|█████████████████▌   | 250/300 [40:39<08:07,  9.76s/it]textattack: Saving checkpoint under "checkpoints\1722285400700.ta.chkpt" at 2024-07-30 04:36:40 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 263 / 8 / 29 / 300: 100%|█████████████████████| 300/300 [51:02<00:00, 10.21s/it]textattack: Saving checkpoint under "checkpoints\1722286023525.ta.chkpt" at 2024-07-30 04:47:03 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 263 / 8 / 29 / 300: 100%|█████████████████████| 300/300 [51:02<00:00, 10.21s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 263    |
| Number of failed attacks:     | 8      |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 2.67%  |
| Attack success rate:          | 97.05% |
| Average perturbed word %:     | 18.58% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 236.66 |
+-------------------------------+--------+


In [113]:
runAttack(clip_lr10_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr10'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr10ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 44 / 2 / 4 / 50:  17%|████▏                    | 50/300 [09:13<46:09, 11.08s/it]textattack: Saving checkpoint under "checkpoints\1722286578344.ta.chkpt" at 2024-07-30 04:56:18 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 87 / 4 / 9 / 100:  33%|███████▋               | 100/300 [16:29<32:59,  9.90s/it]textattack: Saving checkpoint under "checkpoints\1722287014217.ta.chkpt" at 2024-07-30 05:03:34 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 131 / 5 / 14 / 150:  50%|██████████▌          | 150/300 [24:34<24:34,  9.83s/it]textattack: Saving checkpoint under "checkpoints\1722287498789.ta.chkpt" at 2024-07-30 05:11:38 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 174 / 6 / 20 / 200:  67%|██████████████       | 200/300 [32:04<16:02,  9.62s/it]textattack: Saving checkpoint under "checkpoints\1722287948853.ta.chkpt" at 2024-07-30 05:19:08 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 220 / 6 / 24 / 250:  83%|█████████████████▌   | 250/300 [40:03<08:00,  9.61s/it]textattack: Saving checkpoint under "checkpoints\1722288427789.ta.chkpt" at 2024-07-30 05:27:07 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 263 / 8 / 29 / 300: 100%|█████████████████████| 300/300 [49:40<00:00,  9.94s/it]textattack: Saving checkpoint under "checkpoints\1722289005285.ta.chkpt" at 2024-07-30 05:36:45 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 263 / 8 / 29 / 300: 100%|█████████████████████| 300/300 [49:40<00:00,  9.94s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 263    |
| Number of failed attacks:     | 8      |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 2.67%  |
| Attack success rate:          | 97.05% |
| Average perturbed word %:     | 18.46% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 234.45 |
+-------------------------------+--------+


In [114]:
runAttack(clip_rf7_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf7ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 34 / 13 / 3 / 50:  17%|████                    | 50/300 [11:22<56:50, 13.64s/it]textattack: Saving checkpoint under "checkpoints\1722289687701.ta.chkpt" at 2024-07-30 05:48:07 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 68 / 21 / 11 / 100:  33%|███████              | 100/300 [22:04<44:08, 13.24s/it]textattack: Saving checkpoint under "checkpoints\1722290329621.ta.chkpt" at 2024-07-30 05:58:49 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 105 / 29 / 16 / 150:  50%|██████████          | 150/300 [33:09<33:09, 13.26s/it]textattack: Saving checkpoint under "checkpoints\1722290994710.ta.chkpt" at 2024-07-30 06:09:54 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 133 / 36 / 31 / 200:  67%|█████████████▎      | 200/300 [41:29<20:44, 12.45s/it]textattack: Saving checkpoint under "checkpoints\1722291494568.ta.chkpt" at 2024-07-30 06:18:14 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 166 / 46 / 38 / 250:  83%|████████████████▋   | 250/300 [52:36<10:31, 12.63s/it]textattack: Saving checkpoint under "checkpoints\1722292162329.ta.chkpt" at 2024-07-30 06:29:22 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 200 / 57 / 43 / 300: 100%|██████████████████| 300/300 [1:05:10<00:00, 13.03s/it]textattack: Saving checkpoint under "checkpoints\1722292915906.ta.chkpt" at 2024-07-30 06:41:55 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 200 / 57 / 43 / 300: 100%|██████████████████| 300/300 [1:05:10<00:00, 13.03s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 200    |
| Number of failed attacks:     | 57     |
| Number of skipped attacks:    | 43     |
| Original accuracy:            | 85.67% |
| Accuracy under attack:        | 19.0%  |
| Attack success rate:          | 77.82% |
| Average perturbed word %:     | 18.33% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 322.87 |
+-------------------------------+--------+


In [115]:
runAttack(clip_rf14_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf14'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf14ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 33 / 15 / 2 / 50:  17%|███▋                  | 50/300 [12:33<1:02:47, 15.07s/it]textattack: Saving checkpoint under "checkpoints\1722293669611.ta.chkpt" at 2024-07-30 06:54:29 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 68 / 25 / 7 / 100:  33%|███████▎              | 100/300 [25:13<50:26, 15.13s/it]textattack: Saving checkpoint under "checkpoints\1722294429272.ta.chkpt" at 2024-07-30 07:07:09 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 98 / 39 / 13 / 150:  50%|██████████▌          | 150/300 [38:00<38:00, 15.20s/it]textattack: Saving checkpoint under "checkpoints\1722295196272.ta.chkpt" at 2024-07-30 07:19:56 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 127 / 50 / 23 / 200:  67%|█████████████▎      | 200/300 [48:36<24:18, 14.58s/it]textattack: Saving checkpoint under "checkpoints\1722295832654.ta.chkpt" at 2024-07-30 07:30:32 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 156 / 66 / 28 / 250:  83%|███████████████   | 250/300 [1:01:22<12:16, 14.73s/it]textattack: Saving checkpoint under "checkpoints\1722296598604.ta.chkpt" at 2024-07-30 07:43:18 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 179 / 88 / 33 / 300: 100%|██████████████████| 300/300 [1:17:35<00:00, 15.52s/it]textattack: Saving checkpoint under "checkpoints\1722297571955.ta.chkpt" at 2024-07-30 07:59:31 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 179 / 88 / 33 / 300: 100%|██████████████████| 300/300 [1:17:35<00:00, 15.52s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 179    |
| Number of failed attacks:     | 88     |
| Number of skipped attacks:    | 33     |
| Original accuracy:            | 89.0%  |
| Accuracy under attack:        | 29.33% |
| Attack success rate:          | 67.04% |
| Average perturbed word %:     | 17.79% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 365.74 |
+-------------------------------+--------+


In [116]:
runAttack(clip_rf30_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf30'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf30ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 28 / 20 / 2 / 50:  17%|███▋                  | 50/300 [16:21<1:21:45, 19.62s/it]textattack: Saving checkpoint under "checkpoints\1722298553076.ta.chkpt" at 2024-07-30 08:15:53 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 59 / 33 / 8 / 100:  33%|███████▎              | 100/300 [29:24<58:49, 17.65s/it]textattack: Saving checkpoint under "checkpoints\1722299336837.ta.chkpt" at 2024-07-30 08:28:56 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 90 / 48 / 12 / 150:  50%|██████████▌          | 150/300 [42:21<42:21, 16.94s/it]textattack: Saving checkpoint under "checkpoints\1722300113356.ta.chkpt" at 2024-07-30 08:41:53 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 117 / 62 / 21 / 200:  67%|█████████████▎      | 200/300 [53:17<26:38, 15.99s/it]textattack: Saving checkpoint under "checkpoints\1722300769130.ta.chkpt" at 2024-07-30 08:52:49 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 146 / 78 / 26 / 250:  83%|███████████████   | 250/300 [1:06:28<13:17, 15.95s/it]textattack: Saving checkpoint under "checkpoints\1722301560697.ta.chkpt" at 2024-07-30 09:06:00 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 172 / 98 / 30 / 300: 100%|██████████████████| 300/300 [1:22:16<00:00, 16.46s/it]textattack: Saving checkpoint under "checkpoints\1722302508793.ta.chkpt" at 2024-07-30 09:21:48 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 172 / 98 / 30 / 300: 100%|██████████████████| 300/300 [1:22:16<00:00, 16.46s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 172    |
| Number of failed attacks:     | 98     |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 32.67% |
| Attack success rate:          | 63.7%  |
| Average perturbed word %:     | 15.41% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 375.01 |
+-------------------------------+--------+


In [117]:
runAttack(clip_knn7_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn7'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn7ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 5 / 44 / 1 / 50:  17%|███▊                   | 50/300 [51:57<4:19:49, 62.36s/it]textattack: Saving checkpoint under "checkpoints\1722305626810.ta.chkpt" at 2024-07-30 10:13:46 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 19 / 77 / 4 / 100:  33%|██████            | 100/300 [1:14:58<2:29:57, 44.99s/it]textattack: Saving checkpoint under "checkpoints\1722307007670.ta.chkpt" at 2024-07-30 10:36:47 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 27 / 116 / 7 / 150:  50%|████████▌        | 150/300 [1:38:38<1:38:38, 39.46s/it]textattack: Saving checkpoint under "checkpoints\1722308427548.ta.chkpt" at 2024-07-30 11:00:27 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 37 / 149 / 14 / 200:  67%|████████████      | 200/300 [1:58:34<59:17, 35.57s/it]textattack: Saving checkpoint under "checkpoints\1722309623866.ta.chkpt" at 2024-07-30 11:20:23 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 51 / 182 / 17 / 250:  83%|███████████████   | 250/300 [2:22:14<28:26, 34.14s/it]textattack: Saving checkpoint under "checkpoints\1722311043571.ta.chkpt" at 2024-07-30 11:44:03 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 58 / 220 / 22 / 300: 100%|██████████████████| 300/300 [2:45:55<00:00, 33.18s/it]textattack: Saving checkpoint under "checkpoints\1722312464145.ta.chkpt" at 2024-07-30 12:07:44 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 58 / 220 / 22 / 300: 100%|██████████████████| 300/300 [2:45:55<00:00, 33.18s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 58     |
| Number of failed attacks:     | 220    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 73.33% |
| Attack success rate:          | 20.86% |
| Average perturbed word %:     | 5.35%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 542.74 |
+-------------------------------+--------+


In [118]:
runAttack(clip_knn35_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn35'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn35ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 14 / 36 / 0 / 50:  17%|███▋                  | 50/300 [21:49<1:49:07, 26.19s/it]textattack: Saving checkpoint under "checkpoints\1722313773687.ta.chkpt" at 2024-07-30 12:29:33 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 31 / 66 / 3 / 100:  33%|██████▋             | 100/300 [43:29<1:26:58, 26.09s/it]textattack: Saving checkpoint under "checkpoints\1722315073233.ta.chkpt" at 2024-07-30 12:51:13 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 51 / 93 / 6 / 150:  50%|█████████         | 150/300 [1:03:25<1:03:25, 25.37s/it]textattack: Saving checkpoint under "checkpoints\1722316269764.ta.chkpt" at 2024-07-30 13:11:09 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 68 / 119 / 13 / 200:  67%|████████████      | 200/300 [1:21:55<40:57, 24.58s/it]textattack: Saving checkpoint under "checkpoints\1722317379938.ta.chkpt" at 2024-07-30 13:29:39 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 84 / 150 / 16 / 250:  83%|███████████████   | 250/300 [1:43:54<20:46, 24.94s/it]textattack: Saving checkpoint under "checkpoints\1722318698547.ta.chkpt" at 2024-07-30 13:51:38 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 95 / 183 / 22 / 300: 100%|██████████████████| 300/300 [2:06:42<00:00, 25.34s/it]textattack: Saving checkpoint under "checkpoints\1722320066778.ta.chkpt" at 2024-07-30 14:14:26 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 95 / 183 / 22 / 300: 100%|██████████████████| 300/300 [2:06:42<00:00, 25.34s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 95     |
| Number of failed attacks:     | 183    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 61.0%  |
| Attack success rate:          | 34.17% |
| Average perturbed word %:     | 12.17% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 499.95 |
+-------------------------------+--------+


In [119]:
runAttack(clip_knn175_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn175'+suffix, target_ds_ag, 0.5, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn175ep0809.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.5
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8090140682897256
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 25 / 24 / 1 / 50:  17%|███▋                  | 50/300 [18:33<1:32:46, 22.27s/it]textattack: Saving checkpoint under "checkpoints\1722321180142.ta.chkpt" at 2024-07-30 14:33:00 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 54 / 41 / 5 / 100:  33%|██████▋             | 100/300 [36:25<1:12:50, 21.85s/it]textattack: Saving checkpoint under "checkpoints\1722322251961.ta.chkpt" at 2024-07-30 14:50:51 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 78 / 63 / 9 / 150:  50%|███████████           | 150/300 [54:05<54:05, 21.63s/it]textattack: Saving checkpoint under "checkpoints\1722323312059.ta.chkpt" at 2024-07-30 15:08:32 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 96 / 83 / 21 / 200:  67%|████████████▋      | 200/300 [1:09:32<34:46, 20.86s/it]textattack: Saving checkpoint under "checkpoints\1722324239589.ta.chkpt" at 2024-07-30 15:23:59 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 117 / 105 / 28 / 250:  83%|██████████████▏  | 250/300 [1:27:58<17:35, 21.11s/it]textattack: Saving checkpoint under "checkpoints\1722325344984.ta.chkpt" at 2024-07-30 15:42:24 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 134 / 132 / 34 / 300: 100%|█████████████████| 300/300 [1:48:48<00:00, 21.76s/it]textattack: Saving checkpoint under "checkpoints\1722326595595.ta.chkpt" at 2024-07-30 16:03:15 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 134 / 132 / 34 / 300: 100%|█████████████████| 300/300 [1:48:48<00:00, 21.76s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 134    |
| Number of failed attacks:     | 132    |
| Number of skipped attacks:    | 34     |
| Original accuracy:            | 88.67% |
| Accuracy under attack:        | 44.0%  |
| Attack success rate:          | 50.38% |
| Average perturbed word %:     | 20.64% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 447.62 |
+-------------------------------+--------+


In [120]:
et5 = datetime.datetime.now()
et5 - et4

datetime.timedelta(seconds=81423, microseconds=861509)

### MinSim 0.6, threshold 0.5

In [125]:
suffix = 'sim06.csv'
thre = 1-0.5/np.pi

In [126]:
st = datetime.datetime.now()

#### BERT

In [127]:
runAttack(bert_lr1_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr1'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr1sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']




  0%|                                                                                          | 0/300 [00:00<?, ?it/s]

  0%|▎                                                                               | 1/300 [00:54<4:32:18, 54.65s/it]

[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   0%|                          | 1/300 [00:54<4:32:23, 54.66s/it]

[Succeeded / Failed / Skipped / Total] 1 / 0 / 0 / 1:   1%|▏                         | 2/300 [00:59<2:27:16, 29.65s/it]

[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▏                         | 2/300 [00:59<2:27:19, 29.66s/it]

[Succeeded / Failed / Skipped / Total] 2 / 0 / 0 / 2:   1%|▎                         | 3/300 [01:09<1:55:26, 23.32s/it]

[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 3/300 [01:09<1:55:28, 23.33s/it]

[Succeeded / Failed / Skipped / Total] 3 / 0 / 0 / 3:   1%|▎                         | 4/300 [01:30<1:51:27, 22.59s/it]

[Succeeded / Failed / Skipped 



[Succeeded / Failed / Skipped / Total] 43 / 2 / 5 / 50:  17%|████▎                    | 51/300 [08:35<41:56, 10.11s/it]

[Succeeded / Failed / Skipped / Total] 44 / 2 / 5 / 51:  17%|████▎                    | 51/300 [08:35<41:56, 10.11s/it]

[Succeeded / Failed / Skipped / Total] 44 / 2 / 5 / 51:  17%|████▎                    | 52/300 [08:41<41:28, 10.03s/it]

[Succeeded / Failed / Skipped / Total] 45 / 2 / 5 / 52:  17%|████▎                    | 52/300 [08:41<41:28, 10.03s/it]

[Succeeded / Failed / Skipped / Total] 45 / 2 / 5 / 52:  18%|████▍                    | 53/300 [09:06<42:28, 10.32s/it]

[Succeeded / Failed / Skipped / Total] 46 / 2 / 5 / 53:  18%|████▍                    | 53/300 [09:06<42:29, 10.32s/it]

[Succeeded / Failed / Skipped / Total] 46 / 2 / 5 / 53:  18%|████▌                    | 54/300 [09:17<42:18, 10.32s/it]

[Succeeded / Failed / Skipped / Total] 47 / 2 / 5 / 54:  18%|████▌                    | 54/300 [09:17<42:18, 10.32s/it]

[Succeeded / Failed / Skipped 



[Succeeded / Failed / Skipped / Total] 88 / 2 / 10 / 100:  34%|███████▍              | 101/300 [17:05<33:40, 10.15s/it]

[Succeeded / Failed / Skipped / Total] 89 / 2 / 10 / 101:  34%|███████▍              | 101/300 [17:05<33:40, 10.15s/it]

[Succeeded / Failed / Skipped / Total] 89 / 2 / 10 / 101:  34%|███████▍              | 102/300 [17:11<33:21, 10.11s/it]

[Succeeded / Failed / Skipped / Total] 90 / 2 / 10 / 102:  34%|███████▍              | 102/300 [17:11<33:21, 10.11s/it]

[Succeeded / Failed / Skipped / Total] 90 / 2 / 10 / 102:  34%|███████▌              | 103/300 [17:17<33:04, 10.08s/it]

[Succeeded / Failed / Skipped / Total] 91 / 2 / 10 / 103:  34%|███████▌              | 103/300 [17:17<33:05, 10.08s/it]

[Succeeded / Failed / Skipped / Total] 91 / 2 / 10 / 103:  35%|███████▋              | 104/300 [17:24<32:48, 10.04s/it]

[Succeeded / Failed / Skipped / Total] 92 / 2 / 10 / 104:  35%|███████▋              | 104/300 [17:24<32:48, 10.04s/it]

[Succeeded / Failed / Skipped 



[Succeeded / Failed / Skipped / Total] 130 / 5 / 15 / 150:  50%|██████████▌          | 151/300 [26:53<26:31, 10.68s/it]

[Succeeded / Failed / Skipped / Total] 131 / 5 / 15 / 151:  50%|██████████▌          | 151/300 [26:53<26:31, 10.68s/it]

[Succeeded / Failed / Skipped / Total] 131 / 5 / 15 / 151:  51%|██████████▋          | 152/300 [27:17<26:33, 10.77s/it]

[Succeeded / Failed / Skipped / Total] 132 / 5 / 15 / 152:  51%|██████████▋          | 152/300 [27:17<26:33, 10.77s/it]

[Succeeded / Failed / Skipped / Total] 132 / 5 / 15 / 152:  51%|██████████▋          | 153/300 [27:23<26:19, 10.74s/it]

[Succeeded / Failed / Skipped / Total] 133 / 5 / 15 / 153:  51%|██████████▋          | 153/300 [27:23<26:19, 10.74s/it]

[Succeeded / Failed / Skipped / Total] 133 / 5 / 15 / 153:  51%|██████████▊          | 154/300 [27:28<26:02, 10.70s/it]

[Succeeded / Failed / Skipped / Total] 134 / 5 / 15 / 154:  51%|██████████▊          | 154/300 [27:28<26:02, 10.70s/it]

[Succeeded / Failed / Skipped 



[Succeeded / Failed / Skipped / Total] 172 / 7 / 21 / 200:  67%|██████████████       | 201/300 [36:35<18:01, 10.92s/it]

[Succeeded / Failed / Skipped / Total] 173 / 7 / 21 / 201:  67%|██████████████       | 201/300 [36:35<18:01, 10.92s/it]

[Succeeded / Failed / Skipped / Total] 173 / 7 / 21 / 201:  67%|██████████████▏      | 202/300 [36:45<17:49, 10.92s/it]

[Succeeded / Failed / Skipped / Total] 174 / 7 / 21 / 202:  67%|██████████████▏      | 202/300 [36:45<17:49, 10.92s/it]

[Succeeded / Failed / Skipped / Total] 174 / 7 / 21 / 202:  68%|██████████████▏      | 203/300 [37:20<17:50, 11.04s/it]

[Succeeded / Failed / Skipped / Total] 174 / 8 / 21 / 203:  68%|██████████████▏      | 203/300 [37:20<17:50, 11.04s/it]

[Succeeded / Failed / Skipped / Total] 174 / 8 / 21 / 203:  68%|██████████████▎      | 204/300 [37:24<17:36, 11.00s/it]

[Succeeded / Failed / Skipped / Total] 175 / 8 / 21 / 204:  68%|██████████████▎      | 204/300 [37:24<17:36, 11.00s/it]

[Succeeded / Failed / Skipped 



[Succeeded / Failed / Skipped / Total] 215 / 10 / 25 / 250:  84%|████████████████▋   | 251/300 [45:39<08:54, 10.92s/it]

[Succeeded / Failed / Skipped / Total] 216 / 10 / 25 / 251:  84%|████████████████▋   | 251/300 [45:39<08:54, 10.92s/it]

[Succeeded / Failed / Skipped / Total] 216 / 10 / 25 / 251:  84%|████████████████▊   | 252/300 [46:01<08:45, 10.96s/it]

[Succeeded / Failed / Skipped / Total] 217 / 10 / 25 / 252:  84%|████████████████▊   | 252/300 [46:01<08:45, 10.96s/it]

[Succeeded / Failed / Skipped / Total] 217 / 10 / 25 / 252:  84%|████████████████▊   | 253/300 [46:16<08:35, 10.97s/it]

[Succeeded / Failed / Skipped / Total] 218 / 10 / 25 / 253:  84%|████████████████▊   | 253/300 [46:16<08:35, 10.97s/it]

[Succeeded / Failed / Skipped / Total] 218 / 10 / 25 / 253:  85%|████████████████▉   | 254/300 [46:22<08:23, 10.96s/it]

[Succeeded / Failed / Skipped / Total] 219 / 10 / 25 / 254:  85%|████████████████▉   | 254/300 [46:22<08:23, 10.96s/it]

[Succeeded / Failed / Skipped 





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 259    |
| Number of failed attacks:     | 11     |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 3.67%  |
| Attack success rate:          | 95.93% |
| Average perturbed word %:     | 16.32% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 154.2  |
+-------------------------------+--------+


In [128]:
runAttack(bert_lr01_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr01'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr01sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 43 / 2 / 5 / 50:  17%|████▏                    | 50/300 [07:31<37:35,  9.02s/it]textattack: Saving checkpoint under "checkpoints\1722341906484.ta.chkpt" at 2024-07-30 20:18:26 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 87 / 2 / 11 / 100:  33%|███████▎              | 100/300 [15:40<31:21,  9.41s/it]textattack: Saving checkpoint under "checkpoints\1722342395941.ta.chkpt" at 2024-07-30 20:26:35 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 126 / 8 / 16 / 150:  50%|██████████▌          | 150/300 [25:26<25:26, 10.18s/it]textattack: Saving checkpoint under "checkpoints\1722342981819.ta.chkpt" at 2024-07-30 20:36:21 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 169 / 8 / 23 / 200:  67%|██████████████       | 200/300 [34:57<17:28, 10.49s/it]textattack: Saving checkpoint under "checkpoints\1722343552565.ta.chkpt" at 2024-07-30 20:45:52 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 213 / 10 / 27 / 250:  83%|████████████████▋   | 250/300 [43:46<08:45, 10.51s/it]textattack: Saving checkpoint under "checkpoints\1722344081634.ta.chkpt" at 2024-07-30 20:54:41 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 256 / 12 / 32 / 300: 100%|████████████████████| 300/300 [53:53<00:00, 10.78s/it]textattack: Saving checkpoint under "checkpoints\1722344689094.ta.chkpt" at 2024-07-30 21:04:49 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 256 / 12 / 32 / 300: 100%|████████████████████| 300/300 [53:53<00:00, 10.78s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 256    |
| Number of failed attacks:     | 12     |
| Number of skipped attacks:    | 32     |
| Original accuracy:            | 89.33% |
| Accuracy under attack:        | 4.0%   |
| Attack success rate:          | 95.52% |
| Average perturbed word %:     | 16.9%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 156.56 |
+-------------------------------+--------+


In [129]:
runAttack(bert_lr10_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr10'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr10sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 43 / 2 / 5 / 50:  17%|████▏                    | 50/300 [07:21<36:46,  8.83s/it]textattack: Saving checkpoint under "checkpoints\1722345130597.ta.chkpt" at 2024-07-30 21:12:10 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 87 / 2 / 11 / 100:  33%|███████▎              | 100/300 [15:10<30:21,  9.11s/it]textattack: Saving checkpoint under "checkpoints\1722345599832.ta.chkpt" at 2024-07-30 21:19:59 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 129 / 5 / 16 / 150:  50%|██████████▌          | 150/300 [24:28<24:28,  9.79s/it]textattack: Saving checkpoint under "checkpoints\1722346158095.ta.chkpt" at 2024-07-30 21:29:18 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 172 / 6 / 22 / 200:  67%|██████████████       | 200/300 [34:04<17:02, 10.22s/it]textattack: Saving checkpoint under "checkpoints\1722346733986.ta.chkpt" at 2024-07-30 21:38:53 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 216 / 8 / 26 / 250:  83%|█████████████████▌   | 250/300 [42:33<08:30, 10.21s/it]textattack: Saving checkpoint under "checkpoints\1722347242356.ta.chkpt" at 2024-07-30 21:47:22 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 260 / 9 / 31 / 300: 100%|█████████████████████| 300/300 [52:43<00:00, 10.55s/it]textattack: Saving checkpoint under "checkpoints\1722347852749.ta.chkpt" at 2024-07-30 21:57:32 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 260 / 9 / 31 / 300: 100%|█████████████████████| 300/300 [52:43<00:00, 10.55s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 260    |
| Number of failed attacks:     | 9      |
| Number of skipped attacks:    | 31     |
| Original accuracy:            | 89.67% |
| Accuracy under attack:        | 3.0%   |
| Attack success rate:          | 96.65% |
| Average perturbed word %:     | 16.35% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 151.88 |
+-------------------------------+--------+


In [130]:
runAttack(bert_rf7_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf7'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf7sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 32 / 5 / 13 / 50:  17%|████                    | 50/300 [05:16<26:20,  6.32s/it]textattack: Saving checkpoint under "checkpoints\1722348169152.ta.chkpt" at 2024-07-30 22:02:49 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 66 / 5 / 29 / 100:  33%|███████▎              | 100/300 [09:54<19:49,  5.95s/it]textattack: Saving checkpoint under "checkpoints\1722348447609.ta.chkpt" at 2024-07-30 22:07:27 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 103 / 7 / 40 / 150:  50%|██████████▌          | 150/300 [15:52<15:52,  6.35s/it]textattack: Saving checkpoint under "checkpoints\1722348805169.ta.chkpt" at 2024-07-30 22:13:25 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 135 / 9 / 56 / 200:  67%|██████████████       | 200/300 [24:04<12:02,  7.22s/it]textattack: Saving checkpoint under "checkpoints\1722349297930.ta.chkpt" at 2024-07-30 22:21:37 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 176 / 11 / 63 / 250:  83%|████████████████▋   | 250/300 [29:11<05:50,  7.01s/it]textattack: Saving checkpoint under "checkpoints\1722349604738.ta.chkpt" at 2024-07-30 22:26:44 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 213 / 13 / 74 / 300: 100%|████████████████████| 300/300 [35:08<00:00,  7.03s/it]textattack: Saving checkpoint under "checkpoints\1722349961532.ta.chkpt" at 2024-07-30 22:32:41 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 213 / 13 / 74 / 300: 100%|████████████████████| 300/300 [35:08<00:00,  7.03s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 213    |
| Number of failed attacks:     | 13     |
| Number of skipped attacks:    | 74     |
| Original accuracy:            | 75.33% |
| Accuracy under attack:        | 4.33%  |
| Attack success rate:          | 94.25% |
| Average perturbed word %:     | 8.76%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 110.92 |
+-------------------------------+--------+

In [131]:
runAttack(bert_rf14_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf14'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf14sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 39 / 2 / 9 / 50:  17%|████▏                    | 50/300 [07:40<38:23,  9.21s/it]textattack: Saving checkpoint under "checkpoints\1722350422389.ta.chkpt" at 2024-07-30 22:40:22 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 79 / 2 / 19 / 100:  33%|███████▎              | 100/300 [14:12<28:24,  8.52s/it]textattack: Saving checkpoint under "checkpoints\1722350813958.ta.chkpt" at 2024-07-30 22:46:53 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 117 / 6 / 27 / 150:  50%|██████████▌          | 150/300 [21:32<21:32,  8.62s/it]textattack: Saving checkpoint under "checkpoints\1722351254133.ta.chkpt" at 2024-07-30 22:54:14 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 146 / 11 / 43 / 200:  67%|█████████████▎      | 200/300 [31:59<15:59,  9.60s/it]textattack: Saving checkpoint under "checkpoints\1722351881287.ta.chkpt" at 2024-07-30 23:04:41 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 187 / 14 / 49 / 250:  83%|████████████████▋   | 250/300 [39:19<07:51,  9.44s/it]textattack: Saving checkpoint under "checkpoints\1722352321118.ta.chkpt" at 2024-07-30 23:12:01 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 226 / 17 / 57 / 300: 100%|████████████████████| 300/300 [48:19<00:00,  9.67s/it]textattack: Saving checkpoint under "checkpoints\1722352861554.ta.chkpt" at 2024-07-30 23:21:01 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 226 / 17 / 57 / 300: 100%|████████████████████| 300/300 [48:19<00:00,  9.67s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 226    |
| Number of failed attacks:     | 17     |
| Number of skipped attacks:    | 57     |
| Original accuracy:            | 81.0%  |
| Accuracy under attack:        | 5.67%  |
| Attack success rate:          | 93.0%  |
| Average perturbed word %:     | 10.9%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 142.56 |
+-------------------------------+--------+


In [132]:
runAttack(bert_rf30_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf30'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf30sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 37 / 7 / 6 / 50:  17%|████▏                    | 50/300 [08:09<40:47,  9.79s/it]textattack: Saving checkpoint under "checkpoints\1722353351257.ta.chkpt" at 2024-07-30 23:29:11 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 72 / 9 / 19 / 100:  33%|███████▎              | 100/300 [14:56<29:53,  8.97s/it]textattack: Saving checkpoint under "checkpoints\1722353758389.ta.chkpt" at 2024-07-30 23:35:58 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 108 / 16 / 26 / 150:  50%|██████████          | 150/300 [22:29<22:29,  9.00s/it]textattack: Saving checkpoint under "checkpoints\1722354211097.ta.chkpt" at 2024-07-30 23:43:31 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 142 / 19 / 39 / 200:  67%|█████████████▎      | 200/300 [33:28<16:44, 10.04s/it]textattack: Saving checkpoint under "checkpoints\1722354869773.ta.chkpt" at 2024-07-30 23:54:29 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 181 / 23 / 46 / 250:  83%|████████████████▋   | 250/300 [42:26<08:29, 10.19s/it]textattack: Saving checkpoint under "checkpoints\1722355408625.ta.chkpt" at 2024-07-31 00:03:28 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 221 / 26 / 53 / 300: 100%|████████████████████| 300/300 [50:59<00:00, 10.20s/it]textattack: Saving checkpoint under "checkpoints\1722355921402.ta.chkpt" at 2024-07-31 00:12:01 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 221 / 26 / 53 / 300: 100%|████████████████████| 300/300 [50:59<00:00, 10.20s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 221    |
| Number of failed attacks:     | 26     |
| Number of skipped attacks:    | 53     |
| Original accuracy:            | 82.33% |
| Accuracy under attack:        | 8.67%  |
| Attack success rate:          | 89.47% |
| Average perturbed word %:     | 10.37% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 151.55 |
+-------------------------------+--------+


In [133]:
runAttack(bert_knn7_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn7'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn7sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 29 / 10 / 11 / 50:  17%|███▌                 | 50/300 [28:16<2:21:22, 33.93s/it]textattack: Saving checkpoint under "checkpoints\1722357618180.ta.chkpt" at 2024-07-31 00:40:18 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 65 / 15 / 20 / 100:  33%|██████▎            | 100/300 [37:25<1:14:51, 22.46s/it]textattack: Saving checkpoint under "checkpoints\1722358167493.ta.chkpt" at 2024-07-31 00:49:27 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 95 / 23 / 32 / 150:  50%|██████████▌          | 150/300 [47:04<47:04, 18.83s/it]textattack: Saving checkpoint under "checkpoints\1722358746172.ta.chkpt" at 2024-07-31 00:59:06 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 124 / 31 / 45 / 200:  67%|█████████████▎      | 200/300 [58:19<29:09, 17.50s/it]textattack: Saving checkpoint under "checkpoints\1722359420987.ta.chkpt" at 2024-07-31 01:10:20 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 158 / 40 / 52 / 250:  83%|███████████████   | 250/300 [1:08:54<13:46, 16.54s/it]textattack: Saving checkpoint under "checkpoints\1722360056501.ta.chkpt" at 2024-07-31 01:20:56 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 196 / 46 / 58 / 300: 100%|██████████████████| 300/300 [1:18:10<00:00, 15.64s/it]textattack: Saving checkpoint under "checkpoints\1722360612185.ta.chkpt" at 2024-07-31 01:30:12 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 196 / 46 / 58 / 300: 100%|██████████████████| 300/300 [1:18:10<00:00, 15.64s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 196    |
| Number of failed attacks:     | 46     |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 80.67% |
| Accuracy under attack:        | 15.33% |
| Attack success rate:          | 80.99% |
| Average perturbed word %:     | 5.29%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 154.55 |
+-------------------------------+--------+


In [134]:
runAttack(bert_knn35_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn35'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn35sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 34 / 7 / 9 / 50:  17%|████▏                    | 50/300 [08:52<44:22, 10.65s/it]textattack: Saving checkpoint under "checkpoints\1722361145094.ta.chkpt" at 2024-07-31 01:39:05 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 70 / 11 / 19 / 100:  33%|███████              | 100/300 [17:33<35:07, 10.54s/it]textattack: Saving checkpoint under "checkpoints\1722361666527.ta.chkpt" at 2024-07-31 01:47:46 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 105 / 17 / 28 / 150:  50%|██████████          | 150/300 [27:53<27:53, 11.15s/it]textattack: Saving checkpoint under "checkpoints\1722362285875.ta.chkpt" at 2024-07-31 01:58:05 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 134 / 23 / 43 / 200:  67%|█████████████▎      | 200/300 [40:32<20:16, 12.16s/it]textattack: Saving checkpoint under "checkpoints\1722363045101.ta.chkpt" at 2024-07-31 02:10:45 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 170 / 29 / 51 / 250:  83%|████████████████▋   | 250/300 [50:24<10:04, 12.10s/it]textattack: Saving checkpoint under "checkpoints\1722363637629.ta.chkpt" at 2024-07-31 02:20:37 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 211 / 33 / 56 / 300: 100%|████████████████████| 300/300 [59:36<00:00, 11.92s/it]textattack: Saving checkpoint under "checkpoints\1722364189142.ta.chkpt" at 2024-07-31 02:29:49 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 211 / 33 / 56 / 300: 100%|████████████████████| 300/300 [59:36<00:00, 11.92s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 211    |
| Number of failed attacks:     | 33     |
| Number of skipped attacks:    | 56     |
| Original accuracy:            | 81.33% |
| Accuracy under attack:        | 11.0%  |
| Attack success rate:          | 86.48% |
| Average perturbed word %:     | 8.71%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 151.47 |
+-------------------------------+--------+


In [135]:
runAttack(bert_knn175_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn175'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn175sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 37 / 4 / 9 / 50:  17%|████▏                    | 50/300 [07:22<36:50,  8.84s/it]textattack: Saving checkpoint under "checkpoints\1722364631462.ta.chkpt" at 2024-07-31 02:37:11 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 75 / 5 / 20 / 100:  33%|███████▎              | 100/300 [14:17<28:35,  8.58s/it]textattack: Saving checkpoint under "checkpoints\1722365046984.ta.chkpt" at 2024-07-31 02:44:06 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 111 / 6 / 33 / 150:  50%|██████████▌          | 150/300 [21:44<21:44,  8.70s/it]textattack: Saving checkpoint under "checkpoints\1722365493625.ta.chkpt" at 2024-07-31 02:51:33 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 145 / 8 / 47 / 200:  67%|██████████████       | 200/300 [30:58<15:29,  9.29s/it]textattack: Saving checkpoint under "checkpoints\1722366048181.ta.chkpt" at 2024-07-31 03:00:48 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 185 / 11 / 54 / 250:  83%|████████████████▋   | 250/300 [39:02<07:48,  9.37s/it]textattack: Saving checkpoint under "checkpoints\1722366531712.ta.chkpt" at 2024-07-31 03:08:51 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 226 / 14 / 60 / 300: 100%|████████████████████| 300/300 [47:32<00:00,  9.51s/it]textattack: Saving checkpoint under "checkpoints\1722367041712.ta.chkpt" at 2024-07-31 03:17:21 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 226 / 14 / 60 / 300: 100%|████████████████████| 300/300 [47:32<00:00,  9.51s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 226    |
| Number of failed attacks:     | 14     |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 80.0%  |
| Accuracy under attack:        | 4.67%  |
| Attack success rate:          | 94.17% |
| Average perturbed word %:     | 10.01% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 123.75 |
+-------------------------------+--------+


#### CLIP

In [136]:
runAttack(clip_lr1_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr1'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr1sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 39 / 7 / 4 / 50:  17%|████▏                    | 50/300 [08:39<43:19, 10.40s/it]textattack: Saving checkpoint under "checkpoints\1722367561811.ta.chkpt" at 2024-07-31 03:26:01 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 82 / 9 / 9 / 100:  33%|███████▋               | 100/300 [15:38<31:16,  9.38s/it]textattack: Saving checkpoint under "checkpoints\1722367980220.ta.chkpt" at 2024-07-31 03:33:00 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 123 / 13 / 14 / 150:  50%|██████████          | 150/300 [22:37<22:37,  9.05s/it]textattack: Saving checkpoint under "checkpoints\1722368399800.ta.chkpt" at 2024-07-31 03:39:59 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 164 / 16 / 20 / 200:  67%|█████████████▎      | 200/300 [30:06<15:03,  9.03s/it]textattack: Saving checkpoint under "checkpoints\1722368848145.ta.chkpt" at 2024-07-31 03:47:28 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 207 / 19 / 24 / 250:  83%|████████████████▋   | 250/300 [37:02<07:24,  8.89s/it]textattack: Saving checkpoint under "checkpoints\1722369264675.ta.chkpt" at 2024-07-31 03:54:24 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 246 / 25 / 29 / 300: 100%|████████████████████| 300/300 [45:03<00:00,  9.01s/it]textattack: Saving checkpoint under "checkpoints\1722369744947.ta.chkpt" at 2024-07-31 04:02:24 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 246 / 25 / 29 / 300: 100%|████████████████████| 300/300 [45:03<00:00,  9.01s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 246    |
| Number of failed attacks:     | 25     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 8.33%  |
| Attack success rate:          | 90.77% |
| Average perturbed word %:     | 21.22% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 193.81 |
+-------------------------------+--------+


In [137]:
runAttack(clip_lr01_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr01'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr01sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 39 / 7 / 4 / 50:  17%|████▏                    | 50/300 [07:55<39:37,  9.51s/it]textattack: Saving checkpoint under "checkpoints\1722370220648.ta.chkpt" at 2024-07-31 04:10:20 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 82 / 9 / 9 / 100:  33%|███████▋               | 100/300 [14:30<29:01,  8.71s/it]textattack: Saving checkpoint under "checkpoints\1722370615635.ta.chkpt" at 2024-07-31 04:16:55 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 123 / 13 / 14 / 150:  50%|██████████          | 150/300 [21:13<21:13,  8.49s/it]textattack: Saving checkpoint under "checkpoints\1722371018642.ta.chkpt" at 2024-07-31 04:23:38 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 164 / 16 / 20 / 200:  67%|█████████████▎      | 200/300 [27:55<13:57,  8.38s/it]textattack: Saving checkpoint under "checkpoints\1722371420462.ta.chkpt" at 2024-07-31 04:30:20 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 207 / 19 / 24 / 250:  83%|████████████████▋   | 250/300 [34:47<06:57,  8.35s/it]textattack: Saving checkpoint under "checkpoints\1722371832144.ta.chkpt" at 2024-07-31 04:37:12 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 246 / 25 / 29 / 300: 100%|████████████████████| 300/300 [42:48<00:00,  8.56s/it]textattack: Saving checkpoint under "checkpoints\1722372313347.ta.chkpt" at 2024-07-31 04:45:13 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 246 / 25 / 29 / 300: 100%|████████████████████| 300/300 [42:48<00:00,  8.56s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 246    |
| Number of failed attacks:     | 25     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 8.33%  |
| Attack success rate:          | 90.77% |
| Average perturbed word %:     | 21.35% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 193.72 |
+-------------------------------+--------+


In [138]:
runAttack(clip_lr10_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr10'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr10sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 39 / 7 / 4 / 50:  17%|████▏                    | 50/300 [07:52<39:23,  9.46s/it]textattack: Saving checkpoint under "checkpoints\1722372786304.ta.chkpt" at 2024-07-31 04:53:06 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 82 / 9 / 9 / 100:  33%|███████▋               | 100/300 [14:30<29:00,  8.70s/it]textattack: Saving checkpoint under "checkpoints\1722373183704.ta.chkpt" at 2024-07-31 04:59:43 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 123 / 13 / 14 / 150:  50%|██████████          | 150/300 [21:18<21:18,  8.52s/it]textattack: Saving checkpoint under "checkpoints\1722373592182.ta.chkpt" at 2024-07-31 05:06:32 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 164 / 16 / 20 / 200:  67%|█████████████▎      | 200/300 [27:54<13:57,  8.37s/it]textattack: Saving checkpoint under "checkpoints\1722373987820.ta.chkpt" at 2024-07-31 05:13:07 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 207 / 19 / 24 / 250:  83%|████████████████▋   | 250/300 [34:47<06:57,  8.35s/it]textattack: Saving checkpoint under "checkpoints\1722374401051.ta.chkpt" at 2024-07-31 05:20:01 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 246 / 25 / 29 / 300: 100%|████████████████████| 300/300 [42:39<00:00,  8.53s/it]textattack: Saving checkpoint under "checkpoints\1722374873052.ta.chkpt" at 2024-07-31 05:27:53 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 246 / 25 / 29 / 300: 100%|████████████████████| 300/300 [42:39<00:00,  8.53s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 246    |
| Number of failed attacks:     | 25     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 8.33%  |
| Attack success rate:          | 90.77% |
| Average perturbed word %:     | 21.16% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 193.23 |
+-------------------------------+--------+


In [139]:
runAttack(clip_rf7_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf7'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf7sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 31 / 16 / 3 / 50:  17%|████                    | 50/300 [08:35<42:58, 10.31s/it]textattack: Saving checkpoint under "checkpoints\1722375388961.ta.chkpt" at 2024-07-31 05:36:28 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 61 / 28 / 11 / 100:  33%|███████              | 100/300 [17:09<34:19, 10.30s/it]textattack: Saving checkpoint under "checkpoints\1722375902891.ta.chkpt" at 2024-07-31 05:45:02 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 89 / 45 / 16 / 150:  50%|██████████▌          | 150/300 [26:21<26:21, 10.54s/it]textattack: Saving checkpoint under "checkpoints\1722376454814.ta.chkpt" at 2024-07-31 05:54:14 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 114 / 55 / 31 / 200:  67%|█████████████▎      | 200/300 [33:24<16:42, 10.02s/it]textattack: Saving checkpoint under "checkpoints\1722376877750.ta.chkpt" at 2024-07-31 06:01:17 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 141 / 71 / 38 / 250:  83%|████████████████▋   | 250/300 [42:15<08:27, 10.14s/it]textattack: Saving checkpoint under "checkpoints\1722377408450.ta.chkpt" at 2024-07-31 06:10:08 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 169 / 88 / 43 / 300: 100%|████████████████████| 300/300 [52:15<00:00, 10.45s/it]textattack: Saving checkpoint under "checkpoints\1722378008234.ta.chkpt" at 2024-07-31 06:20:08 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 169 / 88 / 43 / 300: 100%|████████████████████| 300/300 [52:15<00:00, 10.45s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 169    |
| Number of failed attacks:     | 88     |
| Number of skipped attacks:    | 43     |
| Original accuracy:            | 85.67% |
| Accuracy under attack:        | 29.33% |
| Attack success rate:          | 65.76% |
| Average perturbed word %:     | 18.3%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 244.04 |
+-------------------------------+--------+


In [140]:
runAttack(clip_rf14_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf14'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf14sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 27 / 21 / 2 / 50:  17%|████                    | 50/300 [10:13<51:05, 12.26s/it]textattack: Saving checkpoint under "checkpoints\1722378621484.ta.chkpt" at 2024-07-31 06:30:21 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 56 / 37 / 7 / 100:  33%|███████▎              | 100/300 [21:04<42:08, 12.64s/it]textattack: Saving checkpoint under "checkpoints\1722379272504.ta.chkpt" at 2024-07-31 06:41:12 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 82 / 55 / 13 / 150:  50%|██████████▌          | 150/300 [30:58<30:58, 12.39s/it]textattack: Saving checkpoint under "checkpoints\1722379866903.ta.chkpt" at 2024-07-31 06:51:06 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 105 / 72 / 23 / 200:  67%|█████████████▎      | 200/300 [39:18<19:39, 11.79s/it]textattack: Saving checkpoint under "checkpoints\1722380366424.ta.chkpt" at 2024-07-31 06:59:26 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 128 / 94 / 28 / 250:  83%|████████████████▋   | 250/300 [49:06<09:49, 11.79s/it]textattack: Saving checkpoint under "checkpoints\1722380954653.ta.chkpt" at 2024-07-31 07:09:14 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 149 / 118 / 33 / 300: 100%|█████████████████| 300/300 [1:01:00<00:00, 12.20s/it]textattack: Saving checkpoint under "checkpoints\1722381668864.ta.chkpt" at 2024-07-31 07:21:08 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 149 / 118 / 33 / 300: 100%|█████████████████| 300/300 [1:01:00<00:00, 12.20s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 149    |
| Number of failed attacks:     | 118    |
| Number of skipped attacks:    | 33     |
| Original accuracy:            | 89.0%  |
| Accuracy under attack:        | 39.33% |
| Attack success rate:          | 55.81% |
| Average perturbed word %:     | 17.7%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 272.51 |
+-------------------------------+--------+


In [141]:
runAttack(clip_rf30_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf30'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf30sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 25 / 23 / 2 / 50:  17%|████                    | 50/300 [11:52<59:21, 14.25s/it]textattack: Saving checkpoint under "checkpoints\1722382381330.ta.chkpt" at 2024-07-31 07:33:01 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 52 / 40 / 8 / 100:  33%|███████▎              | 100/300 [22:41<45:23, 13.62s/it]textattack: Saving checkpoint under "checkpoints\1722383030641.ta.chkpt" at 2024-07-31 07:43:50 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 75 / 63 / 12 / 150:  50%|██████████▌          | 150/300 [32:54<32:54, 13.16s/it]textattack: Saving checkpoint under "checkpoints\1722383643693.ta.chkpt" at 2024-07-31 07:54:03 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 99 / 80 / 21 / 200:  67%|██████████████       | 200/300 [40:52<20:26, 12.26s/it]textattack: Saving checkpoint under "checkpoints\1722384121607.ta.chkpt" at 2024-07-31 08:02:01 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 122 / 102 / 26 / 250:  83%|███████████████▊   | 250/300 [50:31<10:06, 12.13s/it]textattack: Saving checkpoint under "checkpoints\1722384700828.ta.chkpt" at 2024-07-31 08:11:40 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 144 / 126 / 30 / 300: 100%|█████████████████| 300/300 [1:01:48<00:00, 12.36s/it]textattack: Saving checkpoint under "checkpoints\1722385377517.ta.chkpt" at 2024-07-31 08:22:57 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 144 / 126 / 30 / 300: 100%|█████████████████| 300/300 [1:01:48<00:00, 12.36s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 144    |
| Number of failed attacks:     | 126    |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 42.0%  |
| Attack success rate:          | 53.33% |
| Average perturbed word %:     | 15.46% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 269.71 |
+-------------------------------+--------+


In [142]:
runAttack(clip_knn7_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn7'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn7sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 2 / 47 / 1 / 50:  17%|███▊                   | 50/300 [49:08<4:05:41, 58.97s/it]textattack: Saving checkpoint under "checkpoints\1722388325953.ta.chkpt" at 2024-07-31 09:12:05 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 14 / 82 / 4 / 100:  33%|██████            | 100/300 [1:05:39<2:11:18, 39.39s/it]textattack: Saving checkpoint under "checkpoints\1722389317079.ta.chkpt" at 2024-07-31 09:28:37 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 22 / 121 / 7 / 150:  50%|████████▌        | 150/300 [1:22:11<1:22:11, 32.88s/it]textattack: Saving checkpoint under "checkpoints\1722390309017.ta.chkpt" at 2024-07-31 09:45:09 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 31 / 155 / 14 / 200:  67%|████████████      | 200/300 [1:36:31<48:15, 28.96s/it]textattack: Saving checkpoint under "checkpoints\1722391168674.ta.chkpt" at 2024-07-31 09:59:28 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 41 / 192 / 17 / 250:  83%|███████████████   | 250/300 [1:53:31<22:42, 27.25s/it]textattack: Saving checkpoint under "checkpoints\1722392189229.ta.chkpt" at 2024-07-31 10:16:29 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 46 / 232 / 22 / 300: 100%|██████████████████| 300/300 [2:10:20<00:00, 26.07s/it]textattack: Saving checkpoint under "checkpoints\1722393198352.ta.chkpt" at 2024-07-31 10:33:18 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 46 / 232 / 22 / 300: 100%|██████████████████| 300/300 [2:10:20<00:00, 26.07s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 46     |
| Number of failed attacks:     | 232    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 77.33% |
| Attack success rate:          | 16.55% |
| Average perturbed word %:     | 5.7%   |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 361.9  |
+-------------------------------+--------+


In [143]:
runAttack(clip_knn35_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn35'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn35sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 11 / 39 / 0 / 50:  17%|███▋                  | 50/300 [15:40<1:18:24, 18.82s/it]textattack: Saving checkpoint under "checkpoints\1722394139377.ta.chkpt" at 2024-07-31 10:48:59 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 27 / 70 / 3 / 100:  33%|██████▋             | 100/300 [31:03<1:02:06, 18.63s/it]textattack: Saving checkpoint under "checkpoints\1722395061673.ta.chkpt" at 2024-07-31 11:04:21 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 44 / 100 / 6 / 150:  50%|██████████▌          | 150/300 [45:18<45:18, 18.12s/it]textattack: Saving checkpoint under "checkpoints\1722395917113.ta.chkpt" at 2024-07-31 11:18:37 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 56 / 131 / 13 / 200:  67%|█████████████▎      | 200/300 [59:05<29:32, 17.73s/it]textattack: Saving checkpoint under "checkpoints\1722396743784.ta.chkpt" at 2024-07-31 11:32:23 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 70 / 164 / 16 / 250:  83%|███████████████   | 250/300 [1:15:24<15:04, 18.10s/it]textattack: Saving checkpoint under "checkpoints\1722397722952.ta.chkpt" at 2024-07-31 11:48:42 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 79 / 199 / 22 / 300: 100%|██████████████████| 300/300 [1:31:07<00:00, 18.23s/it]textattack: Saving checkpoint under "checkpoints\1722398666419.ta.chkpt" at 2024-07-31 12:04:26 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 79 / 199 / 22 / 300: 100%|██████████████████| 300/300 [1:31:08<00:00, 18.23s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 79     |
| Number of failed attacks:     | 199    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 66.33% |
| Attack success rate:          | 28.42% |
| Average perturbed word %:     | 11.75% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 334.52 |
+-------------------------------+--------+


In [144]:
runAttack(clip_knn175_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn175'+suffix, target_ds_ag, 0.6, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn175sim06.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.6
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 16 / 33 / 1 / 50:  17%|███▋                  | 50/300 [13:39<1:08:17, 16.39s/it]textattack: Saving checkpoint under "checkpoints\1722399486134.ta.chkpt" at 2024-07-31 12:18:06 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 39 / 56 / 5 / 100:  33%|███████▎              | 100/300 [27:01<54:03, 16.22s/it]textattack: Saving checkpoint under "checkpoints\1722400288087.ta.chkpt" at 2024-07-31 12:31:28 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 61 / 80 / 9 / 150:  50%|███████████           | 150/300 [39:53<39:53, 15.96s/it]textattack: Saving checkpoint under "checkpoints\1722401059981.ta.chkpt" at 2024-07-31 12:44:19 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 77 / 102 / 21 / 200:  67%|█████████████▎      | 200/300 [51:54<25:57, 15.57s/it]textattack: Saving checkpoint under "checkpoints\1722401780967.ta.chkpt" at 2024-07-31 12:56:20 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 94 / 128 / 28 / 250:  83%|███████████████   | 250/300 [1:05:13<13:02, 15.65s/it]textattack: Saving checkpoint under "checkpoints\1722402580116.ta.chkpt" at 2024-07-31 13:09:40 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 107 / 159 / 34 / 300: 100%|█████████████████| 300/300 [1:20:24<00:00, 16.08s/it]textattack: Saving checkpoint under "checkpoints\1722403490642.ta.chkpt" at 2024-07-31 13:24:50 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 107 / 159 / 34 / 300: 100%|█████████████████| 300/300 [1:20:24<00:00, 16.08s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 107    |
| Number of failed attacks:     | 159    |
| Number of skipped attacks:    | 34     |
| Original accuracy:            | 88.67% |
| Accuracy under attack:        | 53.0%  |
| Attack success rate:          | 40.23% |
| Average perturbed word %:     | 20.22% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 310.11 |
+-------------------------------+--------+


In [145]:
et6 = datetime.datetime.now()
et6 - st

datetime.timedelta(seconds=65384, microseconds=897450)

### MinSim 0.7, threshold 0.5

In [146]:
suffix = 'sim07.csv'
thre = 1-0.5/np.pi

#### BERT

In [147]:
runAttack(bert_lr1_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr1'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr1sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 42 / 3 / 5 / 50:  17%|████▏                    | 50/300 [06:57<34:48,  8.35s/it]textattack: Saving checkpoint under "checkpoints\1722403908893.ta.chkpt" at 2024-07-31 13:31:48 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 83 / 7 / 10 / 100:  33%|███████▎              | 100/300 [14:07<28:14,  8.47s/it]textattack: Saving checkpoint under "checkpoints\1722404338281.ta.chkpt" at 2024-07-31 13:38:58 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 122 / 13 / 15 / 150:  50%|██████████          | 150/300 [21:52<21:52,  8.75s/it]textattack: Saving checkpoint under "checkpoints\1722404803349.ta.chkpt" at 2024-07-31 13:46:43 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 161 / 18 / 21 / 200:  67%|█████████████▎      | 200/300 [30:49<15:24,  9.25s/it]textattack: Saving checkpoint under "checkpoints\1722405340439.ta.chkpt" at 2024-07-31 13:55:40 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 203 / 22 / 25 / 250:  83%|████████████████▋   | 250/300 [37:54<07:34,  9.10s/it]textattack: Saving checkpoint under "checkpoints\1722405765702.ta.chkpt" at 2024-07-31 14:02:45 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 242 / 28 / 30 / 300: 100%|████████████████████| 300/300 [46:21<00:00,  9.27s/it]textattack: Saving checkpoint under "checkpoints\1722406272286.ta.chkpt" at 2024-07-31 14:11:12 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 242 / 28 / 30 / 300: 100%|████████████████████| 300/300 [46:21<00:00,  9.27s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 242    |
| Number of failed attacks:     | 28     |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 9.33%  |
| Attack success rate:          | 89.63% |
| Average perturbed word %:     | 18.56% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 120.01 |
+-------------------------------+--------+


In [148]:
runAttack(bert_lr01_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr01'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr01sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 40 / 5 / 5 / 50:  17%|████▏                    | 50/300 [06:10<30:50,  7.40s/it]textattack: Saving checkpoint under "checkpoints\1722406642656.ta.chkpt" at 2024-07-31 14:17:22 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 80 / 9 / 11 / 100:  33%|███████▎              | 100/300 [13:05<26:10,  7.85s/it]textattack: Saving checkpoint under "checkpoints\1722407058100.ta.chkpt" at 2024-07-31 14:24:18 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 118 / 16 / 16 / 150:  50%|██████████          | 150/300 [20:50<20:50,  8.34s/it]textattack: Saving checkpoint under "checkpoints\1722407523414.ta.chkpt" at 2024-07-31 14:32:03 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 156 / 21 / 23 / 200:  67%|█████████████▎      | 200/300 [28:58<14:29,  8.69s/it]textattack: Saving checkpoint under "checkpoints\1722408011094.ta.chkpt" at 2024-07-31 14:40:11 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 197 / 26 / 27 / 250:  83%|████████████████▋   | 250/300 [36:22<07:16,  8.73s/it]textattack: Saving checkpoint under "checkpoints\1722408455296.ta.chkpt" at 2024-07-31 14:47:35 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 234 / 34 / 32 / 300: 100%|████████████████████| 300/300 [44:22<00:00,  8.87s/it]textattack: Saving checkpoint under "checkpoints\1722408934683.ta.chkpt" at 2024-07-31 14:55:34 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 234 / 34 / 32 / 300: 100%|████████████████████| 300/300 [44:22<00:00,  8.87s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 234    |
| Number of failed attacks:     | 34     |
| Number of skipped attacks:    | 32     |
| Original accuracy:            | 89.33% |
| Accuracy under attack:        | 11.33% |
| Attack success rate:          | 87.31% |
| Average perturbed word %:     | 17.87% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 119.73 |
+-------------------------------+--------+


In [149]:
runAttack(bert_lr10_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr10'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr10sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 42 / 3 / 5 / 50:  17%|████▏                    | 50/300 [06:07<30:36,  7.34s/it]textattack: Saving checkpoint under "checkpoints\1722409302073.ta.chkpt" at 2024-07-31 15:01:42 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 84 / 5 / 11 / 100:  33%|███████▎              | 100/300 [12:50<25:41,  7.71s/it]textattack: Saving checkpoint under "checkpoints\1722409705535.ta.chkpt" at 2024-07-31 15:08:25 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 123 / 11 / 16 / 150:  50%|██████████          | 150/300 [20:11<20:11,  8.08s/it]textattack: Saving checkpoint under "checkpoints\1722410146346.ta.chkpt" at 2024-07-31 15:15:46 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 162 / 16 / 22 / 200:  67%|█████████████▎      | 200/300 [28:36<14:18,  8.58s/it]textattack: Saving checkpoint under "checkpoints\1722410651559.ta.chkpt" at 2024-07-31 15:24:11 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 202 / 22 / 26 / 250:  83%|████████████████▋   | 250/300 [35:43<07:08,  8.57s/it]textattack: Saving checkpoint under "checkpoints\1722411078203.ta.chkpt" at 2024-07-31 15:31:18 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 241 / 28 / 31 / 300: 100%|████████████████████| 300/300 [43:48<00:00,  8.76s/it]textattack: Saving checkpoint under "checkpoints\1722411563766.ta.chkpt" at 2024-07-31 15:39:23 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 241 / 28 / 31 / 300: 100%|████████████████████| 300/300 [43:48<00:00,  8.76s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 241    |
| Number of failed attacks:     | 28     |
| Number of skipped attacks:    | 31     |
| Original accuracy:            | 89.67% |
| Accuracy under attack:        | 9.33%  |
| Attack success rate:          | 89.59% |
| Average perturbed word %:     | 18.39% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 118.55 |
+-------------------------------+--------+


In [150]:
runAttack(bert_rf7_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf7'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf7sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 33 / 4 / 13 / 50:  17%|████                    | 50/300 [03:47<18:55,  4.54s/it]textattack: Saving checkpoint under "checkpoints\1722411791187.ta.chkpt" at 2024-07-31 15:43:11 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 65 / 6 / 29 / 100:  33%|███████▎              | 100/300 [07:38<15:16,  4.58s/it]textattack: Saving checkpoint under "checkpoints\1722412022204.ta.chkpt" at 2024-07-31 15:47:02 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 98 / 12 / 40 / 150:  50%|██████████▌          | 150/300 [12:12<12:12,  4.88s/it]textattack: Saving checkpoint under "checkpoints\1722412296579.ta.chkpt" at 2024-07-31 15:51:36 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 125 / 19 / 56 / 200:  67%|█████████████▎      | 200/300 [18:44<09:22,  5.62s/it]textattack: Saving checkpoint under "checkpoints\1722412688331.ta.chkpt" at 2024-07-31 15:58:08 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 165 / 22 / 63 / 250:  83%|████████████████▋   | 250/300 [22:48<04:33,  5.47s/it]textattack: Saving checkpoint under "checkpoints\1722412932153.ta.chkpt" at 2024-07-31 16:02:12 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 200 / 26 / 74 / 300: 100%|████████████████████| 300/300 [27:53<00:00,  5.58s/it]textattack: Saving checkpoint under "checkpoints\1722413237575.ta.chkpt" at 2024-07-31 16:07:17 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 200 / 26 / 74 / 300: 100%|████████████████████| 300/300 [27:53<00:00,  5.58s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 200    |
| Number of failed attacks:     | 26     |
| Number of skipped attacks:    | 74     |
| Original accuracy:            | 75.33% |
| Accuracy under attack:        | 8.67%  |
| Attack success rate:          | 88.5%  |
| Average perturbed word %:     | 9.49%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 87.59  |
+-------------------------------+--------+


In [151]:
runAttack(bert_rf14_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf14'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf14sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 36 / 5 / 9 / 50:  17%|████▏                    | 50/300 [05:36<28:01,  6.73s/it]textattack: Saving checkpoint under "checkpoints\1722413574091.ta.chkpt" at 2024-07-31 16:12:54 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 72 / 9 / 19 / 100:  33%|███████▎              | 100/300 [10:28<20:57,  6.29s/it]textattack: Saving checkpoint under "checkpoints\1722413866473.ta.chkpt" at 2024-07-31 16:17:46 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 109 / 14 / 27 / 150:  50%|██████████          | 150/300 [16:31<16:31,  6.61s/it]textattack: Saving checkpoint under "checkpoints\1722414229282.ta.chkpt" at 2024-07-31 16:23:49 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 129 / 28 / 43 / 200:  67%|█████████████▎      | 200/300 [24:11<12:05,  7.26s/it]textattack: Saving checkpoint under "checkpoints\1722414689303.ta.chkpt" at 2024-07-31 16:31:29 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 164 / 37 / 49 / 250:  83%|████████████████▋   | 250/300 [30:58<06:11,  7.44s/it]textattack: Saving checkpoint under "checkpoints\1722415096477.ta.chkpt" at 2024-07-31 16:38:16 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 200 / 43 / 57 / 300: 100%|████████████████████| 300/300 [38:13<00:00,  7.64s/it]textattack: Saving checkpoint under "checkpoints\1722415530747.ta.chkpt" at 2024-07-31 16:45:30 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 200 / 43 / 57 / 300: 100%|████████████████████| 300/300 [38:13<00:00,  7.64s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 200    |
| Number of failed attacks:     | 43     |
| Number of skipped attacks:    | 57     |
| Original accuracy:            | 81.0%  |
| Accuracy under attack:        | 14.33% |
| Attack success rate:          | 82.3%  |
| Average perturbed word %:     | 10.89% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 113.42 |
+-------------------------------+--------+


In [152]:
runAttack(bert_rf30_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf30'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf30sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 37 / 7 / 6 / 50:  17%|████▏                    | 50/300 [06:33<32:47,  7.87s/it]textattack: Saving checkpoint under "checkpoints\1722415924908.ta.chkpt" at 2024-07-31 16:52:04 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 68 / 13 / 19 / 100:  33%|███████              | 100/300 [12:00<24:01,  7.21s/it]textattack: Saving checkpoint under "checkpoints\1722416252025.ta.chkpt" at 2024-07-31 16:57:32 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 98 / 26 / 26 / 150:  50%|██████████▌          | 150/300 [18:39<18:39,  7.46s/it]textattack: Saving checkpoint under "checkpoints\1722416650653.ta.chkpt" at 2024-07-31 17:04:10 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 126 / 35 / 39 / 200:  67%|█████████████▎      | 200/300 [26:28<13:14,  7.94s/it]textattack: Saving checkpoint under "checkpoints\1722417119689.ta.chkpt" at 2024-07-31 17:11:59 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 158 / 46 / 46 / 250:  83%|████████████████▋   | 250/300 [34:32<06:54,  8.29s/it]textattack: Saving checkpoint under "checkpoints\1722417603719.ta.chkpt" at 2024-07-31 17:20:03 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 193 / 54 / 53 / 300: 100%|████████████████████| 300/300 [41:54<00:00,  8.38s/it]textattack: Saving checkpoint under "checkpoints\1722418046271.ta.chkpt" at 2024-07-31 17:27:26 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 193 / 54 / 53 / 300: 100%|████████████████████| 300/300 [41:54<00:00,  8.38s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 193    |
| Number of failed attacks:     | 54     |
| Number of skipped attacks:    | 53     |
| Original accuracy:            | 82.33% |
| Accuracy under attack:        | 18.0%  |
| Attack success rate:          | 78.14% |
| Average perturbed word %:     | 10.29% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 115.71 |
+-------------------------------+--------+


In [153]:
runAttack(bert_knn7_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn7'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn7sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 31 / 8 / 11 / 50:  17%|███▋                  | 50/300 [32:23<2:41:57, 38.87s/it]textattack: Saving checkpoint under "checkpoints\1722419989922.ta.chkpt" at 2024-07-31 17:59:49 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 63 / 17 / 20 / 100:  33%|██████▎            | 100/300 [40:25<1:20:51, 24.26s/it]textattack: Saving checkpoint under "checkpoints\1722420472211.ta.chkpt" at 2024-07-31 18:07:52 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 89 / 29 / 32 / 150:  50%|██████████▌          | 150/300 [48:03<48:03, 19.22s/it]textattack: Saving checkpoint under "checkpoints\1722420930033.ta.chkpt" at 2024-07-31 18:15:30 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 118 / 37 / 45 / 200:  67%|█████████████▎      | 200/300 [56:09<28:04, 16.85s/it]textattack: Saving checkpoint under "checkpoints\1722421415735.ta.chkpt" at 2024-07-31 18:23:35 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 148 / 50 / 52 / 250:  83%|███████████████   | 250/300 [1:04:43<12:56, 15.54s/it]textattack: Saving checkpoint under "checkpoints\1722421930236.ta.chkpt" at 2024-07-31 18:32:10 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 185 / 57 / 58 / 300: 100%|██████████████████| 300/300 [1:12:00<00:00, 14.40s/it]textattack: Saving checkpoint under "checkpoints\1722422367376.ta.chkpt" at 2024-07-31 18:39:27 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 185 / 57 / 58 / 300: 100%|██████████████████| 300/300 [1:12:01<00:00, 14.40s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 185    |
| Number of failed attacks:     | 57     |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 80.67% |
| Accuracy under attack:        | 19.0%  |
| Attack success rate:          | 76.45% |
| Average perturbed word %:     | 5.28%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 112.05 |
+-------------------------------+--------+


In [154]:
runAttack(bert_knn35_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn35'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn35sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 34 / 7 / 9 / 50:  17%|████▏                    | 50/300 [06:35<32:59,  7.92s/it]textattack: Saving checkpoint under "checkpoints\1722422763444.ta.chkpt" at 2024-07-31 18:46:03 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 68 / 13 / 19 / 100:  33%|███████              | 100/300 [14:01<28:03,  8.42s/it]textattack: Saving checkpoint under "checkpoints\1722423209269.ta.chkpt" at 2024-07-31 18:53:29 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 102 / 20 / 28 / 150:  50%|██████████          | 150/300 [21:40<21:40,  8.67s/it]textattack: Saving checkpoint under "checkpoints\1722423668094.ta.chkpt" at 2024-07-31 19:01:08 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 127 / 30 / 43 / 200:  67%|█████████████▎      | 200/300 [30:51<15:25,  9.26s/it]textattack: Saving checkpoint under "checkpoints\1722424219269.ta.chkpt" at 2024-07-31 19:10:19 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 160 / 39 / 51 / 250:  83%|████████████████▋   | 250/300 [38:54<07:46,  9.34s/it]textattack: Saving checkpoint under "checkpoints\1722424701840.ta.chkpt" at 2024-07-31 19:18:21 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 197 / 47 / 56 / 300: 100%|████████████████████| 300/300 [46:07<00:00,  9.22s/it]textattack: Saving checkpoint under "checkpoints\1722425134607.ta.chkpt" at 2024-07-31 19:25:34 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 197 / 47 / 56 / 300: 100%|████████████████████| 300/300 [46:07<00:00,  9.22s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 197    |
| Number of failed attacks:     | 47     |
| Number of skipped attacks:    | 56     |
| Original accuracy:            | 81.33% |
| Accuracy under attack:        | 15.67% |
| Attack success rate:          | 80.74% |
| Average perturbed word %:     | 9.09%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 110.27 |
+-------------------------------+--------+


In [155]:
runAttack(bert_knn175_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn175'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn175sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 37 / 4 / 9 / 50:  17%|████▏                    | 50/300 [05:34<27:53,  6.70s/it]textattack: Saving checkpoint under "checkpoints\1722425469567.ta.chkpt" at 2024-07-31 19:31:09 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 75 / 5 / 20 / 100:  33%|███████▎              | 100/300 [11:39<23:18,  6.99s/it]textattack: Saving checkpoint under "checkpoints\1722425834015.ta.chkpt" at 2024-07-31 19:37:14 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 108 / 9 / 33 / 150:  50%|██████████▌          | 150/300 [18:27<18:27,  7.38s/it]textattack: Saving checkpoint under "checkpoints\1722426241972.ta.chkpt" at 2024-07-31 19:44:01 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 140 / 13 / 47 / 200:  67%|█████████████▎      | 200/300 [26:22<13:11,  7.91s/it]textattack: Saving checkpoint under "checkpoints\1722426717024.ta.chkpt" at 2024-07-31 19:51:57 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 180 / 16 / 54 / 250:  83%|████████████████▋   | 250/300 [33:57<06:47,  8.15s/it]textattack: Saving checkpoint under "checkpoints\1722427172462.ta.chkpt" at 2024-07-31 19:59:32 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 219 / 21 / 60 / 300: 100%|████████████████████| 300/300 [41:16<00:00,  8.26s/it]textattack: Saving checkpoint under "checkpoints\1722427611441.ta.chkpt" at 2024-07-31 20:06:51 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 219 / 21 / 60 / 300: 100%|████████████████████| 300/300 [41:16<00:00,  8.26s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 219    |
| Number of failed attacks:     | 21     |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 80.0%  |
| Accuracy under attack:        | 7.0%   |
| Attack success rate:          | 91.25% |
| Average perturbed word %:     | 11.05% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 95.52  |
+-------------------------------+--------+


#### CLIP

In [156]:
runAttack(clip_lr1_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr1'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr1sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 31 / 15 / 4 / 50:  17%|████                    | 50/300 [06:53<34:26,  8.27s/it]textattack: Saving checkpoint under "checkpoints\1722428025005.ta.chkpt" at 2024-07-31 20:13:45 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 70 / 21 / 9 / 100:  33%|███████▎              | 100/300 [12:26<24:53,  7.47s/it]textattack: Saving checkpoint under "checkpoints\1722428358363.ta.chkpt" at 2024-07-31 20:19:18 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 105 / 31 / 14 / 150:  50%|██████████          | 150/300 [17:54<17:54,  7.17s/it]textattack: Saving checkpoint under "checkpoints\1722428686591.ta.chkpt" at 2024-07-31 20:24:46 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 142 / 38 / 20 / 200:  67%|█████████████▎      | 200/300 [23:39<11:49,  7.10s/it]textattack: Saving checkpoint under "checkpoints\1722429031045.ta.chkpt" at 2024-07-31 20:30:31 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 180 / 46 / 24 / 250:  83%|████████████████▋   | 250/300 [29:09<05:49,  7.00s/it]textattack: Saving checkpoint under "checkpoints\1722429361260.ta.chkpt" at 2024-07-31 20:36:01 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 211 / 60 / 29 / 300: 100%|████████████████████| 300/300 [35:07<00:00,  7.03s/it]textattack: Saving checkpoint under "checkpoints\1722429719499.ta.chkpt" at 2024-07-31 20:41:59 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 211 / 60 / 29 / 300: 100%|████████████████████| 300/300 [35:07<00:00,  7.03s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 211    |
| Number of failed attacks:     | 60     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 20.0%  |
| Attack success rate:          | 77.86% |
| Average perturbed word %:     | 21.98% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 142.8  |
+-------------------------------+--------+


In [157]:
runAttack(clip_lr01_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr01'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr01sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 31 / 15 / 4 / 50:  17%|████                    | 50/300 [06:10<30:53,  7.41s/it]textattack: Saving checkpoint under "checkpoints\1722430090328.ta.chkpt" at 2024-07-31 20:48:10 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 70 / 21 / 9 / 100:  33%|███████▎              | 100/300 [11:40<23:20,  7.00s/it]textattack: Saving checkpoint under "checkpoints\1722430419894.ta.chkpt" at 2024-07-31 20:53:39 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 105 / 31 / 14 / 150:  50%|██████████          | 150/300 [16:57<16:57,  6.78s/it]textattack: Saving checkpoint under "checkpoints\1722430736643.ta.chkpt" at 2024-07-31 20:58:56 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 142 / 38 / 20 / 200:  67%|█████████████▎      | 200/300 [22:11<11:05,  6.66s/it]textattack: Saving checkpoint under "checkpoints\1722431051617.ta.chkpt" at 2024-07-31 21:04:11 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 179 / 47 / 24 / 250:  83%|████████████████▋   | 250/300 [27:38<05:31,  6.63s/it]textattack: Saving checkpoint under "checkpoints\1722431377939.ta.chkpt" at 2024-07-31 21:09:37 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 210 / 61 / 29 / 300: 100%|████████████████████| 300/300 [33:39<00:00,  6.73s/it]textattack: Saving checkpoint under "checkpoints\1722431739011.ta.chkpt" at 2024-07-31 21:15:39 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 210 / 61 / 29 / 300: 100%|████████████████████| 300/300 [33:39<00:00,  6.73s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 210    |
| Number of failed attacks:     | 61     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 20.33% |
| Attack success rate:          | 77.49% |
| Average perturbed word %:     | 22.06% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 143.28 |
+-------------------------------+--------+


In [158]:
runAttack(clip_lr10_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr10'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr10sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 31 / 15 / 4 / 50:  17%|████                    | 50/300 [06:10<30:50,  7.40s/it]textattack: Saving checkpoint under "checkpoints\1722432109250.ta.chkpt" at 2024-07-31 21:21:49 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 70 / 21 / 9 / 100:  33%|███████▎              | 100/300 [11:36<23:13,  6.97s/it]textattack: Saving checkpoint under "checkpoints\1722432436123.ta.chkpt" at 2024-07-31 21:27:16 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 105 / 31 / 14 / 150:  50%|██████████          | 150/300 [16:50<16:50,  6.74s/it]textattack: Saving checkpoint under "checkpoints\1722432749512.ta.chkpt" at 2024-07-31 21:32:29 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 142 / 38 / 20 / 200:  67%|█████████████▎      | 200/300 [22:04<11:02,  6.62s/it]textattack: Saving checkpoint under "checkpoints\1722433064047.ta.chkpt" at 2024-07-31 21:37:44 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 179 / 47 / 24 / 250:  83%|████████████████▋   | 250/300 [27:27<05:29,  6.59s/it]textattack: Saving checkpoint under "checkpoints\1722433386701.ta.chkpt" at 2024-07-31 21:43:06 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 210 / 61 / 29 / 300: 100%|████████████████████| 300/300 [33:21<00:00,  6.67s/it]textattack: Saving checkpoint under "checkpoints\1722433740804.ta.chkpt" at 2024-07-31 21:49:00 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 210 / 61 / 29 / 300: 100%|████████████████████| 300/300 [33:21<00:00,  6.67s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 210    |
| Number of failed attacks:     | 61     |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 20.33% |
| Attack success rate:          | 77.49% |
| Average perturbed word %:     | 21.91% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 142.83 |
+-------------------------------+--------+


In [159]:
runAttack(clip_rf7_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf7'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf7sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 26 / 21 / 3 / 50:  17%|████                    | 50/300 [06:35<32:56,  7.91s/it]textattack: Saving checkpoint under "checkpoints\1722434136295.ta.chkpt" at 2024-07-31 21:55:36 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 51 / 38 / 11 / 100:  33%|███████              | 100/300 [12:59<25:59,  7.80s/it]textattack: Saving checkpoint under "checkpoints\1722434520701.ta.chkpt" at 2024-07-31 22:02:00 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 75 / 59 / 16 / 150:  50%|██████████▌          | 150/300 [19:32<19:32,  7.82s/it]textattack: Saving checkpoint under "checkpoints\1722434913294.ta.chkpt" at 2024-07-31 22:08:33 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 96 / 73 / 31 / 200:  67%|██████████████       | 200/300 [24:19<12:09,  7.30s/it]textattack: Saving checkpoint under "checkpoints\1722435200376.ta.chkpt" at 2024-07-31 22:13:20 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 120 / 92 / 38 / 250:  83%|████████████████▋   | 250/300 [30:34<06:06,  7.34s/it]textattack: Saving checkpoint under "checkpoints\1722435575351.ta.chkpt" at 2024-07-31 22:19:35 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 142 / 115 / 43 / 300: 100%|███████████████████| 300/300 [38:07<00:00,  7.63s/it]textattack: Saving checkpoint under "checkpoints\1722436028780.ta.chkpt" at 2024-07-31 22:27:08 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 142 / 115 / 43 / 300: 100%|███████████████████| 300/300 [38:07<00:00,  7.63s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 142    |
| Number of failed attacks:     | 115    |
| Number of skipped attacks:    | 43     |
| Original accuracy:            | 85.67% |
| Accuracy under attack:        | 38.33% |
| Attack success rate:          | 55.25% |
| Average perturbed word %:     | 19.1%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 168.56 |
+-------------------------------+--------+


In [160]:
runAttack(clip_rf14_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf14'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf14sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 18 / 30 / 2 / 50:  17%|████                    | 50/300 [07:45<38:49,  9.32s/it]textattack: Saving checkpoint under "checkpoints\1722436494875.ta.chkpt" at 2024-07-31 22:34:54 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 39 / 54 / 7 / 100:  33%|███████▎              | 100/300 [15:45<31:30,  9.45s/it]textattack: Saving checkpoint under "checkpoints\1722436973938.ta.chkpt" at 2024-07-31 22:42:53 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 62 / 75 / 13 / 150:  50%|██████████▌          | 150/300 [22:36<22:36,  9.04s/it]textattack: Saving checkpoint under "checkpoints\1722437385543.ta.chkpt" at 2024-07-31 22:49:45 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 84 / 93 / 23 / 200:  67%|██████████████       | 200/300 [28:24<14:12,  8.52s/it]textattack: Saving checkpoint under "checkpoints\1722437733596.ta.chkpt" at 2024-07-31 22:55:33 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 102 / 120 / 28 / 250:  83%|███████████████▊   | 250/300 [35:31<07:06,  8.52s/it]textattack: Saving checkpoint under "checkpoints\1722438159998.ta.chkpt" at 2024-07-31 23:02:39 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 119 / 148 / 33 / 300: 100%|███████████████████| 300/300 [43:29<00:00,  8.70s/it]textattack: Saving checkpoint under "checkpoints\1722438638308.ta.chkpt" at 2024-07-31 23:10:38 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 119 / 148 / 33 / 300: 100%|███████████████████| 300/300 [43:29<00:00,  8.70s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 119    |
| Number of failed attacks:     | 148    |
| Number of skipped attacks:    | 33     |
| Original accuracy:            | 89.0%  |
| Accuracy under attack:        | 49.33% |
| Attack success rate:          | 44.57% |
| Average perturbed word %:     | 17.27% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 178.92 |
+-------------------------------+--------+


In [161]:
runAttack(clip_rf30_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf30'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf30sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 20 / 28 / 2 / 50:  17%|████                    | 50/300 [08:47<43:59, 10.56s/it]textattack: Saving checkpoint under "checkpoints\1722439166409.ta.chkpt" at 2024-07-31 23:19:26 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 42 / 50 / 8 / 100:  33%|███████▎              | 100/300 [16:05<32:11,  9.66s/it]textattack: Saving checkpoint under "checkpoints\1722439604272.ta.chkpt" at 2024-07-31 23:26:44 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 61 / 77 / 12 / 150:  50%|██████████▌          | 150/300 [23:16<23:16,  9.31s/it]textattack: Saving checkpoint under "checkpoints\1722440034835.ta.chkpt" at 2024-07-31 23:33:54 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 77 / 102 / 21 / 200:  67%|█████████████▎      | 200/300 [29:29<14:44,  8.85s/it]textattack: Saving checkpoint under "checkpoints\1722440408409.ta.chkpt" at 2024-07-31 23:40:08 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 96 / 128 / 26 / 250:  83%|████████████████▋   | 250/300 [36:54<07:22,  8.86s/it]textattack: Saving checkpoint under "checkpoints\1722440852850.ta.chkpt" at 2024-07-31 23:47:32 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 114 / 156 / 30 / 300: 100%|███████████████████| 300/300 [44:28<00:00,  8.90s/it]textattack: Saving checkpoint under "checkpoints\1722441307072.ta.chkpt" at 2024-07-31 23:55:07 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 114 / 156 / 30 / 300: 100%|███████████████████| 300/300 [44:28<00:00,  8.90s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 114    |
| Number of failed attacks:     | 156    |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 52.0%  |
| Attack success rate:          | 42.22% |
| Average perturbed word %:     | 15.03% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 179.76 |
+-------------------------------+--------+

In [162]:
runAttack(clip_knn7_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn7'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn7sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 2 / 47 / 1 / 50:  17%|███▊                   | 50/300 [45:22<3:46:53, 54.45s/it]textattack: Saving checkpoint under "checkpoints\1722444029974.ta.chkpt" at 2024-08-01 00:40:29 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 9 / 87 / 4 / 100:  33%|███████              | 100/300 [57:14<1:54:28, 34.34s/it]textattack: Saving checkpoint under "checkpoints\1722444741585.ta.chkpt" at 2024-08-01 00:52:21 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 15 / 128 / 7 / 150:  50%|████████▌        | 150/300 [1:08:10<1:08:10, 27.27s/it]textattack: Saving checkpoint under "checkpoints\1722445397491.ta.chkpt" at 2024-08-01 01:03:17 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 23 / 163 / 14 / 200:  67%|████████████      | 200/300 [1:17:35<38:47, 23.28s/it]textattack: Saving checkpoint under "checkpoints\1722445962550.ta.chkpt" at 2024-08-01 01:12:42 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 31 / 202 / 17 / 250:  83%|███████████████   | 250/300 [1:28:39<17:43, 21.28s/it]textattack: Saving checkpoint under "checkpoints\1722446626580.ta.chkpt" at 2024-08-01 01:23:46 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 34 / 244 / 22 / 300: 100%|██████████████████| 300/300 [1:39:43<00:00, 19.95s/it]textattack: Saving checkpoint under "checkpoints\1722447291174.ta.chkpt" at 2024-08-01 01:34:51 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 34 / 244 / 22 / 300: 100%|██████████████████| 300/300 [1:39:43<00:00, 19.95s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 34     |
| Number of failed attacks:     | 244    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 81.33% |
| Attack success rate:          | 12.23% |
| Average perturbed word %:     | 4.61%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 216.61 |
+-------------------------------+--------+


In [163]:
runAttack(clip_knn35_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn35'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn35sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 9 / 41 / 0 / 50:  17%|████▏                    | 50/300 [10:48<54:00, 12.96s/it]textattack: Saving checkpoint under "checkpoints\1722447939425.ta.chkpt" at 2024-08-01 01:45:39 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 20 / 77 / 3 / 100:  33%|███████▎              | 100/300 [21:45<43:31, 13.06s/it]textattack: Saving checkpoint under "checkpoints\1722448597202.ta.chkpt" at 2024-08-01 01:56:37 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 34 / 110 / 6 / 150:  50%|██████████▌          | 150/300 [31:30<31:30, 12.60s/it]textattack: Saving checkpoint under "checkpoints\1722449181639.ta.chkpt" at 2024-08-01 02:06:21 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 44 / 143 / 13 / 200:  67%|█████████████▎      | 200/300 [40:38<20:19, 12.19s/it]textattack: Saving checkpoint under "checkpoints\1722449729382.ta.chkpt" at 2024-08-01 02:15:29 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 55 / 179 / 16 / 250:  83%|████████████████▋   | 250/300 [51:24<10:16, 12.34s/it]textattack: Saving checkpoint under "checkpoints\1722450375746.ta.chkpt" at 2024-08-01 02:26:15 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 63 / 215 / 22 / 300: 100%|██████████████████| 300/300 [1:01:43<00:00, 12.35s/it]textattack: Saving checkpoint under "checkpoints\1722450995156.ta.chkpt" at 2024-08-01 02:36:35 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 63 / 215 / 22 / 300: 100%|██████████████████| 300/300 [1:01:43<00:00, 12.35s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 63     |
| Number of failed attacks:     | 215    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 71.67% |
| Attack success rate:          | 22.66% |
| Average perturbed word %:     | 11.17% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 206.32 |
+-------------------------------+--------+


In [164]:
runAttack(clip_knn175_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn175'+suffix, target_ds_ag, 0.7, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn175sim07.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.7
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 12 / 37 / 1 / 50:  17%|████                    | 50/300 [09:56<49:41, 11.93s/it]textattack: Saving checkpoint under "checkpoints\1722451591735.ta.chkpt" at 2024-08-01 02:46:31 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 32 / 63 / 5 / 100:  33%|███████▎              | 100/300 [19:29<38:59, 11.70s/it]textattack: Saving checkpoint under "checkpoints\1722452165135.ta.chkpt" at 2024-08-01 02:56:05 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 52 / 89 / 9 / 150:  50%|███████████           | 150/300 [28:19<28:19, 11.33s/it]textattack: Saving checkpoint under "checkpoints\1722452694849.ta.chkpt" at 2024-08-01 03:04:54 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 63 / 116 / 21 / 200:  67%|█████████████▎      | 200/300 [36:48<18:24, 11.04s/it]textattack: Saving checkpoint under "checkpoints\1722453203849.ta.chkpt" at 2024-08-01 03:13:23 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 79 / 143 / 28 / 250:  83%|████████████████▋   | 250/300 [45:57<09:11, 11.03s/it]textattack: Saving checkpoint under "checkpoints\1722453752469.ta.chkpt" at 2024-08-01 03:22:32 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 90 / 176 / 34 / 300: 100%|████████████████████| 300/300 [55:57<00:00, 11.19s/it]textattack: Saving checkpoint under "checkpoints\1722454352411.ta.chkpt" at 2024-08-01 03:32:32 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 90 / 176 / 34 / 300: 100%|████████████████████| 300/300 [55:57<00:00, 11.19s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 90     |
| Number of failed attacks:     | 176    |
| Number of skipped attacks:    | 34     |
| Original accuracy:            | 88.67% |
| Accuracy under attack:        | 58.67% |
| Attack success rate:          | 33.83% |
| Average perturbed word %:     | 20.38% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 195.57 |
+-------------------------------+--------+


In [165]:
et7 = datetime.datetime.now()
et7 - et6

datetime.timedelta(seconds=50861, microseconds=862338)

### MinSim 0.8, threshold 0.5

In [166]:
suffix = 'sim08.csv'
thre = 1-0.5/np.pi

#### BERT

In [167]:
runAttack(bert_lr1_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr1'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr1sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 31 / 14 / 5 / 50:  17%|████                    | 50/300 [05:51<29:19,  7.04s/it]textattack: Saving checkpoint under "checkpoints\1722454705242.ta.chkpt" at 2024-08-01 03:38:25 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 64 / 26 / 10 / 100:  33%|███████              | 100/300 [11:51<23:42,  7.11s/it]textattack: Saving checkpoint under "checkpoints\1722455064392.ta.chkpt" at 2024-08-01 03:44:24 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 93 / 42 / 15 / 150:  50%|██████████▌          | 150/300 [17:49<17:49,  7.13s/it]textattack: Saving checkpoint under "checkpoints\1722455423016.ta.chkpt" at 2024-08-01 03:50:23 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 124 / 55 / 21 / 200:  67%|█████████████▎      | 200/300 [24:17<12:08,  7.29s/it]textattack: Saving checkpoint under "checkpoints\1722455810300.ta.chkpt" at 2024-08-01 03:56:50 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 148 / 77 / 25 / 250:  83%|████████████████▋   | 250/300 [30:52<06:10,  7.41s/it]textattack: Saving checkpoint under "checkpoints\1722456205718.ta.chkpt" at 2024-08-01 04:03:25 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 173 / 97 / 30 / 300: 100%|████████████████████| 300/300 [37:14<00:00,  7.45s/it]textattack: Saving checkpoint under "checkpoints\1722456588155.ta.chkpt" at 2024-08-01 04:09:48 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 173 / 97 / 30 / 300: 100%|████████████████████| 300/300 [37:14<00:00,  7.45s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 173    |
| Number of failed attacks:     | 97     |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 32.33% |
| Attack success rate:          | 64.07% |
| Average perturbed word %:     | 17.48% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 87.84  |
+-------------------------------+--------+


In [168]:
runAttack(bert_lr01_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr01'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr01sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 28 / 17 / 5 / 50:  17%|████                    | 50/300 [05:24<27:02,  6.49s/it]textattack: Saving checkpoint under "checkpoints\1722456913646.ta.chkpt" at 2024-08-01 04:15:13 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 59 / 30 / 11 / 100:  33%|███████              | 100/300 [10:42<21:24,  6.42s/it]textattack: Saving checkpoint under "checkpoints\1722457231254.ta.chkpt" at 2024-08-01 04:20:31 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 88 / 46 / 16 / 150:  50%|██████████▌          | 150/300 [16:11<16:11,  6.48s/it]textattack: Saving checkpoint under "checkpoints\1722457560440.ta.chkpt" at 2024-08-01 04:26:00 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 117 / 60 / 23 / 200:  67%|█████████████▎      | 200/300 [22:03<11:01,  6.62s/it]textattack: Saving checkpoint under "checkpoints\1722457912253.ta.chkpt" at 2024-08-01 04:31:52 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 146 / 77 / 27 / 250:  83%|████████████████▋   | 250/300 [28:08<05:37,  6.75s/it]textattack: Saving checkpoint under "checkpoints\1722458277648.ta.chkpt" at 2024-08-01 04:37:57 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 172 / 96 / 32 / 300: 100%|████████████████████| 300/300 [34:30<00:00,  6.90s/it]textattack: Saving checkpoint under "checkpoints\1722458659677.ta.chkpt" at 2024-08-01 04:44:19 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 172 / 96 / 32 / 300: 100%|████████████████████| 300/300 [34:30<00:00,  6.90s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 172    |
| Number of failed attacks:     | 96     |
| Number of skipped attacks:    | 32     |
| Original accuracy:            | 89.33% |
| Accuracy under attack:        | 32.0%  |
| Attack success rate:          | 64.18% |
| Average perturbed word %:     | 18.35% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 88.7   |
+-------------------------------+--------+


In [169]:
runAttack(bert_lr10_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr10'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr10sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 32 / 13 / 5 / 50:  17%|████                    | 50/300 [05:13<26:09,  6.28s/it]textattack: Saving checkpoint under "checkpoints\1722458973755.ta.chkpt" at 2024-08-01 04:49:33 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 66 / 23 / 11 / 100:  33%|███████              | 100/300 [10:33<21:06,  6.33s/it]textattack: Saving checkpoint under "checkpoints\1722459292993.ta.chkpt" at 2024-08-01 04:54:52 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 95 / 39 / 16 / 150:  50%|██████████▌          | 150/300 [16:01<16:01,  6.41s/it]textattack: Saving checkpoint under "checkpoints\1722459620810.ta.chkpt" at 2024-08-01 05:00:20 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 126 / 52 / 22 / 200:  67%|█████████████▎      | 200/300 [21:53<10:56,  6.57s/it]textattack: Saving checkpoint under "checkpoints\1722459973113.ta.chkpt" at 2024-08-01 05:06:13 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 151 / 73 / 26 / 250:  83%|████████████████▋   | 250/300 [27:52<05:34,  6.69s/it]textattack: Saving checkpoint under "checkpoints\1722460331879.ta.chkpt" at 2024-08-01 05:12:11 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 176 / 93 / 31 / 300: 100%|████████████████████| 300/300 [34:04<00:00,  6.82s/it]textattack: Saving checkpoint under "checkpoints\1722460704679.ta.chkpt" at 2024-08-01 05:18:24 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 176 / 93 / 31 / 300: 100%|████████████████████| 300/300 [34:04<00:00,  6.82s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 176    |
| Number of failed attacks:     | 93     |
| Number of skipped attacks:    | 31     |
| Original accuracy:            | 89.67% |
| Accuracy under attack:        | 31.0%  |
| Attack success rate:          | 65.43% |
| Average perturbed word %:     | 17.77% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 87.68  |
+-------------------------------+--------+


In [170]:
runAttack(bert_rf7_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf7'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf7sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 30 / 7 / 13 / 50:  17%|████                    | 50/300 [03:12<16:00,  3.84s/it]textattack: Saving checkpoint under "checkpoints\1722460896876.ta.chkpt" at 2024-08-01 05:21:36 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 59 / 12 / 29 / 100:  33%|███████              | 100/300 [06:19<12:39,  3.80s/it]textattack: Saving checkpoint under "checkpoints\1722461084477.ta.chkpt" at 2024-08-01 05:24:44 after 100 attacks.
[Succeeded / Failed / Skipped / Total] 59 / 12 / 30 / 101:  34%|███████              | 101/300 [06:19<12:28,  3.76s/it]

[Succeeded / Failed / Skipped / Total] 89 / 21 / 40 / 150:  50%|██████████▌          | 150/300 [10:10<10:10,  4.07s/it]textattack: Saving checkpoint under "checkpoints\1722461314958.ta.chkpt" at 2024-08-01 05:28:34 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 114 / 30 / 56 / 200:  67%|█████████████▎      | 200/300 [14:20<07:10,  4.30s/it]textattack: Saving checkpoint under "checkpoints\1722461565110.ta.chkpt" at 2024-08-01 05:32:45 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 150 / 37 / 63 / 250:  83%|████████████████▋   | 250/300 [18:10<03:38,  4.36s/it]textattack: Saving checkpoint under "checkpoints\1722461795545.ta.chkpt" at 2024-08-01 05:36:35 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 180 / 46 / 74 / 300: 100%|████████████████████| 300/300 [22:12<00:00,  4.44s/it]textattack: Saving checkpoint under "checkpoints\1722462037171.ta.chkpt" at 2024-08-01 05:40:37 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 180 / 46 / 74 / 300: 100%|████████████████████| 300/300 [22:12<00:00,  4.44s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 180    |
| Number of failed attacks:     | 46     |
| Number of skipped attacks:    | 74     |
| Original accuracy:            | 75.33% |
| Accuracy under attack:        | 15.33% |
| Attack success rate:          | 79.65% |
| Average perturbed word %:     | 10.17% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 67.33  |
+-------------------------------+--------+


In [171]:
runAttack(bert_rf14_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf14'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf14sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 31 / 10 / 9 / 50:  17%|████                    | 50/300 [04:13<21:05,  5.06s/it]textattack: Saving checkpoint under "checkpoints\1722462290556.ta.chkpt" at 2024-08-01 05:44:50 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 61 / 20 / 19 / 100:  33%|███████              | 100/300 [08:22<16:44,  5.02s/it]textattack: Saving checkpoint under "checkpoints\1722462539740.ta.chkpt" at 2024-08-01 05:48:59 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 90 / 33 / 27 / 150:  50%|██████████▌          | 150/300 [12:46<12:46,  5.11s/it]textattack: Saving checkpoint under "checkpoints\1722462803984.ta.chkpt" at 2024-08-01 05:53:23 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 110 / 47 / 43 / 200:  67%|█████████████▎      | 200/300 [17:46<08:53,  5.33s/it]textattack: Saving checkpoint under "checkpoints\1722463103962.ta.chkpt" at 2024-08-01 05:58:23 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 141 / 60 / 49 / 250:  83%|████████████████▋   | 250/300 [22:58<04:35,  5.51s/it]textattack: Saving checkpoint under "checkpoints\1722463415552.ta.chkpt" at 2024-08-01 06:03:35 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 169 / 74 / 57 / 300: 100%|████████████████████| 300/300 [28:21<00:00,  5.67s/it]textattack: Saving checkpoint under "checkpoints\1722463739099.ta.chkpt" at 2024-08-01 06:08:59 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 169 / 74 / 57 / 300: 100%|████████████████████| 300/300 [28:21<00:00,  5.67s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 169    |
| Number of failed attacks:     | 74     |
| Number of skipped attacks:    | 57     |
| Original accuracy:            | 81.0%  |
| Accuracy under attack:        | 24.67% |
| Attack success rate:          | 69.55% |
| Average perturbed word %:     | 11.52% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 79.07  |
+-------------------------------+--------+


In [172]:
runAttack(bert_rf30_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf30'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf30sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 33 / 11 / 6 / 50:  17%|████                    | 50/300 [05:08<25:41,  6.17s/it]textattack: Saving checkpoint under "checkpoints\1722464047626.ta.chkpt" at 2024-08-01 06:14:07 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 57 / 24 / 19 / 100:  33%|███████              | 100/300 [09:33<19:06,  5.73s/it]textattack: Saving checkpoint under "checkpoints\1722464312395.ta.chkpt" at 2024-08-01 06:18:32 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 83 / 41 / 26 / 150:  50%|██████████▌          | 150/300 [14:17<14:17,  5.72s/it]textattack: Saving checkpoint under "checkpoints\1722464597012.ta.chkpt" at 2024-08-01 06:23:17 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 108 / 53 / 39 / 200:  67%|█████████████▎      | 200/300 [19:14<09:37,  5.77s/it]textattack: Saving checkpoint under "checkpoints\1722464893788.ta.chkpt" at 2024-08-01 06:28:13 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 132 / 72 / 46 / 250:  83%|████████████████▋   | 250/300 [24:36<04:55,  5.91s/it]textattack: Saving checkpoint under "checkpoints\1722465215912.ta.chkpt" at 2024-08-01 06:33:35 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 160 / 87 / 53 / 300: 100%|████████████████████| 300/300 [30:04<00:00,  6.01s/it]textattack: Saving checkpoint under "checkpoints\1722465543775.ta.chkpt" at 2024-08-01 06:39:03 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 160 / 87 / 53 / 300: 100%|████████████████████| 300/300 [30:04<00:00,  6.02s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 160    |
| Number of failed attacks:     | 87     |
| Number of skipped attacks:    | 53     |
| Original accuracy:            | 82.33% |
| Accuracy under attack:        | 29.0%  |
| Attack success rate:          | 64.78% |
| Average perturbed word %:     | 10.48% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 80.47  |
+-------------------------------+--------+


In [173]:
runAttack(bert_knn7_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn7'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn7sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 22 / 17 / 11 / 50:  17%|███▌                 | 50/300 [32:32<2:42:42, 39.05s/it]textattack: Saving checkpoint under "checkpoints\1722467496501.ta.chkpt" at 2024-08-01 07:11:36 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 50 / 30 / 20 / 100:  33%|██████▎            | 100/300 [38:06<1:16:12, 22.86s/it]textattack: Saving checkpoint under "checkpoints\1722467829963.ta.chkpt" at 2024-08-01 07:17:09 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 74 / 44 / 32 / 150:  50%|██████████▌          | 150/300 [43:28<43:28, 17.39s/it]textattack: Saving checkpoint under "checkpoints\1722468152375.ta.chkpt" at 2024-08-01 07:22:32 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 95 / 60 / 45 / 200:  67%|██████████████       | 200/300 [49:52<24:56, 14.96s/it]textattack: Saving checkpoint under "checkpoints\1722468535917.ta.chkpt" at 2024-08-01 07:28:55 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 123 / 75 / 52 / 250:  83%|████████████████▋   | 250/300 [56:28<11:17, 13.55s/it]textattack: Saving checkpoint under "checkpoints\1722468932243.ta.chkpt" at 2024-08-01 07:35:32 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 152 / 90 / 58 / 300: 100%|██████████████████| 300/300 [1:02:54<00:00, 12.58s/it]textattack: Saving checkpoint under "checkpoints\1722469318701.ta.chkpt" at 2024-08-01 07:41:58 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 152 / 90 / 58 / 300: 100%|██████████████████| 300/300 [1:02:54<00:00, 12.58s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 152    |
| Number of failed attacks:     | 90     |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 80.67% |
| Accuracy under attack:        | 30.0%  |
| Attack success rate:          | 62.81% |
| Average perturbed word %:     | 4.99%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 78.16  |
+-------------------------------+--------+


In [174]:
runAttack(bert_knn35_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn35'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn35sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 29 / 12 / 9 / 50:  17%|████                    | 50/300 [05:14<26:14,  6.30s/it]textattack: Saving checkpoint under "checkpoints\1722469633798.ta.chkpt" at 2024-08-01 07:47:13 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 56 / 25 / 19 / 100:  33%|███████              | 100/300 [11:05<22:10,  6.65s/it]textattack: Saving checkpoint under "checkpoints\1722469984164.ta.chkpt" at 2024-08-01 07:53:04 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 81 / 41 / 28 / 150:  50%|██████████▌          | 150/300 [17:12<17:12,  6.88s/it]textattack: Saving checkpoint under "checkpoints\1722470351167.ta.chkpt" at 2024-08-01 07:59:11 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 98 / 59 / 43 / 200:  67%|██████████████       | 200/300 [23:58<11:59,  7.19s/it]textattack: Saving checkpoint under "checkpoints\1722470757220.ta.chkpt" at 2024-08-01 08:05:57 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 124 / 75 / 51 / 250:  83%|████████████████▋   | 250/300 [30:53<06:10,  7.42s/it]textattack: Saving checkpoint under "checkpoints\1722471172839.ta.chkpt" at 2024-08-01 08:12:52 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 151 / 93 / 56 / 300: 100%|████████████████████| 300/300 [37:32<00:00,  7.51s/it]textattack: Saving checkpoint under "checkpoints\1722471571396.ta.chkpt" at 2024-08-01 08:19:31 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 151 / 93 / 56 / 300: 100%|████████████████████| 300/300 [37:32<00:00,  7.51s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 151    |
| Number of failed attacks:     | 93     |
| Number of skipped attacks:    | 56     |
| Original accuracy:            | 81.33% |
| Accuracy under attack:        | 31.0%  |
| Attack success rate:          | 61.89% |
| Average perturbed word %:     | 8.28%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 79.64  |
+-------------------------------+--------+


In [175]:
runAttack(bert_knn175_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn175'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn175sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 35 / 6 / 9 / 50:  17%|████▏                    | 50/300 [04:47<23:59,  5.76s/it]textattack: Saving checkpoint under "checkpoints\1722471859404.ta.chkpt" at 2024-08-01 08:24:19 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 65 / 15 / 20 / 100:  33%|███████              | 100/300 [09:58<19:56,  5.98s/it]textattack: Saving checkpoint under "checkpoints\1722472169549.ta.chkpt" at 2024-08-01 08:29:29 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 92 / 25 / 33 / 150:  50%|██████████▌          | 150/300 [14:51<14:51,  5.94s/it]textattack: Saving checkpoint under "checkpoints\1722472462625.ta.chkpt" at 2024-08-01 08:34:22 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 117 / 36 / 47 / 200:  67%|█████████████▎      | 200/300 [21:05<10:32,  6.33s/it]textattack: Saving checkpoint under "checkpoints\1722472837115.ta.chkpt" at 2024-08-01 08:40:37 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 150 / 46 / 54 / 250:  83%|████████████████▋   | 250/300 [27:20<05:28,  6.56s/it]textattack: Saving checkpoint under "checkpoints\1722473212250.ta.chkpt" at 2024-08-01 08:46:52 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 187 / 53 / 60 / 300: 100%|████████████████████| 300/300 [33:30<00:00,  6.70s/it]textattack: Saving checkpoint under "checkpoints\1722473582347.ta.chkpt" at 2024-08-01 08:53:02 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 187 / 53 / 60 / 300: 100%|████████████████████| 300/300 [33:30<00:00,  6.70s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 187    |
| Number of failed attacks:     | 53     |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 80.0%  |
| Accuracy under attack:        | 17.67% |
| Attack success rate:          | 77.92% |
| Average perturbed word %:     | 11.3%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 72.6   |
+-------------------------------+--------+


#### CLIP

In [176]:
runAttack(clip_lr1_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr1'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr1sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 16 / 30 / 4 / 50:  17%|████                    | 50/300 [05:11<25:58,  6.23s/it]textattack: Saving checkpoint under "checkpoints\1722473894191.ta.chkpt" at 2024-08-01 08:58:14 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 34 / 57 / 9 / 100:  33%|███████▎              | 100/300 [10:06<20:13,  6.07s/it]textattack: Saving checkpoint under "checkpoints\1722474189268.ta.chkpt" at 2024-08-01 09:03:09 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 60 / 76 / 14 / 150:  50%|██████████▌          | 150/300 [14:19<14:19,  5.73s/it]textattack: Saving checkpoint under "checkpoints\1722474442192.ta.chkpt" at 2024-08-01 09:07:22 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 85 / 95 / 20 / 200:  67%|██████████████       | 200/300 [18:35<09:17,  5.58s/it]textattack: Saving checkpoint under "checkpoints\1722474697942.ta.chkpt" at 2024-08-01 09:11:37 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 106 / 120 / 24 / 250:  83%|███████████████▊   | 250/300 [23:16<04:39,  5.59s/it]textattack: Saving checkpoint under "checkpoints\1722474979314.ta.chkpt" at 2024-08-01 09:16:19 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 127 / 144 / 29 / 300: 100%|███████████████████| 300/300 [27:45<00:00,  5.55s/it]textattack: Saving checkpoint under "checkpoints\1722475247896.ta.chkpt" at 2024-08-01 09:20:47 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 127 / 144 / 29 / 300: 100%|███████████████████| 300/300 [27:45<00:00,  5.55s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 127    |
| Number of failed attacks:     | 144    |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 48.0%  |
| Attack success rate:          | 46.86% |
| Average perturbed word %:     | 21.28% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 100.82 |
+-------------------------------+--------+


In [177]:
runAttack(clip_lr01_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr01'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr01sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 16 / 30 / 4 / 50:  17%|████                    | 50/300 [04:36<23:03,  5.53s/it]textattack: Saving checkpoint under "checkpoints\1722475524778.ta.chkpt" at 2024-08-01 09:25:24 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 34 / 57 / 9 / 100:  33%|███████▎              | 100/300 [09:19<18:39,  5.60s/it]textattack: Saving checkpoint under "checkpoints\1722475807679.ta.chkpt" at 2024-08-01 09:30:07 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 60 / 76 / 14 / 150:  50%|██████████▌          | 150/300 [13:22<13:22,  5.35s/it]textattack: Saving checkpoint under "checkpoints\1722476050037.ta.chkpt" at 2024-08-01 09:34:10 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 84 / 96 / 20 / 200:  67%|██████████████       | 200/300 [17:33<08:46,  5.27s/it]textattack: Saving checkpoint under "checkpoints\1722476301379.ta.chkpt" at 2024-08-01 09:38:21 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 105 / 121 / 24 / 250:  83%|███████████████▊   | 250/300 [22:13<04:26,  5.33s/it]textattack: Saving checkpoint under "checkpoints\1722476581439.ta.chkpt" at 2024-08-01 09:43:01 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 126 / 145 / 29 / 300: 100%|███████████████████| 300/300 [26:40<00:00,  5.33s/it]textattack: Saving checkpoint under "checkpoints\1722476848403.ta.chkpt" at 2024-08-01 09:47:28 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 126 / 145 / 29 / 300: 100%|███████████████████| 300/300 [26:40<00:00,  5.33s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 126    |
| Number of failed attacks:     | 145    |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 48.33% |
| Attack success rate:          | 46.49% |
| Average perturbed word %:     | 21.27% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 101.1  |
+-------------------------------+--------+


In [178]:
runAttack(clip_lr10_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr10'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr10sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 17 / 29 / 4 / 50:  17%|████                    | 50/300 [04:38<23:10,  5.56s/it]textattack: Saving checkpoint under "checkpoints\1722477126667.ta.chkpt" at 2024-08-01 09:52:06 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 35 / 56 / 9 / 100:  33%|███████▎              | 100/300 [09:22<18:44,  5.62s/it]textattack: Saving checkpoint under "checkpoints\1722477410997.ta.chkpt" at 2024-08-01 09:56:50 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 61 / 75 / 14 / 150:  50%|██████████▌          | 150/300 [13:27<13:27,  5.38s/it]textattack: Saving checkpoint under "checkpoints\1722477656233.ta.chkpt" at 2024-08-01 10:00:56 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 86 / 94 / 20 / 200:  67%|██████████████       | 200/300 [17:36<08:48,  5.28s/it]textattack: Saving checkpoint under "checkpoints\1722477905559.ta.chkpt" at 2024-08-01 10:05:05 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 107 / 119 / 24 / 250:  83%|███████████████▊   | 250/300 [22:18<04:27,  5.35s/it]textattack: Saving checkpoint under "checkpoints\1722478186912.ta.chkpt" at 2024-08-01 10:09:46 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 128 / 143 / 29 / 300: 100%|███████████████████| 300/300 [26:43<00:00,  5.34s/it]textattack: Saving checkpoint under "checkpoints\1722478451816.ta.chkpt" at 2024-08-01 10:14:11 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 128 / 143 / 29 / 300: 100%|███████████████████| 300/300 [26:43<00:00,  5.34s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 128    |
| Number of failed attacks:     | 143    |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 47.67% |
| Attack success rate:          | 47.23% |
| Average perturbed word %:     | 21.4%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 100.84 |
+-------------------------------+--------+


In [179]:
runAttack(clip_rf7_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf7'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf7sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 16 / 31 / 3 / 50:  17%|████                    | 50/300 [04:28<22:24,  5.38s/it]textattack: Saving checkpoint under "checkpoints\1722478721014.ta.chkpt" at 2024-08-01 10:18:41 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 34 / 55 / 11 / 100:  33%|███████              | 100/300 [09:02<18:05,  5.43s/it]textattack: Saving checkpoint under "checkpoints\1722478994876.ta.chkpt" at 2024-08-01 10:23:14 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 49 / 85 / 16 / 150:  50%|██████████▌          | 150/300 [13:40<13:40,  5.47s/it]textattack: Saving checkpoint under "checkpoints\1722479272598.ta.chkpt" at 2024-08-01 10:27:52 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 62 / 107 / 31 / 200:  67%|█████████████▎      | 200/300 [16:50<08:25,  5.05s/it]textattack: Saving checkpoint under "checkpoints\1722479462700.ta.chkpt" at 2024-08-01 10:31:02 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 77 / 135 / 38 / 250:  83%|████████████████▋   | 250/300 [21:07<04:13,  5.07s/it]textattack: Saving checkpoint under "checkpoints\1722479719915.ta.chkpt" at 2024-08-01 10:35:19 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 88 / 169 / 43 / 300: 100%|████████████████████| 300/300 [26:16<00:00,  5.25s/it]textattack: Saving checkpoint under "checkpoints\1722480028197.ta.chkpt" at 2024-08-01 10:40:28 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 88 / 169 / 43 / 300: 100%|████████████████████| 300/300 [26:16<00:00,  5.25s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 88     |
| Number of failed attacks:     | 169    |
| Number of skipped attacks:    | 43     |
| Original accuracy:            | 85.67% |
| Accuracy under attack:        | 56.33% |
| Attack success rate:          | 34.24% |
| Average perturbed word %:     | 15.64% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 103.36 |
+-------------------------------+--------+


In [180]:
runAttack(clip_rf14_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf14'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf14sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 7 / 41 / 2 / 50:  17%|████▏                    | 50/300 [05:15<26:19,  6.32s/it]textattack: Saving checkpoint under "checkpoints\1722480344248.ta.chkpt" at 2024-08-01 10:45:44 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 18 / 75 / 7 / 100:  33%|███████▎              | 100/300 [10:13<20:27,  6.14s/it]textattack: Saving checkpoint under "checkpoints\1722480642330.ta.chkpt" at 2024-08-01 10:50:42 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 31 / 106 / 13 / 150:  50%|██████████          | 150/300 [15:03<15:03,  6.02s/it]textattack: Saving checkpoint under "checkpoints\1722480931763.ta.chkpt" at 2024-08-01 10:55:31 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 45 / 132 / 23 / 200:  67%|█████████████▎      | 200/300 [18:51<09:25,  5.66s/it]textattack: Saving checkpoint under "checkpoints\1722481160083.ta.chkpt" at 2024-08-01 10:59:20 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 58 / 164 / 28 / 250:  83%|████████████████▋   | 250/300 [23:35<04:43,  5.66s/it]textattack: Saving checkpoint under "checkpoints\1722481443530.ta.chkpt" at 2024-08-01 11:04:03 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 66 / 201 / 33 / 300: 100%|████████████████████| 300/300 [28:49<00:00,  5.77s/it]textattack: Saving checkpoint under "checkpoints\1722481757903.ta.chkpt" at 2024-08-01 11:09:17 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 66 / 201 / 33 / 300: 100%|████████████████████| 300/300 [28:49<00:00,  5.77s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 66     |
| Number of failed attacks:     | 201    |
| Number of skipped attacks:    | 33     |
| Original accuracy:            | 89.0%  |
| Accuracy under attack:        | 67.0%  |
| Attack success rate:          | 24.72% |
| Average perturbed word %:     | 12.94% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 107.75 |
+-------------------------------+--------+


In [181]:
runAttack(clip_rf30_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf30'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf30sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 10 / 38 / 2 / 50:  17%|████                    | 50/300 [05:29<27:29,  6.60s/it]textattack: Saving checkpoint under "checkpoints\1722482087901.ta.chkpt" at 2024-08-01 11:14:47 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 25 / 67 / 8 / 100:  33%|███████▎              | 100/300 [10:22<20:44,  6.22s/it]textattack: Saving checkpoint under "checkpoints\1722482380037.ta.chkpt" at 2024-08-01 11:19:40 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 39 / 99 / 12 / 150:  50%|██████████▌          | 150/300 [15:01<15:01,  6.01s/it]textattack: Saving checkpoint under "checkpoints\1722482659442.ta.chkpt" at 2024-08-01 11:24:19 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 54 / 125 / 21 / 200:  67%|█████████████▎      | 200/300 [18:48<09:24,  5.64s/it]textattack: Saving checkpoint under "checkpoints\1722482886684.ta.chkpt" at 2024-08-01 11:28:06 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 68 / 156 / 26 / 250:  83%|████████████████▋   | 250/300 [23:29<04:41,  5.64s/it]textattack: Saving checkpoint under "checkpoints\1722483167221.ta.chkpt" at 2024-08-01 11:32:47 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 78 / 192 / 30 / 300: 100%|████████████████████| 300/300 [28:34<00:00,  5.72s/it]textattack: Saving checkpoint under "checkpoints\1722483472958.ta.chkpt" at 2024-08-01 11:37:52 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 78 / 192 / 30 / 300: 100%|████████████████████| 300/300 [28:34<00:00,  5.72s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 78     |
| Number of failed attacks:     | 192    |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 64.0%  |
| Attack success rate:          | 28.89% |
| Average perturbed word %:     | 11.72% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 105.22 |
+-------------------------------+--------+


In [182]:
runAttack(clip_knn7_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn7'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn7sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 2 / 47 / 1 / 50:  17%|███▊                   | 50/300 [39:15<3:16:17, 47.11s/it]textattack: Saving checkpoint under "checkpoints\1722485828613.ta.chkpt" at 2024-08-01 12:17:08 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 8 / 88 / 4 / 100:  33%|███████              | 100/300 [46:37<1:33:15, 27.98s/it]textattack: Saving checkpoint under "checkpoints\1722486270869.ta.chkpt" at 2024-08-01 12:24:30 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 11 / 132 / 7 / 150:  50%|██████████▌          | 150/300 [53:46<53:46, 21.51s/it]textattack: Saving checkpoint under "checkpoints\1722486699722.ta.chkpt" at 2024-08-01 12:31:39 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 15 / 171 / 14 / 200:  67%|████████████      | 200/300 [1:00:24<30:12, 18.12s/it]textattack: Saving checkpoint under "checkpoints\1722487097102.ta.chkpt" at 2024-08-01 12:38:17 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 18 / 215 / 17 / 250:  83%|███████████████   | 250/300 [1:08:03<13:36, 16.34s/it]textattack: Saving checkpoint under "checkpoints\1722487556948.ta.chkpt" at 2024-08-01 12:45:56 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 21 / 257 / 22 / 300: 100%|██████████████████| 300/300 [1:15:10<00:00, 15.03s/it]textattack: Saving checkpoint under "checkpoints\1722487983224.ta.chkpt" at 2024-08-01 12:53:03 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 21 / 257 / 22 / 300: 100%|██████████████████| 300/300 [1:15:10<00:00, 15.03s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 21     |
| Number of failed attacks:     | 257    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 85.67% |
| Attack success rate:          | 7.55%  |
| Average perturbed word %:     | 4.35%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 117.41 |
+-------------------------------+--------+


In [183]:
runAttack(clip_knn35_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn35'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn35sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 6 / 44 / 0 / 50:  17%|████▏                    | 50/300 [07:11<35:55,  8.62s/it]textattack: Saving checkpoint under "checkpoints\1722488414441.ta.chkpt" at 2024-08-01 13:00:14 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 13 / 84 / 3 / 100:  33%|███████▎              | 100/300 [14:33<29:07,  8.74s/it]textattack: Saving checkpoint under "checkpoints\1722488857297.ta.chkpt" at 2024-08-01 13:07:37 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 22 / 122 / 6 / 150:  50%|██████████▌          | 150/300 [21:11<21:11,  8.48s/it]textattack: Saving checkpoint under "checkpoints\1722489254957.ta.chkpt" at 2024-08-01 13:14:14 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 30 / 157 / 13 / 200:  67%|█████████████▎      | 200/300 [27:18<13:39,  8.19s/it]textattack: Saving checkpoint under "checkpoints\1722489621911.ta.chkpt" at 2024-08-01 13:20:21 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 39 / 195 / 16 / 250:  83%|████████████████▋   | 250/300 [34:31<06:54,  8.28s/it]textattack: Saving checkpoint under "checkpoints\1722490054474.ta.chkpt" at 2024-08-01 13:27:34 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 42 / 236 / 22 / 300: 100%|████████████████████| 300/300 [41:29<00:00,  8.30s/it]textattack: Saving checkpoint under "checkpoints\1722490472506.ta.chkpt" at 2024-08-01 13:34:32 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 42 / 236 / 22 / 300: 100%|████████████████████| 300/300 [41:29<00:00,  8.30s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 42     |
| Number of failed attacks:     | 236    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 78.67% |
| Attack success rate:          | 15.11% |
| Average perturbed word %:     | 9.72%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 113.42 |
+-------------------------------+--------+


In [184]:
runAttack(clip_knn175_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn175'+suffix, target_ds_ag, 0.8, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn175sim08.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.8
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 5 / 44 / 1 / 50:  17%|████▏                    | 50/300 [07:03<35:19,  8.48s/it]textattack: Saving checkpoint under "checkpoints\1722490896631.ta.chkpt" at 2024-08-01 13:41:36 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 17 / 78 / 5 / 100:  33%|███████▎              | 100/300 [13:51<27:43,  8.32s/it]textattack: Saving checkpoint under "checkpoints\1722491304273.ta.chkpt" at 2024-08-01 13:48:24 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 30 / 111 / 9 / 150:  50%|██████████▌          | 150/300 [20:13<20:13,  8.09s/it]textattack: Saving checkpoint under "checkpoints\1722491686329.ta.chkpt" at 2024-08-01 13:54:46 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 37 / 142 / 21 / 200:  67%|█████████████▎      | 200/300 [25:56<12:58,  7.78s/it]textattack: Saving checkpoint under "checkpoints\1722492028784.ta.chkpt" at 2024-08-01 14:00:28 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 48 / 174 / 28 / 250:  83%|████████████████▋   | 250/300 [32:23<06:28,  7.77s/it]textattack: Saving checkpoint under "checkpoints\1722492415935.ta.chkpt" at 2024-08-01 14:06:55 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 50 / 216 / 34 / 300: 100%|████████████████████| 300/300 [39:28<00:00,  7.90s/it]textattack: Saving checkpoint under "checkpoints\1722492841490.ta.chkpt" at 2024-08-01 14:14:01 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 50 / 216 / 34 / 300: 100%|████████████████████| 300/300 [39:28<00:00,  7.90s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 50     |
| Number of failed attacks:     | 216    |
| Number of skipped attacks:    | 34     |
| Original accuracy:            | 88.67% |
| Accuracy under attack:        | 72.0%  |
| Attack success rate:          | 18.8%  |
| Average perturbed word %:     | 16.15% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 112.78 |
+-------------------------------+--------+


In [185]:
et8 = datetime.datetime.now()
et8 - et7

datetime.timedelta(seconds=38489, microseconds=31797)

### MinSim 0.9, threshold 0.5

In [186]:
suffix = 'sim09.csv'
thre = 1-0.5/np.pi

#### BERT

In [187]:
runAttack(bert_lr1_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr1'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr1sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 9 / 36 / 5 / 50:  17%|████▏                    | 50/300 [03:49<19:06,  4.59s/it]textattack: Saving checkpoint under "checkpoints\1722493071334.ta.chkpt" at 2024-08-01 14:17:51 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 27 / 63 / 10 / 100:  33%|███████              | 100/300 [07:49<15:38,  4.69s/it]textattack: Saving checkpoint under "checkpoints\1722493311113.ta.chkpt" at 2024-08-01 14:21:51 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 43 / 92 / 15 / 150:  50%|██████████▌          | 150/300 [11:48<11:48,  4.73s/it]textattack: Saving checkpoint under "checkpoints\1722493550942.ta.chkpt" at 2024-08-01 14:25:50 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 54 / 125 / 21 / 200:  67%|█████████████▎      | 200/300 [16:20<08:10,  4.90s/it]textattack: Saving checkpoint under "checkpoints\1722493822820.ta.chkpt" at 2024-08-01 14:30:22 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 65 / 160 / 25 / 250:  83%|████████████████▋   | 250/300 [20:59<04:11,  5.04s/it]textattack: Saving checkpoint under "checkpoints\1722494101712.ta.chkpt" at 2024-08-01 14:35:01 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 71 / 199 / 30 / 300: 100%|████████████████████| 300/300 [25:43<00:00,  5.15s/it]textattack: Saving checkpoint under "checkpoints\1722494385629.ta.chkpt" at 2024-08-01 14:39:45 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 71 / 199 / 30 / 300: 100%|████████████████████| 300/300 [25:43<00:00,  5.15s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 71     |
| Number of failed attacks:     | 199    |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 66.33% |
| Attack success rate:          | 26.3%  |
| Average perturbed word %:     | 12.98% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 58.51  |
+-------------------------------+--------+


In [188]:
runAttack(bert_lr01_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr01'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr01sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 6 / 39 / 5 / 50:  17%|████▏                    | 50/300 [04:07<20:38,  4.95s/it]textattack: Saving checkpoint under "checkpoints\1722494634143.ta.chkpt" at 2024-08-01 14:43:54 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 22 / 67 / 11 / 100:  33%|███████              | 100/300 [07:59<15:58,  4.79s/it]textattack: Saving checkpoint under "checkpoints\1722494865943.ta.chkpt" at 2024-08-01 14:47:45 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 36 / 98 / 16 / 150:  50%|██████████▌          | 150/300 [12:03<12:03,  4.82s/it]textattack: Saving checkpoint under "checkpoints\1722495109517.ta.chkpt" at 2024-08-01 14:51:49 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 48 / 129 / 23 / 200:  67%|█████████████▎      | 200/300 [16:16<08:08,  4.88s/it]textattack: Saving checkpoint under "checkpoints\1722495362831.ta.chkpt" at 2024-08-01 14:56:02 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 58 / 165 / 27 / 250:  83%|████████████████▋   | 250/300 [20:41<04:08,  4.97s/it]textattack: Saving checkpoint under "checkpoints\1722495628112.ta.chkpt" at 2024-08-01 15:00:28 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 63 / 205 / 32 / 300: 100%|████████████████████| 300/300 [25:21<00:00,  5.07s/it]textattack: Saving checkpoint under "checkpoints\1722495907633.ta.chkpt" at 2024-08-01 15:05:07 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 63 / 205 / 32 / 300: 100%|████████████████████| 300/300 [25:21<00:00,  5.07s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 63     |
| Number of failed attacks:     | 205    |
| Number of skipped attacks:    | 32     |
| Original accuracy:            | 89.33% |
| Accuracy under attack:        | 68.33% |
| Attack success rate:          | 23.51% |
| Average perturbed word %:     | 12.53% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 58.53  |
+-------------------------------+--------+


In [189]:
runAttack(bert_lr10_ag, n_samples, '../attack_results_new/aghyper/bertagattacklr10'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattacklr10sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 9 / 36 / 5 / 50:  17%|████▏                    | 50/300 [03:52<19:24,  4.66s/it]textattack: Saving checkpoint under "checkpoints\1722496140700.ta.chkpt" at 2024-08-01 15:09:00 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 24 / 65 / 11 / 100:  33%|███████              | 100/300 [07:52<15:45,  4.73s/it]textattack: Saving checkpoint under "checkpoints\1722496380533.ta.chkpt" at 2024-08-01 15:13:00 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 39 / 95 / 16 / 150:  50%|██████████▌          | 150/300 [11:53<11:53,  4.76s/it]textattack: Saving checkpoint under "checkpoints\1722496621532.ta.chkpt" at 2024-08-01 15:17:01 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 50 / 128 / 22 / 200:  67%|█████████████▎      | 200/300 [16:12<08:06,  4.86s/it]textattack: Saving checkpoint under "checkpoints\1722496880005.ta.chkpt" at 2024-08-01 15:21:20 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 60 / 164 / 26 / 250:  83%|████████████████▋   | 250/300 [20:37<04:07,  4.95s/it]textattack: Saving checkpoint under "checkpoints\1722497145755.ta.chkpt" at 2024-08-01 15:25:45 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 66 / 203 / 31 / 300: 100%|████████████████████| 300/300 [25:23<00:00,  5.08s/it]textattack: Saving checkpoint under "checkpoints\1722497431763.ta.chkpt" at 2024-08-01 15:30:31 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 66 / 203 / 31 / 300: 100%|████████████████████| 300/300 [25:24<00:00,  5.08s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 66     |
| Number of failed attacks:     | 203    |
| Number of skipped attacks:    | 31     |
| Original accuracy:            | 89.67% |
| Accuracy under attack:        | 67.67% |
| Attack success rate:          | 24.54% |
| Average perturbed word %:     | 12.44% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 58.39  |
+-------------------------------+--------+


In [190]:
runAttack(bert_rf7_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf7'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf7sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 20 / 17 / 13 / 50:  17%|███▊                   | 50/300 [02:34<12:52,  3.09s/it]textattack: Saving checkpoint under "checkpoints\1722497586503.ta.chkpt" at 2024-08-01 15:33:06 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 37 / 34 / 29 / 100:  33%|███████              | 100/300 [05:18<10:37,  3.19s/it]textattack: Saving checkpoint under "checkpoints\1722497750865.ta.chkpt" at 2024-08-01 15:35:50 after 100 attacks.
[Succeeded / Failed / Skipped / Total] 37 / 34 / 30 / 101:  34%|███████              | 101/300 [05:19<10:28,  3.16s/it]

[Succeeded / Failed / Skipped / Total] 58 / 52 / 40 / 150:  50%|██████████▌          | 150/300 [08:35<08:35,  3.44s/it]textattack: Saving checkpoint under "checkpoints\1722497947766.ta.chkpt" at 2024-08-01 15:39:07 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 73 / 71 / 56 / 200:  67%|██████████████       | 200/300 [11:45<05:52,  3.53s/it]textattack: Saving checkpoint under "checkpoints\1722498137443.ta.chkpt" at 2024-08-01 15:42:17 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 99 / 88 / 63 / 250:  83%|█████████████████▌   | 250/300 [15:00<03:00,  3.60s/it]textattack: Saving checkpoint under "checkpoints\1722498332688.ta.chkpt" at 2024-08-01 15:45:32 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 118 / 108 / 74 / 300: 100%|███████████████████| 300/300 [18:33<00:00,  3.71s/it]textattack: Saving checkpoint under "checkpoints\1722498545158.ta.chkpt" at 2024-08-01 15:49:05 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 118 / 108 / 74 / 300: 100%|███████████████████| 300/300 [18:33<00:00,  3.71s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 118    |
| Number of failed attacks:     | 108    |
| Number of skipped attacks:    | 74     |
| Original accuracy:            | 75.33% |
| Accuracy under attack:        | 36.0%  |
| Attack success rate:          | 52.21% |
| Average perturbed word %:     | 8.94%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 50.85  |
+-------------------------------+--------+


In [191]:
runAttack(bert_rf14_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf14'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf14sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 16 / 25 / 9 / 50:  17%|████                    | 50/300 [03:36<18:02,  4.33s/it]textattack: Saving checkpoint under "checkpoints\1722498761864.ta.chkpt" at 2024-08-01 15:52:41 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 32 / 49 / 19 / 100:  33%|███████              | 100/300 [07:00<14:01,  4.21s/it]textattack: Saving checkpoint under "checkpoints\1722498965901.ta.chkpt" at 2024-08-01 15:56:05 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 49 / 74 / 27 / 150:  50%|██████████▌          | 150/300 [10:32<10:32,  4.22s/it]textattack: Saving checkpoint under "checkpoints\1722499178106.ta.chkpt" at 2024-08-01 15:59:38 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 60 / 97 / 43 / 200:  67%|██████████████       | 200/300 [13:50<06:55,  4.15s/it]textattack: Saving checkpoint under "checkpoints\1722499375634.ta.chkpt" at 2024-08-01 16:02:55 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 79 / 122 / 49 / 250:  83%|████████████████▋   | 250/300 [17:41<03:32,  4.24s/it]textattack: Saving checkpoint under "checkpoints\1722499606512.ta.chkpt" at 2024-08-01 16:06:46 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 92 / 151 / 57 / 300: 100%|████████████████████| 300/300 [21:51<00:00,  4.37s/it]textattack: Saving checkpoint under "checkpoints\1722499857066.ta.chkpt" at 2024-08-01 16:10:57 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 92 / 151 / 57 / 300: 100%|████████████████████| 300/300 [21:51<00:00,  4.37s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 92     |
| Number of failed attacks:     | 151    |
| Number of skipped attacks:    | 57     |
| Original accuracy:            | 81.0%  |
| Accuracy under attack:        | 50.33% |
| Attack success rate:          | 37.86% |
| Average perturbed word %:     | 8.91%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 54.23  |
+-------------------------------+--------+


In [192]:
runAttack(bert_rf30_ag, n_samples, '../attack_results_new/aghyper/bertagattackrf30'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackrf30sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 20 / 24 / 6 / 50:  17%|████                    | 50/300 [04:08<20:42,  4.97s/it]textattack: Saving checkpoint under "checkpoints\1722500105722.ta.chkpt" at 2024-08-01 16:15:05 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 32 / 49 / 19 / 100:  33%|███████              | 100/300 [07:31<15:03,  4.52s/it]textattack: Saving checkpoint under "checkpoints\1722500308796.ta.chkpt" at 2024-08-01 16:18:28 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 51 / 73 / 26 / 150:  50%|██████████▌          | 150/300 [10:49<10:49,  4.33s/it]textattack: Saving checkpoint under "checkpoints\1722500506284.ta.chkpt" at 2024-08-01 16:21:46 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 64 / 97 / 39 / 200:  67%|██████████████       | 200/300 [14:21<07:10,  4.31s/it]textattack: Saving checkpoint under "checkpoints\1722500719135.ta.chkpt" at 2024-08-01 16:25:19 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 80 / 124 / 46 / 250:  83%|████████████████▋   | 250/300 [18:18<03:39,  4.39s/it]textattack: Saving checkpoint under "checkpoints\1722500955760.ta.chkpt" at 2024-08-01 16:29:15 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 90 / 157 / 53 / 300: 100%|████████████████████| 300/300 [22:30<00:00,  4.50s/it]textattack: Saving checkpoint under "checkpoints\1722501207955.ta.chkpt" at 2024-08-01 16:33:27 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 90 / 157 / 53 / 300: 100%|████████████████████| 300/300 [22:30<00:00,  4.50s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 90     |
| Number of failed attacks:     | 157    |
| Number of skipped attacks:    | 53     |
| Original accuracy:            | 82.33% |
| Accuracy under attack:        | 52.33% |
| Attack success rate:          | 36.44% |
| Average perturbed word %:     | 7.7%   |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 53.72  |
+-------------------------------+--------+


In [193]:
runAttack(bert_knn7_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn7'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn7sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 17 / 22 / 11 / 50:  17%|███▌                 | 50/300 [29:36<2:28:02, 35.53s/it]textattack: Saving checkpoint under "checkpoints\1722502984536.ta.chkpt" at 2024-08-01 17:03:04 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 40 / 40 / 20 / 100:  33%|██████▎            | 100/300 [34:00<1:08:00, 20.40s/it]textattack: Saving checkpoint under "checkpoints\1722503248396.ta.chkpt" at 2024-08-01 17:07:28 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 57 / 61 / 32 / 150:  50%|██████████▌          | 150/300 [38:05<38:05, 15.24s/it]textattack: Saving checkpoint under "checkpoints\1722503493597.ta.chkpt" at 2024-08-01 17:11:33 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 73 / 82 / 45 / 200:  67%|██████████████       | 200/300 [42:39<21:19, 12.80s/it]textattack: Saving checkpoint under "checkpoints\1722503767345.ta.chkpt" at 2024-08-01 17:16:07 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 90 / 108 / 52 / 250:  83%|████████████████▋   | 250/300 [47:59<09:35, 11.52s/it]textattack: Saving checkpoint under "checkpoints\1722504087243.ta.chkpt" at 2024-08-01 17:21:27 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 108 / 134 / 58 / 300: 100%|███████████████████| 300/300 [53:12<00:00, 10.64s/it]textattack: Saving checkpoint under "checkpoints\1722504400365.ta.chkpt" at 2024-08-01 17:26:40 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 108 / 134 / 58 / 300: 100%|███████████████████| 300/300 [53:12<00:00, 10.64s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 108    |
| Number of failed attacks:     | 134    |
| Number of skipped attacks:    | 58     |
| Original accuracy:            | 80.67% |
| Accuracy under attack:        | 44.67% |
| Attack success rate:          | 44.63% |
| Average perturbed word %:     | 4.56%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 52.47  |
+-------------------------------+--------+


In [194]:
runAttack(bert_knn35_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn35'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn35sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 20 / 21 / 9 / 50:  17%|████                    | 50/300 [04:20<21:44,  5.22s/it]textattack: Saving checkpoint under "checkpoints\1722504661345.ta.chkpt" at 2024-08-01 17:31:01 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 40 / 41 / 19 / 100:  33%|███████              | 100/300 [08:52<17:45,  5.33s/it]textattack: Saving checkpoint under "checkpoints\1722504933007.ta.chkpt" at 2024-08-01 17:35:33 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 58 / 64 / 28 / 150:  50%|██████████▌          | 150/300 [13:30<13:30,  5.40s/it]textattack: Saving checkpoint under "checkpoints\1722505211200.ta.chkpt" at 2024-08-01 17:40:11 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 70 / 87 / 43 / 200:  67%|██████████████       | 200/300 [18:12<09:06,  5.46s/it]textattack: Saving checkpoint under "checkpoints\1722505493180.ta.chkpt" at 2024-08-01 17:44:53 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 83 / 116 / 51 / 250:  83%|████████████████▋   | 250/300 [23:42<04:44,  5.69s/it]textattack: Saving checkpoint under "checkpoints\1722505823330.ta.chkpt" at 2024-08-01 17:50:23 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 103 / 141 / 56 / 300: 100%|███████████████████| 300/300 [29:27<00:00,  5.89s/it]textattack: Saving checkpoint under "checkpoints\1722506168415.ta.chkpt" at 2024-08-01 17:56:08 after 300 attacks.


[Succeeded / Failed / Skipped / Total] 103 / 141 / 56 / 300: 100%|███████████████████| 300/300 [29:28<00:00,  5.89s/it]


+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 103    |
| Number of failed attacks:     | 141    |
| Number of skipped attacks:    | 56     |
| Original accuracy:            | 81.33% |
| Accuracy under attack:        | 47.0%  |
| Attack success rate:          | 42.21% |
| Average perturbed word %:     | 7.69%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 53.87  |
+-------------------------------+--------+


In [195]:
runAttack(bert_knn175_ag, n_samples, '../attack_results_new/aghyper/bertagattackknn175'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.bert.modeling_bert.BertModel'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/bertagattackknn175sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 21 / 20 / 9 / 50:  17%|████                    | 50/300 [04:05<20:25,  4.90s/it]textattack: Saving checkpoint under "checkpoints\1722506413971.ta.chkpt" at 2024-08-01 18:00:13 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 40 / 40 / 20 / 100:  33%|███████              | 100/300 [08:33<17:07,  5.14s/it]textattack: Saving checkpoint under "checkpoints\1722506682293.ta.chkpt" at 2024-08-01 18:04:42 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 55 / 62 / 33 / 150:  50%|██████████▌          | 150/300 [12:58<12:58,  5.19s/it]textattack: Saving checkpoint under "checkpoints\1722506947314.ta.chkpt" at 2024-08-01 18:09:07 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 70 / 83 / 47 / 200:  67%|██████████████       | 200/300 [17:29<08:44,  5.25s/it]textattack: Saving checkpoint under "checkpoints\1722507218567.ta.chkpt" at 2024-08-01 18:13:38 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 89 / 107 / 54 / 250:  83%|████████████████▋   | 250/300 [22:41<04:32,  5.45s/it]textattack: Saving checkpoint under "checkpoints\1722507530064.ta.chkpt" at 2024-08-01 18:18:50 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 109 / 131 / 60 / 300: 100%|███████████████████| 300/300 [27:52<00:00,  5.58s/it]textattack: Saving checkpoint under "checkpoints\1722507841324.ta.chkpt" at 2024-08-01 18:24:01 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 109 / 131 / 60 / 300: 100%|███████████████████| 300/300 [27:52<00:00,  5.58s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 109    |
| Number of failed attacks:     | 131    |
| Number of skipped attacks:    | 60     |
| Original accuracy:            | 80.0%  |
| Accuracy under attack:        | 43.67% |
| Attack success rate:          | 45.42% |
| Average perturbed word %:     | 7.92%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 52.05  |
+-------------------------------+--------+


#### CLIP

In [196]:
runAttack(clip_lr1_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr1'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr1sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 1 / 45 / 4 / 50:  17%|████▏                    | 50/300 [03:31<17:38,  4.23s/it]textattack: Saving checkpoint under "checkpoints\1722508053157.ta.chkpt" at 2024-08-01 18:27:33 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 9 / 82 / 9 / 100:  33%|███████▋               | 100/300 [06:51<13:42,  4.11s/it]textattack: Saving checkpoint under "checkpoints\1722508252676.ta.chkpt" at 2024-08-01 18:30:52 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 15 / 121 / 14 / 150:  50%|██████████          | 150/300 [10:03<10:03,  4.02s/it]textattack: Saving checkpoint under "checkpoints\1722508445076.ta.chkpt" at 2024-08-01 18:34:05 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 25 / 155 / 20 / 200:  67%|█████████████▎      | 200/300 [13:05<06:32,  3.93s/it]textattack: Saving checkpoint under "checkpoints\1722508627143.ta.chkpt" at 2024-08-01 18:37:07 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 33 / 193 / 24 / 250:  83%|████████████████▋   | 250/300 [16:24<03:16,  3.94s/it]textattack: Saving checkpoint under "checkpoints\1722508826269.ta.chkpt" at 2024-08-01 18:40:26 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 40 / 231 / 29 / 300: 100%|████████████████████| 300/300 [19:38<00:00,  3.93s/it]textattack: Saving checkpoint under "checkpoints\1722509020158.ta.chkpt" at 2024-08-01 18:43:40 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 40 / 231 / 29 / 300: 100%|████████████████████| 300/300 [19:38<00:00,  3.93s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 40     |
| Number of failed attacks:     | 231    |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 77.0%  |
| Attack success rate:          | 14.76% |
| Average perturbed word %:     | 12.86% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 60.12  |
+-------------------------------+--------+


In [197]:
runAttack(clip_lr01_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr01'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr01sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 1 / 45 / 4 / 50:  17%|████▏                    | 50/300 [03:03<15:15,  3.66s/it]textattack: Saving checkpoint under "checkpoints\1722509203439.ta.chkpt" at 2024-08-01 18:46:43 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 9 / 82 / 9 / 100:  33%|███████▋               | 100/300 [06:12<12:24,  3.72s/it]textattack: Saving checkpoint under "checkpoints\1722509392693.ta.chkpt" at 2024-08-01 18:49:52 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 15 / 121 / 14 / 150:  50%|██████████          | 150/300 [09:19<09:19,  3.73s/it]textattack: Saving checkpoint under "checkpoints\1722509579525.ta.chkpt" at 2024-08-01 18:52:59 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 25 / 155 / 20 / 200:  67%|█████████████▎      | 200/300 [12:16<06:08,  3.68s/it]textattack: Saving checkpoint under "checkpoints\1722509756641.ta.chkpt" at 2024-08-01 18:55:56 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 33 / 193 / 24 / 250:  83%|████████████████▋   | 250/300 [15:30<03:06,  3.72s/it]textattack: Saving checkpoint under "checkpoints\1722509950473.ta.chkpt" at 2024-08-01 18:59:10 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 40 / 231 / 29 / 300: 100%|████████████████████| 300/300 [18:44<00:00,  3.75s/it]textattack: Saving checkpoint under "checkpoints\1722510144967.ta.chkpt" at 2024-08-01 19:02:24 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 40 / 231 / 29 / 300: 100%|████████████████████| 300/300 [18:44<00:00,  3.75s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 40     |
| Number of failed attacks:     | 231    |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 77.0%  |
| Attack success rate:          | 14.76% |
| Average perturbed word %:     | 12.69% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 60.08  |
+-------------------------------+--------+


In [198]:
runAttack(clip_lr10_ag, n_samples, '../attack_results_new/aghyper/clipagattacklr10'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattacklr10sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 1 / 45 / 4 / 50:  17%|████▏                    | 50/300 [03:01<15:08,  3.64s/it]textattack: Saving checkpoint under "checkpoints\1722510326955.ta.chkpt" at 2024-08-01 19:05:26 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 9 / 82 / 9 / 100:  33%|███████▋               | 100/300 [06:09<12:19,  3.70s/it]textattack: Saving checkpoint under "checkpoints\1722510514959.ta.chkpt" at 2024-08-01 19:08:34 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 15 / 121 / 14 / 150:  50%|██████████          | 150/300 [09:15<09:15,  3.71s/it]textattack: Saving checkpoint under "checkpoints\1722510701152.ta.chkpt" at 2024-08-01 19:11:41 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 25 / 155 / 20 / 200:  67%|█████████████▎      | 200/300 [12:12<06:06,  3.66s/it]textattack: Saving checkpoint under "checkpoints\1722510878127.ta.chkpt" at 2024-08-01 19:14:38 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 33 / 193 / 24 / 250:  83%|████████████████▋   | 250/300 [15:28<03:05,  3.71s/it]textattack: Saving checkpoint under "checkpoints\1722511073312.ta.chkpt" at 2024-08-01 19:17:53 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 40 / 231 / 29 / 300: 100%|████████████████████| 300/300 [18:40<00:00,  3.74s/it]textattack: Saving checkpoint under "checkpoints\1722511265941.ta.chkpt" at 2024-08-01 19:21:05 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 40 / 231 / 29 / 300: 100%|████████████████████| 300/300 [18:40<00:00,  3.74s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 40     |
| Number of failed attacks:     | 231    |
| Number of skipped attacks:    | 29     |
| Original accuracy:            | 90.33% |
| Accuracy under attack:        | 77.0%  |
| Attack success rate:          | 14.76% |
| Average perturbed word %:     | 12.86% |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 60.12  |
+-------------------------------+--------+


In [199]:
runAttack(clip_rf7_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf7'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf7sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 4 / 43 / 3 / 50:  17%|████▏                    | 50/300 [03:01<15:05,  3.62s/it]textattack: Saving checkpoint under "checkpoints\1722511447301.ta.chkpt" at 2024-08-01 19:24:07 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 11 / 78 / 11 / 100:  33%|███████              | 100/300 [05:59<11:58,  3.59s/it]textattack: Saving checkpoint under "checkpoints\1722511625191.ta.chkpt" at 2024-08-01 19:27:05 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 16 / 118 / 16 / 150:  50%|██████████          | 150/300 [08:59<08:59,  3.60s/it]textattack: Saving checkpoint under "checkpoints\1722511805819.ta.chkpt" at 2024-08-01 19:30:05 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 26 / 143 / 31 / 200:  67%|█████████████▎      | 200/300 [11:04<05:32,  3.32s/it]textattack: Saving checkpoint under "checkpoints\1722511930301.ta.chkpt" at 2024-08-01 19:32:10 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 34 / 178 / 38 / 250:  83%|████████████████▋   | 250/300 [14:00<02:48,  3.36s/it]textattack: Saving checkpoint under "checkpoints\1722512106489.ta.chkpt" at 2024-08-01 19:35:06 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 37 / 220 / 43 / 300: 100%|████████████████████| 300/300 [17:22<00:00,  3.48s/it]textattack: Saving checkpoint under "checkpoints\1722512308629.ta.chkpt" at 2024-08-01 19:38:28 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 37 / 220 / 43 / 300: 100%|████████████████████| 300/300 [17:22<00:00,  3.48s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 37     |
| Number of failed attacks:     | 220    |
| Number of skipped attacks:    | 43     |
| Original accuracy:            | 85.67% |
| Accuracy under attack:        | 73.33% |
| Attack success rate:          | 14.4%  |
| Average perturbed word %:     | 7.43%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 58.68  |
+-------------------------------+--------+


In [200]:
runAttack(clip_rf14_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf14'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf14sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 4 / 44 / 2 / 50:  17%|████▏                    | 50/300 [03:26<17:13,  4.14s/it]textattack: Saving checkpoint under "checkpoints\1722512515500.ta.chkpt" at 2024-08-01 19:41:55 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 9 / 84 / 7 / 100:  33%|███████▋               | 100/300 [06:42<13:24,  4.02s/it]textattack: Saving checkpoint under "checkpoints\1722512710846.ta.chkpt" at 2024-08-01 19:45:10 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 13 / 124 / 13 / 150:  50%|██████████          | 150/300 [09:47<09:47,  3.92s/it]textattack: Saving checkpoint under "checkpoints\1722512896514.ta.chkpt" at 2024-08-01 19:48:16 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 22 / 155 / 23 / 200:  67%|█████████████▎      | 200/300 [12:25<06:12,  3.73s/it]textattack: Saving checkpoint under "checkpoints\1722513053805.ta.chkpt" at 2024-08-01 19:50:53 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 28 / 194 / 28 / 250:  83%|████████████████▋   | 250/300 [15:40<03:08,  3.76s/it]textattack: Saving checkpoint under "checkpoints\1722513249683.ta.chkpt" at 2024-08-01 19:54:09 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 31 / 236 / 33 / 300: 100%|████████████████████| 300/300 [19:00<00:00,  3.80s/it]textattack: Saving checkpoint under "checkpoints\1722513449226.ta.chkpt" at 2024-08-01 19:57:29 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 31 / 236 / 33 / 300: 100%|████████████████████| 300/300 [19:00<00:00,  3.80s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 31     |
| Number of failed attacks:     | 236    |
| Number of skipped attacks:    | 33     |
| Original accuracy:            | 89.0%  |
| Accuracy under attack:        | 78.67% |
| Attack success rate:          | 11.61% |
| Average perturbed word %:     | 8.8%   |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 59.79  |
+-------------------------------+--------+


In [201]:
runAttack(clip_rf30_ag, n_samples, '../attack_results_new/aghyper/clipagattackrf30'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackrf30sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 3 / 45 / 2 / 50:  17%|████▏                    | 50/300 [04:10<20:53,  5.01s/it]textattack: Saving checkpoint under "checkpoints\1722513699991.ta.chkpt" at 2024-08-01 20:01:39 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 8 / 84 / 8 / 100:  33%|███████▋               | 100/300 [07:37<15:14,  4.57s/it]textattack: Saving checkpoint under "checkpoints\1722513906777.ta.chkpt" at 2024-08-01 20:05:06 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 14 / 124 / 12 / 150:  50%|██████████          | 150/300 [10:45<10:45,  4.30s/it]textattack: Saving checkpoint under "checkpoints\1722514094865.ta.chkpt" at 2024-08-01 20:08:14 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 23 / 156 / 21 / 200:  67%|█████████████▎      | 200/300 [13:22<06:41,  4.01s/it]textattack: Saving checkpoint under "checkpoints\1722514251563.ta.chkpt" at 2024-08-01 20:10:51 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 29 / 195 / 26 / 250:  83%|████████████████▋   | 250/300 [16:43<03:20,  4.01s/it]textattack: Saving checkpoint under "checkpoints\1722514452594.ta.chkpt" at 2024-08-01 20:14:12 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 33 / 237 / 30 / 300: 100%|████████████████████| 300/300 [20:06<00:00,  4.02s/it]textattack: Saving checkpoint under "checkpoints\1722514656233.ta.chkpt" at 2024-08-01 20:17:36 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 33 / 237 / 30 / 300: 100%|████████████████████| 300/300 [20:06<00:00,  4.02s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 33     |
| Number of failed attacks:     | 237    |
| Number of skipped attacks:    | 30     |
| Original accuracy:            | 90.0%  |
| Accuracy under attack:        | 79.0%  |
| Attack success rate:          | 12.22% |
| Average perturbed word %:     | 6.66%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 59.3   |
+-------------------------------+--------+


In [202]:
runAttack(clip_knn7_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn7'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn7sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 0 / 49 / 1 / 50:  17%|███▊                   | 50/300 [34:57<2:54:48, 41.95s/it]textattack: Saving checkpoint under "checkpoints\1722516754106.ta.chkpt" at 2024-08-01 20:52:34 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 3 / 93 / 4 / 100:  33%|███████              | 100/300 [39:45<1:19:30, 23.85s/it]textattack: Saving checkpoint under "checkpoints\1722517041469.ta.chkpt" at 2024-08-01 20:57:21 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 6 / 137 / 7 / 150:  50%|███████████           | 150/300 [44:17<44:17, 17.71s/it]textattack: Saving checkpoint under "checkpoints\1722517313515.ta.chkpt" at 2024-08-01 21:01:53 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 6 / 180 / 14 / 200:  67%|██████████████       | 200/300 [48:44<24:22, 14.62s/it]textattack: Saving checkpoint under "checkpoints\1722517580725.ta.chkpt" at 2024-08-01 21:06:20 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 9 / 224 / 17 / 250:  83%|█████████████████▌   | 250/300 [53:38<10:43, 12.87s/it]textattack: Saving checkpoint under "checkpoints\1722517874946.ta.chkpt" at 2024-08-01 21:11:14 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 10 / 268 / 22 / 300: 100%|████████████████████| 300/300 [58:09<00:00, 11.63s/it]textattack: Saving checkpoint under "checkpoints\1722518145942.ta.chkpt" at 2024-08-01 21:15:45 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 10 / 268 / 22 / 300: 100%|████████████████████| 300/300 [58:09<00:00, 11.63s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 10     |
| Number of failed attacks:     | 268    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 89.33% |
| Attack success rate:          | 3.6%   |
| Average perturbed word %:     | 3.31%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 61.58  |
+-------------------------------+--------+


In [203]:
runAttack(clip_knn35_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn35'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn35sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 2 / 48 / 0 / 50:  17%|████▏                    | 50/300 [04:32<22:44,  5.46s/it]textattack: Saving checkpoint under "checkpoints\1722518418881.ta.chkpt" at 2024-08-01 21:20:18 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 8 / 89 / 3 / 100:  33%|███████▋               | 100/300 [09:21<18:42,  5.61s/it]textattack: Saving checkpoint under "checkpoints\1722518707397.ta.chkpt" at 2024-08-01 21:25:07 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 11 / 133 / 6 / 150:  50%|██████████▌          | 150/300 [13:52<13:52,  5.55s/it]textattack: Saving checkpoint under "checkpoints\1722518978738.ta.chkpt" at 2024-08-01 21:29:38 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 16 / 171 / 13 / 200:  67%|█████████████▎      | 200/300 [17:59<08:59,  5.40s/it]textattack: Saving checkpoint under "checkpoints\1722519225109.ta.chkpt" at 2024-08-01 21:33:45 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 19 / 215 / 16 / 250:  83%|████████████████▋   | 250/300 [22:58<04:35,  5.51s/it]textattack: Saving checkpoint under "checkpoints\1722519524783.ta.chkpt" at 2024-08-01 21:38:44 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 21 / 257 / 22 / 300: 100%|████████████████████| 300/300 [27:27<00:00,  5.49s/it]textattack: Saving checkpoint under "checkpoints\1722519793115.ta.chkpt" at 2024-08-01 21:43:13 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 21 / 257 / 22 / 300: 100%|████████████████████| 300/300 [27:27<00:00,  5.49s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 21     |
| Number of failed attacks:     | 257    |
| Number of skipped attacks:    | 22     |
| Original accuracy:            | 92.67% |
| Accuracy under attack:        | 85.67% |
| Attack success rate:          | 7.55%  |
| Average perturbed word %:     | 6.31%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 61.11  |
+-------------------------------+--------+


In [204]:
runAttack(clip_knn175_ag, n_samples, '../attack_results_new/aghyper/clipagattackknn175'+suffix, target_ds_ag, 0.9, thre)

textattack: Unknown if model of class <class 'transformers.models.clip.modeling_clip.CLIPTextTransformer'> compatible with goal function <class 'textattack.goal_functions.classification.untargeted_classification.UntargetedClassification'>.
textattack: Logging to CSV at path ../attack_results_new/aghyper/clipagattackknn175sim09.csv


Attack(
  (search_method): GreedyWordSwapWIR(
    (wir_method):  delete
  )
  (goal_function):  UntargetedClassification
  (transformation):  WordSwapEmbedding(
    (max_candidates):  50
    (embedding):  WordEmbedding
  )
  (constraints): 
    (0): WordEmbeddingDistance(
        (embedding):  WordEmbedding
        (min_cos_sim):  0.9
        (cased):  False
        (include_unknown_words):  True
        (compare_against_original):  True
      )
    (1): PartOfSpeech(
        (tagger_type):  nltk
        (tagset):  universal
        (allow_verb_noun_swap):  True
        (compare_against_original):  True
      )
    (2): UniversalSentenceEncoder(
        (metric):  angular
        (threshold):  0.8408450569081046
        (window_size):  15
        (skip_text_shorter_than_window):  True
        (compare_against_original):  False
      )
    (3): RepeatModification
    (4): StopwordModification
    (5): InputColumnModification(
        (matching_column_labels):  ['premise', 'hypothesis']


[Succeeded / Failed / Skipped / Total] 2 / 47 / 1 / 50:  17%|████▏                    | 50/300 [04:23<21:57,  5.27s/it]textattack: Saving checkpoint under "checkpoints\1722520056817.ta.chkpt" at 2024-08-01 21:47:36 after 50 attacks.


[Succeeded / Failed / Skipped / Total] 9 / 86 / 5 / 100:  33%|███████▋               | 100/300 [08:45<17:30,  5.25s/it]textattack: Saving checkpoint under "checkpoints\1722520318832.ta.chkpt" at 2024-08-01 21:51:58 after 100 attacks.


[Succeeded / Failed / Skipped / Total] 13 / 128 / 9 / 150:  50%|██████████▌          | 150/300 [13:10<13:10,  5.27s/it]textattack: Saving checkpoint under "checkpoints\1722520583855.ta.chkpt" at 2024-08-01 21:56:23 after 150 attacks.


[Succeeded / Failed / Skipped / Total] 16 / 163 / 21 / 200:  67%|█████████████▎      | 200/300 [16:58<08:29,  5.09s/it]textattack: Saving checkpoint under "checkpoints\1722520812341.ta.chkpt" at 2024-08-01 22:00:12 after 200 attacks.


[Succeeded / Failed / Skipped / Total] 18 / 204 / 28 / 250:  83%|████████████████▋   | 250/300 [21:48<04:21,  5.24s/it]textattack: Saving checkpoint under "checkpoints\1722521102285.ta.chkpt" at 2024-08-01 22:05:02 after 250 attacks.


[Succeeded / Failed / Skipped / Total] 19 / 247 / 34 / 300: 100%|████████████████████| 300/300 [26:27<00:00,  5.29s/it]textattack: Saving checkpoint under "checkpoints\1722521380958.ta.chkpt" at 2024-08-01 22:09:40 after 300 attacks.
[Succeeded / Failed / Skipped / Total] 19 / 247 / 34 / 300: 100%|████████████████████| 300/300 [26:27<00:00,  5.29s/it]





+-------------------------------+--------+
| Attack Results                |        |
+-------------------------------+--------+
| Number of successful attacks: | 19     |
| Number of failed attacks:     | 247    |
| Number of skipped attacks:    | 34     |
| Original accuracy:            | 88.67% |
| Accuracy under attack:        | 82.33% |
| Attack success rate:          | 7.14%  |
| Average perturbed word %:     | 9.93%  |
| Average num. words per input: | 39.3   |
| Avg num queries:              | 60.62  |
+-------------------------------+--------+


In [205]:
et9 = datetime.datetime.now()
et9 - et8

datetime.timedelta(seconds=28539, microseconds=429397)